In [1]:
print('start')

start


In [2]:
import numpy as np
import pandas as pd
import re
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor, AdaBoostRegressor, ExtraTreesRegressor
from sklearn.linear_model import LinearRegression, LogisticRegression  # LogisticRegression is not used for regression
from sklearn.neighbors import KNeighborsRegressor
from sklearn.svm import SVR
from sklearn.neural_network import MLPRegressor
import xgboost as xgb
import lightgbm as lgb
from sklearn.model_selection import KFold, GridSearchCV
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from scipy.stats import pearsonr, spearmanr
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt

In [3]:
def train_and_test_predict(models, X_train, y_train, X_test, y_test):
    kf = KFold(n_splits=5, shuffle=True, random_state=101)
    results = {}
    predictions = []  

    for model in models:
        model_name = model.__class__.__name__
        predictions_train = []
        actual_y_train = []

        test_predictions_folds = []

        

        for train_index, val_index in kf.split(X_train):
            X_train_fold, X_val_fold = X_train.iloc[train_index], X_train.iloc[val_index]
            y_train_fold, y_val_fold = y_train.iloc[train_index], y_train.iloc[val_index]

            model.fit(X_train_fold, y_train_fold)

            y_pred_fold = model.predict(X_val_fold)
            y_pred_fold = np.clip(y_pred_fold, -10, -4.0)
            predictions_train.extend(y_pred_fold)
            actual_y_train.extend(y_val_fold)

            predictions_test_fold = model.predict(X_test)
            predictions_test_fold = np.clip(predictions_test_fold, -10, -4.0)
            test_predictions_folds.append(predictions_test_fold)


        mse_train = mean_squared_error(actual_y_train, predictions_train)
        mae_train = mean_absolute_error(actual_y_train, predictions_train)
        rmse_train = np.sqrt(mse_train)
        r2_train = r2_score(actual_y_train, predictions_train)
        pearson_train, _ = pearsonr(actual_y_train, predictions_train)
        spearman_train, _ = spearmanr(actual_y_train, predictions_train)


        predictions_test_mean = np.mean(test_predictions_folds, axis=0)
        predictions_test_std = np.std(test_predictions_folds, axis=0)

        mse_test = mean_squared_error(y_test, predictions_test_mean)
        mae_test = mean_absolute_error(y_test, predictions_test_mean)
        rmse_test = np.sqrt(mse_test)
        r2_test = r2_score(y_test, predictions_test_mean)
        print(r2_test)
        pearson_test, _ = pearsonr(y_test, predictions_test_mean)
        spearman_test, _ = spearmanr(y_test, predictions_test_mean)
        
        

        predictions.append({
            'Model': model_name,
            'Y Train pred': predictions_train,
            'Y Test actual': y_test,
            'Test prediction folds': test_predictions_folds,
            'Test Predictions Mean': predictions_test_mean,
            'Test Predictions Std': predictions_test_std,

        })

        results[model_name] = {
            'Train MSE (5 fold cv)': f"{mse_train:.4f}",
            'Train MAE (5 fold cv)': f"{mae_train:.4f}",
            'Train RMSE (5 fold cv)': f"{rmse_train:.4f}",
            'Train RMSE (5 fold cv)': f"{rmse_train:.4f}",
            'Train R2 (5 fold cv)': f"{r2_train:.4f}",
            'Train PCC (5 fold cv)': f"{pearson_train:.4f}",
            'Train SCC (5 fold cv)': f"{spearman_train:.4f}",
            'Test MSE': f"{mse_test:.4f}",
            'Test MAE': f"{mae_test:.4f}",
            'Test RMSE': f"{rmse_test:.4f}",
            'Test R2': f"{r2_test:.4f}",
            'Test Pearson Correlation': f"{pearson_test:.4f}",
            'Test Spearman Correlation': f"{spearman_test:.4f}",
        }

    results_df = pd.DataFrame(results).T
    predictions_df = pd.DataFrame(predictions)

    return results_df, predictions_df



In [4]:
#Monomeric models
def clean_feature_names(df):
    def clean_name(name):
        return re.sub(r'[^a-zA-Z0-9_]', '_', name)

    df.columns = [clean_name(col) for col in df.columns]
    return df

In [9]:
#Monomer composition
df_mc_train = pd.read_csv('features/Monomeric/Train_mon_comp_MDCK.csv')
df_mc_train = clean_feature_names(df_mc_train)
X_train = df_mc_train.drop(['ID','SMILES','Permeability'], axis=1)
y_train = df_mc_train['Permeability']
print(X_train.shape)
print(y_train.shape)
df_mc_test = pd.read_csv('features/Monomeric/Test_mon_comp_MDCK.csv')
df_mc_test = clean_feature_names(df_mc_test)
X_test = df_mc_test.drop(['ID','SMILES','Permeability'], axis=1)
y_test = df_mc_test['Permeability']
print(X_test.shape)
print(y_test.shape)
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    xgb.XGBRegressor(random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    SVR(),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3), 
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

(51, 385)
(51,)
(13, 385)
(13,)
0.2923202922753174
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000057 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 6
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 1
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [W

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-1.2776285723570941


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
ExtraTreesRegressor                      0.7296                0.5823   
LGBMRegressor                            0.6446                0.6796   
XGBRegressor                             0.8507                0.6431   
DecisionTreeRegressor                    1.0375                0.6894   
RandomForestRegressor                    0.6361                0.6084   
GradientBoostingRegressor                0.7810                0.6339   
AdaBoostRegressor                        0.7158                0.6462   
SVR                                      0.7202                0.6786   
LinearRegression                         1.1792                0.8393   
KNeighborsRegressor                      0.8570                0.7338   
MLPRegressor                             2.4154                1.2616   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
ExtraTreesRegressor                       0.8542              -0.1279   
LGBMRegressor                             0.8028               0.0036   
XGBRegressor                              0.9224              -0.3151   
DecisionTreeRegressor                     1.0186              -0.6039   
RandomForestRegressor                     0.7976               0.0166   
GradientBoostingRegressor                 0.8837              -0.2073   
AdaBoostRegressor                         0.8461              -0.1066   
SVR                                       0.8487              -0.1133   
LinearRegression                          1.0859              -0.8229   
KNeighborsRegressor                       0.9258              -0.3249   
MLPRegressor                              1.5542              -2.7339   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
ExtraTreesRegressor                      0.2558                0.3734   
LGBMRegressor                            0.1308                0.1395   
XGBRegressor                             0.2721                0.3560   
DecisionTreeRegressor                    0.0966                0.2015   
RandomForestRegressor                    0.2675                0.3387   
GradientBoostingRegressor                0.1955                0.2986   
AdaBoostRegressor                        0.1428                0.2387   
SVR                                      0.0479               -0.0587   
LinearRegression                         0.1790                0.2027   
KNeighborsRegressor                      0.1005                0.1947   
MLPRegressor                            -0.0864               -0.0235   

                          Test MSE Test MAE Test RMSE  Test R2  \
ExtraTreesRegressor         0.4163   0.5215    0.6452   0.2923   
LGBMRegressor               0.5276   0.5751    0.7263   0.1031   
XGBRegressor                0.3258   0.4432    0.5708   0.4462   
DecisionTreeRegressor       0.3747   0.4881    0.6121   0.3630   
RandomForestRegressor       0.3256   0.5001    0.5706   0.4465   
GradientBoostingRegressor   0.3042   0.4338    0.5515   0.4829   
AdaBoostRegressor           0.2580   0.4479    0.5079   0.5614   
SVR                         0.3813   0.5052    0.6175   0.3518   
LinearRegression            0.5803   0.5368    0.7618   0.0134   
KNeighborsRegressor         0.3572   0.4786    0.5976   0.3928   
MLPRegressor                1.3398   0.8793    1.1575  -1.2776   

                          Test Pearson Correlation Test Spearman Correlation  
ExtraTreesRegressor                         0.5979                    0.2865  
LGBMRegressor                               0.4182                    0.3245  
XGBRegressor                                0.7110                    0.4628  
DecisionTreeRegressor                       0.6606                    0.4077  
RandomForestRegressor                       0.6707                    0.4353  
GradientBoostingRegressor                   0.7093                    0.4628  
AdaBoostRegressor                           0.753

In [10]:
prediction_df

Model  \
0         ExtraTreesRegressor   
1               LGBMRegressor   
2                XGBRegressor   
3       DecisionTreeRegressor   
4       RandomForestRegressor   
5   GradientBoostingRegressor   
6           AdaBoostRegressor   
7                         SVR   
8            LinearRegression   
9         KNeighborsRegressor   
10               MLPRegressor   

                                         Y Train pred  \
0   [-6.048558046430011, -6.80190000000001, -5.657...   
1   [-5.72429500042461, -5.781901428122076, -5.781...   
2   [-6.2183466, -7.569528, -5.4499307, -5.596678,...   
3   [-5.22, -6.97, -5.06, -5.22, -6.929917083, -5....   
4   [-5.865097338736674, -6.371899999999998, -5.77...   
5   [-6.048170161042695, -6.6922024002120635, -5.6...   
6   [-5.639976052304348, -6.77, -5.663214181444443...   
7   [-5.693891035066837, -5.65413016780909, -5.747...   
8   [-4.126989483536487, -4.717425534753499, -6.53...   
9   [-5.1866666666666665, -6.07, -6.07, -6.0404790...   
10  [-4.0, -6.767604618760506, -5.908965472322045,...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.8029044125550024, -5.753935149195002, -5....   
1   [[-5.72429500042461, -5.72429500042461, -5.781...   
2   [[-5.985038, -5.706633, -6.759508, -6.9262185,...   
3   [[-5.295, -5.22, -6.85, -6.927245587, -5.22, -...   
4   [[-5.692643656850002, -5.5981434520383395, -5....   
5   [[-5.871766622783936, -5.6245522063437186, -6....   
6   [[-5.663214181444443, -5.600981205750001, -5.5...   
7   [[-5.666661130052129, -5.701594019876477, -5.4...   
8   [[-4.0, -4.0, -6.272531131732464, -6.922973078...   
9   [[-5.613333333333333, -5.2783009283333335, -5....   
10  [[-4.0, -4.0, -4.4577024051895915, -6.90534328...   

                                Test Predictions Mean  \
0   [-5.700078470685001, -5.582273631594001, -5.96...   
1   [-5.508673793612709, -5.508673793612709, -5.62...   
2   [-5.8299103, -5.498244, -6.1002665, -6.6718307...   
3   [-5.832, -5.3859667324, -6.609017847999999, -6...   
4   [-5.653318263936335, -5.516528619457403, -5.86...   
5   [-5.739107746439394, -5.420930018864825, -5.97...   
6   [-5.574862276957454, -5.546830403219381, -5.62...   
7   [-5.531594480261154, -5.693265666274938, -5.46...   
8   [-4.0, -5.632525333476553, -5.828073967233101,...   
9   [-5.528666666666667, -5.258158495866667, -4.96...   
10  [-4.04038067530402, -5.4234312431206035, -4.21...   

                                 Test Predictions Std  
0   [0.3900394892473089, 0.09680365467181355, 0.28...  
1   [0.1956217934002597, 0.1956217934002597, 0.192...  
2   [0.43846768, 0.26189202, 0.6996025, 0.5103311,...  
3   [1.138229326629744, 0.24822520835348863, 0.300...  
4   [0.10946989771195936, 0.05882262933001048, 0.2...  
5   [0.33465932282986494, 0.13293890920620488, 0.4...  
6   [0.13067365045804516, 0.08403370405403282, 0.2...  
7   [0.14780547145157835, 0.029695389201786812, 0....  
8   [0.0, 1.0051831044888202, 0.8372471943944391, ...  
9   [0.1545689346393881, 0.0726709195073452, 0.137...  
10  [0.08076135060803899, 0.7213267372253405, 0.22...

In [11]:
result_df.to_csv('results/Monomeric/Monomer_comp_results_MDCK.csv')
prediction_df.to_csv('results/Monomeric/Monomer_comp_prediction_data_MDCK.csv')

In [5]:
#Removal of constant columns
def remove_constant_columns(df):
    constant_columns = [col for col in df.columns if df[col].nunique() <= 1]
    
    df_cleaned = df.drop(columns=constant_columns)
    
    return df_cleaned, constant_columns

In [13]:
df_mc_train = pd.read_csv('features/Monomeric/Train_mon_comp_MDCK.csv')
df_mc_train = clean_feature_names(df_mc_train)
df_mc_train, const_col = remove_constant_columns(df_mc_train)
X_train = df_mc_train.drop(['ID','SMILES','Permeability'], axis=1)
y_train = df_mc_train['Permeability']
print(X_train.shape)
print(y_train.shape)
df_mc_test = pd.read_csv('features/Monomeric/Test_mon_comp_MDCK.csv')
df_mc_test = clean_feature_names(df_mc_test)
X_test = df_mc_test.drop(['ID','SMILES','Permeability'], axis=1)
X_test = X_test.drop(const_col, axis=1)
y_test = df_mc_test['Permeability']
print(X_test.shape)
print(y_test.shape)
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    xgb.XGBRegressor(random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    SVR(),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3), 
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

(51, 33)
(51,)
(13, 33)
(13,)
0.2999025104491113
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000010 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 6
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 1
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No fu

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-1.2748725696629006


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
ExtraTreesRegressor                      0.7537                0.5905   
LGBMRegressor                            0.6446                0.6796   
XGBRegressor                             0.8507                0.6431   
DecisionTreeRegressor                    0.8154                0.6095   
RandomForestRegressor                    0.6376                0.6071   
GradientBoostingRegressor                0.8067                0.6449   
AdaBoostRegressor                        0.7124                0.6660   
SVR                                      0.7202                0.6786   
LinearRegression                         1.1792                0.8393   
KNeighborsRegressor                      0.8570                0.7338   
MLPRegressor                             2.3698                1.2343   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
ExtraTreesRegressor                       0.8682              -0.1651   
LGBMRegressor                             0.8028               0.0036   
XGBRegressor                              0.9224              -0.3151   
DecisionTreeRegressor                     0.9030              -0.2606   
RandomForestRegressor                     0.7985               0.0143   
GradientBoostingRegressor                 0.8982              -0.2470   
AdaBoostRegressor                         0.8440              -0.1012   
SVR                                       0.8487              -0.1134   
LinearRegression                          1.0859              -0.8229   
KNeighborsRegressor                       0.9258              -0.3249   
MLPRegressor                              1.5394              -2.6633   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
ExtraTreesRegressor                      0.2344                0.3590   
LGBMRegressor                            0.1308                0.1395   
XGBRegressor                             0.2721                0.3560   
DecisionTreeRegressor                    0.2759                0.3843   
RandomForestRegressor                    0.2657                0.3357   
GradientBoostingRegressor                0.1782                0.2606   
AdaBoostRegressor                        0.1452                0.1895   
SVR                                      0.0478               -0.0587   
LinearRegression                         0.1790                0.2027   
KNeighborsRegressor                      0.1005                0.1947   
MLPRegressor                            -0.0496                0.0337   

                          Test MSE Test MAE Test RMSE  Test R2  \
ExtraTreesRegressor         0.4118   0.5214    0.6417   0.2999   
LGBMRegressor               0.5276   0.5751    0.7263   0.1031   
XGBRegressor                0.3258   0.4432    0.5708   0.4462   
DecisionTreeRegressor       0.4612   0.5201    0.6791   0.2160   
RandomForestRegressor       0.3200   0.4941    0.5657   0.4560   
GradientBoostingRegressor   0.3139   0.4470    0.5602   0.4664   
AdaBoostRegressor           0.2491   0.4436    0.4991   0.5766   
SVR                         0.3813   0.5052    0.6175   0.3518   
LinearRegression            0.5803   0.5368    0.7618   0.0134   
KNeighborsRegressor         0.3572   0.4786    0.5976   0.3928   
MLPRegressor                1.3381   0.9074    1.1568  -1.2749   

                          Test Pearson Correlation Test Spearman Correlation  
ExtraTreesRegressor                         0.6024                    0.2865  
LGBMRegressor                               0.4182                    0.3245  
XGBRegressor                                0.7110                    0.4628  
DecisionTreeRegressor                       0.5814                    0.3636  
RandomForestRegressor                       0.6792                    0.4187  
GradientBoostingRegressor                   0.6983                    0.4628  
AdaBoostRegressor                           0.770

In [14]:
prediction_df

Model  \
0         ExtraTreesRegressor   
1               LGBMRegressor   
2                XGBRegressor   
3       DecisionTreeRegressor   
4       RandomForestRegressor   
5   GradientBoostingRegressor   
6           AdaBoostRegressor   
7                         SVR   
8            LinearRegression   
9         KNeighborsRegressor   
10               MLPRegressor   

                                         Y Train pred  \
0   [-6.043058404850012, -6.858800000000014, -5.61...   
1   [-5.72429500042461, -5.781901428122076, -5.781...   
2   [-6.2183466, -7.569528, -5.4499307, -5.596678,...   
3   [-5.22, -6.97, -5.93, -5.22, -6.929917083, -5....   
4   [-5.789949056884673, -6.3782637986, -5.7064473...   
5   [-6.01954291884001, -6.896882968962064, -5.848...   
6   [-5.732601341625002, -6.826250000000001, -5.68...   
7   [-5.693891238094307, -5.654130024953056, -5.74...   
8   [-4.126989483536487, -4.717425534753501, -6.53...   
9   [-5.1866666666666665, -6.07, -6.07, -6.0404790...   
10  [-4.0, -6.5949980817752, -6.1962831998406545, ...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.827461524290002, -5.842012402510005, -5.6...   
1   [[-5.72429500042461, -5.72429500042461, -5.781...   
2   [[-5.985038, -5.706633, -6.759508, -6.9262185,...   
3   [[-5.295, -5.22, -6.85, -6.927245587, -5.22, -...   
4   [[-5.726976346974669, -5.602294175914672, -5.9...   
5   [[-5.871766622783936, -5.6245522063437186, -6....   
6   [[-5.664027293571428, -5.5025569934375005, -5....   
7   [[-5.6666614021657615, -5.7015941795430045, -5...   
8   [[-4.0, -4.0, -6.272531131732463, -6.922973078...   
9   [[-5.613333333333333, -5.2783009283333335, -5....   
10  [[-4.601746194505385, -4.0, -4.0, -6.925573038...   

                                Test Predictions Mean  \
0   [-5.710546744568001, -5.608915493959001, -5.95...   
1   [-5.508673793612709, -5.508673793612709, -5.62...   
2   [-5.8299103, -5.498244, -6.1002665, -6.6718307...   
3   [-5.804, -5.3859667324, -6.384, -6.6710733941,...   
4   [-5.6589558541721345, -5.500899846052269, -5.8...   
5   [-5.656593247102809, -5.426784452298417, -5.91...   
6   [-5.633116740219047, -5.646040413013983, -5.85...   
7   [-5.531588059386451, -5.693262986683411, -5.46...   
8   [-4.0, -5.632525333476573, -5.828073967233261,...   
9   [-5.528666666666667, -5.258158495866667, -4.96...   
10  [-4.539578993672536, -5.722590262446076, -4.04...   

                                 Test Predictions Std  
0   [0.3906250531695762, 0.12201030103337158, 0.24...  
1   [0.1956217934002597, 0.1956217934002597, 0.192...  
2   [0.43846768, 0.26189202, 0.6996025, 0.5103311,...  
3   [0.4317105511798386, 0.24822520835348863, 0.79...  
4   [0.11596493811230052, 0.07139148305302195, 0.2...  
5   [0.254960206681533, 0.12943965011407715, 0.440...  
6   [0.1488838914294579, 0.15159057733235587, 0.52...  
7   [0.14780058278796937, 0.02969453085614056, 0.0...  
8   [0.0, 1.0051831044888169, 0.8372471943942058, ...  
9   [0.1545689346393881, 0.0726709195073452, 0.137...  
10  [0.4817912837962266, 0.8753864270158885, 0.098...

In [15]:
const_col

['Ala_tBu_',
 'Ala_indol_2_yl_',
 'dAla_indol_2_yl_',
 'Me_Ala_indol_2_yl_',
 'Ala_5_Tet_',
 'Me_dAbu',
 'Me_Abu_morpholino_',
 '2Abz',
 'Aib',
 'Aoc_2_',
 '5_Ava',
 'Bal',
 'Me_Bal',
 'HOCOCH2_Bal',
 'Cys_EtO2H__NH2',
 'dCha',
 'Me_Cha',
 'D',
 'meD',
 'Asp_piperidide',
 'Asp_OMe_',
 'Asp_Ph_2_NH2__',
 'dAsp_pyrrol_1_yl_',
 'E',
 'Glu_NH2',
 'Glu_3R_Me_',
 'Glu_OMe_',
 'dGlu_OMe_',
 'Phe_4_F_',
 'dPhe_4_F_',
 'Phe_4_CF3_',
 'Phe_4_NO2_',
 'Phe_CHF2_',
 'dPhe_3_4_diF_',
 'Et_Phe',
 'H2NEt_Phe',
 'Me_Phe_3_Cl_',
 'Me_Phe_4_Cl_',
 'Me_Phe_a_b_dehydro_',
 'G',
 'Bn_Gly',
 'Bn_4_Cl__Gly',
 'Bn_4_OH__Gly',
 'Bu_Gly',
 'EtOEt_Gly',
 'HOCOCH2_Gly_ol',
 'MeOEt_Gly',
 'NH2Bu_Gly',
 'PhEt_Gly',
 'PhPr_Gly',
 'isoamyl_Gly',
 'pentyl_Gly',
 '3_pyridylethyl_Gly',
 '2_pyridylmethyl_Gly',
 'd_N__O_Gly_allyl_',
 'GABA',
 'H',
 'Hph',
 'Me_Hph',
 'bHph',
 'Hph_2_Cl_',
 'Hph_3_Cl_',
 'Hph_4_Cl_',
 'Hse_Et_',
 'dHyp',
 'Hyp_Et_',
 'dI',
 'meI',
 'Me_dI',
 '_N__O_xiIle',
 'd_N__O_aIle',
 'K',
 'dK',
 'meK

In [16]:
result_df.to_csv('results/Monomeric/Monomer_comp_constRemoval_results_MDCK.csv')
prediction_df.to_csv('results/Monomeric/Monomer_comp_constRemoval_prediction_data_MDCK.csv')

In [6]:
#Low variance column removal
def remove_low_variance_columns(df, threshold=0.005):
    # df = df.drop(['ID','SMILES','Permeability'],axis=1)
    variances = df.var()
    
    low_variance_columns = variances[variances < threshold].index.tolist()
    
    df_cleaned = df.drop(columns=low_variance_columns)
    
    return df_cleaned, low_variance_columns

In [18]:
df_train = pd.read_csv('features/Monomeric/Train_mon_comp_MDCK.csv')
df_mc_train = clean_feature_names(df_train)
df_mc_train = df_mc_train.drop(['ID','SMILES','Permeability'],axis=1)
df_mc, const_col = remove_low_variance_columns(df_mc_train)
X_train = df_mc
y_train = df_train['Permeability']
print(X_train.shape)
print(y_train.shape)

df_mc_test = pd.read_csv('features/Monomeric/Test_mon_comp_MDCK.csv')
df_mc_test = clean_feature_names(df_mc_test)
X_test = df_mc_test.drop(['ID','SMILES','Permeability'], axis=1)
X_test = X_test.drop(const_col, axis=1)
y_test = df_mc_test['Permeability']
print(X_test.shape)
print(y_test.shape)
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    xgb.XGBRegressor(random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    SVR(),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3), 
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

(51, 7)
(51,)
(13, 7)
(13,)
0.3807880935153942
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000016 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 6
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 1
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warni

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-1.377499296426219


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
ExtraTreesRegressor                      0.7330                0.6004   
LGBMRegressor                            0.6446                0.6796   
XGBRegressor                             0.8510                0.6477   
DecisionTreeRegressor                    0.9274                0.6765   
RandomForestRegressor                    0.6588                0.6228   
GradientBoostingRegressor                0.7493                0.6204   
AdaBoostRegressor                        0.7706                0.6881   
SVR                                      0.7647                0.6556   
LinearRegression                         0.7019                0.6858   
KNeighborsRegressor                      0.8033                0.7184   
MLPRegressor                             1.4697                0.9222   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
ExtraTreesRegressor                       0.8562              -0.1331   
LGBMRegressor                             0.8028               0.0036   
XGBRegressor                              0.9225              -0.3155   
DecisionTreeRegressor                     0.9630              -0.4336   
RandomForestRegressor                     0.8116              -0.0184   
GradientBoostingRegressor                 0.8656              -0.1583   
AdaBoostRegressor                         0.8778              -0.1912   
SVR                                       0.8745              -0.1822   
LinearRegression                          0.8378              -0.0850   
KNeighborsRegressor                       0.8963              -0.2418   
MLPRegressor                              1.2123              -1.2719   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
ExtraTreesRegressor                      0.2581                0.3520   
LGBMRegressor                            0.1308                0.1395   
XGBRegressor                             0.2543                0.2836   
DecisionTreeRegressor                    0.1762                0.2434   
RandomForestRegressor                    0.2437                0.2863   
GradientBoostingRegressor                0.2217                0.2691   
AdaBoostRegressor                        0.0359                0.0470   
SVR                                      0.0480                0.1248   
LinearRegression                         0.1833                0.1044   
KNeighborsRegressor                     -0.0628               -0.0163   
MLPRegressor                             0.0444                0.0818   

                          Test MSE Test MAE Test RMSE  Test R2  \
ExtraTreesRegressor         0.3642   0.4812    0.6035   0.3808   
LGBMRegressor               0.5276   0.5751    0.7263   0.1031   
XGBRegressor                0.2849   0.4069    0.5338   0.5156   
DecisionTreeRegressor       0.3480   0.4894    0.5899   0.4084   
RandomForestRegressor       0.3054   0.4776    0.5527   0.4808   
GradientBoostingRegressor   0.3581   0.5027    0.5984   0.3912   
AdaBoostRegressor           0.2600   0.4420    0.5099   0.5580   
SVR                         0.4922   0.5599    0.7016   0.1632   
LinearRegression            0.4294   0.5007    0.6553   0.2700   
KNeighborsRegressor         0.5373   0.6093    0.7330   0.0866   
MLPRegressor                1.3985   0.8720    1.1826  -1.3775   

                          Test Pearson Correlation Test Spearman Correlation  
ExtraTreesRegressor                         0.6495                    0.4662  
LGBMRegressor                               0.4182                    0.3245  
XGBRegressor                                0.7517                    0.5655  
DecisionTreeRegressor                       0.6746                    0.5048  
RandomForestRegressor                       0.6955                    0.5600  
GradientBoostingRegressor                   0.6624                    0.4662  
AdaBoostRegressor                           0.753

In [19]:
prediction_df

Model  \
0         ExtraTreesRegressor   
1               LGBMRegressor   
2                XGBRegressor   
3       DecisionTreeRegressor   
4       RandomForestRegressor   
5   GradientBoostingRegressor   
6           AdaBoostRegressor   
7                         SVR   
8            LinearRegression   
9         KNeighborsRegressor   
10               MLPRegressor   

                                         Y Train pred  \
0   [-6.220000000000016, -6.733600000000011, -5.67...   
1   [-5.72429500042461, -5.781901428122076, -5.781...   
2   [-6.218839, -6.9695864, -5.9245267, -5.540827,...   
3   [-6.22, -6.97, -5.93, -5.5406878929999985, -6....   
4   [-5.981101583799694, -6.357333925255005, -5.77...   
5   [-5.957345547511532, -6.681787871239538, -6.03...   
6   [-5.612922772666667, -6.1899999999999995, -5.8...   
7   [-5.790601714892611, -6.346966090150607, -5.82...   
8   [-5.146109898623878, -6.299279317299723, -5.97...   
9   [-5.691405793666665, -6.293333333333333, -5.86...   
10  [-5.912940343801409, -6.851067367617211, -6.35...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-6.220000000000016, -6.129689426090013, -5.5...   
1   [[-5.72429500042461, -5.72429500042461, -5.781...   
2   [[-6.218839, -5.885452, -6.576931, -6.7478294,...   
3   [[-6.22, -5.5406878929999985, -6.06, -6.748412...   
4   [[-5.981101583799692, -5.9044673180604335, -5....   
5   [[-5.957345547511532, -5.896933982419868, -5.5...   
6   [[-5.612922772666667, -5.612922772666667, -5.7...   
7   [[-5.790601714892611, -5.99114964406607, -5.68...   
8   [[-5.146109898623878, -5.038286352092517, -5.8...   
9   [[-5.691405793666665, -5.691405793666665, -5.3...   
10  [[-5.912940343801409, -8.299198944602646, -5.0...   

                                Test Predictions Mean  \
0   [-6.019999999999998, -5.871163893482627, -5.86...   
1   [-5.508673793612709, -5.508673793612709, -5.62...   
2   [-6.019603, -5.778534, -6.264598, -6.5054007, ...   
3   [-6.02, -5.7864103901199995, -5.592, -6.505002...   
4   [-5.908064044092657, -5.75531720488374, -5.993...   
5   [-5.897891961686751, -5.790969423295177, -5.57...   
6   [-5.617266178315978, -5.6086070870843105, -5.8...   
7   [-5.734015775011687, -5.756433936050504, -5.53...   
8   [-5.199828524003662, -5.126777978281019, -6.14...   
9   [-5.7596246898, -5.7596246898, -5.308666666666...   
10  [-5.764426322846368, -7.757908668479388, -5.17...   

                                 Test Predictions Std  
0   [0.12649110640673977, 0.1526077768687823, 0.36...  
1   [0.1956217934002597, 0.1956217934002597, 0.192...  
2   [0.12594935, 0.23116368, 0.9168826, 0.48475742...  
3   [0.126491106406735, 0.2171104101154356, 0.4400...  
4   [0.10046023128790825, 0.10967448772312777, 0.4...  
5   [0.07287761692143958, 0.1132398759357142, 0.53...  
6   [0.061062592201174014, 0.05490751298716359, 0....  
7   [0.02829382771721455, 0.12837677657045846, 0.1...  
8   [0.0916506680229044, 0.18610857810771805, 0.26...  
9   [0.1003320012147988, 0.1003320012147988, 0.089...  
10  [0.17680832663450227, 0.39570386343612035, 0.2...

In [20]:
result_df.to_csv('results/Monomeric/Monomer_comp_LVR_results_MDCK.csv')
prediction_df.to_csv('results/Monomeric/Monomer_comp_LVR_prediction_data_MDCK.csv')

In [21]:
#AA composition
df_aac_train = pd.read_csv('features/Monomeric/Train_aac_MDCK.csv')
X_train = df_aac_train.drop(['ID','SMILES','Permeability'], axis=1)
y_train = df_aac_train['Permeability']
print(X_train.shape)
print(y_train.shape)
df_aac_test = pd.read_csv('features/Monomeric/Test_aac_MDCK.csv')
X_test = df_aac_test.drop(['ID','SMILES','Permeability'], axis=1)
y_test = df_aac_test['Permeability']
print(X_test.shape)
print(y_test.shape)
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    xgb.XGBRegressor(random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    SVR(),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3), 
    MLPRegressor(random_state=101)
]
aac_comp,prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
aac_comp

(51, 21)
(51,)
(13, 21)
(13,)
0.14535106206428194
[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 0
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training 

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-1.1766483032998134


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
ExtraTreesRegressor                      0.9105                0.7913   
LGBMRegressor                            0.7103                0.6855   
XGBRegressor                             0.8803                0.7819   
DecisionTreeRegressor                    0.8846                0.7892   
RandomForestRegressor                    0.7994                0.7403   
GradientBoostingRegressor                0.8959                0.7802   
AdaBoostRegressor                        0.6927                0.6829   
SVR                                      0.7771                0.7354   
LinearRegression                         0.6729                0.6570   
KNeighborsRegressor                      0.8517                0.7793   
MLPRegressor                             1.0649                0.8347   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
ExtraTreesRegressor                       0.9542              -0.4075   
LGBMRegressor                             0.8428              -0.0980   
XGBRegressor                              0.9382              -0.3608   
DecisionTreeRegressor                     0.9405              -0.3674   
RandomForestRegressor                     0.8941              -0.2358   
GradientBoostingRegressor                 0.9465              -0.3850   
AdaBoostRegressor                         0.8323              -0.0708   
SVR                                       0.8815              -0.2013   
LinearRegression                          0.8203              -0.0401   
KNeighborsRegressor                       0.9229              -0.3166   
MLPRegressor                              1.0319              -0.6461   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
ExtraTreesRegressor                      0.0662                0.0958   
LGBMRegressor                           -0.0872               -0.0382   
XGBRegressor                             0.1149                0.1300   
DecisionTreeRegressor                    0.1210                0.1529   
RandomForestRegressor                    0.1161                0.1597   
GradientBoostingRegressor                0.0762                0.1065   
AdaBoostRegressor                        0.2134                0.1629   
SVR                                     -0.0179                0.0463   
LinearRegression                         0.2564                0.2745   
KNeighborsRegressor                      0.0841                0.1587   
MLPRegressor                             0.1772                0.1084   

                          Test MSE Test MAE Test RMSE  Test R2  \
ExtraTreesRegressor         0.5027   0.6301    0.7090   0.1454   
LGBMRegressor               0.5616   0.6033    0.7494   0.0453   
XGBRegressor                0.5710   0.6658    0.7557   0.0292   
DecisionTreeRegressor       0.5861   0.6714    0.7656   0.0036   
RandomForestRegressor       0.4479   0.5874    0.6692   0.2386   
GradientBoostingRegressor   0.4825   0.6189    0.6947   0.1797   
AdaBoostRegressor           0.4370   0.5747    0.6610   0.2571   
SVR                         0.5337   0.5730    0.7306   0.0927   
LinearRegression            0.5771   0.6134    0.7597   0.0188   
KNeighborsRegressor         0.6329   0.6084    0.7955  -0.0759   
MLPRegressor                1.2804   0.8772    1.1315  -1.1766   

                          Test Pearson Correlation Test Spearman Correlation  
ExtraTreesRegressor                         0.4367                    0.1710  
LGBMRegressor                               0.2513                    0.2733  
XGBRegressor                                0.3601                    0.1710  
DecisionTreeRegressor                       0.3416                    0.1186  
RandomForestRegressor                       0.5065                    0.2152  
GradientBoostingRegressor                   0.4651                    0.2538  
AdaBoostRegressor                           0.512

In [22]:
prediction_df

Model  \
0         ExtraTreesRegressor   
1               LGBMRegressor   
2                XGBRegressor   
3       DecisionTreeRegressor   
4       RandomForestRegressor   
5   GradientBoostingRegressor   
6           AdaBoostRegressor   
7                         SVR   
8            LinearRegression   
9         KNeighborsRegressor   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.2950000000000035, -6.221999999999991, -6.2...   
1   [-5.753098213672638, -5.753098213672638, -5.75...   
2   [-5.29548, -6.2220545, -6.2220545, -6.0047245,...   
3   [-5.295, -6.2219999999999995, -6.2219999999999...   
4   [-5.368503426139999, -6.193135364357863, -6.19...   
5   [-5.346659526734528, -6.216450432194516, -6.21...   
6   [-5.592, -6.054603827840001, -6.05460382784000...   
7   [-5.413858664579116, -5.82956840885068, -5.829...   
8   [-5.375994735925552, -6.2219999999999995, -6.2...   
9   [-5.183333333333334, -5.786666666666666, -5.78...   
10  [-4.325230941368543, -6.160026946023642, -6.16...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.366350000000006, -6.25, -5.29500000000000...   
1   [[-5.753098213672638, -5.753098213672638, -5.7...   
2   [[-4.7313776, -6.24856, -5.29548, -6.9255056, ...   
3   [[-4.61, -6.25, -5.295, -6.927245587, -5.45349...   
4   [[-5.130029644703837, -5.868885041386251, -5.3...   
5   [[-4.670062194839065, -6.199897901570898, -5.3...   
6   [[-4.778333333333333, -5.830838848000001, -5.5...   
7   [[-5.363969723180899, -5.932967024967623, -5.4...   
8   [[-4.759507417751967, -5.229049185524878, -5.3...   
9   [[-5.319999999999999, -5.503333333333333, -5.1...   
10  [[-4.197642350309595, -4.036831941767715, -4.3...   

                                Test Predictions Mean  \
0   [-5.17693135088315, -6.022842056844859, -5.470...   
1   [-5.551464208338411, -5.661144897664251, -5.55...   
2   [-4.87979, -6.0119925, -5.4701047, -6.6387153,...   
3   [-4.8556, -6.038, -5.470000000000001, -6.64376...   
4   [-5.250813480455994, -5.726103386135561, -5.50...   
5   [-5.224380017202935, -5.946667124709225, -5.48...   
6   [-5.156329494904314, -5.6220478939843135, -5.5...   
7   [-5.239878595545685, -5.758998418057883, -5.44...   
8   [-4.594681909532405, -5.083414903889928, -5.40...   
9   [-5.101333333333333, -5.472, -5.368, -6.240415...   
10  [-4.133178910408494, -4.065319902381349, -4.63...   

                                 Test Predictions Std  
0   [0.3538069070444989, 0.4543158863102818, 0.147...  
1   [0.14966825667694483, 0.07209968741488275, 0.1...  
2   [0.3947066, 0.47240928, 0.14748119, 0.5733854,...  
3   [0.4911999999999996, 0.4239999999999998, 0.147...  
4   [0.20369569259445852, 0.2784406428026411, 0.12...  
5   [0.4669255230923063, 0.5513825208708881, 0.137...  
6   [0.39867371132640117, 0.33264565920264694, 0.2...  
7   [0.14297492202777257, 0.3118904242653825, 0.14...  
8   [0.24062890175128807, 0.2421002251172405, 0.04...  
9   [0.20126930549225178, 0.18465102220134053, 0.1...  
10  [0.11019459649955715, 0.076217074601495, 0.189...

In [23]:
aac_comp.to_csv('results/Monomeric/AAC_comp_results_MDCK.csv')
prediction_df.to_csv('results/Monomeric/AAC_comp_prediction_data_MDCK.csv')

In [24]:
#Constant column removal
df_mc_train = pd.read_csv('features/Monomeric/Train_aac_MDCK.csv')
df_mc_train, const_col = remove_constant_columns(df_mc_train)
X_train = df_mc_train.drop(['ID','SMILES','Permeability'], axis=1)
y_train = df_mc_train['Permeability']
print(X_train.shape)
print(y_train.shape)
df_mc_test = pd.read_csv('features/Monomeric/Test_aac_MDCK.csv')
X_test = df_mc_test.drop(['ID','SMILES','Permeability'], axis=1)
X_test = X_test.drop(const_col, axis=1)
y_test = df_mc_test['Permeability']
print(X_test.shape)
print(y_test.shape)
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models_mc = [
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    xgb.XGBRegressor(random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    SVR(),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3), 
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models_mc, X_train,y_train, X_test,  y_test)
result_df

(51, 11)
(51,)
(13, 11)
(13,)
0.12519451244472146
[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 0
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training 

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-1.0883109453369375


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
ExtraTreesRegressor                      0.9191                0.8004   
LGBMRegressor                            0.7103                0.6855   
XGBRegressor                             0.8803                0.7819   
DecisionTreeRegressor                    0.8935                0.7805   
RandomForestRegressor                    0.7929                0.7376   
GradientBoostingRegressor                0.8990                0.7823   
AdaBoostRegressor                        0.6846                0.6823   
SVR                                      0.7771                0.7354   
LinearRegression                         0.6729                0.6570   
KNeighborsRegressor                      0.8517                0.7793   
MLPRegressor                             1.1704                0.8805   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
ExtraTreesRegressor                       0.9587              -0.4208   
LGBMRegressor                             0.8428              -0.0980   
XGBRegressor                              0.9382              -0.3608   
DecisionTreeRegressor                     0.9453              -0.3813   
RandomForestRegressor                     0.8905              -0.2257   
GradientBoostingRegressor                 0.9482              -0.3897   
AdaBoostRegressor                         0.8274              -0.0583   
SVR                                       0.8815              -0.2013   
LinearRegression                          0.8203              -0.0401   
KNeighborsRegressor                       0.9229              -0.3166   
MLPRegressor                              1.0818              -0.8092   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
ExtraTreesRegressor                      0.0563                0.0858   
LGBMRegressor                           -0.0872               -0.0382   
XGBRegressor                             0.1149                0.1300   
DecisionTreeRegressor                    0.0810                0.1225   
RandomForestRegressor                    0.1219                0.1717   
GradientBoostingRegressor                0.0738                0.1135   
AdaBoostRegressor                        0.2317                0.1776   
SVR                                     -0.0179                0.0463   
LinearRegression                         0.2564                0.2745   
KNeighborsRegressor                      0.0841                0.1607   
MLPRegressor                             0.1314                0.0815   

                          Test MSE Test MAE Test RMSE  Test R2  \
ExtraTreesRegressor         0.5146   0.6357    0.7173   0.1252   
LGBMRegressor               0.5616   0.6033    0.7494   0.0453   
XGBRegressor                0.5710   0.6658    0.7557   0.0292   
DecisionTreeRegressor       0.6123   0.6824    0.7825  -0.0409   
RandomForestRegressor       0.4580   0.5959    0.6767   0.2214   
GradientBoostingRegressor   0.4839   0.6198    0.6956   0.1774   
AdaBoostRegressor           0.4010   0.5536    0.6333   0.3183   
SVR                         0.5337   0.5729    0.7305   0.0928   
LinearRegression            0.5771   0.6134    0.7597   0.0188   
KNeighborsRegressor         0.6329   0.6084    0.7955  -0.0759   
MLPRegressor                1.2284   0.8400    1.1083  -1.0883   

                          Test Pearson Correlation Test Spearman Correlation  
ExtraTreesRegressor                         0.4230                    0.1710  
LGBMRegressor                               0.2513                    0.2733  
XGBRegressor                                0.3601                    0.1710  
DecisionTreeRegressor                       0.3195                    0.0662  
RandomForestRegressor                       0.4893                    0.2152  
GradientBoostingRegressor                   0.4639                    0.2538  
AdaBoostRegressor                           0.564

In [25]:
prediction_df

Model  \
0         ExtraTreesRegressor   
1               LGBMRegressor   
2                XGBRegressor   
3       DecisionTreeRegressor   
4       RandomForestRegressor   
5   GradientBoostingRegressor   
6           AdaBoostRegressor   
7                         SVR   
8            LinearRegression   
9         KNeighborsRegressor   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.2950000000000035, -6.221999999999991, -6.2...   
1   [-5.753098213672638, -5.753098213672638, -5.75...   
2   [-5.29548, -6.2220545, -6.2220545, -6.0047245,...   
3   [-5.295, -6.2219999999999995, -6.2219999999999...   
4   [-5.378811377966667, -6.193135364357865, -6.19...   
5   [-5.346659526734528, -6.216450432194516, -6.21...   
6   [-5.639388053500001, -6.054603827840001, -6.05...   
7   [-5.41385908973807, -5.8295669306780855, -5.82...   
8   [-5.375994735925552, -6.2219999999999995, -6.2...   
9   [-5.183333333333334, -5.786666666666666, -5.78...   
10  [-4.6700622407938965, -6.174277012698101, -6.1...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.267200000000006, -6.25, -5.29500000000000...   
1   [[-5.753098213672638, -5.753098213672638, -5.7...   
2   [[-4.7313776, -6.24856, -5.29548, -6.9255056, ...   
3   [[-4.61, -6.25, -5.295, -6.927245587, -5.22, -...   
4   [[-5.151233314944576, -5.8698978409558356, -5....   
5   [[-4.673265557952084, -6.199897901570898, -5.3...   
6   [[-4.778333333333333, -5.798008666214286, -5.6...   
7   [[-5.363974989317022, -5.932975284667058, -5.4...   
8   [[-4.759507417751967, -5.229049185524878, -5.3...   
9   [[-5.319999999999999, -5.503333333333333, -5.1...   
10  [[-4.060258818775952, -4.006923195239289, -4.6...   

                                Test Predictions Mean  \
0   [-5.108304899434407, -6.007034036174002, -5.47...   
1   [-5.551464208338411, -5.661144897664251, -5.55...   
2   [-4.87979, -6.0119925, -5.4701047, -6.6387153,...   
3   [-4.7487342614, -6.038, -5.470000000000001, -6...   
4   [-5.21894731896135, -5.7283366737621835, -5.51...   
5   [-5.212882550149957, -5.932998463099878, -5.48...   
6   [-5.288716192270877, -5.687453808178583, -5.65...   
7   [-5.239930218648427, -5.759037921475825, -5.44...   
8   [-4.594681909532405, -5.083414903889928, -5.40...   
9   [-5.101333333333334, -5.472, -5.368, -6.240415...   
10  [-4.013515420125098, -4.011034842164758, -4.96...   

                                 Test Predictions Std  
0   [0.39648064298813945, 0.48593192765199694, 0.1...  
1   [0.14966825667694483, 0.07209968741488275, 0.1...  
2   [0.3947066, 0.47240928, 0.14748119, 0.5733854,...  
3   [0.27746852279999995, 0.4239999999999998, 0.14...  
4   [0.18159984983084346, 0.26673485448750067, 0.1...  
5   [0.4387149057116776, 0.5787140006464542, 0.137...  
6   [0.37632143239522436, 0.26006021173346516, 0.1...  
7   [0.14292461001976278, 0.31186830181873276, 0.1...  
8   [0.2406289017512884, 0.24210022511724086, 0.04...  
9   [0.20126930549225144, 0.18465102220134053, 0.1...  
10  [0.02354293772541056, 0.01880027887692886, 0.1...

In [26]:
result_df.to_csv('results/Monomeric/AAC_comp_const_rem_results_MDCK.csv')
prediction_df.to_csv('results/Monomeric/AAC_comp_const_rem_prediction_data_MDCK.csv')

In [27]:
#LVR column removal
df_mc_train = pd.read_csv('features/Monomeric/Train_aac_MDCK.csv')
X_train = df_mc_train.drop(['ID','SMILES','Permeability'], axis=1)
X_train, const_col = remove_low_variance_columns(X_train)

y_train = df_mc_train['Permeability']
print(X_train.shape)
print(y_train.shape)
df_mc_test = pd.read_csv('features/Monomeric/Test_aac_MDCK.csv')
X_test = df_mc_test.drop(['ID','SMILES','Permeability'], axis=1)
X_test = X_test.drop(const_col, axis=1)
y_test = df_mc_test['Permeability']
print(X_test.shape)
print(y_test.shape)
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models_mc = [
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    xgb.XGBRegressor(random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    SVR(),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3), 
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models_mc, X_train,y_train, X_test,  y_test)
result_df

(51, 5)
(51,)
(13, 5)
(13,)
0.15769216486706372
[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 0
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training be

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-1.8365009629725537


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
ExtraTreesRegressor                      0.8601                0.7564   
LGBMRegressor                            0.7142                0.6874   
XGBRegressor                             0.8357                0.7519   
DecisionTreeRegressor                    0.8939                0.7768   
RandomForestRegressor                    0.7738                0.7153   
GradientBoostingRegressor                0.8658                0.7665   
AdaBoostRegressor                        0.6420                0.6607   
SVR                                      0.7514                0.6959   
LinearRegression                         0.6437                0.6500   
KNeighborsRegressor                      0.7370                0.6871   
MLPRegressor                             2.2385                1.2235   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
ExtraTreesRegressor                       0.9274              -0.3296   
LGBMRegressor                             0.8451              -0.1040   
XGBRegressor                              0.9142              -0.2919   
DecisionTreeRegressor                     0.9455              -0.3819   
RandomForestRegressor                     0.8797              -0.1962   
GradientBoostingRegressor                 0.9305              -0.3384   
AdaBoostRegressor                         0.8013               0.0076   
SVR                                       0.8668              -0.1615   
LinearRegression                          0.8023               0.0049   
KNeighborsRegressor                       0.8585              -0.1393   
MLPRegressor                              1.4961              -2.4603   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
ExtraTreesRegressor                      0.0965                0.1326   
LGBMRegressor                           -0.0961               -0.0057   
XGBRegressor                             0.1066                0.1575   
DecisionTreeRegressor                    0.0741                0.1111   
RandomForestRegressor                    0.1169                0.1626   
GradientBoostingRegressor                0.0702                0.0792   
AdaBoostRegressor                        0.2842                0.2180   
SVR                                      0.1108                0.1974   
LinearRegression                         0.2687                0.3193   
KNeighborsRegressor                      0.2059                0.2896   
MLPRegressor                             0.0751               -0.0283   

                          Test MSE Test MAE Test RMSE  Test R2  \
ExtraTreesRegressor         0.4955   0.6429    0.7039   0.1577   
LGBMRegressor               0.5734   0.6093    0.7572   0.0252   
XGBRegressor                0.5804   0.6872    0.7619   0.0133   
DecisionTreeRegressor       0.5442   0.6802    0.7377   0.0749   
RandomForestRegressor       0.4658   0.6137    0.6825   0.2081   
GradientBoostingRegressor   0.5154   0.6452    0.7179   0.1238   
AdaBoostRegressor           0.4010   0.5458    0.6333   0.3182   
SVR                         0.5653   0.5999    0.7519   0.0390   
LinearRegression            0.6587   0.6629    0.8116  -0.1199   
KNeighborsRegressor         0.6620   0.6279    0.8136  -0.1254   
MLPRegressor                1.6685   1.0622    1.2917  -1.8365   

                          Test Pearson Correlation Test Spearman Correlation  
ExtraTreesRegressor                         0.4428                    0.2317  
LGBMRegressor                               0.1643                    0.1981  
XGBRegressor                                0.3488                    0.1600  
DecisionTreeRegressor                       0.3795                    0.1600  
RandomForestRegressor                       0.4734                    0.1986  
GradientBoostingRegressor                   0.4243                    0.2648  
AdaBoostRegressor                           0.567

In [28]:
prediction_df

Model  \
0         ExtraTreesRegressor   
1               LGBMRegressor   
2                XGBRegressor   
3       DecisionTreeRegressor   
4       RandomForestRegressor   
5   GradientBoostingRegressor   
6           AdaBoostRegressor   
7                         SVR   
8            LinearRegression   
9         KNeighborsRegressor   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.2950000000000035, -6.221999999999991, -6.2...   
1   [-5.753098213672638, -5.753098213672638, -5.75...   
2   [-5.2943735, -6.2216816, -6.2216816, -5.882914...   
3   [-5.295, -6.2219999999999995, -6.2219999999999...   
4   [-5.357729213069999, -6.193135364357865, -6.19...   
5   [-5.280803795917586, -6.212501921859376, -6.21...   
6   [-5.416666666666667, -6.054603827840001, -6.05...   
7   [-5.1255559504553245, -5.430416887688733, -5.4...   
8   [-5.432670445883795, -5.81963513804729, -5.819...   
9   [-5.136666666666667, -5.786666666666666, -5.78...   
10  [-4.0, -5.404568118002157, -5.404568118002157,...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.493000000000006, -6.25, -5.29500000000000...   
1   [[-5.753098213672638, -5.753098213672638, -5.7...   
2   [[-4.7308993, -6.2486463, -5.2943735, -6.92498...   
3   [[-4.61, -6.25, -5.295, -6.927245587, -5.37858...   
4   [[-5.187422741160974, -5.930343215755667, -5.3...   
5   [[-4.395883403028521, -6.232020096947168, -5.2...   
6   [[-5.592013923733333, -5.592013923733333, -5.4...   
7   [[-5.482072747197859, -6.149482561085053, -5.1...   
8   [[-4.657723138447146, -5.031221947794083, -5.4...   
9   [[-5.319999999999999, -5.284768119, -5.1366666...   
10  [[-4.0, -4.0, -4.0, -5.334313646629317, -4.0, ...   

                                Test Predictions Mean  \
0   [-5.289147032051578, -6.01276316731743, -5.470...   
1   [-5.563857796772694, -5.688173775878739, -5.56...   
2   [-4.8916063, -6.0391207, -5.469754, -6.6509256...   
3   [-5.146, -6.038, -5.470000000000001, -6.645208...   
4   [-5.2584346971367015, -5.723190282761889, -5.5...   
5   [-5.128101961908328, -6.022487121988138, -5.45...   
6   [-5.2540714516027744, -5.600426497564314, -5.5...   
7   [-5.401018283756371, -5.959983045139651, -5.40...   
8   [-4.57083102201134, -4.937827834893946, -5.368...   
9   [-5.0920000000000005, -5.2613094257999995, -5....   
10  [-4.0, -4.0, -4.048170750693543, -5.3647748000...   

                                 Test Predictions Std  
0   [0.35837322109765557, 0.4744736653651401, 0.14...  
1   [0.15098156155020348, 0.09747574238919043, 0.1...  
2   [0.3361239, 0.41782245, 0.14764787, 0.54866576...  
3   [0.6364149589693817, 0.4239999999999998, 0.147...  
4   [0.18565477668203204, 0.2884345799868826, 0.11...  
5   [0.5787362440737861, 0.42978622984557263, 0.13...  
6   [0.36181938597529073, 0.12192205449916106, 0.1...  
7   [0.16916132598435032, 0.35717463096306273, 0.1...  
8   [0.26908157615036793, 0.2592305670934972, 0.07...  
9   [0.19610201426808416, 0.181834057691948, 0.136...  
10  [0.0, 0.0, 0.05963273635971064, 0.252128025495...

In [29]:
result_df.to_csv('results/Monomeric/AAC_comp_LVR_results_MDCK.csv')
prediction_df.to_csv('results/Monomeric/AAC_comp_LVR_prediction_data_MDCK.csv')

In [30]:
#Atomic models
df_train = pd.read_csv('features/Atomic/Train_all_atomic_desc_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Atomic/Test_all_atomic_desc_MDCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models_degree = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models_degree, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 23)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 23)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000054 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 10
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 1
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with 

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


0.21088004498339585


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6352                0.6581   
DecisionTreeRegressor                    0.9770                0.7465   
RandomForestRegressor                    0.7208                0.6718   
GradientBoostingRegressor                0.9244                0.7330   
AdaBoostRegressor                        0.6644                0.6473   
XGBRegressor                             0.9284                0.7406   
ExtraTreesRegressor                      0.8315                0.7196   
LinearRegression                         0.8011                0.6724   
KNeighborsRegressor                      0.6035                0.6162   
SVR                                      0.6565                0.6301   
MLPRegressor                             1.0003                0.7900   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7970               0.0180   
DecisionTreeRegressor                     0.9885              -0.5104   
RandomForestRegressor                     0.8490              -0.1142   
GradientBoostingRegressor                 0.9615              -0.4290   
AdaBoostRegressor                         0.8151              -0.0271   
XGBRegressor                              0.9635              -0.4351   
ExtraTreesRegressor                       0.9119              -0.2854   
LinearRegression                          0.8950              -0.2383   
KNeighborsRegressor                       0.7769               0.0670   
SVR                                       0.8102              -0.0148   
MLPRegressor                              1.0002              -0.5464   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2095                0.2556   
DecisionTreeRegressor                    0.1998                0.3301   
RandomForestRegressor                    0.2609                0.2915   
GradientBoostingRegressor                0.1934                0.3197   
AdaBoostRegressor                        0.3346                0.3994   
XGBRegressor                             0.2348                0.3847   
ExtraTreesRegressor                      0.2574                0.3662   
LinearRegression                         0.2747                0.3276   
KNeighborsRegressor                      0.4287                0.4489   
SVR                                      0.2482                0.1837   
MLPRegressor                             0.1627                0.1297   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.4738   0.5765    0.6883  0.1946   
DecisionTreeRegressor       0.5878   0.6842    0.7667  0.0007   
RandomForestRegressor       0.4523   0.6170    0.6725  0.2310   
GradientBoostingRegressor   0.4531   0.6099    0.6732  0.2297   
AdaBoostRegressor           0.4028   0.5815    0.6347  0.3153   
XGBRegressor                0.5276   0.6344    0.7264  0.1030   
ExtraTreesRegressor         0.4578   0.6145    0.6766  0.2217   
LinearRegression            0.3999   0.5440    0.6324  0.3201   
KNeighborsRegressor         0.4117   0.5695    0.6417  0.3000   
SVR                         0.3816   0.4913    0.6178  0.3512   
MLPRegressor                0.4642   0.5618    0.6813  0.2109   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4619                    0.3928  
DecisionTreeRegressor                       0.5665                    0.3503  
RandomForestRegressor                       0.5850                    0.2755  
GradientBoostingRegressor                   0.6410                    0.3691  
AdaBoostRegressor                           0.6216                    0.3471  
XGBRegressor                                0.5850                    0.2424  
ExtraTreesRegressor                         0.6482           

In [31]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.965745329504426, -5.965745329504426, -5.96...   
1   [-5.295, -5.195, -6.97, -6.929917083, -6.92991...   
2   [-5.363379999999999, -5.349524999999997, -6.50...   
3   [-5.302816986363614, -5.210833578301628, -6.92...   
4   [-5.295, -5.293333333333333, -6.61029337845454...   
5   [-5.295471, -5.195101, -6.968063, -6.9289513, ...   
6   [-5.2950000000000035, -5.194999999999996, -6.9...   
7   [-5.365590535765415, -6.1816013389543, -6.2457...   
8   [-5.613333333333333, -5.786666666666666, -5.78...   
9   [-5.5500601501148354, -5.702291087924101, -5.7...   
10  [-6.280898349733659, -6.2766122433291045, -6.1...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.965745329504426, -5.540451101521032, -5.5...   
1   [[-5.295, -6.25, -6.25, -6.927245587, -7.82, -...   
2   [[-5.349423333333333, -5.994491570946668, -6.0...   
3   [[-5.337353846375231, -6.228767526566608, -6.1...   
4   [[-5.295, -6.02614462275, -6.13, -6.7828334522...   
5   [[-5.3076005, -6.2483983, -5.9604754, -6.92772...   
6   [[-5.282550000000003, -6.25, -6.13724999999999...   
7   [[-5.229704550628526, -5.607117279972588, -5.6...   
8   [[-5.613333333333333, -5.613333333333333, -5.6...   
9   [[-5.49343417031825, -5.608575903802059, -5.64...   
10  [[-7.150332050788022, -5.530646303104944, -5.1...   

                                Test Predictions Mean  \
0   [-5.626978421003314, -5.367659698329064, -5.36...   
1   [-4.983, -6.093999999999999, -6.09399999999999...   
2   [-5.261993585553428, -5.916150197676856, -5.90...   
3   [-5.24919859948122, -6.075529405460093, -6.055...   
4   [-5.313476190476189, -5.818762229842382, -5.83...   
5   [-5.1549377, -6.093379, -5.9614635, -6.8631706...   
6   [-5.370626666666672, -6.0955400000000015, -6.0...   
7   [-5.343710306767623, -5.434628259905332, -5.66...   
8   [-5.6259999999999994, -5.666, -5.666, -6.43727...   
9   [-5.5997993801996415, -5.708491166221073, -5.7...   
10  [-6.929321723525808, -5.46817684268188, -5.139...   

                                 Test Predictions Std  
0   [0.1708394140073482, 0.21696786900259085, 0.21...  
1   [0.2459999999999998, 0.3120000000000001, 0.312...  
2   [0.09167580506668391, 0.21318781557600078, 0.2...  
3   [0.10527411802820809, 0.3144815147967797, 0.34...  
4   [0.21182479818169594, 0.21207596740944587, 0.2...  
5   [0.2368334, 0.31175116, 0.3512696, 0.12672764,...  
6   [0.17154458461610458, 0.30891999999999625, 0.3...  
7   [0.16200289293830036, 0.3257056247751279, 0.24...  
8   [0.16096100286853474, 0.14081350945290877, 0.1...  
9   [0.07210610503450504, 0.11201598713907131, 0.1...  
10  [0.2106860080211059, 0.20673004294856898, 0.20...

In [32]:
result_df.to_csv('results/Atomic/Results_all_atomic_desc_MDCK.csv')
prediction_df.to_csv('results/Atomic/Prediction_data_all_atomic_desc_MDCK.csv')

In [7]:
#Atomic + monomeric_composition based features
df1 = pd.read_csv('features/Monomeric/Train_mon_comp_MDCK.csv')
df2 = pd.read_csv('features/Atomic/Train_all_atomic_desc_MDCK.csv')
df_train = pd.merge(df1, df2, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_train

ID                                             SMILES  Permeability  \
0   1114  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -4.940000   
1   1113  CC(C)C[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@@H](Cc2...     -5.820000   
2   1117  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.650000   
3   1119  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.250000   
4   2428  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.350000   
5   2446  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -6.850000   
6   2445  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -5.270000   
7   2427  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -6.340000   
8   8145  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.569578   
9   1107  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -4.610000   
10  1116  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)N(C)C(=O)[C@H]2...     -5.220000   
11  1110  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...     -4.730000   
12  8121  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.927246   
13  5836  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -5.060000   
14  6187  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -5.010000   
15  6584  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.330000   
16  6571  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.100000   
17  5803  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -6.970000   
18  2422  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.630000   
19  2440  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -7.760000   
20  8140  CCC[C@H]1C(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=...     -5.453495   
21  8131  CCC[C@@H]1NC(=O)CN(CCC)C(=O)[C@H](CC(C)C)NC(=O...     -5.509834   
22  8346  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.672617   
23  8184  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.929917   
24  6505  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.930000   
25  8342  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -4.994304   
26  8160  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.167475   
27  8341  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.822199   
28  8344  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.241518   
29  8343  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.131653   
30  8156  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.178526   
31  8150  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.834862   
32  8152  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.105008   
33  8116  CCCN1CC(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=O)N...     -5.400722   
34  8128  CCCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=...     -5.793469   
35  8138  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.303671   
36  6666  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -7.820000   
37  1115  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.190000   
38  8126  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.983385   
39  8114  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.309384   
40  1111  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C...     -6.220000   
41  1109  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N(C)C(...     -6.120000   
42  1112  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](C)NC(=O)[...     -6.170000   
43  1018  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...     -4.500000   
44  1845  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.960000   
45  1847  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.740000   
46  1841  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.410000   
47  1017  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...     -6.550000   
48  1840  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.480000   
49  1844  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -5.100000   
50  1846  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.820000   

 

In [8]:
df1 = pd.read_csv('features/Monomeric/Test_mon_comp_MDCK.csv')
df2 = pd.read_csv('features/Atomic/Test_all_atomic_desc_MDCK.csv')
df_test = pd.merge(df1, df2, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_test

ID                                             SMILES  Permeability  \
0   1120  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.300000   
1   1118  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](Cc2...     -5.350000   
2   1121  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...     -6.200000   
3   8133  CCC[C@@H]1NC(=O)CN(CC)C(=O)[C@H](CC(C)C)NC(=O)...     -5.965681   
4   8143  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.676306   
5   8119  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.516110   
6   6496  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.060000   
7   8168  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(C)[C@...     -5.977700   
8   8345  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(CC(C)...     -6.342777   
9   6423  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)...     -7.210000   
10  1108  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -5.180000   
11  1843  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.400000   
12  1842  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.400000   

      A   dA       meA     Me_dA  Ala(tBu)  Ala(indol-2-yl)  dAla(indol-2-yl)  \
0   0.0  0.0  0.200000  0.000000       0.0              0.0               0.0   
1   0.0  0.0  0.400000  0.000000       0.0              0.0               0.0   
2   0.2  0.0  0.000000  0.000000       0.0              0.0               0.0   
3   0.0  0.0  0.222222  0.000000       0.0              0.0               0.0   
4   0.0  0.0  0.222222  0.000000       0.0              0.0               0.0   
5   0.0  0.0  0.222222  0.000000       0.0              0.0               0.0   
6   0.0  0.0  0.000000  0.100000       0.0              0.0               0.0   
7   0.0  0.0  0.111111  0.222222       0.0              0.0               0.0   
8   0.0  0.0  0.111111  0.222222       0.0              0.0               0.0   
9   0.1  0.0  0.000000  0.000000       0.0              0.0               0.0   
10  0.0  0.0  0.400000  0.200000       0.0              0.0               0.0   
11  0.0  0.0  0.000000  0.000000       0.0              0.0               0.0   
12  0.0  0.0  0.000000  0.000000       0.0              0.0               0.0   

    ...  Degree_S  Single  Double  Triple  Aromatic  Conjugated  No-bond  \
0   ...         0      66      10       0        12           0        0   
1   ...         0      60      10       0        12           0        0   
2   ...         0      60      10       0        12           0        0   
3   ...         2      64      10       0         0           0        0   
4   ...         2      62      10       0         0           0        0   
5   ...         2      61      10       0         0           0        0   
6   ...         0      63      10       0         0           0        0   
7   ...         2      59      10       0         0           0        0   
8   ...         2      59      10       0         0           0        0   
9   ...         0      62      10       0         0           0        0   
10  ...         0      58      10       0         0           0        0   
11  ...         0      38       6       0        12           0        0   
12  ...         0      40       6       0         6           0        0   

    Overall_Formal_Charge  Is_Aromatic  Is_In_Ring  
0                     102            1           1  
1                     102            1           1  
2                     102            1           1  
3                      94            0           1  
4                      95            0           1  
5                      94            0           1  
6                      92            0           1  
7                      94            0           1  
8                      94            0           1  
9                      92            0           1  
10                     90            0           1  
11                     67            1           1  
12                     61            1

In [7]:
import re
def clean_feature_names(df):
    def clean_name(name):
        return re.sub(r'[^a-zA-Z0-9_]', '_', name)

    df.columns = [clean_name(col) for col in df.columns]
    return df

In [8]:
#Removal of constant columns
def remove_constant_columns(df):
    constant_columns = [col for col in df.columns if df[col].nunique() <= 1]
    
    df_cleaned = df.drop(columns=constant_columns)
    
    return df_cleaned, constant_columns

In [11]:
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = clean_feature_names(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = clean_feature_names(X_test)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 408)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 408)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000027 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 16
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 2
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive 

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.6911929466188871


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.5925                0.6462   
DecisionTreeRegressor                    0.8452                0.6014   
RandomForestRegressor                    0.6196                0.6139   
GradientBoostingRegressor                0.7917                0.6344   
AdaBoostRegressor                        0.7316                0.6605   
XGBRegressor                             0.7512                0.6157   
ExtraTreesRegressor                      0.7052                0.6066   
LinearRegression                         5.6413                1.6446   
KNeighborsRegressor                      0.7792                0.6877   
SVR                                      0.7181                0.6804   
MLPRegressor                             2.2557                1.1844   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7697               0.0842   
DecisionTreeRegressor                     0.9193              -0.3065   
RandomForestRegressor                     0.7872               0.0422   
GradientBoostingRegressor                 0.8898              -0.2238   
AdaBoostRegressor                         0.8553              -0.1310   
XGBRegressor                              0.8667              -0.1613   
ExtraTreesRegressor                       0.8398              -0.0901   
LinearRegression                          2.3752              -7.7207   
KNeighborsRegressor                       0.8827              -0.2045   
SVR                                       0.8474              -0.1100   
MLPRegressor                              1.5019              -2.4870   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2978                0.3452   
DecisionTreeRegressor                    0.2377                0.3955   
RandomForestRegressor                    0.3374                0.3979   
GradientBoostingRegressor                0.2420                0.3260   
AdaBoostRegressor                        0.2356                0.3035   
XGBRegressor                             0.3252                0.3985   
ExtraTreesRegressor                      0.2956                0.3406   
LinearRegression                        -0.2651               -0.1591   
KNeighborsRegressor                      0.1884                0.2396   
SVR                                      0.0831                0.0334   
MLPRegressor                            -0.0639               -0.0356   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4601   0.5649    0.6783   0.2178   
DecisionTreeRegressor       0.4299   0.4963    0.6557   0.2691   
RandomForestRegressor       0.3423   0.4966    0.5851   0.4180   
GradientBoostingRegressor   0.4180   0.5022    0.6465   0.2893   
AdaBoostRegressor           0.3009   0.4951    0.5486   0.4884   
XGBRegressor                0.4873   0.5501    0.6981   0.1716   
ExtraTreesRegressor         0.4109   0.5239    0.6411   0.3014   
LinearRegression            1.7674   1.0058    1.3294  -2.0046   
KNeighborsRegressor         0.3100   0.4936    0.5568   0.4730   
SVR                         0.3605   0.4868    0.6004   0.3871   
MLPRegressor                0.9948   0.7896    0.9974  -0.6912   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4908                    0.4242  
DecisionTreeRegressor                       0.6696                    0.3691  
RandomForestRegressor                       0.6630                    0.4242  
GradientBoostingRegressor                   0.6244                    0.2920  
AdaBoostRegressor                           0.7113                    0.3802  
XGBRegressor                                0.6173                    0.3471  
ExtraTreesRegressor                         0.629

In [12]:
result_df.to_csv('results/Atomic/Results_all_atomic_desc_and_mono_comp_MDCK.csv')
prediction_df.to_csv('results/Atomic/Prediction_data_all_atomic_desc_and_mono_comp_MDCK.csv')

In [13]:
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = clean_feature_names(X_train)
X_train, const_col = remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = clean_feature_names(X_test)
X_test = X_test.drop(const_col,axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 44)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 44)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000008 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 16
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 2
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive ga

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.7336560360630215


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.5925                0.6462   
DecisionTreeRegressor                    0.9522                0.6424   
RandomForestRegressor                    0.6189                0.6175   
GradientBoostingRegressor                0.7879                0.6359   
AdaBoostRegressor                        0.6813                0.6507   
XGBRegressor                             0.7512                0.6157   
ExtraTreesRegressor                      0.7336                0.6193   
LinearRegression                         5.6413                1.6446   
KNeighborsRegressor                      0.7792                0.6877   
SVR                                      0.7181                0.6804   
MLPRegressor                             2.1056                1.1317   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7697               0.0842   
DecisionTreeRegressor                     0.9758              -0.4720   
RandomForestRegressor                     0.7867               0.0433   
GradientBoostingRegressor                 0.8877              -0.2180   
AdaBoostRegressor                         0.8254              -0.0532   
XGBRegressor                              0.8667              -0.1613   
ExtraTreesRegressor                       0.8565              -0.1340   
LinearRegression                          2.3752              -7.7207   
KNeighborsRegressor                       0.8827              -0.2045   
SVR                                       0.8474              -0.1100   
MLPRegressor                              1.4511              -2.2549   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2978                0.3452   
DecisionTreeRegressor                    0.1765                0.3146   
RandomForestRegressor                    0.3409                0.4012   
GradientBoostingRegressor                0.2486                0.3507   
AdaBoostRegressor                        0.2540                0.3129   
XGBRegressor                             0.3252                0.3985   
ExtraTreesRegressor                      0.2663                0.3221   
LinearRegression                        -0.2651               -0.1591   
KNeighborsRegressor                      0.1884                0.2396   
SVR                                      0.0831                0.0334   
MLPRegressor                            -0.0344                0.0522   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4601   0.5649    0.6783   0.2178   
DecisionTreeRegressor       0.4552   0.5058    0.6747   0.2261   
RandomForestRegressor       0.3385   0.4894    0.5818   0.4245   
GradientBoostingRegressor   0.4203   0.5029    0.6483   0.2855   
AdaBoostRegressor           0.2990   0.4981    0.5468   0.4917   
XGBRegressor                0.4873   0.5501    0.6981   0.1716   
ExtraTreesRegressor         0.4042   0.5173    0.6358   0.3128   
LinearRegression            1.7674   1.0058    1.3294  -2.0046   
KNeighborsRegressor         0.2925   0.4800    0.5409   0.5027   
SVR                         0.3605   0.4868    0.6004   0.3871   
MLPRegressor                1.0198   0.7129    1.0098  -0.7337   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4908                    0.4242  
DecisionTreeRegressor                       0.6500                    0.4298  
RandomForestRegressor                       0.6682                    0.4187  
GradientBoostingRegressor                   0.6237                    0.2975  
AdaBoostRegressor                           0.7164                    0.3967  
XGBRegressor                                0.6173                    0.3471  
ExtraTreesRegressor                         0.633

In [14]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.93773412153736, -5.983867338806448, -5.983...   
1   [-5.295, -6.97, -5.06, -6.927245587, -6.929917...   
2   [-5.199322852306668, -6.1032, -5.9719156004853...   
3   [-5.340313349521261, -5.875076441062632, -6.22...   
4   [-5.25, -6.112082641571429, -6.075085482266667...   
5   [-5.269669, -6.4541073, -5.929844, -5.891423, ...   
6   [-5.464314347820004, -6.478000000000008, -5.79...   
7   [-10.0, -5.114003259911044, -6.519430345382716...   
8   [-5.613333333333333, -5.786666666666666, -6.07...   
9   [-5.603287247427174, -5.654331805907437, -5.78...   
10  [-4.0, -5.628337129620289, -6.265659404892453,...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.93773412153736, -5.522329091122372, -5.56...   
1   [[-5.295, -6.25, -6.34, -6.927245587, -6.92724...   
2   [[-5.2844938284800005, -5.5573819193866685, -5...   
3   [[-5.366950699318421, -6.022222154868427, -6.1...   
4   [[-5.2774981592307695, -5.840014536727272, -5....   
5   [[-5.316853, -5.6233106, -5.8720407, -6.926082...   
6   [[-5.468499170830004, -5.891488861390001, -5.6...   
7   [[-4.0, -10.0, -10.0, -6.927245586999788, -10....   
8   [[-5.613333333333333, -5.613333333333333, -5.3...   
9   [[-5.609303475363959, -5.621233619080112, -5.4...   
10  [[-4.0, -4.0, -4.0, -6.765330764992578, -4.485...   

                                Test Predictions Mean  \
0   [-5.513319307793336, -5.30371095852256, -5.390...   
1   [-4.8740000000000006, -5.6674000366, -6.753, -...   
2   [-5.173279848922666, -5.690885473969334, -6.04...   
3   [-5.140454034240314, -5.801680050946473, -6.04...   
4   [-5.232638352341153, -5.732087806195454, -5.83...   
5   [-4.9429846, -5.847226, -5.946418, -6.6580553,...   
6   [-5.4116388265180015, -5.763699381808001, -5.8...   
7   [-5.2, -7.719579234674027, -9.47307106647092, ...   
8   [-5.4126666666666665, -5.638, -5.4946666666666...   
9   [-5.492972801252818, -5.674890303016237, -5.51...   
10  [-4.0668185064279125, -5.685895176551434, -4.0...   

                                 Test Predictions Std  
0   [0.23692144274442523, 0.22305643559392596, 0.2...  
1   [0.3981130492711837, 0.3363303407234969, 0.947...  
2   [0.09513265885634099, 0.16224735896136933, 0.2...  
3   [0.20585295811257112, 0.21193960638716092, 0.4...  
4   [0.10924366869176487, 0.2335388613917509, 0.32...  
5   [0.24036725, 0.19860332, 0.49665016, 0.5372004...  
6   [0.3533603053615431, 0.14542657087010974, 0.37...  
7   [2.4, 1.2189088722922783, 1.0538578670581593, ...  
8   [0.21437661564017046, 0.16956938927111156, 0.2...  
9   [0.1608086109511643, 0.03594912096921638, 0.15...  
10  [0.12137003968703829, 0.8475164456543341, 0.0,...

In [15]:
result_df.to_csv('results/Atomic/Results_all_atomic_desc_and_mono_comp_const_rem_MDCK.csv')
prediction_df.to_csv('results/Atomic/Prediction_data_all_atomic_desc_and_mono_comp_const_rem_MDCK.csv')

In [16]:
const_col

['Ala_tBu_',
 'Ala_indol_2_yl_',
 'dAla_indol_2_yl_',
 'Me_Ala_indol_2_yl_',
 'Ala_5_Tet_',
 'Me_dAbu',
 'Me_Abu_morpholino_',
 '2Abz',
 'Aib',
 'Aoc_2_',
 '5_Ava',
 'Bal',
 'Me_Bal',
 'HOCOCH2_Bal',
 'Cys_EtO2H__NH2',
 'dCha',
 'Me_Cha',
 'D',
 'meD',
 'Asp_piperidide',
 'Asp_OMe_',
 'Asp_Ph_2_NH2__',
 'dAsp_pyrrol_1_yl_',
 'E',
 'Glu_NH2',
 'Glu_3R_Me_',
 'Glu_OMe_',
 'dGlu_OMe_',
 'Phe_4_F_',
 'dPhe_4_F_',
 'Phe_4_CF3_',
 'Phe_4_NO2_',
 'Phe_CHF2_',
 'dPhe_3_4_diF_',
 'Et_Phe',
 'H2NEt_Phe',
 'Me_Phe_3_Cl_',
 'Me_Phe_4_Cl_',
 'Me_Phe_a_b_dehydro_',
 'G',
 'Bn_Gly',
 'Bn_4_Cl__Gly',
 'Bn_4_OH__Gly',
 'Bu_Gly',
 'EtOEt_Gly',
 'HOCOCH2_Gly_ol',
 'MeOEt_Gly',
 'NH2Bu_Gly',
 'PhEt_Gly',
 'PhPr_Gly',
 'isoamyl_Gly',
 'pentyl_Gly',
 '3_pyridylethyl_Gly',
 '2_pyridylmethyl_Gly',
 'd_N__O_Gly_allyl_',
 'GABA',
 'H',
 'Hph',
 'Me_Hph',
 'bHph',
 'Hph_2_Cl_',
 'Hph_3_Cl_',
 'Hph_4_Cl_',
 'Hse_Et_',
 'dHyp',
 'Hyp_Et_',
 'dI',
 'meI',
 'Me_dI',
 '_N__O_xiIle',
 'd_N__O_aIle',
 'K',
 'dK',
 'meK

In [4]:
#Fingerprints models
#All fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/All_fingerprints_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/All_fingerprints_test_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 20188)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 20188)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002196 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 665
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 177
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spl

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6859                0.7022   
DecisionTreeRegressor                    1.2508                0.8872   
RandomForestRegressor                    0.7375                0.7025   
GradientBoostingRegressor                0.9869                0.7881   
AdaBoostRegressor                        0.6947                0.6800   
XGBRegressor                             1.0337                0.7926   
ExtraTreesRegressor                      1.0782                0.8126   
LinearRegression                         1.2517                0.8227   
KNeighborsRegressor                      0.7367                0.6927   
SVR                                      0.7239                0.6942   
MLPRegressor                             1.8877                1.0685   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8282              -0.0604   
DecisionTreeRegressor                     1.1184              -0.9336   
RandomForestRegressor                     0.8588              -0.1400   
GradientBoostingRegressor                 0.9934              -0.5256   
AdaBoostRegressor                         0.8335              -0.0739   
XGBRegressor                              1.0167              -0.5980   
ExtraTreesRegressor                       1.0384              -0.6667   
LinearRegression                          1.1188              -0.9350   
KNeighborsRegressor                       0.8583              -0.1389   
SVR                                       0.8508              -0.1190   
MLPRegressor                              1.3739              -1.9181   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.1121                0.1744   
DecisionTreeRegressor                    0.1248                0.1626   
RandomForestRegressor                    0.1544                0.1797   
GradientBoostingRegressor                0.0853                0.1348   
AdaBoostRegressor                        0.2326                0.2835   
XGBRegressor                             0.1139                0.1784   
ExtraTreesRegressor                      0.0936                0.1396   
LinearRegression                         0.1099                0.1722   
KNeighborsRegressor                      0.1940                0.2564   
SVR                                      0.0642                0.0709   
MLPRegressor                             0.0497                0.0653   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4641   0.5902    0.6812   0.2111   
DecisionTreeRegressor       0.4415   0.5841    0.6645   0.2494   
RandomForestRegressor       0.2640   0.4502    0.5138   0.5511   
GradientBoostingRegressor   0.3372   0.5100    0.5807   0.4267   
AdaBoostRegressor           0.2603   0.4427    0.5102   0.5575   
XGBRegressor                0.2862   0.4573    0.5350   0.5135   
ExtraTreesRegressor         0.3686   0.5229    0.6071   0.3734   
LinearRegression            0.6979   0.6548    0.8354  -0.1864   
KNeighborsRegressor         0.3412   0.5067    0.5842   0.4199   
SVR                         0.3692   0.5095    0.6076   0.3723   
MLPRegressor                0.4531   0.5451    0.6731   0.2297   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4866                    0.4408  
DecisionTreeRegressor                       0.6629                    0.4044  
RandomForestRegressor                       0.7475                    0.3384  
GradientBoostingRegressor                   0.7196                    0.3494  
AdaBoostRegressor                           0.7586                    0.3659  
XGBRegressor                                0.7589                    0.5254  
ExtraTreesRegressor                         0.705

In [5]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.682897517574019, -6.114074271195862, -6.33...   
1   [-4.94, -6.97, -5.06, -5.793469425, -6.9299170...   
2   [-5.2730352908908324, -6.218100000000004, -5.7...   
3   [-5.001145771268826, -6.103753715980014, -5.46...   
4   [-5.290073526111111, -5.688648896041666, -5.86...   
5   [-5.0236025, -6.0459657, -5.1496067, -5.867244...   
6   [-4.959199999999999, -6.840900000000009, -5.22...   
7   [-4.412120833994302, -6.311838740957112, -4.62...   
8   [-5.613333333333333, -5.786666666666666, -5.44...   
9   [-5.522848894407083, -5.669700115999046, -5.67...   
10  [-4.0, -6.087849618350355, -4.469569001048019,...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.682897517574019, -5.696941666398196, -5.9...   
1   [[-4.61, -6.25, -7.82, -6.927245587, -6.929917...   
2   [[-5.480949170829999, -5.693703562856668, -6.4...   
3   [[-4.837844258263351, -5.859508342863473, -6.9...   
4   [[-5.114, -5.868222216653847, -5.9433462714999...   
5   [[-5.3382225, -5.579111, -6.318296, -6.9381027...   
6   [[-4.772100000000005, -6.23240082135, -7.59890...   
7   [[-5.897533518349219, -5.4847159888925425, -9....   
8   [[-5.613333333333333, -5.613333333333334, -5.1...   
9   [[-5.794299384358194, -5.810164240519107, -5.3...   
10  [[-5.129379453150613, -5.205459871147378, -7.7...   

                                Test Predictions Mean  \
0   [-5.503795248512171, -5.506604078277007, -5.75...   
1   [-4.894, -5.9, -6.99, -6.521304152800001, -5.9...   
2   [-5.355840829118435, -5.653452067015069, -6.39...   
3   [-5.159889235135806, -5.904519174531797, -6.74...   
4   [-5.29443206796, -5.715445626647236, -6.035609...   
5   [-5.3215857, -5.763702, -6.736338, -6.595792, ...   
6   [-5.043259164152005, -5.864540164270002, -7.03...   
7   [-5.147759128402, -5.22978135830437, -8.174240...   
8   [-5.6546666666666665, -5.666000000000001, -5.3...   
9   [-5.696688171402978, -5.741273304873648, -5.40...   
10  [-4.924312283200024, -5.565704728026846, -7.23...   

                                 Test Predictions Std  
0   [0.17432552151726882, 0.17727684879712866, 0.1...  
1   [0.6797823180989632, 0.7, 1.0600000000000005, ...  
2   [0.16765190204929076, 0.2860020468905707, 0.38...  
3   [0.4114737482275645, 0.3753212181355212, 0.592...  
4   [0.23157917717277252, 0.29272400833988077, 0.3...  
5   [0.27006215, 0.50087476, 0.7288663, 0.30035895...  
6   [0.4507059606812378, 0.6000287153602135, 0.752...  
7   [1.3027994618818746, 0.6419525138669969, 0.701...  
8   [0.14230796026770795, 0.14081350945290821, 0.1...  
9   [0.28568219415239465, 0.2574184408049692, 0.05...  
10  [0.5930445113515215, 0.8895462638316705, 0.918...

In [6]:
result_df.to_csv('results/Fingerprints/Results_All_fingerprints_fp_MDCK.csv')
prediction_df.to_csv('results/Fingerprints/Prediction_data_All_fingerprints_fp_MDCK.csv')

In [7]:
#Removal of constant columns
def remove_constant_columns(df):
    constant_columns = [col for col in df.columns if df[col].nunique() <= 1]
    
    df_cleaned = df.drop(columns=constant_columns)
    
    return df_cleaned, constant_columns

In [8]:
#Low variance column removal
def remove_low_variance_columns(df, threshold=0.005):
    df = df.drop(['ID','SMILES','Permeability'],axis=1)
    variances = df.var()
    
    low_variance_columns = variances[variances < threshold].index.tolist()
    
    df_cleaned = df.drop(columns=low_variance_columns)
    
    return df_cleaned, low_variance_columns

In [9]:
#All fingerprints constant removal
df_train = pd.read_csv('features/Fingerprints/Train/All_fingerprints_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train, const_col = remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/All_fingerprints_test_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 2131)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 2131)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.070110 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 665
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 177
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further split

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6859                0.7022   
DecisionTreeRegressor                    1.3223                0.8992   
RandomForestRegressor                    0.7195                0.6877   
GradientBoostingRegressor                0.9941                0.7879   
AdaBoostRegressor                        0.7080                0.6711   
XGBRegressor                             1.0337                0.7926   
ExtraTreesRegressor                      1.0775                0.8118   
LinearRegression                         1.2517                0.8227   
KNeighborsRegressor                      0.7367                0.6927   
SVR                                      0.7238                0.6942   
MLPRegressor                             1.9724                1.1055   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8282              -0.0604   
DecisionTreeRegressor                     1.1499              -1.0441   
RandomForestRegressor                     0.8482              -0.1122   
GradientBoostingRegressor                 0.9970              -0.5367   
AdaBoostRegressor                         0.8414              -0.0945   
XGBRegressor                              1.0167              -0.5980   
ExtraTreesRegressor                       1.0380              -0.6656   
LinearRegression                          1.1188              -0.9350   
KNeighborsRegressor                       0.8583              -0.1389   
SVR                                       0.8508              -0.1190   
MLPRegressor                              1.4044              -2.0490   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.1121                0.1744   
DecisionTreeRegressor                    0.0921                0.1744   
RandomForestRegressor                    0.1795                0.2169   
GradientBoostingRegressor                0.0889                0.1733   
AdaBoostRegressor                        0.2424                0.2960   
XGBRegressor                             0.1139                0.1784   
ExtraTreesRegressor                      0.0910                0.1533   
LinearRegression                         0.1099                0.1722   
KNeighborsRegressor                      0.1940                0.2564   
SVR                                      0.0642                0.0709   
MLPRegressor                             0.0217                0.0459   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4641   0.5902    0.6812   0.2111   
DecisionTreeRegressor       0.4442   0.6020    0.6665   0.2448   
RandomForestRegressor       0.2572   0.4442    0.5072   0.5627   
GradientBoostingRegressor   0.3477   0.5147    0.5897   0.4089   
AdaBoostRegressor           0.2536   0.4308    0.5036   0.5688   
XGBRegressor                0.2862   0.4573    0.5350   0.5135   
ExtraTreesRegressor         0.3711   0.5230    0.6092   0.3691   
LinearRegression            0.6979   0.6548    0.8354  -0.1864   
KNeighborsRegressor         0.3412   0.5067    0.5842   0.4199   
SVR                         0.3692   0.5095    0.6076   0.3724   
MLPRegressor                0.3237   0.5048    0.5690   0.4497   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4866                    0.4408  
DecisionTreeRegressor                       0.6686                    0.4044  
RandomForestRegressor                       0.7549                    0.3384  
GradientBoostingRegressor                   0.7100                    0.3494  
AdaBoostRegressor                           0.7637                    0.4044  
XGBRegressor                                0.7589                    0.5254  
ExtraTreesRegressor                         0.701

In [10]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.682897517574019, -6.114074271195862, -6.33...   
1   [-4.94, -6.97, -5.06, -5.793469425, -5.7934694...   
2   [-5.311991913136663, -6.02709578491, -5.757391...   
3   [-5.001145771268826, -5.958810528606914, -5.45...   
4   [-5.282500000000001, -5.741428571428572, -5.86...   
5   [-5.0236025, -6.0459657, -5.1496067, -5.867244...   
6   [-4.933399999999999, -6.926500000000008, -5.23...   
7   [-4.412120833994424, -6.311838740957146, -4.62...   
8   [-5.613333333333333, -5.786666666666666, -5.44...   
9   [-5.523043330238771, -5.669801407333472, -5.67...   
10  [-4.0, -6.070852667762768, -4.948383939352297,...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.682897517574019, -5.696941666398196, -5.9...   
1   [[-4.61, -6.25, -7.82, -6.927245587, -6.929917...   
2   [[-5.391189713396666, -5.672530490213334, -6.3...   
3   [[-4.798097169834813, -5.859508342863473, -6.9...   
4   [[-5.173192133999999, -5.977412934681819, -6.0...   
5   [[-5.3382225, -5.579111, -6.318296, -6.9381027...   
6   [[-4.8094000000000054, -6.219100000000001, -7....   
7   [[-5.897533518349335, -5.48471598889263, -9.04...   
8   [[-5.613333333333333, -5.613333333333334, -5.1...   
9   [[-5.794644222213698, -5.810487310164273, -5.3...   
10  [[-5.9502562279446, -5.085679109481434, -6.968...   

                                Test Predictions Mean  \
0   [-5.503795248512171, -5.506604078277007, -5.75...   
1   [-4.962000000000001, -5.922, -7.004, -6.521304...   
2   [-5.360490696511768, -5.656821579548169, -6.38...   
3   [-5.112701245363833, -5.908847555856864, -6.69...   
4   [-5.2676068478526314, -5.682049759195207, -6.0...   
5   [-5.3215857, -5.763702, -6.736338, -6.595792, ...   
6   [-5.004502175707505, -5.836185707168002, -7.00...   
7   [-5.147759128402035, -5.229781358304389, -8.17...   
8   [-5.6546666666666665, -5.666000000000001, -5.3...   
9   [-5.6967319987484855, -5.7412999999274605, -5....   
10  [-5.5000009847880715, -5.558492286090503, -6.9...   

                                 Test Predictions Std  
0   [0.17432552151726882, 0.17727684879712866, 0.1...  
1   [0.6456748407673941, 0.6559999999999998, 1.111...  
2   [0.17893768805714805, 0.2569776098740846, 0.37...  
3   [0.37243758249407755, 0.3833700518428232, 0.62...  
4   [0.17495638215281503, 0.37109269488091773, 0.4...  
5   [0.27006215, 0.50087476, 0.7288663, 0.30035895...  
6   [0.47273804711970324, 0.6054635015919565, 0.76...  
7   [1.3027994618818817, 0.6419525138670001, 0.701...  
8   [0.14230796026770795, 0.14081350945290821, 0.1...  
9   [0.285552106577087, 0.25728693551069687, 0.058...  
10  [0.8087661076365754, 0.9216148894311592, 0.536...

In [11]:
result_df.to_csv('results/Fingerprints/Results_All_const_rem_fingerprints_MDCK.csv')
prediction_df.to_csv('results/Fingerprints/Prediction_data_All_const_rem_fingerprints_MDCK.csv')

In [12]:
#Morgan fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/morgan_fp_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/morgan_fp_test_MDCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_morgan_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_morgan_fp

X_train shape:  (51, 2048)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 2048)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000174 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 12
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 4
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits w

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.7445                0.7088   
DecisionTreeRegressor                    0.9207                0.7323   
RandomForestRegressor                    0.7561                0.6826   
GradientBoostingRegressor                0.8936                0.7018   
AdaBoostRegressor                        0.7112                0.6818   
XGBRegressor                             0.9075                0.6994   
ExtraTreesRegressor                      0.9418                0.7338   
LinearRegression                         1.0265                0.7080   
KNeighborsRegressor                      0.7691                0.7171   
SVR                                      0.7732                0.7225   
MLPRegressor                             1.9714                1.0829   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8629              -0.1510   
DecisionTreeRegressor                     0.9595              -0.4233   
RandomForestRegressor                     0.8696              -0.1689   
GradientBoostingRegressor                 0.9453              -0.3813   
AdaBoostRegressor                         0.8433              -0.0994   
XGBRegressor                              0.9527              -0.4029   
ExtraTreesRegressor                       0.9704              -0.4558   
LinearRegression                          1.0132              -0.5868   
KNeighborsRegressor                       0.8770              -0.1889   
SVR                                       0.8793              -0.1952   
MLPRegressor                              1.4041              -2.0476   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.0942               -0.0393   
DecisionTreeRegressor                    0.1887                0.2807   
RandomForestRegressor                    0.2092                0.3127   
GradientBoostingRegressor                0.2221                0.3511   
AdaBoostRegressor                        0.2119                0.2766   
XGBRegressor                             0.2162                0.3746   
ExtraTreesRegressor                      0.1682                0.2768   
LinearRegression                         0.2650                0.3239   
KNeighborsRegressor                      0.2225                0.2974   
SVR                                     -0.0060                0.0024   
MLPRegressor                            -0.0305                0.0069   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.5459   0.5726    0.7389  0.0719   
DecisionTreeRegressor       0.3263   0.4973    0.5712  0.4453   
RandomForestRegressor       0.2173   0.4196    0.4662  0.6305   
GradientBoostingRegressor   0.2983   0.4905    0.5462  0.4928   
AdaBoostRegressor           0.2247   0.3999    0.4741  0.6179   
XGBRegressor                0.3171   0.4895    0.5631  0.4610   
ExtraTreesRegressor         0.3585   0.5194    0.5988  0.3905   
LinearRegression            0.5535   0.6196    0.7440  0.0590   
KNeighborsRegressor         0.4473   0.5219    0.6688  0.2395   
SVR                         0.3507   0.5081    0.5922  0.4039   
MLPRegressor                0.3808   0.5141    0.6171  0.3526   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.2686                    0.2271  
DecisionTreeRegressor                       0.7380                    0.4711  
RandomForestRegressor                       0.7962                    0.4601  
GradientBoostingRegressor                   0.7724                    0.5702  
AdaBoostRegressor                           0.7919                    0.5372  
XGBRegressor                                0.7264                    0.5041  
ExtraTreesRegressor                         0.7093           

In [13]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.558160996952212, -5.948035428178268, -5.94...   
1   [-6.929917083, -6.97, -5.195, -5.793469425, -5...   
2   [-5.444057791020001, -6.835970000000008, -5.25...   
3   [-5.6248985009875545, -7.6553987686755685, -4....   
4   [-5.5322460303181815, -6.888333333333333, -5.5...   
5   [-6.0731106, -7.8135104, -5.187934, -6.146343,...   
6   [-6.391680929090008, -6.970000000000017, -5.14...   
7   [-4.697589991787713, -6.738835677961945, -4.42...   
8   [-5.183333333333334, -5.786666666666666, -5.44...   
9   [-5.59323403953569, -5.954349517113198, -5.618...   
10  [-4.0, -6.329610908081167, -5.047794791115381,...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.558160996952212, -5.558160996952212, -5.5...   
1   [[-6.25, -6.25, -7.82, -6.927245587, -5.453495...   
2   [[-5.516890837496668, -5.688767504163336, -6.5...   
3   [[-5.6473838477230425, -5.865850383798877, -6....   
4   [[-5.52125, -5.5377225707777775, -6.09, -6.064...   
5   [[-5.3840137, -6.2445383, -6.4294143, -6.89694...   
6   [[-5.561200000000005, -6.25, -7.82000000000001...   
7   [[-5.838188606117533, -5.554719750175392, -6.1...   
8   [[-5.503333333333333, -5.503333333333333, -4.8...   
9   [[-5.778955248416474, -5.736412124225234, -5.3...   
10  [[-5.313424247476278, -4.0, -5.830023064464588...   

                                Test Predictions Mean  \
0   [-5.431899695363696, -5.431899695363696, -5.43...   
1   [-5.361, -5.391, -6.861999999999999, -6.809796...   
2   [-5.405798983036735, -5.656295180114808, -6.45...   
3   [-5.569206768627078, -5.863218633412728, -7.05...   
4   [-5.334547903576611, -5.430791200095166, -6.07...   
5   [-5.112603, -6.02817, -6.604773, -6.6355524, -...   
6   [-5.164850000000003, -5.4750346852280005, -6.8...   
7   [-5.196967516931039, -5.5426177065939735, -5.9...   
8   [-5.390666666666666, -5.483333333333333, -4.75...   
9   [-5.558253001620082, -5.629575116892168, -5.28...   
10  [-4.967137277722762, -4.842470017020301, -5.75...   

                                 Test Predictions Std  
0   [0.08096631896519323, 0.08096631896519323, 0.0...  
1   [0.7633505092681866, 0.599102662320908, 0.9452...  
2   [0.23598314192653955, 0.21365990223656536, 0.2...  
3   [0.41422433770853745, 0.28472121221116664, 0.5...  
4   [0.13475896263685877, 0.12497547567278622, 0.2...  
5   [0.47593063, 0.29658327, 0.6902337, 0.3530023,...  
6   [0.3518338698874813, 0.6009241337334386, 0.878...  
7   [0.529316879399676, 0.5984889146578108, 0.4527...  
8   [0.19764614845728687, 0.187936159373336, 0.181...  
9   [0.35570124192838404, 0.22985032593113042, 0.0...  
10  [0.4944846531327948, 0.705364591798827, 0.2992...

In [14]:
df_morgan_fp.to_csv('results/Fingerprints/Results_Morgan_fp_MDCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_Morgan_fp_MDCK.csv')

In [15]:
#Morgan count fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/count_morgan_fp_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/count_morgan_fp_test_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_morgan_count_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_morgan_count_fp

X_train shape:  (51, 2048)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 2048)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000238 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 38
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 8
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits w

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


0.028134297862200452


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.7844                0.7307   
DecisionTreeRegressor                    0.9775                0.7711   
RandomForestRegressor                    0.7518                0.7041   
GradientBoostingRegressor                1.0399                0.8056   
AdaBoostRegressor                        0.8571                0.7587   
XGBRegressor                             1.1280                0.8403   
ExtraTreesRegressor                      0.8863                0.7433   
LinearRegression                         1.3863                0.8953   
KNeighborsRegressor                      0.8014                0.7430   
SVR                                      0.7349                0.6977   
MLPRegressor                             1.9318                1.0834   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8857              -0.2126   
DecisionTreeRegressor                     0.9887              -0.5110   
RandomForestRegressor                     0.8671              -0.1622   
GradientBoostingRegressor                 1.0197              -0.6075   
AdaBoostRegressor                         0.9258              -0.3250   
XGBRegressor                              1.0621              -0.7437   
ExtraTreesRegressor                       0.9415              -0.3701   
LinearRegression                          1.1774              -1.1431   
KNeighborsRegressor                       0.8952              -0.2388   
SVR                                       0.8573              -0.1361   
MLPRegressor                              1.3899              -1.9863   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.1428               -0.0731   
DecisionTreeRegressor                    0.2115                0.2734   
RandomForestRegressor                    0.1383                0.2032   
GradientBoostingRegressor               -0.0248               -0.0317   
AdaBoostRegressor                        0.0457                0.0214   
XGBRegressor                             0.0306                0.0482   
ExtraTreesRegressor                      0.1371                0.1782   
LinearRegression                         0.1079                0.1668   
KNeighborsRegressor                      0.1485                0.2365   
SVR                                      0.0468                0.0245   
MLPRegressor                             0.0083                0.0544   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.5262   0.5746    0.7254   0.1054   
DecisionTreeRegressor       0.3713   0.5238    0.6094   0.3688   
RandomForestRegressor       0.2572   0.4463    0.5072   0.5627   
GradientBoostingRegressor   0.3848   0.5468    0.6203   0.3458   
AdaBoostRegressor           0.2641   0.4260    0.5139   0.5510   
XGBRegressor                0.3314   0.4894    0.5757   0.4365   
ExtraTreesRegressor         0.4085   0.5534    0.6392   0.3055   
LinearRegression            0.7527   0.6573    0.8676  -0.2796   
KNeighborsRegressor         0.4625   0.5464    0.6801   0.2137   
SVR                         0.3367   0.4951    0.5803   0.4276   
MLPRegressor                0.5717   0.6164    0.7561   0.0281   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.3337                    0.2928  
DecisionTreeRegressor                       0.6759                    0.3659  
RandomForestRegressor                       0.7524                    0.3769  
GradientBoostingRegressor                   0.6833                    0.4264  
AdaBoostRegressor                           0.7503                    0.4209  
XGBRegressor                                0.6981                    0.4649  
ExtraTreesRegressor                         0.672

In [16]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.424136649304684, -6.082059775932106, -5.99...   
1   [-6.22, -5.93, -5.195, -5.793469425, -5.547418...   
2   [-5.545743328870002, -6.451074170830005, -5.55...   
3   [-5.781373743769475, -7.058643488327688, -4.99...   
4   [-5.561668507615385, -6.736449117399999, -5.81...   
5   [-5.737909, -7.4206095, -5.037543, -5.8247414,...   
6   [-5.965666448120007, -6.6105000000000045, -5.3...   
7   [-4.0, -5.585596460555274, -4.0, -5.6089634708...   
8   [-5.613333333333333, -5.786666666666666, -5.44...   
9   [-5.609201158915962, -5.6646398202271175, -5.6...   
10  [-4.0, -4.931422751576346, -4.678761946532418,...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.424136649304684, -5.424136649304684, -5.6...   
1   [[-4.61, -6.25, -6.17, -6.927245587, -5.453495...   
2   [[-5.456660870676669, -5.744730992470002, -6.5...   
3   [[-5.45957738103695, -6.176454414422514, -7.39...   
4   [[-5.281999999999999, -5.819615094814815, -5.6...   
5   [[-5.051465, -6.243319, -6.221617, -6.936932, ...   
6   [[-4.865000000000008, -6.2281669404499995, -7....   
7   [[-4.0, -4.225460828221529, -9.884734317384428...   
8   [[-5.613333333333333, -5.613333333333333, -4.8...   
9   [[-5.670689936298147, -5.723245533802789, -5.5...   
10  [[-4.388831944942902, -4.0, -7.445447937320379...   

                                Test Predictions Mean  \
0   [-5.392722008630507, -5.392722008630507, -5.61...   
1   [-5.0961444334, -5.8691444334, -6.396, -6.5263...   
2   [-5.341749295657665, -5.642562720364613, -6.39...   
3   [-5.142652865284374, -5.814178953146951, -6.90...   
4   [-5.273926052330476, -5.588487210795127, -6.04...   
5   [-5.0392733, -5.913934, -5.977878, -6.688245, ...   
6   [-5.041258393322006, -5.797182829229667, -6.82...   
7   [-4.0, -4.759746928757257, -7.4479125422094254...   
8   [-5.4126666666666665, -5.666, -4.75, -6.220185...   
9   [-5.4817794010725205, -5.603897278043824, -5.5...   
10  [-4.516250481402217, -4.433194814011299, -7.06...   

                                 Test Predictions Std  
0   [0.14859947763635886, 0.14859947763635886, 0.1...  
1   [0.6531706507117631, 0.4709656090574217, 0.827...  
2   [0.24515355135829134, 0.24293870734742698, 0.3...  
3   [0.5088154694666068, 0.46103050476508345, 0.50...  
4   [0.1680713454303819, 0.2890412714430882, 0.409...  
5   [0.50836474, 0.4824697, 0.13208126, 0.368149, ...  
6   [0.4247036720301815, 0.3721761128851866, 0.416...  
7   [0.0, 0.8337546912336395, 1.701064455015078, 0...  
8   [0.21437661564017046, 0.14081350945290877, 0.1...  
9   [0.25559520867088065, 0.16206752563565405, 0.0...  
10  [0.321835383461054, 0.40909721227561696, 0.613...

In [17]:
df_morgan_count_fp.to_csv('results/Fingerprints/Results_Count_Morgan_fp_MDCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_Count_Morgan_fp_MDCK.csv')

In [18]:
#AtomPairs2d fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/AtomPairs2D_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/AtomPairs2D_test_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_AtomPairs2D_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_AtomPairs2D_fp

X_train shape:  (51, 780)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 780)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000171 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 9
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 3
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't 

0.1421587298869399


/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6960                0.6868   
DecisionTreeRegressor                    0.7538                0.7188   
RandomForestRegressor                    0.7512                0.7178   
GradientBoostingRegressor                0.7538                0.7188   
AdaBoostRegressor                        0.8105                0.7518   
XGBRegressor                             0.7536                0.7187   
ExtraTreesRegressor                      0.7538                0.7188   
LinearRegression                         0.7550                0.7188   
KNeighborsRegressor                      0.8827                0.7893   
SVR                                      0.7278                0.6642   
MLPRegressor                             0.9598                0.7554   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8343              -0.0759   
DecisionTreeRegressor                     0.8682              -0.1652   
RandomForestRegressor                     0.8667              -0.1612   
GradientBoostingRegressor                 0.8682              -0.1652   
AdaBoostRegressor                         0.9003              -0.2530   
XGBRegressor                              0.8681              -0.1649   
ExtraTreesRegressor                       0.8682              -0.1652   
LinearRegression                          0.8689              -0.1671   
KNeighborsRegressor                       0.9395              -0.3645   
SVR                                       0.8531              -0.1250   
MLPRegressor                              0.9797              -0.4837   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.1047                0.0305   
DecisionTreeRegressor                    0.0282                0.0964   
RandomForestRegressor                    0.0264                0.0964   
GradientBoostingRegressor                0.0282                0.0964   
AdaBoostRegressor                       -0.0227                0.0484   
XGBRegressor                             0.0282                0.0964   
ExtraTreesRegressor                      0.0282                0.0964   
LinearRegression                         0.0294                0.0946   
KNeighborsRegressor                     -0.0576                0.0446   
SVR                                      0.0597                0.0846   
MLPRegressor                            -0.1727               -0.0280   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.5304   0.5976    0.7283   0.0984   
DecisionTreeRegressor       0.4854   0.5620    0.6967   0.1748   
RandomForestRegressor       0.4867   0.5629    0.6977   0.1726   
GradientBoostingRegressor   0.4854   0.5620    0.6967   0.1748   
AdaBoostRegressor           0.4782   0.5622    0.6915   0.1870   
XGBRegressor                0.4854   0.5620    0.6967   0.1748   
ExtraTreesRegressor         0.4854   0.5620    0.6967   0.1748   
LinearRegression            0.4854   0.5620    0.6967   0.1748   
KNeighborsRegressor         0.6854   0.6521    0.8279  -0.1652   
SVR                         0.5789   0.5773    0.7609   0.0158   
MLPRegressor                0.5046   0.5875    0.7104   0.1422   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4284                    0.3717  
DecisionTreeRegressor                       0.4377                    0.3379  
RandomForestRegressor                       0.4381                    0.3379  
GradientBoostingRegressor                   0.4377                    0.3379  
AdaBoostRegressor                           0.4404                    0.3379  
XGBRegressor                                0.4377                    0.3379  
ExtraTreesRegressor                         0.437

In [19]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.558160996952212, -5.948035428178268, -5.94...   
1   [-5.346875, -6.2219999999999995, -6.2219999999...   
2   [-5.3613644095540405, -6.193135364357863, -6.1...   
3   [-5.346885789857637, -6.221987545313435, -6.22...   
4   [-5.3088235294117645, -6.27, -6.27, -5.9211516...   
5   [-5.3470435, -6.2218075, -6.2218075, -5.85834,...   
6   [-5.346875000000006, -6.221999999999991, -6.22...   
7   [-5.346875000000001, -6.222, -6.222, -5.858261...   
8   [-5.613333333333333, -5.786666666666666, -5.78...   
9   [-5.19980221288724, -5.830341035767339, -5.830...   
10  [-5.496881848200857, -6.229087681658164, -6.22...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.558160996952212, -5.558160996952212, -5.5...   
1   [[-5.346875, -5.346875, -5.346875, -5.85826198...   
2   [[-5.36136440955404, -5.36136440955404, -5.361...   
3   [[-5.346885789857637, -5.346885789857637, -5.3...   
4   [[-5.3088235294117645, -5.3088235294117645, -5...   
5   [[-5.3470435, -5.3470435, -5.3470435, -5.85834...   
6   [[-5.346875000000006, -5.346875000000006, -5.3...   
7   [[-5.346875000000001, -5.346875000000001, -5.3...   
8   [[-5.613333333333333, -5.613333333333333, -5.6...   
9   [[-5.19980221288724, -5.19980221288724, -5.199...   
10  [[-5.496881848200857, -5.496881848200857, -5.4...   

                                Test Predictions Mean  \
0   [-5.567076712219281, -5.567076712219281, -5.56...   
1   [-5.317460714285714, -5.317460714285714, -5.31...   
2   [-5.315527625950532, -5.315527625950532, -5.31...   
3   [-5.317470119496489, -5.317470119496489, -5.31...   
4   [-5.361861395570374, -5.361861395570374, -5.36...   
5   [-5.3176765, -5.3176765, -5.3176765, -5.807809...   
6   [-5.317460714285722, -5.317460714285722, -5.31...   
7   [-5.317460714285714, -5.317460714285714, -5.31...   
8   [-5.6259999999999994, -5.6259999999999994, -5....   
9   [-5.2063612582588, -5.2063612582588, -5.206361...   
10  [-5.516071486956705, -5.516071486956705, -5.51...   

                                 Test Predictions Std  
0   [0.1272708901920145, 0.1272708901920145, 0.127...  
1   [0.06052896970434374, 0.06052896970434374, 0.0...  
2   [0.06843983365593138, 0.06843983365593138, 0.0...  
3   [0.06052802111288864, 0.06052802111288864, 0.0...  
4   [0.1080421892258728, 0.1080421892258728, 0.108...  
5   [0.060521808, 0.060521808, 0.060521808, 0.0728...  
6   [0.06052896970434286, 0.06052896970434286, 0.0...  
7   [0.06052896970434419, 0.06052896970434419, 0.0...  
8   [0.16096100286853474, 0.16096100286853474, 0.1...  
9   [0.04422598182623809, 0.04422598182623809, 0.0...  
10  [0.07998384307087689, 0.07998384307087689, 0.0...

In [20]:
df_AtomPairs2D_fp.to_csv('results/Fingerprints/Results_AtomPairs2D_fp_MDCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_AtomPairs2D_fp_MDCK.csv')

In [21]:
#AtomPairs2d Count fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/AtomPairs2DCount_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/AtomPairs2DCount_test_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_AtomPairs2DCount_fp , pred_df= train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_AtomPairs2DCount_fp

X_train shape:  (51, 780)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 780)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.015087 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 81
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 12
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits wi

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't 

0.5241691399897415


/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6212                0.6565   
DecisionTreeRegressor                    0.9301                0.7519   
RandomForestRegressor                    0.7170                0.6866   
GradientBoostingRegressor                0.8801                0.7621   
AdaBoostRegressor                        0.7017                0.6896   
XGBRegressor                             0.7931                0.6889   
ExtraTreesRegressor                      0.8526                0.7379   
LinearRegression                         2.6488                1.2609   
KNeighborsRegressor                      0.7623                0.6770   
SVR                                      0.6557                0.6224   
MLPRegressor                             0.8458                0.7277   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7882               0.0397   
DecisionTreeRegressor                     0.9644              -0.4378   
RandomForestRegressor                     0.8467              -0.1083   
GradientBoostingRegressor                 0.9381              -0.3605   
AdaBoostRegressor                         0.8377              -0.0848   
XGBRegressor                              0.8906              -0.2260   
ExtraTreesRegressor                       0.9234              -0.3180   
LinearRegression                          1.6275              -3.0946   
KNeighborsRegressor                       0.8731              -0.1784   
SVR                                       0.8098              -0.0136   
MLPRegressor                              0.9197              -0.3074   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2280                0.1734   
DecisionTreeRegressor                    0.2993                0.3055   
RandomForestRegressor                    0.2229                0.2530   
GradientBoostingRegressor                0.1653                0.1856   
AdaBoostRegressor                        0.2765                0.2401   
XGBRegressor                             0.2798                0.2669   
ExtraTreesRegressor                      0.2058                0.2421   
LinearRegression                         0.2338                0.2745   
KNeighborsRegressor                      0.1943                0.1743   
SVR                                      0.2354                0.1637   
MLPRegressor                             0.1545                0.0994   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4333   0.5746    0.6583   0.2633   
DecisionTreeRegressor       0.3806   0.5518    0.6169   0.3529   
RandomForestRegressor       0.3329   0.4966    0.5770   0.4340   
GradientBoostingRegressor   0.4070   0.5410    0.6380   0.3080   
AdaBoostRegressor           0.3408   0.5079    0.5838   0.4206   
XGBRegressor                0.3873   0.5453    0.6224   0.3415   
ExtraTreesRegressor         0.3898   0.5471    0.6244   0.3373   
LinearRegression            1.1788   0.8583    1.0857  -1.0039   
KNeighborsRegressor         0.3902   0.4879    0.6247   0.3366   
SVR                         0.3427   0.4588    0.5854   0.4174   
MLPRegressor                0.2799   0.4250    0.5291   0.5242   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5732                    0.3269  
DecisionTreeRegressor                       0.6908                    0.2779  
RandomForestRegressor                       0.6984                    0.3329  
GradientBoostingRegressor                   0.6879                    0.3164  
AdaBoostRegressor                           0.7132                    0.2944  
XGBRegressor                                0.6789                    0.3549  
ExtraTreesRegressor                         0.691

In [22]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.801092403684741, -6.279518273163124, -6.27...   
1   [-4.94, -5.33, -6.97, -5.793469425, -6.9299170...   
2   [-5.251199999999996, -5.390091569819997, -6.26...   
3   [-4.964881842643498, -5.128927195404449, -6.34...   
4   [-5.3725, -5.530000000000001, -6.4852695702857...   
5   [-4.9411807, -5.273791, -6.770791, -5.6544137,...   
6   [-4.957299999999998, -5.298899999999999, -6.68...   
7   [-7.884570042809932, -4.0, -5.124744134176638,...   
8   [-5.613333333333333, -5.786666666666666, -6.07...   
9   [-5.516176473156865, -5.522959185174364, -5.69...   
10  [-5.4016570870903715, -5.646281042586869, -6.1...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.801092403684741, -5.801092403684741, -5.8...   
1   [[-6.34, -6.25, -5.93, -6.927245587, -6.569578...   
2   [[-5.677299999999994, -5.872400000000002, -6.2...   
3   [[-5.178081652417845, -6.249346628712105, -6.8...   
4   [[-5.504999999999999, -5.755, -6.2049999999999...   
5   [[-5.7171683, -6.1566877, -5.577727, -6.942414...   
6   [[-5.805699999999996, -6.2083, -6.031668240780...   
7   [[-4.0, -5.770441495156561, -10.0, -6.84710134...   
8   [[-5.613333333333333, -5.613333333333334, -5.9...   
9   [[-5.648025051124643, -5.4792949774874184, -5....   
10  [[-5.179833036772858, -5.420273401095517, -6.0...   

                                Test Predictions Mean  \
0   [-5.721090726827581, -5.721090726827581, -5.72...   
1   [-5.438, -5.922, -5.921999999999999, -6.571015...   
2   [-5.708859999999998, -5.760440000000001, -6.02...   
3   [-5.555170691664529, -5.9747732929507364, -6.1...   
4   [-5.59079462009478, -5.80189561804183, -5.9725...   
5   [-5.528285, -5.9325666, -5.748015, -6.660899, ...   
6   [-5.693159999999999, -5.965580000000001, -5.90...   
7   [-5.169044447737309, -6.635723590784858, -8.80...   
8   [-5.6259999999999994, -5.666000000000001, -6.0...   
9   [-5.685719029310985, -5.556043578716791, -5.57...   
10  [-5.567728740815658, -5.42726825445155, -5.733...   

                                 Test Predictions Std  
0   [0.13644640707471545, 0.13644640707471545, 0.1...  
1   [0.6061484966573784, 0.6559999999999998, 0.625...  
2   [0.09197144339413205, 0.3192603802541123, 0.21...  
3   [0.4346731395012083, 0.4860065778359095, 0.491...  
4   [0.2597673820200409, 0.3218838919915005, 0.313...  
5   [0.2971646, 0.58796966, 0.24468806, 0.30170453...  
6   [0.24348770482305576, 0.4639873162059496, 0.34...  
7   [1.5637243594864858, 1.9280850769377937, 1.469...  
8   [0.16096100286853474, 0.14081350945290821, 0.2...  
9   [0.10578901169302979, 0.15160542404475955, 0.1...  
10  [0.3923000956046614, 0.2303325595281518, 0.343...

In [23]:
df_AtomPairs2DCount_fp.to_csv('results/Fingerprints/Results_AtomPairs2D_Count_fp_MDCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_df_AtomPairs2D_Count_fp_MDCK.csv')

In [24]:
#EState fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/EState_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/EState_test_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_estate_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_estate_fp

X_train shape:  (51, 79)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 79)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 0
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there 

/tmp/ipykernel_3799211/3970550512.py:47: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  pearson_test, _ = pearsonr(y_test, predictions_test_mean)
/tmp/ipykernel_3799211/3970550512.py:48: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  spearman_test, _ = spearmanr(y_test, predictions_test_mean)


0.17702918536074175
0.1793326935898093
0.17997508203356594
0.17936665437141053
0.17933222711882124
0.18322264527500676
-0.14410688305165542
0.04681620962351818
0.055771147711443425


/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't 

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6869                0.6819   
DecisionTreeRegressor                    0.7319                0.7177   
RandomForestRegressor                    0.6943                0.7055   
GradientBoostingRegressor                0.7319                0.7177   
AdaBoostRegressor                        0.6977                0.7020   
XGBRegressor                             0.7314                0.7175   
ExtraTreesRegressor                      0.7319                0.7177   
LinearRegression                         0.6732                0.6916   
KNeighborsRegressor                      0.9268                0.8008   
SVR                                      0.6976                0.6622   
MLPRegressor                             1.1112                0.8079   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8288              -0.0618   
DecisionTreeRegressor                     0.8555              -0.1315   
RandomForestRegressor                     0.8332              -0.0733   
GradientBoostingRegressor                 0.8555              -0.1315   
AdaBoostRegressor                         0.8353              -0.0786   
XGBRegressor                              0.8552              -0.1307   
ExtraTreesRegressor                       0.8555              -0.1315   
LinearRegression                          0.8205              -0.0407   
KNeighborsRegressor                       0.9627              -0.4328   
SVR                                       0.8353              -0.0785   
MLPRegressor                              1.0541              -0.7178   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.3293               -0.3067   
DecisionTreeRegressor                    0.1132                0.1344   
RandomForestRegressor                    0.1474                0.1642   
GradientBoostingRegressor                0.1132                0.1344   
AdaBoostRegressor                        0.1971                0.1695   
XGBRegressor                             0.1136                0.1344   
ExtraTreesRegressor                      0.1132                0.1344   
LinearRegression                         0.1887                0.1825   
KNeighborsRegressor                     -0.0824               -0.0016   
SVR                                      0.1448                0.1258   
MLPRegressor                             0.0432                0.0764   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.5884   0.6227    0.7670  -0.0002   
DecisionTreeRegressor       0.4827   0.5730    0.6948   0.1793   
RandomForestRegressor       0.4841   0.5754    0.6958   0.1770   
GradientBoostingRegressor   0.4827   0.5730    0.6948   0.1793   
AdaBoostRegressor           0.4824   0.5710    0.6945   0.1800   
XGBRegressor                0.4827   0.5730    0.6948   0.1794   
ExtraTreesRegressor         0.4827   0.5730    0.6948   0.1793   
LinearRegression            0.4804   0.5688    0.6931   0.1832   
KNeighborsRegressor         0.6730   0.6327    0.8204  -0.1441   
SVR                         0.5607   0.5876    0.7488   0.0468   
MLPRegressor                0.5554   0.5924    0.7453   0.0558   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                                  nan                       nan  
DecisionTreeRegressor                       0.4322                    0.3037  
RandomForestRegressor                       0.4301                    0.3037  
GradientBoostingRegressor                   0.4322                    0.3037  
AdaBoostRegressor                           0.4336                    0.3037  
XGBRegressor                                0.4322                    0.3037  
ExtraTreesRegressor                         0.432

In [25]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.753098213672638, -5.753098213672638, -5.75...   
1   [-5.247999999999999, -6.357142857142857, -6.35...   
2   [-5.262657238594738, -6.305263512598512, -6.30...   
3   [-5.248013416115953, -6.3571268128729574, -6.3...   
4   [-5.138000000000001, -6.359999999999999, -6.35...   
5   [-5.24825, -6.3566995, -6.3566995, -5.8583474,...   
6   [-5.247999999999995, -6.357142857142854, -6.35...   
7   [-5.235787878787878, -6.33969696969697, -6.339...   
8   [-5.613333333333333, -5.786666666666666, -5.78...   
9   [-5.06042401618693, -5.829928750830033, -5.829...   
10  [-5.522107077314696, -5.855076413643567, -5.85...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.753098213672638, -5.753098213672638, -5.7...   
1   [[-5.247999999999999, -5.247999999999999, -5.2...   
2   [[-5.262657238594738, -5.262657238594738, -5.2...   
3   [[-5.248013416115953, -5.248013416115953, -5.2...   
4   [[-5.138000000000001, -5.138000000000001, -5.1...   
5   [[-5.24825, -5.24825, -5.24825, -5.8583474, -5...   
6   [[-5.247999999999995, -5.247999999999995, -5.2...   
7   [[-5.235787878787878, -5.235787878787878, -5.2...   
8   [[-5.613333333333333, -5.613333333333333, -5.6...   
9   [[-5.06042401618693, -5.06042401618693, -5.060...   
10  [[-5.522107077314696, -5.522107077314696, -5.5...   

                                Test Predictions Mean  \
0   [-5.67155390815037, -5.67155390815037, -5.6715...   
1   [-5.227047474747474, -5.227047474747474, -5.22...   
2   [-5.228165137862138, -5.228165137862138, -5.22...   
3   [-5.227059480539671, -5.227059480539671, -5.22...   
4   [-5.233639393939393, -5.233639393939393, -5.23...   
5   [-5.227351, -5.227351, -5.227351, -5.8077884, ...   
6   [-5.227047474747475, -5.227047474747475, -5.22...   
7   [-5.240701217086212, -5.240701217086212, -5.24...   
8   [-5.6259999999999994, -5.6259999999999994, -5....   
9   [-5.099879802362196, -5.099879802362196, -5.09...   
10  [-5.4610700551771645, -5.4610700551771645, -5....   

                                 Test Predictions Std  
0   [0.06667572909639166, 0.06667572909639166, 0.0...  
1   [0.0640910252723193, 0.0640910252723193, 0.064...  
2   [0.06795565984511041, 0.06795565984511041, 0.0...  
3   [0.0640896010153116, 0.0640896010153116, 0.064...  
4   [0.08352817794349457, 0.08352817794349457, 0.0...  
5   [0.06406123, 0.06406123, 0.06406123, 0.0728661...  
6   [0.06409102527231593, 0.06409102527231593, 0.0...  
7   [0.07628099169213029, 0.07628099169213029, 0.0...  
8   [0.16096100286853474, 0.16096100286853474, 0.1...  
9   [0.057526732934047475, 0.057526732934047475, 0...  
10  [0.0804551421263836, 0.0804551421263836, 0.080...

In [26]:
df_estate_fp.to_csv('results/Fingerprints/Results_EState_fp_MDCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_EState_fp_MDCK.csv')

In [27]:
#Extended fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/Extended_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/Extended_test_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_extended_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_extended_fp

X_train shape:  (51, 1024)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 1024)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000347 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 96
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 32
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits 

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.7231                0.7020   
DecisionTreeRegressor                    0.9944                0.8008   
RandomForestRegressor                    0.8390                0.7594   
GradientBoostingRegressor                0.9208                0.7705   
AdaBoostRegressor                        0.8386                0.7663   
XGBRegressor                             0.9884                0.7985   
ExtraTreesRegressor                      0.9994                0.8021   
LinearRegression                         1.1449                0.8181   
KNeighborsRegressor                      0.8063                0.7114   
SVR                                      0.7777                0.7149   
MLPRegressor                             1.4669                0.9455   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8503              -0.1177   
DecisionTreeRegressor                     0.9972              -0.5372   
RandomForestRegressor                     0.9160              -0.2970   
GradientBoostingRegressor                 0.9596              -0.4234   
AdaBoostRegressor                         0.9157              -0.2963   
XGBRegressor                              0.9942              -0.5280   
ExtraTreesRegressor                       0.9997              -0.5449   
LinearRegression                          1.0700              -0.7698   
KNeighborsRegressor                       0.8979              -0.2464   
SVR                                       0.8819              -0.2022   
MLPRegressor                              1.2111              -1.2676   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.1799               -0.0669   
DecisionTreeRegressor                    0.0568                0.1389   
RandomForestRegressor                    0.0299                0.0834   
GradientBoostingRegressor                0.0518                0.0865   
AdaBoostRegressor                        0.1442                0.1359   
XGBRegressor                             0.0436                0.0835   
ExtraTreesRegressor                      0.0617                0.1451   
LinearRegression                        -0.0286                0.0304   
KNeighborsRegressor                     -0.0324               -0.0060   
SVR                                     -0.0206               -0.0196   
MLPRegressor                            -0.0714               -0.0407   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.5326   0.5985    0.7298   0.0946   
DecisionTreeRegressor       0.6071   0.6793    0.7792  -0.0322   
RandomForestRegressor       0.4963   0.6026    0.7045   0.1563   
GradientBoostingRegressor   0.5408   0.6300    0.7354   0.0806   
AdaBoostRegressor           0.5007   0.5931    0.7076   0.1489   
XGBRegressor                0.5795   0.6521    0.7613   0.0148   
ExtraTreesRegressor         0.5955   0.6698    0.7717  -0.0124   
LinearRegression            0.4158   0.5470    0.6449   0.2931   
KNeighborsRegressor         0.5807   0.5660    0.7620   0.0128   
SVR                         0.5095   0.5453    0.7138   0.1338   
MLPRegressor                0.3975   0.5385    0.6305   0.3242   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4068                    0.3840  
DecisionTreeRegressor                       0.4472                    0.2510  
RandomForestRegressor                       0.4770                    0.3884  
GradientBoostingRegressor                   0.4484                    0.3884  
AdaBoostRegressor                           0.4870                    0.3779  
XGBRegressor                                0.4231                    0.2645  
ExtraTreesRegressor                         0.452

In [28]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.558160996952212, -5.948035428178268, -5.94...   
1   [-5.295, -6.2219999999999995, -6.2219999999999...   
2   [-5.300279999999999, -6.1931353643578655, -6.1...   
3   [-5.253212635373249, -6.2256605091155235, -6.2...   
4   [-5.176666666666667, -6.4514491174, -6.4514491...   
5   [-5.2943616, -6.222085, -6.222085, -5.886463, ...   
6   [-5.2950000000000035, -6.221999999999991, -6.2...   
7   [-5.294999999999997, -6.222, -6.222, -5.705397...   
8   [-5.183333333333334, -5.786666666666666, -5.78...   
9   [-5.040148986263137, -5.8301489931382715, -5.8...   
10  [-5.152476260069688, -6.2618331670644185, -6.2...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.558160996952212, -5.558160996952212, -5.5...   
1   [[-4.6850000000000005, -4.6850000000000005, -5...   
2   [[-4.927544047619049, -4.925586938171549, -5.3...   
3   [[-4.6937941323889, -4.6937941323889, -5.25321...   
4   [[-4.75, -4.75, -5.176666666666667, -6.4514491...   
5   [[-4.6900196, -4.6900196, -5.2943616, -6.57034...   
6   [[-4.690500000000001, -4.690500000000001, -5.2...   
7   [[-5.714005709253274, -5.7057083612022605, -5....   
8   [[-5.206666666666667, -5.206666666666667, -5.1...   
9   [[-5.564512836041758, -5.568422924631442, -5.0...   
10  [[-6.101015813424282, -5.813270076449037, -5.1...   

                                Test Predictions Mean  \
0   [-5.555513440841483, -5.555513440841483, -5.55...   
1   [-4.67, -4.67, -5.470000000000001, -6.46671853...   
2   [-4.972449409741874, -4.974512746134584, -5.46...   
3   [-4.822774316153668, -4.858312933088546, -5.43...   
4   [-4.846040621818181, -4.846040621818181, -5.40...   
5   [-4.698951, -4.7618384, -5.469215, -6.4876556,...   
6   [-4.6874800000000025, -4.686580000000003, -5.4...   
7   [-5.570407704285721, -5.5242652656712234, -5.4...   
8   [-5.259333333333333, -5.259333333333333, -5.36...   
9   [-5.542985817643418, -5.54114243775402, -5.260...   
10  [-5.803610116747073, -5.534606609579173, -5.28...   

                                 Test Predictions Std  
0   [0.13404624229798626, 0.13404624229798626, 0.1...  
1   [0.03000000000000007, 0.03000000000000007, 0.1...  
2   [0.03247505701970131, 0.04053999030841141, 0.1...  
3   [0.11862640051335409, 0.09625417857789582, 0.1...  
4   [0.2526009704735208, 0.2526009704735208, 0.154...  
5   [0.07813407, 0.11411654, 0.14727867, 0.2549756...  
6   [0.0031036430207112384, 0.002257565059970636, ...  
7   [0.6377077157958417, 0.5941530669253395, 0.147...  
8   [0.1053333333333331, 0.1053333333333331, 0.128...  
9   [0.29250263674532545, 0.2860508910364153, 0.18...  
10  [0.7299176581374633, 0.7427787806586372, 0.110...

In [29]:
df_extended_fp.to_csv('results/Fingerprints/Results_Extended_fp_MDCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_Extended_fp_MDCK.csv')

In [30]:
#Fingerprinter fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/Fingerprinter_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/Fingerprinter_test_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_fingerprinter_fp , pred_df= train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_fingerprinter_fp

X_train shape:  (51, 1024)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 1024)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.074684 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 84
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 28
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits 

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.7008                0.6920   
DecisionTreeRegressor                    0.8757                0.7525   
RandomForestRegressor                    0.8132                0.7496   
GradientBoostingRegressor                0.8712                0.7638   
AdaBoostRegressor                        0.8835                0.7908   
XGBRegressor                             0.8555                0.7449   
ExtraTreesRegressor                      0.8567                0.7445   
LinearRegression                         1.0138                0.7989   
KNeighborsRegressor                      0.7671                0.7000   
SVR                                      0.7676                0.7088   
MLPRegressor                             1.4228                0.9201   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8371              -0.0833   
DecisionTreeRegressor                     0.9358              -0.3537   
RandomForestRegressor                     0.9018              -0.2571   
GradientBoostingRegressor                 0.9334              -0.3467   
AdaBoostRegressor                         0.9399              -0.3658   
XGBRegressor                              0.9250              -0.3225   
ExtraTreesRegressor                       0.9256              -0.3244   
LinearRegression                          1.0069              -0.5672   
KNeighborsRegressor                       0.8759              -0.1859   
SVR                                       0.8761              -0.1865   
MLPRegressor                              1.1928              -1.1994   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.0272                0.0291   
DecisionTreeRegressor                    0.0781                0.1715   
RandomForestRegressor                    0.0604                0.1397   
GradientBoostingRegressor                0.0685                0.1256   
AdaBoostRegressor                        0.0628                0.1065   
XGBRegressor                             0.0884                0.1529   
ExtraTreesRegressor                      0.0992                0.1849   
LinearRegression                         0.0275                0.0786   
KNeighborsRegressor                      0.0561                0.0518   
SVR                                     -0.0079               -0.0076   
MLPRegressor                            -0.0757                0.0071   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.5073   0.5769    0.7122   0.1376   
DecisionTreeRegressor       0.5264   0.6152    0.7256   0.1050   
RandomForestRegressor       0.4877   0.5918    0.6983   0.1710   
GradientBoostingRegressor   0.4791   0.5732    0.6922   0.1855   
AdaBoostRegressor           0.5008   0.6195    0.7077   0.1487   
XGBRegressor                0.5443   0.6320    0.7378   0.0746   
ExtraTreesRegressor         0.5228   0.6026    0.7231   0.1112   
LinearRegression            0.4819   0.5888    0.6942   0.1808   
KNeighborsRegressor         0.6029   0.6190    0.7765  -0.0249   
SVR                         0.5144   0.5438    0.7172   0.1256   
MLPRegressor                0.4188   0.5403    0.6471   0.2881   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4284                    0.4501  
DecisionTreeRegressor                       0.4480                    0.3679  
RandomForestRegressor                       0.4611                    0.3287  
GradientBoostingRegressor                   0.4889                    0.3729  
AdaBoostRegressor                           0.4370                    0.3232  
XGBRegressor                                0.3897                    0.1796  
ExtraTreesRegressor                         0.459

In [31]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.558160996952212, -5.948035428178268, -5.94...   
1   [-4.99, -6.2219999999999995, -6.22199999999999...   
2   [-5.066547516082141, -6.193135364357865, -6.19...   
3   [-4.990807370843178, -6.222101638277233, -6.22...   
4   [-4.98, -6.359999999999999, -6.359999999999999...   
5   [-4.9899874, -6.2218585, -6.2218585, -5.739042...   
6   [-4.990000000000006, -6.221999999999991, -6.22...   
7   [-4.9899999999999975, -6.222000000000003, -6.2...   
8   [-5.183333333333334, -5.786666666666666, -5.78...   
9   [-5.039878407664466, -5.8306326450491035, -5.8...   
10  [-5.084185069434939, -6.221098011656664, -6.22...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.558160996952212, -5.558160996952212, -5.5...   
1   [[-4.99, -4.99, -4.99, -6.748412039, -5.739149...   
2   [[-5.135617619047621, -5.2175166082626205, -5....   
3   [[-5.172497143907629, -5.168416726688939, -4.9...   
4   [[-4.98, -4.98, -4.98, -6.927245587, -5.943314...   
5   [[-5.1014094, -5.087356, -4.9899874, -6.748446...   
6   [[-4.990000000000006, -4.990000000000006, -4.9...   
7   [[-4.794999999999992, -4.811511427408459, -4.9...   
8   [[-5.613333333333333, -5.613333333333333, -5.1...   
9   [[-5.5142009354753565, -5.520836777903699, -5....   
10  [[-5.874083897954992, -5.651951544365123, -5.0...   

                                Test Predictions Mean  \
0   [-5.507383922852948, -5.507383922852948, -5.50...   
1   [-4.9997, -4.9997, -5.1716999999999995, -6.524...   
2   [-5.221908540241519, -5.253101202717454, -5.20...   
3   [-5.238239753817956, -5.268910910012542, -5.16...   
4   [-5.136960557015874, -5.205432779238095, -5.17...   
5   [-5.126996, -5.34199, -5.1715727, -6.584859, -...   
6   [-5.0083000000000055, -5.092540000000005, -5.1...   
7   [-5.314792707758762, -5.250376887546194, -5.17...   
8   [-5.666, -5.666, -5.368, -6.2329041285999995, ...   
9   [-5.522728749783225, -5.521933631774096, -5.25...   
10  [-5.655726338685933, -5.46735287318324, -5.187...   

                                 Test Predictions Std  
0   [0.10397057457759268, 0.10397057457759268, 0.1...  
1   [0.21056675901005853, 0.21056675901005853, 0.1...  
2   [0.1256489021265099, 0.10708916347565378, 0.15...  
3   [0.210662778459824, 0.1386778475973629, 0.1622...  
4   [0.14843203635954935, 0.1660036634709048, 0.15...  
5   [0.19015437, 0.25940844, 0.16897678, 0.3269155...  
6   [0.19475974943503702, 0.08034877970448034, 0.1...  
7   [0.5420942432122171, 0.4727976910709499, 0.169...  
8   [0.14081350945290877, 0.14081350945290877, 0.1...  
9   [0.26250057407575483, 0.25646374229123237, 0.1...  
10  [0.7876246136553181, 0.7413610724816, 0.140888...

In [32]:
df_fingerprinter_fp.to_csv('results/Fingerprints/Results_Fingerprinter_fp_MDCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_Fingerprinter_fp_MDCK.csv')

In [33]:
#GraphOnly fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/Graphonly_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/Graphonly_test_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_graph_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_graph_fp

X_train shape:  (51, 1024)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 1024)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000276 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 54
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 18
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits 

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.7037                0.6888   
DecisionTreeRegressor                    0.9848                0.7955   
RandomForestRegressor                    0.8432                0.7617   
GradientBoostingRegressor                0.9554                0.7930   
AdaBoostRegressor                        0.7409                0.7337   
XGBRegressor                             0.9296                0.7793   
ExtraTreesRegressor                      0.9829                0.7967   
LinearRegression                         0.8642                0.7506   
KNeighborsRegressor                      0.8668                0.7656   
SVR                                      0.7731                0.7110   
MLPRegressor                             1.5800                1.0513   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8388              -0.0877   
DecisionTreeRegressor                     0.9924              -0.5223   
RandomForestRegressor                     0.9183              -0.3035   
GradientBoostingRegressor                 0.9775              -0.4769   
AdaBoostRegressor                         0.8607              -0.1452   
XGBRegressor                              0.9641              -0.4370   
ExtraTreesRegressor                       0.9914              -0.5194   
LinearRegression                          0.9296              -0.3359   
KNeighborsRegressor                       0.9310              -0.3400   
SVR                                       0.8793              -0.1951   
MLPRegressor                              1.2570              -1.4424   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.1242                0.0451   
DecisionTreeRegressor                   -0.0000               -0.0230   
RandomForestRegressor                   -0.0127                0.0584   
GradientBoostingRegressor               -0.0295               -0.0026   
AdaBoostRegressor                        0.1086                0.1708   
XGBRegressor                            -0.0032                0.0038   
ExtraTreesRegressor                     -0.0251               -0.0291   
LinearRegression                         0.0659                0.1084   
KNeighborsRegressor                     -0.0281               -0.0282   
SVR                                     -0.0188                0.0118   
MLPRegressor                            -0.0820               -0.0582   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.5315   0.5999    0.7291  0.0964   
DecisionTreeRegressor       0.3912   0.5149    0.6255  0.3349   
RandomForestRegressor       0.4003   0.5372    0.6327  0.3194   
GradientBoostingRegressor   0.3963   0.5316    0.6295  0.3263   
AdaBoostRegressor           0.3929   0.5297    0.6268  0.3320   
XGBRegressor                0.4109   0.5528    0.6410  0.3015   
ExtraTreesRegressor         0.3990   0.5282    0.6316  0.3218   
LinearRegression            0.4189   0.5606    0.6472  0.2878   
KNeighborsRegressor         0.5632   0.5597    0.7505  0.0425   
SVR                         0.4916   0.5312    0.7011  0.1643   
MLPRegressor                0.5167   0.6030    0.7188  0.1216   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4084                    0.3294  
DecisionTreeRegressor                       0.5855                    0.3923  
RandomForestRegressor                       0.5823                    0.3591  
GradientBoostingRegressor                   0.5739                    0.3923  
AdaBoostRegressor                           0.5847                    0.3702  
XGBRegressor                                0.5504                    0.2873  
ExtraTreesRegressor                         0.5711           

In [34]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.558160996952212, -5.948035428178268, -5.94...   
1   [-5.261666666666667, -6.2219999999999995, -6.2...   
2   [-5.3022464907867946, -6.193135364357865, -6.1...   
3   [-5.25750871507881, -6.222580614444872, -6.222...   
4   [-5.148333333333334, -6.359999999999999, -6.35...   
5   [-5.2615204, -6.2220006, -6.2220006, -5.887787...   
6   [-5.26166666666666, -6.221999999999991, -6.221...   
7   [-5.261666666666665, -6.222, -6.222, -5.657991...   
8   [-5.286666666666666, -5.786666666666666, -5.78...   
9   [-5.1700111837710025, -5.83019960096834, -5.83...   
10  [-6.047884558788531, -6.384036208364065, -6.38...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.558160996952212, -5.558160996952212, -5.5...   
1   [[-6.25, -6.25, -5.261666666666667, -6.7484120...   
2   [[-5.799674891774895, -5.799674891774895, -5.3...   
3   [[-6.2406161443326145, -6.2406161443326145, -5...   
4   [[-5.4275254784285725, -5.4275254784285725, -5...   
5   [[-6.2485046, -6.2485046, -5.2615204, -6.73599...   
6   [[-6.25, -6.25, -5.26166666666666, -6.74192791...   
7   [[-6.249999999999999, -6.249999999999999, -5.2...   
8   [[-5.503333333333333, -5.503333333333333, -5.2...   
9   [[-5.5394878696579815, -5.5394878696579815, -5...   
10  [[-5.840528538294072, -5.840528538294072, -6.0...   

                                Test Predictions Mean  \
0   [-5.552891276637582, -5.552891276637582, -5.55...   
1   [-5.922, -5.922, -5.346666666666668, -6.609785...   
2   [-5.68029762359589, -5.68029762359589, -5.3577...   
3   [-5.940087190573535, -5.940087190573535, -5.34...   
4   [-5.644177282676623, -5.644177282676623, -5.37...   
5   [-5.965927, -5.965927, -5.346581, -6.555928, -...   
6   [-5.932270000000002, -5.932270000000002, -5.34...   
7   [-5.964896012280277, -5.964896012280277, -5.34...   
8   [-5.472, -5.472, -5.430000000000001, -6.298406...   
9   [-5.548150441912247, -5.548150441912247, -5.35...   
10  [-5.548117524801115, -5.548117524801115, -6.12...   

                                 Test Predictions Std  
0   [0.11628391047220203, 0.11628391047220203, 0.1...  
1   [0.6559999999999998, 0.6559999999999998, 0.062...  
2   [0.27015794046184377, 0.27015794046184377, 0.0...  
3   [0.5969647341596444, 0.5969647341596444, 0.060...  
4   [0.30840309967909235, 0.30840309967909235, 0.1...  
5   [0.56540805, 0.56540805, 0.06268806, 0.3787084...  
6   [0.6354599999999963, 0.6354599999999963, 0.062...  
7   [0.570207975439447, 0.570207975439447, 0.06270...  
8   [0.18465102220134053, 0.18465102220134053, 0.1...  
9   [0.3393647411080058, 0.3393647411080058, 0.122...  
10  [0.6079070189570092, 0.6079070189570092, 0.257...

In [35]:
df_graph_fp.to_csv('results/Fingerprints/Results_Graphonly_fp_MDCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_Graphonly_fp_MDCK.csv')

In [36]:
#KlekotaRoth fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/KlekotaRoth_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/KlekotaRoth_test_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_KlekotaRoth_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_KlekotaRoth_fp

X_train shape:  (51, 4860)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 4860)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000304 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 75
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 25
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits 

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


0.668619522155389


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.7764                0.7259   
DecisionTreeRegressor                    0.9239                0.6805   
RandomForestRegressor                    0.7204                0.6628   
GradientBoostingRegressor                0.9472                0.7335   
AdaBoostRegressor                        0.7880                0.7035   
XGBRegressor                             0.9422                0.7118   
ExtraTreesRegressor                      0.9183                0.6607   
LinearRegression                         1.4481                0.9169   
KNeighborsRegressor                      0.7973                0.7288   
SVR                                      0.7207                0.6888   
MLPRegressor                             1.6815                0.9556   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8811              -0.2002   
DecisionTreeRegressor                     0.9612              -0.4282   
RandomForestRegressor                     0.8488              -0.1137   
GradientBoostingRegressor                 0.9733              -0.4643   
AdaBoostRegressor                         0.8877              -0.2181   
XGBRegressor                              0.9707              -0.4565   
ExtraTreesRegressor                       0.9583              -0.4196   
LinearRegression                          1.2034              -1.2385   
KNeighborsRegressor                       0.8929              -0.2325   
SVR                                       0.8489              -0.1141   
MLPRegressor                              1.2967              -1.5994   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.1743               -0.1977   
DecisionTreeRegressor                    0.2791                0.3538   
RandomForestRegressor                    0.2405                0.2982   
GradientBoostingRegressor                0.1228                0.1876   
AdaBoostRegressor                        0.1957                0.2251   
XGBRegressor                             0.2095                0.2675   
ExtraTreesRegressor                      0.2457                0.3279   
LinearRegression                         0.0009                0.0157   
KNeighborsRegressor                      0.1925                0.2836   
SVR                                      0.0698                0.0721   
MLPRegressor                            -0.0124                0.0017   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.5657   0.5860    0.7521  0.0383   
DecisionTreeRegressor       0.2490   0.4425    0.4990  0.5767   
RandomForestRegressor       0.1941   0.3839    0.4406  0.6700   
GradientBoostingRegressor   0.1961   0.3925    0.4428  0.6666   
AdaBoostRegressor           0.1869   0.3746    0.4323  0.6823   
XGBRegressor                0.1979   0.3890    0.4448  0.6636   
ExtraTreesRegressor         0.2383   0.4264    0.4882  0.5949   
LinearRegression            0.4075   0.5714    0.6384  0.3072   
KNeighborsRegressor         0.4118   0.5126    0.6417  0.3000   
SVR                         0.3877   0.5271    0.6227  0.3409   
MLPRegressor                0.1949   0.4024    0.4415  0.6686   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.2047                    0.2103  
DecisionTreeRegressor                       0.7619                    0.6298  
RandomForestRegressor                       0.8358                    0.7228  
GradientBoostingRegressor                   0.8203                    0.6234  
AdaBoostRegressor                           0.8344                    0.6179  
XGBRegressor                                0.8185                    0.6566  
ExtraTreesRegressor                         0.7739           

In [37]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.558160996952212, -5.948035428178268, -5.94...   
1   [-5.295, -6.97, -5.195, -5.597095796, -6.92991...   
2   [-5.37972, -6.781705000000011, -5.301308330419...   
3   [-5.339806958570261, -6.904892676348301, -5.21...   
4   [-5.353803037375001, -6.922499999999999, -5.51...   
5   [-5.2961392, -6.9689445, -5.142122, -6.027596,...   
6   [-5.2950000000000035, -6.970000000000017, -5.1...   
7   [-5.295000000000001, -6.9700000000000015, -4.9...   
8   [-5.183333333333334, -6.906666666666666, -5.44...   
9   [-5.313086057158264, -5.985939607960501, -5.48...   
10  [-5.401664388140046, -6.921812277972553, -5.10...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.558160996952212, -5.558160996952212, -5.5...   
1   [[-6.25, -6.25, -5.27, -6.927245587, -5.453495...   
2   [[-5.775941595740002, -5.81105392511928, -6.36...   
3   [[-6.154907757913286, -6.1698402942863275, -6....   
4   [[-5.390746644052632, -5.546407395466668, -6.7...   
5   [[-6.245496, -6.332196, -6.442806, -6.9264865,...   
6   [[-6.25, -6.25, -5.718499999999995, -6.9272455...   
7   [[-6.250000000000002, -6.514546486530007, -8.0...   
8   [[-5.503333333333333, -5.503333333333333, -4.8...   
9   [[-5.7897277117251775, -5.792946768825151, -5....   
10  [[-5.944901663239117, -5.798320249257092, -5.6...   

                                Test Predictions Mean  \
0   [-5.4384167708207585, -5.4384167708207585, -5....   
1   [-5.922, -5.922, -5.7763333333333335, -6.80979...   
2   [-5.668750459223013, -5.687732367614725, -6.20...   
3   [-5.863404415832678, -5.867992960325095, -6.40...   
4   [-5.504687798268892, -5.5358199485516995, -6.5...   
5   [-5.9783907, -5.9774256, -6.3995347, -6.644269...   
6   [-5.922000000000002, -5.920700000000002, -5.98...   
7   [-5.96530262896364, -6.521057604054944, -6.917...   
8   [-5.472, -5.472, -4.761333333333334, -6.220185...   
9   [-5.638075979489695, -5.636847277089234, -5.29...   
10  [-5.786672366230726, -5.6716530498434095, -5.6...   

                                 Test Predictions Std  
0   [0.07334361034928548, 0.07334361034928548, 0.0...  
1   [0.6559999999999998, 0.6559999999999998, 0.918...  
2   [0.3152534779723068, 0.32251412938011464, 0.27...  
3   [0.5869485313880611, 0.5886006848210488, 0.529...  
4   [0.15339622565132824, 0.14252290656622219, 0.3...  
5   [0.53710043, 0.46481588, 0.40066418, 0.5637051...  
6   [0.6559999999999959, 0.6553548351847225, 0.836...  
7   [0.5693947420727226, 1.0214019602942757, 0.924...  
8   [0.18465102220134053, 0.18465102220134053, 0.2...  
9   [0.4224325573178793, 0.415502513751978, 0.0580...  
10  [0.44978314503372013, 0.47041328871268795, 0.1...

In [38]:
df_KlekotaRoth_fp.to_csv('results/Fingerprints/Results_KlekotaRoth_fp_MDCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_KlekotaRoth_fp_MDCK.csv')

In [39]:
#KlekotaRoth Count fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/KlekotaRothCount_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/KlekotaRothCount_test_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_KlekotaRothCount_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_KlekotaRothCount_fp

X_train shape:  (51, 4860)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 4860)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000358 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 177
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 38
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


0.34755488396138434


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.7623                0.7334   
DecisionTreeRegressor                    1.0967                0.7905   
RandomForestRegressor                    0.6629                0.6560   
GradientBoostingRegressor                0.8595                0.7102   
AdaBoostRegressor                        0.6489                0.6456   
XGBRegressor                             0.8724                0.7256   
ExtraTreesRegressor                      0.8470                0.7106   
LinearRegression                         1.1626                0.8145   
KNeighborsRegressor                      0.7410                0.6908   
SVR                                      0.6763                0.6596   
MLPRegressor                             1.7293                0.9923   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8731              -0.1785   
DecisionTreeRegressor                     1.0472              -0.6953   
RandomForestRegressor                     0.8142              -0.0247   
GradientBoostingRegressor                 0.9271              -0.3287   
AdaBoostRegressor                         0.8056              -0.0032   
XGBRegressor                              0.9340              -0.3487   
ExtraTreesRegressor                       0.9203              -0.3094   
LinearRegression                          1.0782              -0.7972   
KNeighborsRegressor                       0.8608              -0.1454   
SVR                                       0.8223              -0.0454   
MLPRegressor                              1.3150              -1.6732   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.0296                0.0596   
DecisionTreeRegressor                    0.2017                0.2662   
RandomForestRegressor                    0.2613                0.2825   
GradientBoostingRegressor                0.2016                0.2302   
AdaBoostRegressor                        0.3153                0.3564   
XGBRegressor                             0.2453                0.3061   
ExtraTreesRegressor                      0.1986                0.2199   
LinearRegression                         0.0111                0.0509   
KNeighborsRegressor                      0.2466                0.3258   
SVR                                      0.1671                0.1417   
MLPRegressor                             0.0067                0.0511   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4757   0.5762    0.6897   0.1913   
DecisionTreeRegressor       0.5088   0.5800    0.7133   0.1350   
RandomForestRegressor       0.3150   0.4920    0.5613   0.4645   
GradientBoostingRegressor   0.4566   0.5717    0.6757   0.2239   
AdaBoostRegressor           0.3100   0.4914    0.5568   0.4729   
XGBRegressor                0.3793   0.5184    0.6159   0.3551   
ExtraTreesRegressor         0.4368   0.5635    0.6609   0.2574   
LinearRegression            1.2889   0.7265    1.1353  -1.1912   
KNeighborsRegressor         0.4180   0.5287    0.6465   0.2894   
SVR                         0.3454   0.5253    0.5877   0.4128   
MLPRegressor                0.3838   0.4609    0.6195   0.3476   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4550                    0.4558  
DecisionTreeRegressor                       0.6362                    0.4738  
RandomForestRegressor                       0.6928                    0.3471  
GradientBoostingRegressor                   0.6511                    0.4187  
AdaBoostRegressor                           0.7246                    0.4077  
XGBRegressor                                0.6905                    0.5289  
ExtraTreesRegressor                         0.659

In [40]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.646273967912512, -6.100853894779576, -6.34...   
1   [-5.295, -6.97, -4.73, -5.597095796, -6.929917...   
2   [-5.388479170829999, -6.096627910608894, -5.61...   
3   [-5.307078762310983, -6.1433452090569665, -5.4...   
4   [-5.3731234502, -5.758, -5.853725935160001, -5...   
5   [-5.2953153, -6.789957, -5.382924, -5.7190976,...   
6   [-5.2950000000000035, -6.708700000000014, -5.3...   
7   [-5.571795709, -5.331886230831336, -4.02905688...   
8   [-5.613333333333333, -5.786666666666666, -5.78...   
9   [-5.5499949765436405, -5.582080580038937, -5.6...   
10  [-6.208863066490276, -5.937389006402623, -6.12...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.646273967912512, -5.500581732532101, -5.7...   
1   [[-4.61, -6.25, -7.82, -6.927245587, -4.61, -5...   
2   [[-5.13659546535203, -5.944299587750141, -6.70...   
3   [[-4.6942009558700875, -6.224347845846239, -7....   
4   [[-5.0333457856923065, -5.8608909024999996, -6...   
5   [[-4.886671, -6.239877, -6.1954083, -6.926992,...   
6   [[-4.631000000000009, -6.083473426140002, -7.6...   
7   [[-4.396637152058657, -5.976127702592757, -10....   
8   [[-5.503333333333333, -5.503333333333333, -5.6...   
9   [[-5.395633442130889, -5.883097707240995, -5.7...   
10  [[-5.67345632523625, -5.595089246864329, -8.37...   

                                Test Predictions Mean  \
0   [-5.484328756914797, -5.377426208017633, -5.73...   
1   [-4.708, -5.9, -7.33, -6.809796469599999, -5.5...   
2   [-5.171218436726399, -5.778331449435433, -6.58...   
3   [-4.876018214373124, -5.934314785751728, -7.12...   
4   [-5.1580099106256965, -5.79013358053692, -6.53...   
5   [-4.970583, -5.989621, -6.7077003, -6.8290367,...   
6   [-4.8463583197740085, -5.909614685228002, -7.0...   
7   [-4.651433057414922, -5.382584089024481, -9.54...   
8   [-5.472, -5.472, -5.482666666666667, -6.220185...   
9   [-5.399348638342914, -5.752008449919346, -5.68...   
10  [-5.047321193681469, -5.497866841580164, -7.28...   

                                 Test Predictions Std  
0   [0.19271094120438179, 0.24682934479138555, 0.0...  
1   [0.19599999999999973, 0.7, 0.6214177338956463,...  
2   [0.2297414553539115, 0.29074522217371146, 0.41...  
3   [0.3726419259742494, 0.4817280750383375, 0.815...  
4   [0.20916519510107348, 0.27089216134759325, 0.3...  
5   [0.41299576, 0.46861646, 0.72191, 0.19605963, ...  
6   [0.4416890259014868, 0.5983225262748127, 0.694...  
7   [0.5141862702677118, 0.6177299295697716, 0.646...  
8   [0.18465102220134053, 0.18465102220134053, 0.0...  
9   [0.3090633676309614, 0.29446790017240904, 0.10...  
10  [0.4137418921304826, 0.8430326004907909, 0.721...

In [41]:
df_KlekotaRothCount_fp.to_csv('results/Fingerprints/Results_KlekotaRoth_Count_fp_MDCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_KlekotaRoth_Count_fp_MDCK.csv')

In [42]:
#MACCS fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/MACCS_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/MACCS_test_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_MACCS_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_MACCS_fp

X_train shape:  (51, 166)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 166)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000183 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 1
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


0.35822785310430516


/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.7695                0.7186   
DecisionTreeRegressor                    1.0227                0.7926   
RandomForestRegressor                    0.8453                0.7543   
GradientBoostingRegressor                1.0106                0.7726   
AdaBoostRegressor                        0.8100                0.7571   
XGBRegressor                             0.9671                0.7906   
ExtraTreesRegressor                      1.0412                0.8008   
LinearRegression                         0.8604                0.6987   
KNeighborsRegressor                      0.9168                0.7714   
SVR                                      0.8291                0.7390   
MLPRegressor                             1.4626                0.9455   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8772              -0.1896   
DecisionTreeRegressor                     1.0113              -0.5809   
RandomForestRegressor                     0.9194              -0.3067   
GradientBoostingRegressor                 1.0053              -0.5623   
AdaBoostRegressor                         0.9000              -0.2521   
XGBRegressor                              0.9834              -0.4950   
ExtraTreesRegressor                       1.0204              -0.6095   
LinearRegression                          0.9276              -0.3300   
KNeighborsRegressor                       0.9575              -0.4173   
SVR                                       0.9106              -0.2817   
MLPRegressor                              1.2094              -1.2609   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.1656               -0.1820   
DecisionTreeRegressor                    0.0742                0.1474   
RandomForestRegressor                    0.0604                0.1128   
GradientBoostingRegressor               -0.0217                0.0228   
AdaBoostRegressor                        0.1300                0.2009   
XGBRegressor                             0.0048                0.0533   
ExtraTreesRegressor                      0.0473                0.1064   
LinearRegression                         0.1589                0.3216   
KNeighborsRegressor                      0.0711                0.1530   
SVR                                     -0.0549               -0.0594   
MLPRegressor                            -0.0873               -0.0180   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.5657   0.5871    0.7521  0.0383   
DecisionTreeRegressor       0.3916   0.5347    0.6258  0.3342   
RandomForestRegressor       0.4321   0.5515    0.6573  0.2655   
GradientBoostingRegressor   0.4066   0.5280    0.6376  0.3088   
AdaBoostRegressor           0.4400   0.5868    0.6634  0.2519   
XGBRegressor                0.4413   0.5647    0.6643  0.2498   
ExtraTreesRegressor         0.4131   0.5405    0.6428  0.2977   
LinearRegression            0.5144   0.6177    0.7172  0.1256   
KNeighborsRegressor         0.5381   0.5565    0.7335  0.0852   
SVR                         0.4931   0.5250    0.7022  0.1617   
MLPRegressor                0.3775   0.4814    0.6144  0.3582   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.2038                    0.2103  
DecisionTreeRegressor                       0.5928                    0.4690  
RandomForestRegressor                       0.5342                    0.3255  
GradientBoostingRegressor                   0.5710                    0.4745  
AdaBoostRegressor                           0.5150                    0.2703  
XGBRegressor                                0.5171                    0.4359  
ExtraTreesRegressor                         0.5653           

In [43]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.558160996952212, -5.948035428178268, -5.94...   
1   [-5.295, -6.906666666666666, -6.90666666666666...   
2   [-5.3739799999999995, -6.8193583333333345, -6....   
3   [-5.252794031482575, -6.88253649380844, -6.882...   
4   [-5.236666666666667, -6.875, -6.875, -5.757542...   
5   [-5.294951, -6.9061813, -6.9061813, -5.72279, ...   
6   [-5.2950000000000035, -6.906666666666649, -6.9...   
7   [-5.321839713533342, -6.906666666666666, -6.90...   
8   [-5.286666666666666, -6.906666666666666, -6.90...   
9   [-5.339483766963183, -5.897711454315428, -5.89...   
10  [-5.308402361221416, -6.625565163894602, -6.62...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.558160996952212, -5.558160996952212, -5.5...   
1   [[-6.25, -6.34, -4.6850000000000005, -6.748412...   
2   [[-5.785365000000001, -5.862533904681032, -4.8...   
3   [[-6.222541999997616, -6.809201562448811, -4.7...   
4   [[-5.495, -6.12, -4.822, -6.199603009750001, -...   
5   [[-6.2486796, -6.2814302, -4.687504, -6.748048...   
6   [[-6.25, -6.339999999999998, -4.68500000000000...   
7   [[-6.196320572933323, -6.145328338738971, -5.3...   
8   [[-5.503333333333333, -5.503333333333333, -4.7...   
9   [[-6.09056301496793, -6.056839776128437, -4.98...   
10  [[-5.92282000017515, -5.407116002738321, -5.14...   

                                Test Predictions Mean  \
0   [-5.444607587024519, -5.444607587024519, -5.44...   
1   [-5.922, -5.9399999999999995, -5.2882000000000...   
2   [-5.58041693282488, -5.615398868105131, -5.076...   
3   [-5.918385764352299, -6.128441812503406, -5.21...   
4   [-5.472389474650001, -5.737549046233334, -5.25...   
5   [-5.9768705, -5.9819894, -5.1174865, -6.494063...   
6   [-5.9251200000000015, -5.941560000000002, -5.1...   
7   [-6.276144949011792, -6.369568718143008, -7.09...   
8   [-5.472, -5.472, -4.7, -6.155622903666667, -5....   
9   [-5.8431152276716345, -5.825878467151289, -4.9...   
10  [-5.579747570968072, -5.214213302128874, -5.20...   

                                 Test Predictions Std  
0   [0.07660067285868521, 0.07660067285868521, 0.0...  
1   [0.6559999999999998, 0.6659129072183537, 0.738...  
2   [0.3727613415270713, 0.38368662633258865, 0.19...  
3   [0.6356978156817632, 0.7839450381941758, 0.422...  
4   [0.3609214205154662, 0.34136457342377896, 0.26...  
5   [0.5436527, 0.54774797, 0.49094775, 0.50878865...  
6   [0.6497599999999963, 0.6589628262656361, 0.598...  
7   [0.07998601035554936, 0.296464477933415, 0.887...  
8   [0.18465102220134053, 0.18465102220134053, 0.0...  
9   [0.40488388841953127, 0.37827187339151847, 0.0...  
10  [0.8020284066296077, 0.6308926102796811, 0.188...

In [44]:
df_MACCS_fp.to_csv('results/Fingerprints/Results_MACCS_fp_MDCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_MACCS_fp_MDCK.csv')

In [45]:
#PubChem fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/PubChem_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/PubChem_test_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_PubChem_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_PubChem_fp

X_train shape:  (51, 881)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 881)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000191 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 18
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 6
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits wit

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6960                0.6868   
DecisionTreeRegressor                    0.8744                0.7535   
RandomForestRegressor                    0.7489                0.7101   
GradientBoostingRegressor                0.8690                0.7483   
AdaBoostRegressor                        0.8041                0.7429   
XGBRegressor                             0.8323                0.7166   
ExtraTreesRegressor                      0.8650                0.7461   
LinearRegression                         0.8498                0.7289   
KNeighborsRegressor                      0.7581                0.6792   
SVR                                      0.7180                0.6721   
MLPRegressor                             1.3549                0.8795   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8343              -0.0759   
DecisionTreeRegressor                     0.9351              -0.3516   
RandomForestRegressor                     0.8654              -0.1577   
GradientBoostingRegressor                 0.9322              -0.3433   
AdaBoostRegressor                         0.8967              -0.2430   
XGBRegressor                              0.9123              -0.2866   
ExtraTreesRegressor                       0.9300              -0.3371   
LinearRegression                          0.9218              -0.3137   
KNeighborsRegressor                       0.8707              -0.1719   
SVR                                       0.8474              -0.1100   
MLPRegressor                              1.1640              -1.0944   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.1047                0.0305   
DecisionTreeRegressor                    0.1181                0.1702   
RandomForestRegressor                    0.1443                0.1766   
GradientBoostingRegressor                0.1101                0.1537   
AdaBoostRegressor                        0.1033                0.1097   
XGBRegressor                             0.1487                0.2058   
ExtraTreesRegressor                      0.1263                0.1764   
LinearRegression                         0.1314                0.1413   
KNeighborsRegressor                      0.1431                0.2075   
SVR                                      0.1221                0.0932   
MLPRegressor                            -0.0284               -0.0003   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.5304   0.5976    0.7283  0.0984   
DecisionTreeRegressor       0.3970   0.5575    0.6301  0.3250   
RandomForestRegressor       0.3776   0.5262    0.6145  0.3581   
GradientBoostingRegressor   0.3844   0.5437    0.6200  0.3465   
AdaBoostRegressor           0.3490   0.5033    0.5908  0.4066   
XGBRegressor                0.3932   0.5547    0.6270  0.3316   
ExtraTreesRegressor         0.3970   0.5575    0.6301  0.3251   
LinearRegression            0.3772   0.5189    0.6142  0.3587   
KNeighborsRegressor         0.5470   0.5862    0.7396  0.0701   
SVR                         0.4550   0.5218    0.6746  0.2264   
MLPRegressor                0.3902   0.5399    0.6247  0.3366   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4284                    0.3717  
DecisionTreeRegressor                       0.5862                    0.3873  
RandomForestRegressor                       0.6056                    0.3679  
GradientBoostingRegressor                   0.5965                    0.4011  
AdaBoostRegressor                           0.6521                    0.3679  
XGBRegressor                                0.5904                    0.3873  
ExtraTreesRegressor                         0.5863           

In [46]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.558160996952212, -5.948035428178268, -5.94...   
1   [-5.295, -6.2219999999999995, -6.2219999999999...   
2   [-5.380913333333332, -6.193135364357865, -6.19...   
3   [-5.33086499502761, -6.232040055044521, -6.232...   
4   [-5.386670581, -6.359999999999999, -6.35999999...   
5   [-5.295287, -6.2218337, -6.2218337, -5.7391624...   
6   [-5.2950000000000035, -6.221999999999991, -6.2...   
7   [-5.6011764705882365, -6.221999999999999, -6.2...   
8   [-5.286666666666666, -5.786666666666666, -5.78...   
9   [-5.449844411179285, -5.830286437610772, -5.83...   
10  [-5.494207824897073, -6.217153495142174, -6.21...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.558160996952212, -5.558160996952212, -5.5...   
1   [[-6.25, -6.25, -5.295, -6.748412039, -5.73914...   
2   [[-5.880185143395239, -5.880185143395239, -5.3...   
3   [[-6.205779559079003, -6.205779559079003, -5.3...   
4   [[-6.0956540701428565, -6.0956540701428565, -5...   
5   [[-6.2474337, -6.2474337, -5.295287, -6.748368...   
6   [[-6.25, -6.25, -5.2950000000000035, -6.748412...   
7   [[-5.63764705882353, -5.63764705882353, -5.601...   
8   [[-5.613333333333333, -5.613333333333333, -5.2...   
9   [[-5.826164230663535, -5.826164230663535, -5.4...   
10  [[-6.2178518989969085, -6.2178518989969085, -5...   

                                Test Predictions Mean  \
0   [-5.567076712219281, -5.567076712219281, -5.56...   
1   [-5.948, -5.948, -5.470000000000001, -6.577568...   
2   [-5.7037480742905755, -5.7037480742905755, -5....   
3   [-5.905872592757811, -5.905872592757811, -5.48...   
4   [-5.701035575933333, -5.701035575933333, -5.53...   
5   [-5.9309845, -5.9309845, -5.4700813, -6.545954...   
6   [-5.947300000000001, -5.947300000000001, -5.47...   
7   [-5.619219251336899, -5.619219251336899, -5.63...   
8   [-5.666, -5.666, -5.430000000000001, -6.232904...   
9   [-5.684033741104497, -5.684033741104497, -5.54...   
10  [-5.852255304035849, -5.852255304035849, -5.60...   

                                 Test Predictions Std  
0   [0.1272708901920145, 0.1272708901920145, 0.127...  
1   [0.604, 0.604, 0.1476143624448516, 0.341687398...  
2   [0.34439656858910195, 0.34439656858910195, 0.1...  
3   [0.6112492768903168, 0.6112492768903168, 0.136...  
4   [0.5255181313142169, 0.5255181313142169, 0.191...  
5   [0.6340118, 0.6340118, 0.14750703, 0.4040401, ...  
6   [0.6053999999999969, 0.6053999999999969, 0.147...  
7   [0.4910505110106937, 0.4910505110106937, 0.180...  
8   [0.14081350945290877, 0.14081350945290877, 0.1...  
9   [0.2313210106073283, 0.2313210106073283, 0.136...  
10  [0.7071605051826132, 0.7071605051826132, 0.149...

In [47]:
df_PubChem_fp.to_csv('results/Fingerprints/Results_PubChem_fp_MDCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_PubChem_fp_MDCK.csv')

In [48]:
#Substructure fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/Substructure_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/Substructure_test_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_Substructure_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_Substructure_fp

X_train shape:  (51, 307)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 307)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 0
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because ther

/tmp/ipykernel_3799211/3970550512.py:47: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  pearson_test, _ = pearsonr(y_test, predictions_test_mean)
/tmp/ipykernel_3799211/3970550512.py:48: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  spearman_test, _ = spearmanr(y_test, predictions_test_mean)


0.16785552978927254
0.16683264642981266
0.15958016186535295
0.1703795471391767
0.1703896633692521
0.16194087316581762
-0.06517317244734078
-0.005025847259860994


/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't 

0.10660882174864461


/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6869                0.6819   
DecisionTreeRegressor                    0.7918                0.6948   
RandomForestRegressor                    0.7534                0.6977   
GradientBoostingRegressor                0.7986                0.7077   
AdaBoostRegressor                        0.8045                0.7372   
XGBRegressor                             0.8102                0.7129   
ExtraTreesRegressor                      0.7941                0.7006   
LinearRegression                         0.7479                0.6872   
KNeighborsRegressor                      0.9029                0.7813   
SVR                                      0.7302                0.6732   
MLPRegressor                             1.1433                0.8536   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8288              -0.0618   
DecisionTreeRegressor                     0.8898              -0.2240   
RandomForestRegressor                     0.8680              -0.1646   
GradientBoostingRegressor                 0.8936              -0.2345   
AdaBoostRegressor                         0.8969              -0.2436   
XGBRegressor                              0.9001              -0.2525   
ExtraTreesRegressor                       0.8911              -0.2276   
LinearRegression                          0.8648              -0.1562   
KNeighborsRegressor                       0.9502              -0.3958   
SVR                                       0.8545              -0.1289   
MLPRegressor                              1.0692              -0.7673   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.3293               -0.3067   
DecisionTreeRegressor                    0.1116                0.1723   
RandomForestRegressor                    0.0817                0.1408   
GradientBoostingRegressor                0.0834                0.1486   
AdaBoostRegressor                        0.0083                0.0701   
XGBRegressor                             0.0880                0.1310   
ExtraTreesRegressor                      0.1049                0.1588   
LinearRegression                         0.1189                0.1574   
KNeighborsRegressor                     -0.0022                0.0890   
SVR                                      0.1182                0.1394   
MLPRegressor                             0.0593                0.0567   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.5884   0.6227    0.7670  -0.0002   
DecisionTreeRegressor       0.4880   0.5595    0.6986   0.1704   
RandomForestRegressor       0.4895   0.5637    0.6996   0.1679   
GradientBoostingRegressor   0.4901   0.5663    0.7001   0.1668   
AdaBoostRegressor           0.4944   0.5834    0.7031   0.1596   
XGBRegressor                0.4880   0.5596    0.6986   0.1704   
ExtraTreesRegressor         0.4880   0.5595    0.6986   0.1704   
LinearRegression            0.4930   0.5694    0.7021   0.1619   
KNeighborsRegressor         0.6266   0.6128    0.7916  -0.0652   
SVR                         0.5912   0.5839    0.7689  -0.0050   
MLPRegressor                0.5255   0.6070    0.7249   0.1066   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                                  nan                       nan  
DecisionTreeRegressor                       0.4378                    0.3563  
RandomForestRegressor                       0.4366                    0.3037  
GradientBoostingRegressor                   0.4338                    0.3037  
AdaBoostRegressor                           0.4085                    0.3037  
XGBRegressor                                0.4378                    0.3563  
ExtraTreesRegressor                         0.437

In [49]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.753098213672638, -5.753098213672638, -5.75...   
1   [-5.248000000000001, -6.2219999999999995, -6.2...   
2   [-5.262657238594738, -6.193135364357863, -6.19...   
3   [-5.239946364820966, -6.205628348380743, -6.20...   
4   [-5.141818181818182, -6.27, -6.27, -5.85171165...   
5   [-5.2481537, -6.221691, -6.221691, -5.8582783,...   
6   [-5.247999999999995, -6.221999999999991, -6.22...   
7   [-5.200000000000001, -6.222, -6.222, -5.858261...   
8   [-5.613333333333333, -5.786666666666666, -5.78...   
9   [-5.059962382312374, -5.829816096728328, -5.82...   
10  [-5.371655873991237, -6.233935348019296, -6.23...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.753098213672638, -5.753098213672638, -5.7...   
1   [[-5.248000000000001, -5.248000000000001, -5.2...   
2   [[-5.262657238594736, -5.262657238594736, -5.2...   
3   [[-5.239946364820966, -5.239946364820966, -5.2...   
4   [[-5.141818181818182, -5.141818181818182, -5.1...   
5   [[-5.2481537, -5.2481537, -5.2481537, -5.85827...   
6   [[-5.247999999999995, -5.247999999999995, -5.2...   
7   [[-5.200000000000001, -5.200000000000001, -5.2...   
8   [[-5.613333333333333, -5.613333333333333, -5.6...   
9   [[-5.059962382312374, -5.059962382312374, -5.0...   
10  [[-5.371655873991237, -5.371655873991237, -5.3...   

                                Test Predictions Mean  \
0   [-5.67155390815037, -5.67155390815037, -5.6715...   
1   [-5.227047474747475, -5.227047474747475, -5.22...   
2   [-5.228165137862137, -5.228165137862137, -5.22...   
3   [-5.222593143880853, -5.222593143880853, -5.22...   
4   [-5.227523410799726, -5.227523410799726, -5.22...   
5   [-5.2272468, -5.2272468, -5.2272468, -5.807703...   
6   [-5.227047474747475, -5.227047474747475, -5.22...   
7   [-5.183047712235579, -5.183047712235579, -5.18...   
8   [-5.6259999999999994, -5.6259999999999994, -5....   
9   [-5.100126817337005, -5.100126817337005, -5.10...   
10  [-5.377759648070336, -5.377759648070336, -5.37...   

                                 Test Predictions Std  
0   [0.06667572909639166, 0.06667572909639166, 0.0...  
1   [0.06409102527231963, 0.06409102527231963, 0.0...  
2   [0.06795565984511047, 0.06795565984511047, 0.0...  
3   [0.0642889610917146, 0.0642889610917146, 0.064...  
4   [0.11937436832431304, 0.11937436832431304, 0.1...  
5   [0.064050004, 0.064050004, 0.064050004, 0.0729...  
6   [0.06409102527231592, 0.06409102527231592, 0.0...  
7   [0.09545678219236824, 0.09545678219236824, 0.0...  
8   [0.16096100286853474, 0.16096100286853474, 0.1...  
9   [0.057708193318498226, 0.057708193318498226, 0...  
10  [0.06812084475794218, 0.06812084475794218, 0.0...

In [50]:
df_Substructure_fp.to_csv('results/Fingerprints/Results_Substructure_fp_MDCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_Substructure_fp_MDCK.csv')

In [51]:
#Substructure Count fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/SubstructureCount_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/SubstructureCount_test_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_SubstructureCount_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_SubstructureCount_fp

X_train shape:  (51, 307)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 307)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000182 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 18
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 2
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits wit

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't 

0.324767405731352


/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6813                0.6884   
DecisionTreeRegressor                    0.9228                0.7283   
RandomForestRegressor                    0.6837                0.6620   
GradientBoostingRegressor                0.8236                0.7077   
AdaBoostRegressor                        0.7001                0.6874   
XGBRegressor                             0.9168                0.7407   
ExtraTreesRegressor                      0.8139                0.6934   
LinearRegression                         0.7815                0.6885   
KNeighborsRegressor                      0.6696                0.6340   
SVR                                      0.7360                0.6888   
MLPRegressor                             1.1246                0.7996   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8254              -0.0532   
DecisionTreeRegressor                     0.9606              -0.4265   
RandomForestRegressor                     0.8268              -0.0569   
GradientBoostingRegressor                 0.9075              -0.2731   
AdaBoostRegressor                         0.8367              -0.0823   
XGBRegressor                              0.9575              -0.4172   
ExtraTreesRegressor                       0.9022              -0.2582   
LinearRegression                          0.8840              -0.2080   
KNeighborsRegressor                       0.8183              -0.0351   
SVR                                       0.8579              -0.1377   
MLPRegressor                              1.0605              -0.7385   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.0743                0.1752   
DecisionTreeRegressor                    0.1862                0.2826   
RandomForestRegressor                    0.2588                0.2755   
GradientBoostingRegressor                0.1980                0.2534   
AdaBoostRegressor                        0.2339                0.1953   
XGBRegressor                             0.2182                0.3135   
ExtraTreesRegressor                      0.2424                0.2959   
LinearRegression                         0.2964                0.2859   
KNeighborsRegressor                      0.2981                0.3094   
SVR                                      0.1127                0.0952   
MLPRegressor                             0.0426                0.0462   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4716   0.5574    0.6867   0.1983   
DecisionTreeRegressor       0.4878   0.5835    0.6984   0.1707   
RandomForestRegressor       0.3344   0.4977    0.5783   0.4314   
GradientBoostingRegressor   0.4014   0.5314    0.6335   0.3177   
AdaBoostRegressor           0.2652   0.4465    0.5150   0.5491   
XGBRegressor                0.4759   0.5724    0.6898   0.1910   
ExtraTreesRegressor         0.4090   0.5417    0.6395   0.3047   
LinearRegression            0.7821   0.5948    0.8843  -0.3295   
KNeighborsRegressor         0.3977   0.5026    0.6306   0.3239   
SVR                         0.4415   0.5193    0.6644   0.2495   
MLPRegressor                0.3972   0.5125    0.6302   0.3248   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5192                    0.4101  
DecisionTreeRegressor                       0.6104                    0.3829  
RandomForestRegressor                       0.6754                    0.3802  
GradientBoostingRegressor                   0.6659                    0.5289  
AdaBoostRegressor                           0.7574                    0.4573  
XGBRegressor                                0.6374                    0.4187  
ExtraTreesRegressor                         0.670

In [52]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.965745329504426, -5.965745329504426, -5.96...   
1   [-5.295, -5.195, -6.97, -5.597095796, -6.92991...   
2   [-5.408102455869999, -5.332574170829997, -6.52...   
3   [-5.326105804774353, -5.247943638226798, -6.89...   
4   [-5.629859874000001, -5.88846153846154, -5.949...   
5   [-5.294992, -5.195351, -6.9684587, -5.719072, ...   
6   [-5.2950000000000035, -5.194999999999996, -6.9...   
7   [-5.31004418799253, -5.347058823529404, -6.076...   
8   [-5.613333333333333, -5.786666666666666, -5.78...   
9   [-5.549524703515771, -5.8088465923891786, -5.8...   
10  [-5.671592497684188, -6.2245561551734845, -6.2...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.965745329504426, -5.540451101521032, -5.9...   
1   [[-4.73, -6.25, -7.82, -6.927245587, -5.453495...   
2   [[-5.092809278564007, -5.989568416857331, -6.7...   
3   [[-4.935964109469702, -6.233585524594672, -6.9...   
4   [[-5.2292905595, -5.891419724941175, -5.949034...   
5   [[-5.022625, -6.2498746, -7.047421, -6.9253483...   
6   [[-4.9377000000000075, -6.25, -7.5051666666666...   
7   [[-5.042728462752941, -5.439568559636504, -8.2...   
8   [[-5.613333333333333, -5.613333333333333, -5.6...   
9   [[-5.416662195074671, -5.766882434821846, -5.5...   
10  [[-5.634787090912264, -4.989064893212669, -5.7...   

                                Test Predictions Mean  \
0   [-5.719544843823677, -5.4137902827731335, -5.6...   
1   [-4.779999999999999, -6.244, -6.66800000000000...   
2   [-5.185977128007052, -5.983516601056534, -6.50...   
3   [-4.944951618875127, -6.098908743899988, -6.78...   
4   [-5.314187798773334, -5.709613707686257, -6.03...   
5   [-5.0143595, -6.145154, -6.9321012, -6.672248,...   
6   [-5.090964350974342, -6.112917976365003, -6.81...   
7   [-4.907157673926278, -5.2872154537543485, -8.3...   
8   [-5.666, -5.666, -5.6259999999999994, -6.14811...   
9   [-5.514204265643601, -5.745455817431809, -5.65...   
10  [-5.721043771002203, -4.938571473298813, -5.78...   

                                 Test Predictions Std  
0   [0.15359601056705807, 0.15486389547404905, 0.1...  
1   [0.22645087767549038, 0.012000000000000099, 1....  
2   [0.21500109989896082, 0.21131925066285692, 0.3...  
3   [0.17561319844768833, 0.2869821943330493, 0.69...  
4   [0.10801011433693447, 0.26510914394588814, 0.2...  
5   [0.24009685, 0.20975846, 0.72851145, 0.5074491...  
6   [0.2434378209427003, 0.27416404726999555, 0.76...  
7   [0.4849634998391451, 0.49119349830531944, 0.30...  
8   [0.14081350945290877, 0.14081350945290877, 0.1...  
9   [0.1161309894522857, 0.14436930471275064, 0.09...  
10  [0.4311261754146368, 0.44557989010586607, 0.29...

In [53]:
df_SubstructureCount_fp.to_csv('results/Fingerprints/Results_Substructure_Count_fp_MDCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_Substructure_Count_fp_MDCK.csv')

In [91]:
#Descriptors models
#2d RDKit descriptors
df_train = pd.read_csv('features/Descriptors/Train_2d_RDKit_des_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_RDKit_des_MDCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models_2drdkit = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models_2drdkit, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 217)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 217)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000052 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 335
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 30
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits w

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-1.549197709861739


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6144                0.6330   
DecisionTreeRegressor                    1.2977                0.8937   
RandomForestRegressor                    0.7069                0.6854   
GradientBoostingRegressor                0.9661                0.7816   
AdaBoostRegressor                        0.7967                0.7064   
XGBRegressor                             1.0072                0.8138   
ExtraTreesRegressor                      0.8096                0.7086   
LinearRegression                         3.1917                1.2767   
KNeighborsRegressor                      0.6755                0.6557   
SVR                                      0.6259                0.6268   
MLPRegressor                             1.2997                0.8620   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7839               0.0502   
DecisionTreeRegressor                     1.1392              -1.0061   
RandomForestRegressor                     0.8408              -0.0927   
GradientBoostingRegressor                 0.9829              -0.4934   
AdaBoostRegressor                         0.8926              -0.2315   
XGBRegressor                              1.0036              -0.5569   
ExtraTreesRegressor                       0.8998              -0.2516   
LinearRegression                          1.7865              -3.9339   
KNeighborsRegressor                       0.8219              -0.0442   
SVR                                       0.7911               0.0325   
MLPRegressor                              1.1400              -1.0091   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2600                0.3210   
DecisionTreeRegressor                    0.1172                0.2267   
RandomForestRegressor                    0.2157                0.2519   
GradientBoostingRegressor                0.1290                0.1707   
AdaBoostRegressor                        0.2161                0.2615   
XGBRegressor                             0.0438                0.0625   
ExtraTreesRegressor                      0.1956                0.2083   
LinearRegression                         0.1092                0.0432   
KNeighborsRegressor                      0.2830                0.3192   
SVR                                      0.2918                0.2408   
MLPRegressor                             0.0868                0.1529   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.3853   0.5321    0.6207   0.3451   
DecisionTreeRegressor       0.3965   0.5358    0.6297   0.3260   
RandomForestRegressor       0.3114   0.4802    0.5580   0.4706   
GradientBoostingRegressor   0.3572   0.4835    0.5977   0.3927   
AdaBoostRegressor           0.2981   0.4464    0.5460   0.4933   
XGBRegressor                0.4038   0.5400    0.6354   0.3136   
ExtraTreesRegressor         0.3799   0.5331    0.6164   0.3541   
LinearRegression            1.3923   0.8926    1.1800  -1.3670   
KNeighborsRegressor         0.3357   0.4399    0.5794   0.4293   
SVR                         0.3195   0.4926    0.5652   0.4568   
MLPRegressor                1.4995   0.8344    1.2245  -1.5492   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6541                    0.5096  
DecisionTreeRegressor                       0.6943                    0.3274  
RandomForestRegressor                       0.7130                    0.3604  
GradientBoostingRegressor                   0.7209                    0.4539  
AdaBoostRegressor                           0.7324                    0.3879  
XGBRegressor                                0.7114                    0.3879  
ExtraTreesRegressor                         0.706

In [92]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.536143010992385, -6.156816999215223, -6.29...   
1   [-5.65, -5.06, -6.97, -6.929917083, -6.9299170...   
2   [-5.277899170829996, -5.309295784909999, -6.34...   
3   [-5.10865391642442, -5.187262267679404, -6.903...   
4   [-5.242156934117649, -5.317665433749999, -6.82...   
5   [-4.922271, -5.8616314, -7.1029534, -5.7418523...   
6   [-5.119283850859998, -5.1053, -6.7394941265700...   
7   [-4.0, -7.956188319024213, -6.4103483481406025...   
8   [-5.3133333333333335, -5.786666666666666, -6.0...   
9   [-5.554470524037222, -5.224643213908656, -5.62...   
10  [-5.1148448476817, -5.148021258903937, -6.0827...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.664411161024185, -5.792529113538625, -5.7...   
1   [[-5.65, -4.94, -6.25, -6.929917083, -5.453495...   
2   [[-5.60912975092, -5.545679234792003, -6.35578...   
3   [[-5.895069707573125, -5.7681843646683815, -6....   
4   [[-5.30537681240909, -5.491019461714286, -5.65...   
5   [[-5.7401524, -5.666066, -6.3228106, -6.709675...   
6   [[-5.15835, -5.91154917083, -7.550736713070008...   
7   [[-4.0, -9.254455419528936, -4.0, -6.840685888...   
8   [[-5.613333333333333, -5.613333333333334, -6.1...   
9   [[-5.738491452700495, -5.999657212622324, -5.8...   
10  [[-4.0, -5.40060305747878, -10.0, -6.846729996...   

                                Test Predictions Mean  \
0   [-5.666812029931583, -5.5713305480511535, -5.8...   
1   [-5.5760000000000005, -5.782, -6.3119999999999...   
2   [-5.568364454949996, -5.5855388292121635, -6.3...   
3   [-5.693704748868479, -5.596495097337898, -6.70...   
4   [-5.41521975647831, -5.479923217749817, -6.082...   
5   [-5.6514807, -5.726673, -7.0044594, -6.63848, ...   
6   [-5.304833137838003, -5.851357010354502, -7.05...   
7   [-6.617857950485297, -7.527326511204049, -4.0,...   
8   [-5.6259999999999994, -5.4126666666666665, -6....   
9   [-5.658532807919006, -5.823951875610088, -5.74...   
10  [-4.2778249446564685, -5.064419918491657, -9.6...   

                                 Test Predictions Std  
0   [0.21835822613593237, 0.20002140796917076, 0.0...  
1   [0.3269617714657173, 0.482883008605604, 0.5778...  
2   [0.10992182033011405, 0.18689638979762557, 0.1...  
3   [0.2772084735419424, 0.2891247922495179, 0.423...  
4   [0.20463762584889672, 0.16790784110240162, 0.3...  
5   [0.30661, 0.43052056, 0.7034079, 0.45411754, 0...  
6   [0.2612945064810428, 0.43699463695086216, 0.51...  
7   [2.7900054093189843, 1.9556044090199518, 0.0, ...  
8   [0.16096100286853474, 0.2143766156401708, 0.24...  
9   [0.07794986786521718, 0.2884268542234521, 0.08...  
10  [0.3148066519209317, 0.5631852619846156, 0.445...

In [93]:
result_df.to_csv('results/Descriptors/Results_2d_RDKit_desc_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2d_RDKit_desc_MDCK.csv')

In [94]:
#2d Mordred descriptors
df_train = pd.read_csv('features/Descriptors/Train_2d_Mordred_desc_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_Mordred_desc_MDCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = X_test.select_dtypes(include=['number'])
X_test = X_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models_2dM = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df , prediction_df= train_and_test_predict(models_2dM, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 1436)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 1436)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000302 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 4840
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 360
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spli

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.5689                0.6356   
DecisionTreeRegressor                    1.0439                0.7474   
RandomForestRegressor                    0.6209                0.6574   
GradientBoostingRegressor                0.6643                0.6710   
AdaBoostRegressor                        0.6278                0.6222   
XGBRegressor                             0.7272                0.6806   
ExtraTreesRegressor                      0.6327                0.6560   
LinearRegression                         1.4614                0.8733   
KNeighborsRegressor                      0.6446                0.6277   
SVR                                      0.6499                0.6327   
MLPRegressor                             1.2783                0.8651   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7543               0.1205   
DecisionTreeRegressor                     1.0217              -0.6136   
RandomForestRegressor                     0.7880               0.0401   
GradientBoostingRegressor                 0.8150              -0.0269   
AdaBoostRegressor                         0.7923               0.0296   
XGBRegressor                              0.8528              -0.1242   
ExtraTreesRegressor                       0.7954               0.0219   
LinearRegression                          1.2089              -1.2591   
KNeighborsRegressor                       0.8029               0.0036   
SVR                                       0.8062              -0.0047   
MLPRegressor                              1.1306              -0.9761   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.3732                0.4268   
DecisionTreeRegressor                    0.0828                0.1914   
RandomForestRegressor                    0.2795                0.2783   
GradientBoostingRegressor                0.2614                0.2445   
AdaBoostRegressor                        0.3270                0.3204   
XGBRegressor                             0.2845                0.2473   
ExtraTreesRegressor                      0.3420                0.3455   
LinearRegression                         0.1213                0.2206   
KNeighborsRegressor                      0.3111                0.3154   
SVR                                      0.2437                0.2427   
MLPRegressor                             0.1567                0.1666   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.3520   0.5043    0.5933  0.4017   
DecisionTreeRegressor       0.3952   0.5624    0.6286  0.3282   
RandomForestRegressor       0.3002   0.4847    0.5479  0.4896   
GradientBoostingRegressor   0.2856   0.4606    0.5345  0.5144   
AdaBoostRegressor           0.3380   0.4779    0.5814  0.4254   
XGBRegressor                0.2722   0.4639    0.5217  0.5373   
ExtraTreesRegressor         0.3436   0.5122    0.5862  0.4158   
LinearRegression            0.5443   0.5546    0.7377  0.0747   
KNeighborsRegressor         0.3445   0.4684    0.5869  0.4143   
SVR                         0.3151   0.4771    0.5613  0.4644   
MLPRegressor                0.5772   0.5941    0.7597  0.0188   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6478                    0.4374  
DecisionTreeRegressor                       0.6884                    0.3494  
RandomForestRegressor                       0.7172                    0.3329  
GradientBoostingRegressor                   0.7596                    0.3329  
AdaBoostRegressor                           0.7007                    0.2889  
XGBRegressor                                0.7764                    0.3989  
ExtraTreesRegressor                         0.7151           

In [95]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.553189223277948, -5.762083386127124, -6.01...   
1   [-5.65, -5.33, -4.73, -6.929917083, -6.9272455...   
2   [-5.651568240779997, -5.495541399969999, -5.73...   
3   [-5.5954307166689485, -5.228433616335078, -5.1...   
4   [-5.474897937454546, -5.36833919, -5.93, -5.98...   
5   [-5.69612, -5.5184503, -4.8876624, -6.4128222,...   
6   [-5.690629635769994, -5.766462100400006, -6.12...   
7   [-6.590483225494487, -5.513462344328166, -5.11...   
8   [-5.6433333333333335, -5.786666666666666, -5.9...   
9   [-5.578029705740392, -5.349600407183299, -5.65...   
10  [-5.925755722027988, -6.475286629543336, -4.74...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.70104546213166, -5.56595266570999, -5.793...   
1   [[-4.73, -6.25, -5.93, -6.927245587, -6.927245...   
2   [[-5.446327593922331, -5.838984782265002, -5.9...   
3   [[-5.006210706231372, -6.198551846962498, -6.0...   
4   [[-5.2565051159583325, -6.048814726833334, -5....   
5   [[-5.16211, -6.119285, -6.4525523, -6.9264083,...   
6   [[-5.3981691634050035, -6.061690177500001, -6....   
7   [[-8.175032551649029, -7.201330799747298, -7.1...   
8   [[-5.613333333333333, -5.613333333333333, -6.4...   
9   [[-5.501403493266325, -5.8910307255329135, -5....   
10  [[-7.295948612107033, -6.1620672368098806, -4....   

                                Test Predictions Mean  \
0   [-5.529763782370577, -5.626879803377877, -6.14...   
1   [-5.3100000000000005, -6.164, -6.4866938849999...   
2   [-5.4983864986423, -5.789393364633268, -6.0415...   
3   [-5.55715750776775, -5.989392374647627, -6.260...   
4   [-5.267883186225952, -5.828556496673485, -6.18...   
5   [-5.6374235, -5.8563933, -6.106925, -6.6213274...   
6   [-5.26019510979817, -5.877045608341501, -6.622...   
7   [-6.270740945214986, -6.362757574720621, -7.91...   
8   [-5.713333333333333, -5.713333333333333, -6.22...   
9   [-5.536962996407043, -5.843872486173774, -5.80...   
10  [-6.703214356677758, -5.911053269739971, -4.13...   

                                 Test Predictions Std  
0   [0.20598848750017978, 0.17165051129096703, 0.2...  
1   [0.38590154184714004, 0.17199999999999988, 0.7...  
2   [0.14620118722672648, 0.17613586949685736, 0.0...  
3   [0.42810212182847185, 0.3053731089460274, 0.33...  
4   [0.2219154352238451, 0.21389420781883928, 0.33...  
5   [0.31398037, 0.30552727, 0.3347825, 0.52454853...  
6   [0.17984962935159388, 0.2655025927151172, 0.18...  
7   [1.065123527345538, 0.9775428087729081, 1.4649...  
8   [0.1707890186425604, 0.1707890186425604, 0.309...  
9   [0.15365119163203037, 0.21856428173859294, 0.1...  
10  [0.608494820349243, 0.5585575298942579, 0.1332...

In [96]:
result_df.to_csv('results/Descriptors/Results_2d_Mordred_desc_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2d_Mordred_desc_MDCK.csv')

In [97]:
#Removal of constant columns
def remove_constant_columns(df):
    constant_columns = [col for col in df.columns if df[col].nunique() <= 1]
    
    df_cleaned = df.drop(columns=constant_columns)
    
    return df_cleaned, constant_columns

In [98]:
#Low variance column removal
def remove_low_variance_columns(df, threshold=0.005):
    variances = df.var()
    
    low_variance_columns = variances[variances < threshold].index.tolist()
    
    df_cleaned = df.drop(columns=low_variance_columns)
    
    return df_cleaned, low_variance_columns

In [99]:
#2d RDKit descriptors const removal
df_train = pd.read_csv('features/Descriptors/Train_2d_RDKit_des_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train, const_col = remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_RDKit_des_MDCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = X_test.drop(const_col,axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 134)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 134)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000041 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 335
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 30
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits w

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


0.4985200968704806


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6144                0.6330   
DecisionTreeRegressor                    1.0600                0.8123   
RandomForestRegressor                    0.6982                0.6791   
GradientBoostingRegressor                0.9427                0.7781   
AdaBoostRegressor                        0.7760                0.7089   
XGBRegressor                             1.0072                0.8138   
ExtraTreesRegressor                      0.7916                0.7043   
LinearRegression                         3.1917                1.2767   
KNeighborsRegressor                      0.6755                0.6557   
SVR                                      0.6259                0.6268   
MLPRegressor                             1.2581                0.8652   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7839               0.0502   
DecisionTreeRegressor                     1.0296              -0.6386   
RandomForestRegressor                     0.8356              -0.0792   
GradientBoostingRegressor                 0.9709              -0.4573   
AdaBoostRegressor                         0.8809              -0.1996   
XGBRegressor                              1.0036              -0.5569   
ExtraTreesRegressor                       0.8897              -0.2237   
LinearRegression                          1.7865              -3.9339   
KNeighborsRegressor                       0.8219              -0.0442   
SVR                                       0.7911               0.0325   
MLPRegressor                              1.1216              -0.9448   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2600                0.3210   
DecisionTreeRegressor                    0.1074                0.1519   
RandomForestRegressor                    0.2282                0.2721   
GradientBoostingRegressor                0.1334                0.1570   
AdaBoostRegressor                        0.2202                0.2704   
XGBRegressor                             0.0438                0.0625   
ExtraTreesRegressor                      0.2105                0.2173   
LinearRegression                         0.1092                0.0432   
KNeighborsRegressor                      0.2830                0.3192   
SVR                                      0.2918                0.2408   
MLPRegressor                             0.1267                0.1700   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.3853   0.5321    0.6207   0.3451   
DecisionTreeRegressor       0.3866   0.4691    0.6218   0.3427   
RandomForestRegressor       0.3064   0.4785    0.5536   0.4791   
GradientBoostingRegressor   0.3377   0.4791    0.5811   0.4259   
AdaBoostRegressor           0.3085   0.4474    0.5555   0.4755   
XGBRegressor                0.4038   0.5400    0.6354   0.3136   
ExtraTreesRegressor         0.3716   0.5282    0.6096   0.3682   
LinearRegression            1.3923   0.8926    1.1800  -1.3670   
KNeighborsRegressor         0.3357   0.4399    0.5794   0.4293   
SVR                         0.3195   0.4925    0.5652   0.4569   
MLPRegressor                0.2950   0.4322    0.5431   0.4985   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6541                    0.5096  
DecisionTreeRegressor                       0.6941                    0.4484  
RandomForestRegressor                       0.7159                    0.3879  
GradientBoostingRegressor                   0.7391                    0.4814  
AdaBoostRegressor                           0.7321                    0.3329  
XGBRegressor                                0.7114                    0.3879  
ExtraTreesRegressor                         0.717

In [100]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.536143010992385, -6.156816999215223, -6.29...   
1   [-5.65, -5.06, -6.97, -6.929917083, -6.9299170...   
2   [-5.284349170829996, -5.3062113300750005, -6.3...   
3   [-5.056555488020928, -5.199656544258757, -6.77...   
4   [-5.28, -5.291249999999999, -6.419104859818183...   
5   [-4.922271, -5.8616314, -7.1029534, -5.7418523...   
6   [-5.147999999999996, -5.079300000000002, -6.71...   
7   [-4.0, -7.956188319024531, -6.410348348140615,...   
8   [-5.3133333333333335, -5.786666666666666, -6.0...   
9   [-5.554476793179216, -5.224608127621062, -5.62...   
10  [-4.952617373480381, -5.354842142362793, -5.82...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.664411161024185, -5.792529113538625, -5.7...   
1   [[-5.65, -4.94, -6.25, -6.927245587, -5.453495...   
2   [[-5.604231192076643, -5.513535647592001, -6.3...   
3   [[-6.0276951123819735, -5.796909733677128, -6....   
4   [[-5.646157390947368, -5.646157390947368, -6.3...   
5   [[-5.7401524, -5.666066, -6.3228106, -6.709675...   
6   [[-5.134937354730003, -6.08245, -7.34019074065...   
7   [[-4.0, -9.254455419529105, -4.0, -6.840685888...   
8   [[-5.613333333333333, -5.613333333333334, -6.1...   
9   [[-5.738480683323801, -5.999654458818311, -5.8...   
10  [[-4.9529250356278185, -5.635800906425421, -6....   

                                Test Predictions Mean  \
0   [-5.666812029931583, -5.5713305480511535, -5.8...   
1   [-5.676, -5.74, -6.297449117399999, -6.7384734...   
2   [-5.554722246491525, -5.5749159733453855, -6.3...   
3   [-5.780324070898283, -5.6199896657596575, -6.6...   
4   [-5.516144032722807, -5.56248130589114, -6.218...   
5   [-5.6514807, -5.726673, -7.0044594, -6.63848, ...   
6   [-5.337058525019502, -5.878268496912002, -7.10...   
7   [-6.617857950485292, -7.527326511204102, -4.0,...   
8   [-5.6259999999999994, -5.4126666666666665, -6....   
9   [-5.658524315287802, -5.824015903459413, -5.74...   
10  [-6.071934039112415, -5.261344100198727, -6.59...   

                                 Test Predictions Std  
0   [0.21835822613593237, 0.20002140796917076, 0.0...  
1   [0.39877813380374816, 0.6250119998848022, 0.41...  
2   [0.13784766283058675, 0.17690268977790705, 0.1...  
3   [0.25059911635927906, 0.2853438141874957, 0.38...  
4   [0.2613749018471754, 0.24580495804870453, 0.40...  
5   [0.30661, 0.43052056, 0.7034079, 0.45411754, 0...  
6   [0.2292245484979095, 0.44007863893686966, 0.44...  
7   [2.790005409318987, 1.955604409019984, 0.0, 0....  
8   [0.16096100286853474, 0.2143766156401708, 0.24...  
9   [0.07795456608354132, 0.28840360230986073, 0.0...  
10  [0.5762823235234925, 0.6380428166436207, 1.284...

In [101]:
result_df.to_csv('results/Descriptors/Results_2d_rdkit_const_rem_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2d_rdkit_const_rem_MDCK.csv')

In [102]:
#2d Mordred descriptors const removal
df_train = pd.read_csv('features/Descriptors/Train_2d_Mordred_desc_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
X_train, const_col = remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_Mordred_desc_MDCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = X_test.select_dtypes(include=['number'])
X_test = X_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models_2dM = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models_2dM, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 1148)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 1148)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000296 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 4840
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 360
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spli

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.5689                0.6356   
DecisionTreeRegressor                    0.7908                0.7004   
RandomForestRegressor                    0.6339                0.6631   
GradientBoostingRegressor                0.6524                0.6670   
AdaBoostRegressor                        0.5955                0.6194   
XGBRegressor                             0.7272                0.6806   
ExtraTreesRegressor                      0.6128                0.6407   
LinearRegression                         1.4614                0.8733   
KNeighborsRegressor                      0.6446                0.6277   
SVR                                      0.6499                0.6327   
MLPRegressor                             1.2646                0.8803   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7543               0.1205   
DecisionTreeRegressor                     0.8893              -0.2225   
RandomForestRegressor                     0.7962               0.0200   
GradientBoostingRegressor                 0.8077              -0.0085   
AdaBoostRegressor                         0.7717               0.0794   
XGBRegressor                              0.8528              -0.1242   
ExtraTreesRegressor                       0.7828               0.0528   
LinearRegression                          1.2089              -1.2591   
KNeighborsRegressor                       0.8029               0.0036   
SVR                                       0.8062              -0.0046   
MLPRegressor                              1.1245              -0.9548   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.3732                0.4268   
DecisionTreeRegressor                    0.2631                0.3437   
RandomForestRegressor                    0.2510                0.2331   
GradientBoostingRegressor                0.2847                0.2720   
AdaBoostRegressor                        0.3695                0.3472   
XGBRegressor                             0.2845                0.2473   
ExtraTreesRegressor                      0.3618                0.3453   
LinearRegression                         0.1213                0.2206   
KNeighborsRegressor                      0.3111                0.3154   
SVR                                      0.2437                0.2427   
MLPRegressor                             0.1215                0.1350   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.3520   0.5043    0.5933  0.4017   
DecisionTreeRegressor       0.5230   0.5867    0.7232  0.1108   
RandomForestRegressor       0.3067   0.4872    0.5538  0.4787   
GradientBoostingRegressor   0.2991   0.4615    0.5469  0.4915   
AdaBoostRegressor           0.3019   0.4693    0.5495  0.4867   
XGBRegressor                0.2722   0.4639    0.5217  0.5373   
ExtraTreesRegressor         0.3330   0.5048    0.5771  0.4338   
LinearRegression            0.5443   0.5546    0.7377  0.0747   
KNeighborsRegressor         0.3445   0.4684    0.5869  0.4143   
SVR                         0.3151   0.4771    0.5613  0.4644   
MLPRegressor                0.2557   0.4345    0.5057  0.5652   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6478                    0.4374  
DecisionTreeRegressor                       0.6004                    0.3054  
RandomForestRegressor                       0.7127                    0.3329  
GradientBoostingRegressor                   0.7494                    0.3439  
AdaBoostRegressor                           0.7435                    0.3604  
XGBRegressor                                0.7764                    0.3989  
ExtraTreesRegressor                         0.7253           

In [103]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.553189223277948, -5.762083386127124, -6.01...   
1   [-5.65, -5.33, -5.1, -6.929917083, -6.92724558...   
2   [-5.609557636606427, -5.554604654275, -5.88675...   
3   [-5.595618382103325, -5.239298104839103, -5.18...   
4   [-5.65, -5.291970879444444, -5.989595051454547...   
5   [-5.69612, -5.5184503, -4.8876624, -6.4128222,...   
6   [-5.673698365874995, -5.89139774658, -5.945885...   
7   [-6.590483225494502, -5.513462344328177, -5.11...   
8   [-5.6433333333333335, -5.786666666666666, -5.9...   
9   [-5.578031046668349, -5.349593503063404, -5.65...   
10  [-5.666470398051259, -5.796281523112971, -5.41...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.70104546213166, -5.56595266570999, -5.793...   
1   [[-4.61, -6.25, -6.85, -6.927245587, -6.927245...   
2   [[-5.51076090808, -5.862385785791669, -5.95240...   
3   [[-5.077696701712457, -6.154795266240203, -6.2...   
4   [[-5.265958313761904, -5.619616091222222, -6.1...   
5   [[-5.16211, -6.119285, -6.4525523, -6.9264083,...   
6   [[-5.429057026422499, -5.97715676172, -6.54777...   
7   [[-8.175032551649032, -7.201330799747323, -7.1...   
8   [[-5.613333333333333, -5.613333333333333, -6.4...   
9   [[-5.5014291898712475, -5.891068502793287, -5....   
10  [[-6.799100911922041, -6.085758933320162, -7.7...   

                                Test Predictions Mean  \
0   [-5.529763782370577, -5.626879803377877, -6.14...   
1   [-5.438, -5.95, -6.4279156982000005, -6.532139...   
2   [-5.531368222817464, -5.7900167333438, -6.0475...   
3   [-5.6091619249240985, -5.939200936747936, -6.2...   
4   [-5.454023363486295, -5.834459007663157, -6.31...   
5   [-5.6374235, -5.8563933, -6.106925, -6.6213274...   
6   [-5.342987946713, -5.834944602552833, -6.61986...   
7   [-6.270740945214962, -6.362757574720617, -7.91...   
8   [-5.713333333333333, -5.713333333333333, -6.22...   
9   [-5.53696304869614, -5.843868785348652, -5.802...   
10  [-6.2239550773985055, -5.796289975533297, -5.3...   

                                 Test Predictions Std  
0   [0.20598848750017978, 0.17165051129096703, 0.2...  
1   [0.5309011207371858, 0.37947331922020555, 0.47...  
2   [0.1209440209332762, 0.16754963900400116, 0.09...  
3   [0.39686422781752306, 0.2622414307964284, 0.27...  
4   [0.19520960298612394, 0.24739244605639968, 0.1...  
5   [0.31398037, 0.30552727, 0.3347825, 0.52454853...  
6   [0.15193389815605052, 0.23651510206489035, 0.2...  
7   [1.065123527345553, 0.9775428087729097, 1.4649...  
8   [0.1707890186425604, 0.1707890186425604, 0.309...  
9   [0.15365230921208542, 0.21856237722668823, 0.1...  
10  [0.6921707325069505, 0.9039058832938548, 1.273...

In [104]:
result_df.to_csv('results/Descriptors/Results_2d_Mordred_const_rem_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_df_2d_Mordred_const_rem_MDCK.csv')

In [105]:
#2d RDKit descriptors LVR
df_train = pd.read_csv('features/Descriptors/Train_2d_RDKit_des_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train, const_col = remove_low_variance_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_RDKit_des_MDCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = X_test.drop(const_col,axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models_LVR_rdkit = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models_LVR_rdkit, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 123)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 123)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000015 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 284
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 25
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positiv

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.47806629881682805


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6795                0.6706   
DecisionTreeRegressor                    1.3350                0.9054   
RandomForestRegressor                    0.6996                0.6832   
GradientBoostingRegressor                0.9325                0.7675   
AdaBoostRegressor                        0.7416                0.6837   
XGBRegressor                             0.9844                0.7822   
ExtraTreesRegressor                      0.8288                0.7215   
LinearRegression                         3.7071                1.3680   
KNeighborsRegressor                      0.6909                0.6528   
SVR                                      0.6231                0.6253   
MLPRegressor                             1.3419                0.8902   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8243              -0.0504   
DecisionTreeRegressor                     1.1554              -1.0636   
RandomForestRegressor                     0.8364              -0.0815   
GradientBoostingRegressor                 0.9657              -0.4415   
AdaBoostRegressor                         0.8611              -0.1464   
XGBRegressor                              0.9922              -0.5218   
ExtraTreesRegressor                       0.9104              -0.2812   
LinearRegression                          1.9254              -4.7307   
KNeighborsRegressor                       0.8312              -0.0681   
SVR                                       0.7894               0.0368   
MLPRegressor                              1.1584              -1.0744   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.1340                0.2187   
DecisionTreeRegressor                    0.0841                0.1853   
RandomForestRegressor                    0.2460                0.3046   
GradientBoostingRegressor                0.1575                0.2121   
AdaBoostRegressor                        0.2566                0.3220   
XGBRegressor                             0.0879                0.1402   
ExtraTreesRegressor                      0.1972                0.2321   
LinearRegression                         0.0383                0.0540   
KNeighborsRegressor                      0.2637                0.2795   
SVR                                      0.3002                0.2536   
MLPRegressor                             0.1409                0.1769   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4107   0.5511    0.6409   0.3018   
DecisionTreeRegressor       0.4186   0.5316    0.6470   0.2884   
RandomForestRegressor       0.3208   0.4891    0.5664   0.4547   
GradientBoostingRegressor   0.3590   0.4923    0.5992   0.3897   
AdaBoostRegressor           0.3088   0.4459    0.5557   0.4750   
XGBRegressor                0.4010   0.5333    0.6333   0.3183   
ExtraTreesRegressor         0.3791   0.5344    0.6157   0.3555   
LinearRegression            0.8383   0.6388    0.9156  -0.4251   
KNeighborsRegressor         0.3468   0.4659    0.5889   0.4104   
SVR                         0.3195   0.4905    0.5653   0.4568   
MLPRegressor                0.8694   0.6436    0.9324  -0.4781   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6337                    0.3774  
DecisionTreeRegressor                       0.6834                    0.4099  
RandomForestRegressor                       0.7020                    0.3714  
GradientBoostingRegressor                   0.7172                    0.3879  
AdaBoostRegressor                           0.7244                    0.3879  
XGBRegressor                                0.7091                    0.3769  
ExtraTreesRegressor                         0.714

In [106]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.536143010992385, -6.156816999215223, -6.29...   
1   [-4.94, -5.06, -5.93, -5.793469425, -6.9299170...   
2   [-5.261718559329996, -5.3724716266999994, -6.3...   
3   [-5.472807967724208, -5.181052058170596, -6.68...   
4   [-5.28, -5.353444142529413, -6.7299834166, -6....   
5   [-4.92453, -5.9122243, -7.021858, -5.67806, -6...   
6   [-5.069799999999999, -5.1142, -6.7781716267000...   
7   [-6.185007936444608, -5.639479384692574, -6.58...   
8   [-5.3133333333333335, -5.786666666666666, -6.0...   
9   [-5.554014438214139, -5.205640452563704, -5.61...   
10  [-5.250760385730441, -5.233515846928384, -6.07...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.664411161024185, -5.792529113538625, -5.7...   
1   [[-5.65, -5.65, -6.929917083, -5.793469425, -5...   
2   [[-5.55181461126, -5.624769316419999, -6.32123...   
3   [[-5.654375736074772, -5.612085049871201, -6.3...   
4   [[-5.258181818181819, -5.385, -6.1816799935714...   
5   [[-5.732529, -5.738987, -6.4222336, -7.023955,...   
6   [[-5.101350000000003, -5.95849578491, -7.51873...   
7   [[-10.0, -6.7463899214047185, -4.1272204282254...   
8   [[-5.613333333333333, -5.613333333333334, -6.1...   
9   [[-5.726217474440237, -6.001449862936582, -5.8...   
10  [[-6.625865218003643, -5.636240497741559, -9.7...   

                                Test Predictions Mean  \
0   [-5.6330422980809995, -5.632885645845008, -5.7...   
1   [-5.562, -6.01, -6.6619668332, -6.5117182544, ...   
2   [-5.529950919176185, -5.655219734989752, -6.32...   
3   [-5.665746381937298, -5.731151545358999, -6.55...   
4   [-5.432285470340851, -5.490211166652814, -6.14...   
5   [-5.6482544, -5.7494774, -7.0320344, -6.598863...   
6   [-5.313630160678004, -5.813896329955002, -7.17...   
7   [-6.4, -7.385993734634875, -6.485840113737058,...   
8   [-5.6259999999999994, -5.6546666666666665, -6....   
9   [-5.652744031977923, -5.836963844727428, -5.74...   
10  [-7.070840965530451, -5.259511523547721, -8.77...   

                                 Test Predictions Std  
0   [0.23685234576893643, 0.24203027799568494, 0.1...  
1   [0.5296942514318991, 0.2939387691339812, 0.796...  
2   [0.11667761704561924, 0.21489849640850642, 0.1...  
3   [0.21608019706210085, 0.33790986104865084, 0.3...  
4   [0.23123134159728428, 0.1636072816419407, 0.27...  
5   [0.40856382, 0.4536152, 0.6499573, 0.4812082, ...  
6   [0.3236274534874776, 0.48308935299843536, 0.57...  
7   [2.939387691339814, 2.323183415515883, 2.23661...  
8   [0.16096100286853474, 0.14230796026770784, 0.2...  
9   [0.08030176667538513, 0.2861844633849581, 0.09...  
10  [0.4451036996718056, 0.6384985804416671, 1.244...

In [107]:
result_df.to_csv('results/Descriptors/Results_2d_rdkit_LVR_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2d_rdkit_LVR_MDCK.csv')

In [108]:
#2d Mordred descriptors LVR
df_train = pd.read_csv('features/Descriptors/Train_2d_Mordred_desc_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
X_train, const_col = remove_low_variance_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_Mordred_desc_MDCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = X_test.select_dtypes(include=['number'])
X_test = X_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
results_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
results_df

X_train shape:  (51, 769)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 769)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000204 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3168
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 236
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


0.6723578691170898


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6351                0.6625   
DecisionTreeRegressor                    0.8087                0.7099   
RandomForestRegressor                    0.6372                0.6654   
GradientBoostingRegressor                0.7982                0.7028   
AdaBoostRegressor                        0.6737                0.6573   
XGBRegressor                             0.8373                0.7589   
ExtraTreesRegressor                      0.6605                0.6628   
LinearRegression                         1.8336                0.9874   
KNeighborsRegressor                      0.6026                0.6162   
SVR                                      0.6454                0.6358   
MLPRegressor                             1.3376                0.9130   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7970               0.0182   
DecisionTreeRegressor                     0.8993              -0.2501   
RandomForestRegressor                     0.7983               0.0149   
GradientBoostingRegressor                 0.8934              -0.2339   
AdaBoostRegressor                         0.8208              -0.0414   
XGBRegressor                              0.9150              -0.2943   
ExtraTreesRegressor                       0.8127              -0.0210   
LinearRegression                          1.3541              -1.8344   
KNeighborsRegressor                       0.7763               0.0684   
SVR                                       0.8034               0.0023   
MLPRegressor                              1.1566              -1.0677   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2765                0.3301   
DecisionTreeRegressor                    0.3173                0.3547   
RandomForestRegressor                    0.2674                0.3016   
GradientBoostingRegressor                0.2349                0.3294   
AdaBoostRegressor                        0.3061                0.2805   
XGBRegressor                             0.1962                0.2836   
ExtraTreesRegressor                      0.3014                0.3180   
LinearRegression                        -0.0161                0.1256   
KNeighborsRegressor                      0.3574                0.3727   
SVR                                      0.2536                0.2482   
MLPRegressor                             0.1403                0.1560   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.3550   0.5262    0.5958  0.3965   
DecisionTreeRegressor       0.3341   0.5172    0.5781  0.4319   
RandomForestRegressor       0.3110   0.4893    0.5576  0.4714   
GradientBoostingRegressor   0.3860   0.5372    0.6213  0.3437   
AdaBoostRegressor           0.3234   0.4692    0.5687  0.4503   
XGBRegressor                0.3578   0.5286    0.5982  0.3917   
ExtraTreesRegressor         0.3261   0.4995    0.5710  0.4456   
LinearRegression            0.4838   0.5479    0.6955  0.1775   
KNeighborsRegressor         0.3447   0.4690    0.5871  0.4140   
SVR                         0.3126   0.4695    0.5591  0.4685   
MLPRegressor                0.1927   0.3918    0.4390  0.6724   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6574                    0.5089  
DecisionTreeRegressor                       0.7314                    0.3659  
RandomForestRegressor                       0.7155                    0.3769  
GradientBoostingRegressor                   0.6976                    0.3549  
AdaBoostRegressor                           0.7205                    0.3164  
XGBRegressor                                0.7174                    0.3714  
ExtraTreesRegressor                         0.7350           

In [109]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.536334600266275, -5.800070490585862, -5.79...   
1   [-5.65, -5.06, -4.94, -6.929917083, -5.4534952...   
2   [-5.529595784909995, -5.668382901070001, -5.94...   
3   [-5.683829602324278, -5.50648748716373, -5.099...   
4   [-5.449549484285713, -5.40780180375, -6.193087...   
5   [-5.645642, -5.329582, -5.3889837, -6.4178996,...   
6   [-5.566999999999998, -5.884735054730003, -6.18...   
7   [-6.547647100696484, -6.16724119836109, -4.681...   
8   [-5.6433333333333335, -5.786666666666666, -6.0...   
9   [-5.5598566135288845, -5.360041381975508, -5.6...   
10  [-5.5543158039723135, -6.496447943742381, -4.5...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.674867140286591, -5.729655706549241, -6.1...   
1   [[-4.73, -6.25, -5.93, -6.927245587, -6.569578...   
2   [[-5.451143759287333, -5.795538351944, -6.2418...   
3   [[-5.037497427644231, -6.0824563930132864, -6....   
4   [[-5.036, -6.036666666666666, -6.0217347125, -...   
5   [[-5.319728, -6.036903, -6.3016453, -7.0434856...   
6   [[-5.309784432580001, -6.102141764717499, -6.4...   
7   [[-9.113817059237686, -7.582885255139203, -6.9...   
8   [[-5.613333333333333, -5.613333333333333, -6.4...   
9   [[-5.570282041548942, -5.915425292105371, -5.8...   
10  [[-6.337529224070472, -5.850883872533922, -5.6...   

                                Test Predictions Mean  \
0   [-5.560723749408672, -5.760891408354489, -6.31...   
1   [-5.33, -6.028293542049999, -6.4724391856, -6....   
2   [-5.553947754013035, -5.797327275282467, -6.33...   
3   [-5.472817582640283, -5.977716917554431, -6.51...   
4   [-5.381309963427077, -5.832756747893453, -6.19...   
5   [-5.4812574, -5.813936, -6.620009, -6.552999, ...   
6   [-5.424161645884835, -5.976622734714001, -6.69...   
7   [-6.650955266440123, -6.1825085847037045, -7.7...   
8   [-5.713333333333333, -5.713333333333333, -6.22...   
9   [-5.582650571975117, -5.851230286646432, -5.83...   
10  [-5.864947223092643, -5.603717697896597, -5.68...   

                                 Test Predictions Std  
0   [0.21328074346600934, 0.20087814245258503, 0.1...  
1   [0.43501724103763983, 0.28267907625068495, 0.3...  
2   [0.16261025029962267, 0.11341393266388204, 0.0...  
3   [0.2966781241909016, 0.24352436676583278, 0.24...  
4   [0.28876656455100796, 0.20503960040015792, 0.2...  
5   [0.09593115, 0.2658951, 0.39809063, 0.5484811,...  
6   [0.15832369672300564, 0.20433303178798568, 0.4...  
7   [1.4586895442816596, 1.2156490493841625, 1.691...  
8   [0.1707890186425604, 0.1707890186425604, 0.309...  
9   [0.12973618164304945, 0.24311360800261486, 0.1...  
10  [1.0079725292999342, 0.8137023619653344, 0.741...

In [110]:
results_df.to_csv('results/Descriptors/Results_2d_Mordred_LVR_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2d_Mordred_LVR_MDCK.csv')

In [111]:
#2d Padel descriptors
df_train = pd.read_csv('features/Descriptors/Train_2d_padel_MDCK.csv')
df_train['ID'] = df_train['Name'].str.extract(r'_(\d+)$')
df_train['ID'] = df_train['ID'].astype(int)
df_train = df_train.drop('Name',axis=1)
df_train = df_train.fillna(0)
df_train

nAcid   ALogP     ALogp2       AMR        apol  naAromAtom  nAromBond  \
0       0 -6.7922  46.133981  200.8102  123.721166           0          0   
1       0 -0.9878   0.975749  203.2963  128.382338           0          0   
2       0 -1.2947   1.676248  186.2062  119.101580           0          0   
3       0 -2.1290   4.532641  277.7356  179.405714           0          0   
4       0 -8.4202  70.899768  189.3712  121.053994           0          0   
5       0 -5.1194  26.208256  249.9738  164.364198           0          0   
6       0 -0.7316   0.535239  184.6007  118.299580           0          0   
7       0 -5.3114  28.210970  240.6548  158.177026           0          0   
8       0 -0.7316   0.535239  184.6007  118.299580           0          0   
9       0 -0.2899   0.084042  200.4822  122.245994           0          0   
10      0 -0.2899   0.084042  200.4822  122.245994           0          0   
11      0 -3.7570  14.115049  266.2966  176.738542           0          0   
12      0 -1.6634   2.766900  183.2267  118.299580           0          0   
13      0 -4.0762  16.615406  266.7120  176.738542           0          0   
14      0 -1.2217   1.492551  199.1082  122.245994           0          0   
15      0 -1.2456   1.551519  309.4986  187.298542           0          0   
16      0 -2.6816   7.190979  307.3786  190.818542           0          0   
17      0 -2.6816   7.190979  307.3786  190.818542           0          0   
18      0 -3.8355  14.711060  255.5490  169.586577           0          0   
19      0 -3.7332  13.936782  261.2457  172.680163           0          0   
20      0 -6.9419  48.189976  250.8127  166.926198           0          0   
21      0 -3.7332  13.936782  261.2457  172.680163           0          0   
22      0 -2.6816   7.190979  307.3786  190.818542           0          0   
23      0 -6.9419  48.189976  250.8127  166.926198           0          0   
24      0 -3.9378  15.506269  249.8523  166.492991           0          0   
25      0 -3.8355  14.711060  255.5490  169.586577           0          0   
26      0 -4.0401  16.322408  244.1556  163.399405           0          0   
27      0 -4.0632  16.509594  245.8503  158.352233           0          0   
28      0 -3.7332  13.936782  261.2457  172.680163           0          0   
29      0 -5.7230  32.752729  279.5151  180.153370           0          0   
30      0 -4.6410  21.538881  249.3823  161.445819           0          0   
31      0 -4.0632  16.509594  245.8503  158.352233           0          0   
32      0 -5.3689  28.825087  280.2868  182.444956           0          0   
33      0 -4.6410  21.538881  249.3823  161.445819           0          0   
34      0 -5.7230  32.752729  279.5151  180.153370           0          0   
35      0 -5.5830  31.169889  254.9353  169.392991           0          0   
36      0 -3.1134   9.693260  255.8998  162.779405           0          0   
37      0 -5.3689  28.825087  280.2868  182.444956           0          0   
38      0 -4.9290  24.295041  252.2939  164.539405           0          0   
39      0 -3.1134   9.693260  255.8998  162.779405           0          0   
40      0 -4.5056  20.300431  249.1276  161.445819           0          0   
41      0 -3.1134   9.693260  255.8998  162.779405           0          0   
42      0 -3.1134   9.693260  255.8998  162.779405           0          0   
43      0 -4.7936  22.978601  252.0392  164.539405           0          0   
44      0 -3.1134   9.693260  255.8998  162.779405           0          0   
45      0 -3.1134   9.693260  255.8998  162.779405           0          0   
46      0 -3.1134   9.693260  255.8998  162.779405           0          0   
47      0 -3.1134   9.693260  255.8998  162.779405           0          0   
48      0 -3.8314  14.679626  254.8398  164.539405           0          0   
49      0 -6.0254  36.305445  258.2126  172.486577           0          0   
50      0 -3.8314  14.679626  254.8398  164.539405           0          0   


In [112]:
df = pd.read_csv('features/Descriptors/Train_2d_Mordred_desc_MDCK.csv')
df 


ID                                             SMILES  Permeability  \
0   1114  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -4.940000   
1   1113  CC(C)C[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@@H](Cc2...     -5.820000   
2   1117  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.650000   
3   1119  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.250000   
4   2428  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.350000   
5   2446  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -6.850000   
6   2445  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -5.270000   
7   2427  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -6.340000   
8   8145  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.569578   
9   1107  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -4.610000   
10  1116  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)N(C)C(=O)[C@H]2...     -5.220000   
11  1110  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...     -4.730000   
12  8121  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.927246   
13  5836  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -5.060000   
14  6187  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -5.010000   
15  6584  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.330000   
16  6571  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.100000   
17  5803  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -6.970000   
18  2422  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.630000   
19  2440  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -7.760000   
20  8140  CCC[C@H]1C(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=...     -5.453495   
21  8131  CCC[C@@H]1NC(=O)CN(CCC)C(=O)[C@H](CC(C)C)NC(=O...     -5.509834   
22  8346  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.672617   
23  8184  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.929917   
24  6505  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.930000   
25  8342  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -4.994304   
26  8160  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.167475   
27  8341  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.822199   
28  8344  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.241518   
29  8343  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.131653   
30  8156  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.178526   
31  8150  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.834862   
32  8152  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.105008   
33  8116  CCCN1CC(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=O)N...     -5.400722   
34  8128  CCCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=...     -5.793469   
35  8138  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.303671   
36  6666  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -7.820000   
37  1115  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.190000   
38  8126  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.983385   
39  8114  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.309384   
40  1111  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C...     -6.220000   
41  1109  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N(C)C(...     -6.120000   
42  1112  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](C)NC(=O)[...     -6.170000   
43  1018  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...     -4.500000   
44  1845  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.960000   
45  1847  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.740000   
46  1841  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.410000   
47  1017  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...     -6.550000   
48  1840  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.480000   
49  1844  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -5.100000   
50  1846  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.820000   

 

In [113]:
merged_df = df_train.merge(df[['ID', 'SMILES', 'Permeability']], on='ID', how='left')
merged_df = merged_df[['ID', 'SMILES', 'Permeability'] + [col for col in merged_df.columns if col not in ['ID', 'SMILES', 'Permeability']]]
merged_df

ID                                             SMILES  Permeability  \
0   1109  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N(C)C(...     -6.120000   
1   1018  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...     -4.500000   
2   1017  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...     -6.550000   
3   1107  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -4.610000   
4   1112  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](C)NC(=O)[...     -6.170000   
5   1115  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.190000   
6   1840  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.480000   
7   1111  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C...     -6.220000   
8   1844  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -5.100000   
9   1841  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.410000   
10  1845  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.960000   
11  1110  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...     -4.730000   
12  1846  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.820000   
13  1116  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)N(C)C(=O)[C@H]2...     -5.220000   
14  1847  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.740000   
15  1119  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.250000   
16  1113  CC(C)C[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@@H](Cc2...     -5.820000   
17  1117  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.650000   
18  5803  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -6.970000   
19  5836  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -5.060000   
20  2422  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.630000   
21  6187  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -5.010000   
22  1114  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -4.940000   
23  2440  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -7.760000   
24  6505  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.930000   
25  6571  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.100000   
26  6666  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -7.820000   
27  8114  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.309384   
28  6584  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.330000   
29  2428  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.350000   
30  8116  CCCN1CC(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=O)N...     -5.400722   
31  8126  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.983385   
32  2427  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -6.340000   
33  8128  CCCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=...     -5.793469   
34  2446  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -6.850000   
35  8121  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.927246   
36  8150  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.834862   
37  2445  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -5.270000   
38  8131  CCC[C@@H]1NC(=O)CN(CCC)C(=O)[C@H](CC(C)C)NC(=O...     -5.509834   
39  8152  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.105008   
40  8138  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.303671   
41  8156  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.178526   
42  8160  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.167475   
43  8140  CCC[C@H]1C(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=...     -5.453495   
44  8341  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.822199   
45  8342  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -4.994304   
46  8343  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.131653   
47  8344  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.241518   
48  8184  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.929917   
49  8145  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.569578   
50  8346  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.672617   

 

In [114]:
df_ordered = merged_df.merge(df[['ID']], on='ID', how='right')
df_ordered = df_ordered.reindex(df.index)
df_ordered

ID                                             SMILES  Permeability  \
0   1114  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -4.940000   
1   1113  CC(C)C[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@@H](Cc2...     -5.820000   
2   1117  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.650000   
3   1119  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.250000   
4   2428  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.350000   
5   2446  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -6.850000   
6   2445  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -5.270000   
7   2427  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -6.340000   
8   8145  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.569578   
9   1107  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -4.610000   
10  1116  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)N(C)C(=O)[C@H]2...     -5.220000   
11  1110  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...     -4.730000   
12  8121  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.927246   
13  5836  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -5.060000   
14  6187  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -5.010000   
15  6584  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.330000   
16  6571  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.100000   
17  5803  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -6.970000   
18  2422  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.630000   
19  2440  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -7.760000   
20  8140  CCC[C@H]1C(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=...     -5.453495   
21  8131  CCC[C@@H]1NC(=O)CN(CCC)C(=O)[C@H](CC(C)C)NC(=O...     -5.509834   
22  8346  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.672617   
23  8184  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.929917   
24  6505  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.930000   
25  8342  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -4.994304   
26  8160  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.167475   
27  8341  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.822199   
28  8344  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.241518   
29  8343  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.131653   
30  8156  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.178526   
31  8150  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.834862   
32  8152  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.105008   
33  8116  CCCN1CC(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=O)N...     -5.400722   
34  8128  CCCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=...     -5.793469   
35  8138  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.303671   
36  6666  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -7.820000   
37  1115  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.190000   
38  8126  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.983385   
39  8114  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.309384   
40  1111  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C...     -6.220000   
41  1109  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N(C)C(...     -6.120000   
42  1112  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](C)NC(=O)[...     -6.170000   
43  1018  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...     -4.500000   
44  1845  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.960000   
45  1847  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.740000   
46  1841  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.410000   
47  1017  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...     -6.550000   
48  1840  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.480000   
49  1844  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -5.100000   
50  1846  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.820000   

 

In [115]:
df_ordered.to_csv('features/Descriptors/Train_2d_padel_curated_MDCK.csv', index=False)

In [116]:
#2d test padel descriptors
df_test = pd.read_csv('features/Descriptors/Test_2d_padel_MDCK.csv')
df_test['ID'] = df_test['Name'].str.extract(r'_(\d+)$')
df_test['ID'] = df_test['ID'].astype(int)
df_test = df_test.drop('Name',axis=1)
df_test = df_test.fillna(0)
df_test

nAcid   ALogP     ALogp2       AMR        apol  naAromAtom  nAromBond  \
0       0 -1.6634   2.766900  183.2267  118.299580           0          0   
1       0 -1.2217   1.492551  199.1082  122.245994           0          0   
2       0 -3.1134   9.693260  255.8998  162.779405           0          0   
3       0 -3.6834  13.567436  252.0938  160.844198           0          0   
4       0 -4.9290  24.295041  252.2939  164.539405           0          0   
5       0 -3.9378  15.506269  249.8523  166.492991           0          0   
6       0 -4.0401  16.322408  244.1556  163.399405           0          0   
7       0 -3.1134   9.693260  255.8998  162.779405           0          0   
8       0 -5.0816  25.822659  254.9508  167.632991           0          0   
9       0 -1.2456   1.551519  309.4986  187.298542           0          0   
10      0 -5.5830  31.169889  254.9353  169.392991           0          0   
11      0  0.3088   0.095357  335.1404  205.860058           0          0   
12      0 -3.0908   9.553045  284.5918  178.444198           0          0   

    nAtom  nHeavyAtom   nH  ...      WTPT-1    WTPT-2     WTPT-3     WTPT-4  \
0     110          50   60  ...   99.084602  1.981692  34.113502  15.397863   
1     111          53   58  ...  106.143859  2.002714  34.176054  15.419528   
2     154          69   85  ...  133.378413  1.933020  59.341751  28.115454   
3     154          68   86  ...  130.791399  1.923403  56.234345  25.152766   
4     155          70   85  ...  136.601049  1.951444  59.784728  28.235280   
5     158          71   87  ...  139.131996  1.959606  56.808725  28.380436   
6     155          70   85  ...  137.310770  1.961582  56.609941  28.393162   
7     154          69   85  ...  133.381424  1.933064  59.345483  28.116662   
8     158          71   87  ...  138.417801  1.949546  59.630333  28.216709   
9     174          80   94  ...  156.622606  1.957783  56.617512  25.292701   
10    159          72   87  ...  141.646739  1.967316  59.761039  28.238710   
11    192          86  106  ...  168.348068  1.957536  56.909620  25.395733   
12    164          78   86  ...  155.443185  1.992861  56.706886  25.570597   

       WTPT-5    WPATH   WPOL   XLogP  Zagreb    ID  
0   18.715639   8694.0   80.0   7.336   248.0  1842  
1   18.756526  10195.0   85.0   7.150   266.0  1843  
2   28.210938  22236.0  115.0   5.397   330.0  8168  
3   31.081579  21154.0  120.0   5.288   332.0  1108  
4   28.531690  22971.0  116.0   5.752   338.0  8119  
5   28.428289  22927.0  118.0   7.404   354.0  6496  
6   28.216778  22212.0  114.0   7.691   348.0  6423  
7   28.212683  22278.0  115.0   5.397   330.0  8345  
8   28.395866  23619.0  120.0   6.424   344.0  8143  
9   31.324812  31648.0  138.0   7.786   396.0  1118  
10  28.504056  24767.0  120.0   6.761   352.0  8133  
11  31.513887  37307.0  146.0  10.656   424.0  1120  
12  31.136289  30176.0  124.0   9.100   392.0  1121  

[13 rows x 1445 columns]

In [117]:
df = pd.read_csv('features/Descriptors/Test_2d_Mordred_desc_MDCK.csv')
df

ID                                             SMILES  Permeability  \
0   1120  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.300000   
1   1118  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](Cc2...     -5.350000   
2   1121  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...     -6.200000   
3   8133  CCC[C@@H]1NC(=O)CN(CC)C(=O)[C@H](CC(C)C)NC(=O)...     -5.965681   
4   8143  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.676306   
5   8119  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.516110   
6   6496  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.060000   
7   8168  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(C)[C@...     -5.977700   
8   8345  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(CC(C)...     -6.342777   
9   6423  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)...     -7.210000   
10  1108  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -5.180000   
11  1843  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.400000   
12  1842  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.400000   

                                             ABCIndex  \
0   module 'numpy' has no attribute 'float'.\n`np....   
1   module 'numpy' has no attribute 'float'.\n`np....   
2   module 'numpy' has no attribute 'float'.\n`np....   
3   module 'numpy' has no attribute 'float'.\n`np....   
4   module 'numpy' has no attribute 'float'.\n`np....   
5   module 'numpy' has no attribute 'float'.\n`np....   
6   module 'numpy' has no attribute 'float'.\n`np....   
7   module 'numpy' has no attribute 'float'.\n`np....   
8   module 'numpy' has no attribute 'float'.\n`np....   
9   module 'numpy' has no attribute 'float'.\n`np....   
10  module 'numpy' has no attribute 'float'.\n`np....   
11  module 'numpy' has no attribute 'float'.\n`np....   
12  module 'numpy' has no attribute 'float'.\n`np....   

                                           ABCGGIndex  AcidicGroupCount  \
0   module 'numpy' has no attribute 'float'.\n`np....                 0   
1   module 'numpy' has no attribute 'float'.\n`np....                 0   
2   module 'numpy' has no attribute 'float'.\n`np....                 0   
3   module 'numpy' has no attribute 'float'.\n`np....                 0   
4   module 'numpy' has no attribute 'float'.\n`np....                 0   
5   module 'numpy' has no attribute 'float'.\n`np....                 0   
6   module 'numpy' has no attribute 'float'.\n`np....                 0   
7   module 'numpy' has no attribute 'float'.\n`np....                 0   
8   module 'numpy' has no attribute 'float'.\n`np....                 0   
9   module 'numpy' has no attribute 'float'.\n`np....                 0   
10  module 'numpy' has no attribute 'float'.\n`np....                 0   
11  module 'numpy' has no attribute 'float'.\n`np....                 0   
12  module 'numpy' has no attribute 'float'.\n`np....                 0   

    BasicGroupCount  AdjacencyMatrix  AdjacencyMatrix.1  AdjacencyMatrix.2  \
0                 0       103.838268           2.420071           4.840143   
1                 0        97.302139           2.412394           4.824787   
2                 0        95.621135           2.421653           4.790984   
3                 0        88.159241           2.431154           4.817857   
4                 0        85.381854           2.437654           4.830440   
5                 0        83.965708           2.427767           4.806183   
6                 0        84.630944           2.429295           4.822808   
7                 0        81.585614           2.381030           4.762061   
8                 0        81.585744           2.384457           4.768915   
9                 0        83.165492           2.427826           4.818625   
10                0        80.342595           2.393888           4.787776   
11                0        66.166214           2.425971           4.807980   
12                0        60.942672           2.424731        

In [118]:
merged_df = df_test.merge(df[['ID', 'SMILES', 'Permeability']], on='ID', how='left')
merged_df = merged_df[['ID', 'SMILES', 'Permeability'] + [col for col in merged_df.columns if col not in ['ID', 'SMILES', 'Permeability']]]
merged_df

ID                                             SMILES  Permeability  \
0   1842  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.400000   
1   1843  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.400000   
2   8168  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(C)[C@...     -5.977700   
3   1108  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -5.180000   
4   8119  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.516110   
5   6496  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.060000   
6   6423  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)...     -7.210000   
7   8345  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(CC(C)...     -6.342777   
8   8143  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.676306   
9   1118  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](Cc2...     -5.350000   
10  8133  CCC[C@@H]1NC(=O)CN(CC)C(=O)[C@H](CC(C)C)NC(=O)...     -5.965681   
11  1120  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.300000   
12  1121  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...     -6.200000   

    nAcid   ALogP     ALogp2       AMR        apol  naAromAtom  nAromBond  \
0       0 -1.6634   2.766900  183.2267  118.299580           0          0   
1       0 -1.2217   1.492551  199.1082  122.245994           0          0   
2       0 -3.1134   9.693260  255.8998  162.779405           0          0   
3       0 -3.6834  13.567436  252.0938  160.844198           0          0   
4       0 -4.9290  24.295041  252.2939  164.539405           0          0   
5       0 -3.9378  15.506269  249.8523  166.492991           0          0   
6       0 -4.0401  16.322408  244.1556  163.399405           0          0   
7       0 -3.1134   9.693260  255.8998  162.779405           0          0   
8       0 -5.0816  25.822659  254.9508  167.632991           0          0   
9       0 -1.2456   1.551519  309.4986  187.298542           0          0   
10      0 -5.5830  31.169889  254.9353  169.392991           0          0   
11      0  0.3088   0.095357  335.1404  205.860058           0          0   
12      0 -3.0908   9.553045  284.5918  178.444198           0          0   

    ...       AMW      WTPT-1    WTPT-2     WTPT-3     WTPT-4     WTPT-5  \
0   ...  6.331431   99.084602  1.981692  34.113502  15.397863  18.715639   
1   ...  6.580557  106.143859  2.002714  34.176054  15.419528  18.756526   
2   ...  6.464993  133.378413  1.933020  59.341751  28.115454  28.210938   
3   ...  6.250992  130.791399  1.923403  56.234345  25.152766  31.081579   
4   ...  6.500703  136.601049  1.951444  59.784728  28.235280  28.531690   
5   ...  6.339573  139.131996  1.959606  56.808725  28.380436  28.428289   
6   ...  6.371851  137.310770  1.961582  56.609941  28.393162  28.216778   
7   ...  6.464993  133.381424  1.933064  59.345483  28.116662  28.212683   
8   ...  6.465978  138.417801  1.949546  59.630333  28.216709  28.395866   
9   ...  6.406411  156.622606  1.957783  56.617512  25.292701  31.324812   
10  ...  6.500783  141.646739  1.967316  59.761039  28.238710  28.504056   
11  ...  6.243799  168.348068  1.957536  56.909620  25.395733  31.513887   
12  ...  6.601542  155.443185  1.992861  56.706886  25.570597  31.136289   

      WPATH   WPOL   XLogP  Zagreb  
0    8694.0   80.0   7.336   248.0  
1   10195.0   85.0   7.150   266.0  
2   22236.0  115.0   5.397   330.0  
3   21154.0  120.0   5.288   332.0  
4   22971.0  116.0   5.752   338.0  
5   22927.0  118.0   7.404   354.0  
6   22212.0  114.0   7.691   348.0  
7   22278.0  115.0   5.397   330.0  
8   23619.0  120.0   6.424   344.0  
9   31648.0  138.0   7.786   396.0  
10  24767.0  120.0   6.761   352.0  
11  37307.0  146.0  10.656   424.0  
12  30176.0  124.0   9.100   392.0  

[13 rows x 1447 columns]

In [119]:
df_ordered = merged_df.merge(df[['ID']], on='ID', how='right')
df_ordered = df_ordered.reindex(df.index)
df_ordered

ID                                             SMILES  Permeability  \
0   1120  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.300000   
1   1118  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](Cc2...     -5.350000   
2   1121  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...     -6.200000   
3   8133  CCC[C@@H]1NC(=O)CN(CC)C(=O)[C@H](CC(C)C)NC(=O)...     -5.965681   
4   8143  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.676306   
5   8119  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.516110   
6   6496  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.060000   
7   8168  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(C)[C@...     -5.977700   
8   8345  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(CC(C)...     -6.342777   
9   6423  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)...     -7.210000   
10  1108  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -5.180000   
11  1843  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.400000   
12  1842  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.400000   

    nAcid   ALogP     ALogp2       AMR        apol  naAromAtom  nAromBond  \
0       0  0.3088   0.095357  335.1404  205.860058           0          0   
1       0 -1.2456   1.551519  309.4986  187.298542           0          0   
2       0 -3.0908   9.553045  284.5918  178.444198           0          0   
3       0 -5.5830  31.169889  254.9353  169.392991           0          0   
4       0 -5.0816  25.822659  254.9508  167.632991           0          0   
5       0 -4.9290  24.295041  252.2939  164.539405           0          0   
6       0 -3.9378  15.506269  249.8523  166.492991           0          0   
7       0 -3.1134   9.693260  255.8998  162.779405           0          0   
8       0 -3.1134   9.693260  255.8998  162.779405           0          0   
9       0 -4.0401  16.322408  244.1556  163.399405           0          0   
10      0 -3.6834  13.567436  252.0938  160.844198           0          0   
11      0 -1.2217   1.492551  199.1082  122.245994           0          0   
12      0 -1.6634   2.766900  183.2267  118.299580           0          0   

    ...       AMW      WTPT-1    WTPT-2     WTPT-3     WTPT-4     WTPT-5  \
0   ...  6.243799  168.348068  1.957536  56.909620  25.395733  31.513887   
1   ...  6.406411  156.622606  1.957783  56.617512  25.292701  31.324812   
2   ...  6.601542  155.443185  1.992861  56.706886  25.570597  31.136289   
3   ...  6.500783  141.646739  1.967316  59.761039  28.238710  28.504056   
4   ...  6.465978  138.417801  1.949546  59.630333  28.216709  28.395866   
5   ...  6.500703  136.601049  1.951444  59.784728  28.235280  28.531690   
6   ...  6.339573  139.131996  1.959606  56.808725  28.380436  28.428289   
7   ...  6.464993  133.378413  1.933020  59.341751  28.115454  28.210938   
8   ...  6.464993  133.381424  1.933064  59.345483  28.116662  28.212683   
9   ...  6.371851  137.310770  1.961582  56.609941  28.393162  28.216778   
10  ...  6.250992  130.791399  1.923403  56.234345  25.152766  31.081579   
11  ...  6.580557  106.143859  2.002714  34.176054  15.419528  18.756526   
12  ...  6.331431   99.084602  1.981692  34.113502  15.397863  18.715639   

      WPATH   WPOL   XLogP  Zagreb  
0   37307.0  146.0  10.656   424.0  
1   31648.0  138.0   7.786   396.0  
2   30176.0  124.0   9.100   392.0  
3   24767.0  120.0   6.761   352.0  
4   23619.0  120.0   6.424   344.0  
5   22971.0  116.0   5.752   338.0  
6   22927.0  118.0   7.404   354.0  
7   22236.0  115.0   5.397   330.0  
8   22278.0  115.0   5.397   330.0  
9   22212.0  114.0   7.691   348.0  
10  21154.0  120.0   5.288   332.0  
11  10195.0   85.0   7.150   266.0  
12   8694.0   80.0   7.336   248.0  

[13 rows x 1447 columns]

In [120]:
df_ordered.to_csv('features/Descriptors/Test_2d_padel_curated_MDCK.csv', index=False)

In [121]:
#3d Train descriptors
df_train = pd.read_csv('features/Descriptors/Train_3d_padel_MDCK.csv')
df_train['ID'] = df_train['Name'].str.extract(r'_(\d+)$')
df_train['ID'] = df_train['ID'].astype(int)
df_train = df_train.drop('Name',axis=1)
df_train = df_train.fillna(0)
df_train

TDB1u     TDB2u     TDB3u     TDB4u     TDB5u     TDB6u     TDB7u  \
0   1.256004  2.172194  3.034317  3.753694  4.466708  5.394142  6.339483   
1   1.262165  2.177943  3.004435  3.729856  4.523804  5.390270  6.124069   
2   1.259218  2.174627  3.008919  3.742963  4.547749  5.368845  6.135800   
3   1.257218  2.181184  3.022483  3.737097  4.542256  5.410557  6.185571   
4   1.261083  2.189218  3.014673  3.757476  4.586469  5.438855  6.191139   
5   1.258727  2.171374  3.005400  3.737842  4.548808  5.285357  6.077064   
6   1.262352  2.189819  3.015138  3.757234  4.579912  5.403821  6.152182   
7   1.260828  2.173701  3.010288  3.742199  4.533928  5.297952  6.073064   
8   1.252407  2.162436  2.998106  3.680852  4.473814  5.347391  6.113602   
9   1.264146  2.203915  3.013835  3.768807  4.634108  5.419729  6.128406   
10  1.263546  2.188964  3.017526  3.765209  4.577209  5.343044  6.140860   
11  1.263376  2.201869  3.014535  3.787893  4.631401  5.431100  6.208603   
12  1.264014  2.178655  2.999957  3.751729  4.601787  5.384973  6.056373   
13  1.264840  2.189118  3.004847  3.763190  4.611307  5.340708  6.016435   
14  1.264507  2.187167  3.002901  3.769268  4.604640  5.374375  6.105402   
15  1.263115  2.188576  2.999190  3.746247  4.588929  5.352004  6.062018   
16  1.264665  2.209461  3.017245  3.775621  4.641111  5.461088  6.183795   
17  1.260020  2.191214  2.994415  3.731383  4.671488  5.441883  6.163758   
18  1.263832  2.180266  2.999129  3.751226  4.597549  5.354668  6.101112   
19  1.264180  2.188773  3.002362  3.747652  4.601199  5.395908  6.172696   
20  1.262563  2.176896  3.006411  3.758941  4.595819  5.269518  5.942241   
21  1.261764  2.172560  3.008931  3.753627  4.547797  5.302576  5.974737   
22  1.261939  2.176030  3.004895  3.729838  4.554712  5.329628  6.027210   
23  1.264126  2.180781  3.000151  3.745292  4.607432  5.405549  6.112726   
24  1.262461  2.179174  2.994636  3.720041  4.573152  5.368101  6.087464   
25  1.262499  2.180361  2.995854  3.745365  4.608359  5.375396  6.055355   
26  1.264427  2.179710  3.019494  3.761886  4.549684  5.377081  6.106328   
27  1.264091  2.179176  3.010315  3.761070  4.592645  5.347331  6.090734   
28  1.265510  2.184069  2.994689  3.748613  4.575185  5.445938  6.272966   
29  1.263029  2.175665  3.006634  3.738415  4.556626  5.338898  6.010042   
30  1.263240  2.181083  3.000256  3.731478  4.550550  5.367295  6.143260   
31  1.263879  2.189504  3.031894  3.791534  4.579507  5.460231  6.410350   
32  1.263556  2.178971  3.005678  3.753001  4.596316  5.403763  6.187853   
33  1.263657  2.182457  3.010755  3.741749  4.535451  5.359544  6.155450   
34  1.264831  2.181769  3.016146  3.763752  4.591115  5.348218  6.051312   
35  1.263895  2.182221  3.001866  3.740031  4.497325  5.328217  6.110589   
36  1.263512  2.179020  3.013314  3.768641  4.600288  5.425294  6.169076   
37  1.260461  2.189321  2.991743  3.731921  4.649893  5.419463  6.093604   
38  1.260341  2.183166  3.018965  3.750979  4.547152  5.353479  6.098901   
39  1.262927  2.178487  3.007320  3.738617  4.548692  5.337387  6.080411   
40  1.261210  2.193071  2.994309  3.715032  4.656017  5.454639  6.179011   
41  1.260009  2.174848  3.012987  3.713801  4.534493  5.356906  6.080149   
42  1.261228  2.173398  3.014764  3.728366  4.499855  5.317612  6.088408   
43  1.259741  2.174189  3.011494  3.712481  4.505099  5.350878  6.103689   
44  1.260636  2.174988  3.013133  3.708422  4.505228  5.315655  6.040851   
45  1.260589  2.173264  3.014534  3.727009  4.512953  5.365309  6.193210   
46  1.260286  2.173964  3.010177  3.717482  4.522173  5.349942  6.043526   
47  1.260183  2.173997  3.014360  3.715310  4.490499  5.329521  6.134486   
48  1.261283  2.175413  3.010988  3.711777  4.522921  5.390969  6.080426   
49  1.264023  2.178676  3.016137  3.752616  4.548977  5.296112  6.055301   
50  1.262353  2.194549  2.999446  3.736655  4.635497  5.482865  6.249461   

       TDB8u     TDB9u    TDB10u  ...       P2s       

In [122]:
df = pd.read_csv('features/Descriptors/Train_2d_Mordred_desc_MDCK.csv')
df 

ID                                             SMILES  Permeability  \
0   1114  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -4.940000   
1   1113  CC(C)C[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@@H](Cc2...     -5.820000   
2   1117  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.650000   
3   1119  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.250000   
4   2428  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.350000   
5   2446  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -6.850000   
6   2445  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -5.270000   
7   2427  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -6.340000   
8   8145  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.569578   
9   1107  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -4.610000   
10  1116  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)N(C)C(=O)[C@H]2...     -5.220000   
11  1110  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...     -4.730000   
12  8121  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.927246   
13  5836  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -5.060000   
14  6187  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -5.010000   
15  6584  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.330000   
16  6571  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.100000   
17  5803  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -6.970000   
18  2422  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.630000   
19  2440  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -7.760000   
20  8140  CCC[C@H]1C(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=...     -5.453495   
21  8131  CCC[C@@H]1NC(=O)CN(CCC)C(=O)[C@H](CC(C)C)NC(=O...     -5.509834   
22  8346  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.672617   
23  8184  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.929917   
24  6505  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.930000   
25  8342  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -4.994304   
26  8160  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.167475   
27  8341  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.822199   
28  8344  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.241518   
29  8343  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.131653   
30  8156  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.178526   
31  8150  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.834862   
32  8152  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.105008   
33  8116  CCCN1CC(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=O)N...     -5.400722   
34  8128  CCCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=...     -5.793469   
35  8138  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.303671   
36  6666  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -7.820000   
37  1115  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.190000   
38  8126  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.983385   
39  8114  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.309384   
40  1111  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C...     -6.220000   
41  1109  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N(C)C(...     -6.120000   
42  1112  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](C)NC(=O)[...     -6.170000   
43  1018  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...     -4.500000   
44  1845  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.960000   
45  1847  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.740000   
46  1841  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.410000   
47  1017  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...     -6.550000   
48  1840  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.480000   
49  1844  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -5.100000   
50  1846  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.820000   

 

In [123]:
merged_df = df_train.merge(df[['ID', 'SMILES', 'Permeability']], on='ID', how='left')
merged_df = merged_df[['ID', 'SMILES', 'Permeability'] + [col for col in merged_df.columns if col not in ['ID', 'SMILES', 'Permeability']]]
merged_df

ID                                             SMILES  Permeability  \
0   1109  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N(C)C(...     -6.120000   
1   1115  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.190000   
2   1111  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C...     -6.220000   
3   1119  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.250000   
4   1113  CC(C)C[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@@H](Cc2...     -5.820000   
5   1116  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)N(C)C(=O)[C@H]2...     -5.220000   
6   1117  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.650000   
7   1110  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...     -4.730000   
8   1107  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -4.610000   
9   1841  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.410000   
10  1114  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -4.940000   
11  1845  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.960000   
12  2422  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.630000   
13  2428  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.350000   
14  2427  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -6.340000   
15  2445  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -5.270000   
16  1847  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.740000   
17  1017  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...     -6.550000   
18  2440  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -7.760000   
19  2446  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -6.850000   
20  5803  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -6.970000   
21  6187  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -5.010000   
22  5836  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -5.060000   
23  6505  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.930000   
24  6571  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.100000   
25  6666  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -7.820000   
26  8114  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.309384   
27  8116  CCCN1CC(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=O)N...     -5.400722   
28  8121  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.927246   
29  6584  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.330000   
30  8131  CCC[C@@H]1NC(=O)CN(CCC)C(=O)[C@H](CC(C)C)NC(=O...     -5.509834   
31  1112  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](C)NC(=O)[...     -6.170000   
32  8138  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.303671   
33  8140  CCC[C@H]1C(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=...     -5.453495   
34  8126  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.983385   
35  8145  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.569578   
36  8128  CCCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=...     -5.793469   
37  1840  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.480000   
38  1018  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...     -4.500000   
39  8184  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.929917   
40  1844  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -5.100000   
41  8160  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.167475   
42  8150  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.834862   
43  8152  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.105008   
44  8156  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.178526   
45  8342  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -4.994304   
46  8341  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.822199   
47  8344  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.241518   
48  8343  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.131653   
49  8346  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.672617   
50  1846  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.820000   

 

In [124]:
df_ordered = merged_df.merge(df[['ID']], on='ID', how='right')
df_ordered = df_ordered.reindex(df.index)
df_ordered

ID                                             SMILES  Permeability  \
0   1114  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -4.940000   
1   1113  CC(C)C[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@@H](Cc2...     -5.820000   
2   1117  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.650000   
3   1119  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.250000   
4   2428  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.350000   
5   2446  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -6.850000   
6   2445  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -5.270000   
7   2427  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -6.340000   
8   8145  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.569578   
9   1107  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -4.610000   
10  1116  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)N(C)C(=O)[C@H]2...     -5.220000   
11  1110  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...     -4.730000   
12  8121  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.927246   
13  5836  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -5.060000   
14  6187  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -5.010000   
15  6584  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.330000   
16  6571  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.100000   
17  5803  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -6.970000   
18  2422  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.630000   
19  2440  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -7.760000   
20  8140  CCC[C@H]1C(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=...     -5.453495   
21  8131  CCC[C@@H]1NC(=O)CN(CCC)C(=O)[C@H](CC(C)C)NC(=O...     -5.509834   
22  8346  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.672617   
23  8184  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.929917   
24  6505  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.930000   
25  8342  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -4.994304   
26  8160  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.167475   
27  8341  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.822199   
28  8344  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.241518   
29  8343  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.131653   
30  8156  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.178526   
31  8150  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.834862   
32  8152  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.105008   
33  8116  CCCN1CC(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=O)N...     -5.400722   
34  8128  CCCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=...     -5.793469   
35  8138  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.303671   
36  6666  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -7.820000   
37  1115  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.190000   
38  8126  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.983385   
39  8114  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.309384   
40  1111  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C...     -6.220000   
41  1109  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N(C)C(...     -6.120000   
42  1112  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](C)NC(=O)[...     -6.170000   
43  1018  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...     -4.500000   
44  1845  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.960000   
45  1847  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.740000   
46  1841  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.410000   
47  1017  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...     -6.550000   
48  1840  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.480000   
49  1844  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -5.100000   
50  1846  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.820000   

 

In [125]:
df_ordered.to_csv('features/Descriptors/Train_3d_padel_curated_MDCK.csv', index=False)

In [126]:
#3d test padel descriptors
df_test = pd.read_csv('features/Descriptors/Test_3d_padel_MDCK.csv')
df_test['ID'] = df_test['Name'].str.extract(r'_(\d+)$')
df_test['ID'] = df_test['ID'].astype(int)
df_test = df_test.drop('Name',axis=1)
df_test = df_test.fillna(0)
df_test

TDB1u     TDB2u     TDB3u     TDB4u     TDB5u     TDB6u     TDB7u  \
0   1.262071  2.179842  2.996935  3.740084  4.656446  5.416241  6.070195   
1   1.254018  2.163124  3.006562  3.718435  4.523601  5.384969  6.020719   
2   1.265653  2.207782  3.013447  3.777693  4.664874  5.433991  6.207650   
3   1.257288  2.179452  3.024774  3.753688  4.541741  5.324373  6.037414   
4   1.265005  2.203042  3.003715  3.755510  4.643888  5.425595  6.130606   
5   1.264406  2.182123  3.012432  3.737651  4.522408  5.376301  6.170496   
6   1.260128  2.172456  3.012249  3.736571  4.547769  5.361418  6.089385   
7   1.264178  2.181512  3.004424  3.733909  4.602144  5.439434  6.212960   
8   1.261144  2.182792  2.986502  3.714280  4.627305  5.440193  6.181705   
9   1.260512  2.173203  3.018396  3.732142  4.499600  5.331553  6.115620   
10  1.265596  2.183941  2.997808  3.747880  4.558068  5.387794  6.072208   
11  1.260237  2.190291  2.993746  3.719427  4.583111  5.419863  6.176098   
12  1.258625  2.178045  3.017671  3.720530  4.539254  5.370155  6.118056   

       TDB8u     TDB9u    TDB10u  ...       P2s       E1s       E2s       E3s  \
0   6.751989  7.460681  8.290323  ...  0.252612  0.485191  0.393955  0.404621   
1   6.773120  7.723639  8.487681  ...  0.388502  0.523799  0.502842  0.421705   
2   6.875381  7.479235  8.131504  ...  0.392542  0.472921  0.421803  0.368107   
3   6.722839  7.487353  8.231476  ...  0.291189  0.444583  0.539683  0.357508   
4   6.860433  7.569793  8.533427  ...  0.343748  0.509549  0.449964  0.374446   
5   6.902463  7.681886  8.593614  ...  0.406031  0.519823  0.544516  0.426875   
6   6.848274  7.795227  8.770288  ...  0.363249  0.588852  0.553764  0.271499   
7   6.988305  8.017577  8.725276  ...  0.404704  0.497301  0.484967  0.300594   
8   6.951036  7.668839  8.441794  ...  0.346100  0.511976  0.468069  0.382243   
9   6.824954  7.602464  8.399841  ...  0.412405  0.532151  0.496837  0.370279   
10  6.739466  7.564491  8.465326  ...  0.431114  0.440987  0.473812  0.406420   
11  6.947103  7.567644  8.284050  ...  0.400169  0.413844  0.487313  0.373768   
12  6.897442  7.701828  8.327868  ...  0.327869  0.524865  0.537605  0.374733   

           Ts          As           Vs        Ks        Ds    ID  
0   49.499572  564.175291  1883.827401  0.530571  1.283767  6496  
1   44.313812  550.245259  2036.042466  0.379606  1.448347  1108  
2   30.606329  264.951713   795.132003  0.372567  1.262831  1843  
3   41.316066  490.042107  2188.204700  0.349545  1.341774  1118  
4   51.553116  710.235475  2723.391067  0.393219  1.333960  1121  
5   45.471900  589.208424  2306.378610  0.370630  1.491215  8143  
6   51.266910  711.978056  2701.028559  0.395248  1.414115  8345  
7   49.677484  690.784960  2675.200579  0.387593  1.282862  8119  
8   44.726179  551.597017  2126.801755  0.369175  1.362288  6423  
9   43.965756  563.139411  2324.612455  0.349052  1.399267  8168  
10  50.076001  689.240384  2342.004744  0.413087  1.321219  8133  
11  29.844133  259.248630   831.974448  0.346020  1.274924  1842  
12  48.372354  683.620826  3396.096064  0.308384  1.437203  1120  

[13 rows x 432 columns]

In [127]:
df = pd.read_csv('features/Descriptors/Test_2d_Mordred_desc_MDCK.csv')
df

ID                                             SMILES  Permeability  \
0   1120  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.300000   
1   1118  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](Cc2...     -5.350000   
2   1121  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...     -6.200000   
3   8133  CCC[C@@H]1NC(=O)CN(CC)C(=O)[C@H](CC(C)C)NC(=O)...     -5.965681   
4   8143  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.676306   
5   8119  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.516110   
6   6496  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.060000   
7   8168  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(C)[C@...     -5.977700   
8   8345  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(CC(C)...     -6.342777   
9   6423  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)...     -7.210000   
10  1108  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -5.180000   
11  1843  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.400000   
12  1842  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.400000   

                                             ABCIndex  \
0   module 'numpy' has no attribute 'float'.\n`np....   
1   module 'numpy' has no attribute 'float'.\n`np....   
2   module 'numpy' has no attribute 'float'.\n`np....   
3   module 'numpy' has no attribute 'float'.\n`np....   
4   module 'numpy' has no attribute 'float'.\n`np....   
5   module 'numpy' has no attribute 'float'.\n`np....   
6   module 'numpy' has no attribute 'float'.\n`np....   
7   module 'numpy' has no attribute 'float'.\n`np....   
8   module 'numpy' has no attribute 'float'.\n`np....   
9   module 'numpy' has no attribute 'float'.\n`np....   
10  module 'numpy' has no attribute 'float'.\n`np....   
11  module 'numpy' has no attribute 'float'.\n`np....   
12  module 'numpy' has no attribute 'float'.\n`np....   

                                           ABCGGIndex  AcidicGroupCount  \
0   module 'numpy' has no attribute 'float'.\n`np....                 0   
1   module 'numpy' has no attribute 'float'.\n`np....                 0   
2   module 'numpy' has no attribute 'float'.\n`np....                 0   
3   module 'numpy' has no attribute 'float'.\n`np....                 0   
4   module 'numpy' has no attribute 'float'.\n`np....                 0   
5   module 'numpy' has no attribute 'float'.\n`np....                 0   
6   module 'numpy' has no attribute 'float'.\n`np....                 0   
7   module 'numpy' has no attribute 'float'.\n`np....                 0   
8   module 'numpy' has no attribute 'float'.\n`np....                 0   
9   module 'numpy' has no attribute 'float'.\n`np....                 0   
10  module 'numpy' has no attribute 'float'.\n`np....                 0   
11  module 'numpy' has no attribute 'float'.\n`np....                 0   
12  module 'numpy' has no attribute 'float'.\n`np....                 0   

    BasicGroupCount  AdjacencyMatrix  AdjacencyMatrix.1  AdjacencyMatrix.2  \
0                 0       103.838268           2.420071           4.840143   
1                 0        97.302139           2.412394           4.824787   
2                 0        95.621135           2.421653           4.790984   
3                 0        88.159241           2.431154           4.817857   
4                 0        85.381854           2.437654           4.830440   
5                 0        83.965708           2.427767           4.806183   
6                 0        84.630944           2.429295           4.822808   
7                 0        81.585614           2.381030           4.762061   
8                 0        81.585744           2.384457           4.768915   
9                 0        83.165492           2.427826           4.818625   
10                0        80.342595           2.393888           4.787776   
11                0        66.166214           2.425971           4.807980   
12                0        60.942672           2.424731        

In [128]:
merged_df = df_test.merge(df[['ID', 'SMILES', 'Permeability']], on='ID', how='left')
merged_df = merged_df[['ID', 'SMILES', 'Permeability'] + [col for col in merged_df.columns if col not in ['ID', 'SMILES', 'Permeability']]]
merged_df

ID                                             SMILES  Permeability  \
0   6496  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.060000   
1   1108  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -5.180000   
2   1843  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.400000   
3   1118  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](Cc2...     -5.350000   
4   1121  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...     -6.200000   
5   8143  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.676306   
6   8345  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(CC(C)...     -6.342777   
7   8119  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.516110   
8   6423  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)...     -7.210000   
9   8168  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(C)[C@...     -5.977700   
10  8133  CCC[C@@H]1NC(=O)CN(CC)C(=O)[C@H](CC(C)C)NC(=O)...     -5.965681   
11  1842  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.400000   
12  1120  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.300000   

       TDB1u     TDB2u     TDB3u     TDB4u     TDB5u     TDB6u     TDB7u  ...  \
0   1.262071  2.179842  2.996935  3.740084  4.656446  5.416241  6.070195  ...   
1   1.254018  2.163124  3.006562  3.718435  4.523601  5.384969  6.020719  ...   
2   1.265653  2.207782  3.013447  3.777693  4.664874  5.433991  6.207650  ...   
3   1.257288  2.179452  3.024774  3.753688  4.541741  5.324373  6.037414  ...   
4   1.265005  2.203042  3.003715  3.755510  4.643888  5.425595  6.130606  ...   
5   1.264406  2.182123  3.012432  3.737651  4.522408  5.376301  6.170496  ...   
6   1.260128  2.172456  3.012249  3.736571  4.547769  5.361418  6.089385  ...   
7   1.264178  2.181512  3.004424  3.733909  4.602144  5.439434  6.212960  ...   
8   1.261144  2.182792  2.986502  3.714280  4.627305  5.440193  6.181705  ...   
9   1.260512  2.173203  3.018396  3.732142  4.499600  5.331553  6.115620  ...   
10  1.265596  2.183941  2.997808  3.747880  4.558068  5.387794  6.072208  ...   
11  1.260237  2.190291  2.993746  3.719427  4.583111  5.419863  6.176098  ...   
12  1.258625  2.178045  3.017671  3.720530  4.539254  5.370155  6.118056  ...   

         P1s       P2s       E1s       E2s       E3s         Ts          As  \
0   0.687047  0.252612  0.485191  0.393955  0.404621  49.499572  564.175291   
1   0.531236  0.388502  0.523799  0.502842  0.421705  44.313812  550.245259   
2   0.522503  0.392542  0.472921  0.421803  0.368107  30.606329  264.951713   
3   0.566363  0.291189  0.444583  0.539683  0.357508  41.316066  490.042107   
4   0.585065  0.343748  0.509549  0.449964  0.374446  51.553116  710.235475   
5   0.507722  0.406031  0.519823  0.544516  0.426875  45.471900  589.208424   
6   0.566916  0.363249  0.588852  0.553764  0.271499  51.266910  711.978056   
7   0.520358  0.404704  0.497301  0.484967  0.300594  49.677484  690.784960   
8   0.566683  0.346100  0.511976  0.468069  0.382243  44.726179  551.597017   
9   0.486963  0.412405  0.532151  0.496837  0.370279  43.965756  563.139411   
10  0.510944  0.431114  0.440987  0.473812  0.406420  50.076001  689.240384   
11  0.497178  0.400169  0.413844  0.487313  0.373768  29.844133  259.248630   
12  0.538922  0.327869  0.524865  0.537605  0.374733  48.372354  683.620826   

             Vs        Ks        Ds  
0   1883.827401  0.530571  1.283767  
1   2036.042466  0.379606  1.448347  
2    795.132003  0.372567  1.262831  
3   2188.204700  0.349545  1.341774  
4   2723.391067  0.393219  1.333960  
5   2306.378610  0.370630  1.491215  
6   2701.028559  0.395248  1.414115  
7   2675.200579  0.387593  1.282862  
8   2126.801755  0.369175  1.362288  
9   2324.612455  0.349052  1.399267  
10  2342.004744  0.413087  1.321219  
11   831.974448  0.346020  1.274924  
12  3396.096064  0.308384  1.437203  

[13 rows x 434 columns]

In [129]:
df_ordered = merged_df.merge(df[['ID']], on='ID', how='right')
df_ordered = df_ordered.reindex(df.index)
df_ordered

ID                                             SMILES  Permeability  \
0   1120  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.300000   
1   1118  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](Cc2...     -5.350000   
2   1121  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...     -6.200000   
3   8133  CCC[C@@H]1NC(=O)CN(CC)C(=O)[C@H](CC(C)C)NC(=O)...     -5.965681   
4   8143  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.676306   
5   8119  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.516110   
6   6496  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.060000   
7   8168  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(C)[C@...     -5.977700   
8   8345  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(CC(C)...     -6.342777   
9   6423  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)...     -7.210000   
10  1108  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -5.180000   
11  1843  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.400000   
12  1842  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.400000   

       TDB1u     TDB2u     TDB3u     TDB4u     TDB5u     TDB6u     TDB7u  ...  \
0   1.258625  2.178045  3.017671  3.720530  4.539254  5.370155  6.118056  ...   
1   1.257288  2.179452  3.024774  3.753688  4.541741  5.324373  6.037414  ...   
2   1.265005  2.203042  3.003715  3.755510  4.643888  5.425595  6.130606  ...   
3   1.265596  2.183941  2.997808  3.747880  4.558068  5.387794  6.072208  ...   
4   1.264406  2.182123  3.012432  3.737651  4.522408  5.376301  6.170496  ...   
5   1.264178  2.181512  3.004424  3.733909  4.602144  5.439434  6.212960  ...   
6   1.262071  2.179842  2.996935  3.740084  4.656446  5.416241  6.070195  ...   
7   1.260512  2.173203  3.018396  3.732142  4.499600  5.331553  6.115620  ...   
8   1.260128  2.172456  3.012249  3.736571  4.547769  5.361418  6.089385  ...   
9   1.261144  2.182792  2.986502  3.714280  4.627305  5.440193  6.181705  ...   
10  1.254018  2.163124  3.006562  3.718435  4.523601  5.384969  6.020719  ...   
11  1.265653  2.207782  3.013447  3.777693  4.664874  5.433991  6.207650  ...   
12  1.260237  2.190291  2.993746  3.719427  4.583111  5.419863  6.176098  ...   

         P1s       P2s       E1s       E2s       E3s         Ts          As  \
0   0.538922  0.327869  0.524865  0.537605  0.374733  48.372354  683.620826   
1   0.566363  0.291189  0.444583  0.539683  0.357508  41.316066  490.042107   
2   0.585065  0.343748  0.509549  0.449964  0.374446  51.553116  710.235475   
3   0.510944  0.431114  0.440987  0.473812  0.406420  50.076001  689.240384   
4   0.507722  0.406031  0.519823  0.544516  0.426875  45.471900  589.208424   
5   0.520358  0.404704  0.497301  0.484967  0.300594  49.677484  690.784960   
6   0.687047  0.252612  0.485191  0.393955  0.404621  49.499572  564.175291   
7   0.486963  0.412405  0.532151  0.496837  0.370279  43.965756  563.139411   
8   0.566916  0.363249  0.588852  0.553764  0.271499  51.266910  711.978056   
9   0.566683  0.346100  0.511976  0.468069  0.382243  44.726179  551.597017   
10  0.531236  0.388502  0.523799  0.502842  0.421705  44.313812  550.245259   
11  0.522503  0.392542  0.472921  0.421803  0.368107  30.606329  264.951713   
12  0.497178  0.400169  0.413844  0.487313  0.373768  29.844133  259.248630   

             Vs        Ks        Ds  
0   3396.096064  0.308384  1.437203  
1   2188.204700  0.349545  1.341774  
2   2723.391067  0.393219  1.333960  
3   2342.004744  0.413087  1.321219  
4   2306.378610  0.370630  1.491215  
5   2675.200579  0.387593  1.282862  
6   1883.827401  0.530571  1.283767  
7   2324.612455  0.349052  1.399267  
8   2701.028559  0.395248  1.414115  
9   2126.801755  0.369175  1.362288  
10  2036.042466  0.379606  1.448347  
11   795.132003  0.372567  1.262831  
12   831.974448  0.346020  1.274924  

[13 rows x 434 columns]

In [130]:
df_ordered.to_csv('features/Descriptors/Test_3d_padel_curated_MDCK.csv', index=False)

In [131]:
#2d Padel descriptors
df_train = pd.read_csv('features/Descriptors/Train_2d_padel_curated_MDCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_padel_curated_MDCK.csv')
df_test = df_test.dropna()
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 1444)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 1444)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000251 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3450
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 255
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spli

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.5961                0.6385   
DecisionTreeRegressor                    0.8770                0.7149   
RandomForestRegressor                    0.6054                0.6416   
GradientBoostingRegressor                0.6708                0.6579   
AdaBoostRegressor                        0.5981                0.6230   
XGBRegressor                             0.7197                0.6682   
ExtraTreesRegressor                      0.6807                0.6676   
LinearRegression                         1.3123                0.8872   
KNeighborsRegressor                      0.5899                0.6026   
SVR                                      0.6624                0.6444   
MLPRegressor                             1.0785                0.7945   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7721               0.0785   
DecisionTreeRegressor                     0.9365              -0.3557   
RandomForestRegressor                     0.7781               0.0641   
GradientBoostingRegressor                 0.8190              -0.0370   
AdaBoostRegressor                         0.7734               0.0754   
XGBRegressor                              0.8483              -0.1125   
ExtraTreesRegressor                       0.8250              -0.0522   
LinearRegression                          1.1456              -1.0286   
KNeighborsRegressor                       0.7681               0.0880   
SVR                                       0.8139              -0.0240   
MLPRegressor                              1.0385              -0.6672   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.3346                0.4345   
DecisionTreeRegressor                    0.1436                0.1671   
RandomForestRegressor                    0.3164                0.3461   
GradientBoostingRegressor                0.2967                0.3218   
AdaBoostRegressor                        0.3506                0.3781   
XGBRegressor                             0.2712                0.3061   
ExtraTreesRegressor                      0.2820                0.3173   
LinearRegression                         0.2001                0.1822   
KNeighborsRegressor                      0.3845                0.3882   
SVR                                      0.2248                0.2369   
MLPRegressor                             0.1914                0.1835   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.3518   0.4970    0.5932   0.4019   
DecisionTreeRegressor       0.3547   0.5295    0.5956   0.3970   
RandomForestRegressor       0.3099   0.4942    0.5567   0.4732   
GradientBoostingRegressor   0.3615   0.5231    0.6013   0.3854   
AdaBoostRegressor           0.3265   0.4916    0.5714   0.4449   
XGBRegressor                0.4233   0.5436    0.6506   0.2804   
ExtraTreesRegressor         0.3478   0.5026    0.5897   0.4088   
LinearRegression            0.9660   0.6423    0.9829  -0.6423   
KNeighborsRegressor         0.3567   0.4905    0.5972   0.3936   
SVR                         0.3024   0.4747    0.5499   0.4859   
MLPRegressor                0.4917   0.6127    0.7012   0.1641   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6416                    0.4924  
DecisionTreeRegressor                       0.7057                    0.3769  
RandomForestRegressor                       0.7070                    0.3329  
GradientBoostingRegressor                   0.6847                    0.3164  
AdaBoostRegressor                           0.7020                    0.3439  
XGBRegressor                                0.6281                    0.3219  
ExtraTreesRegressor                         0.704

In [132]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.403401796264953, -5.801362849910222, -6.40...   
1   [-5.65, -5.33, -5.06, -5.400722167, -6.9299170...   
2   [-5.503513251674998, -5.390131088038332, -5.85...   
3   [-5.3768402880168855, -5.5012534746316994, -5....   
4   [-5.428174651999999, -5.339598512, -5.84428571...   
5   [-5.268087, -5.429548, -5.2928333, -5.811682, ...   
6   [-5.518724182937495, -5.409638708249998, -6.15...   
7   [-5.93357995743354, -5.581520558444441, -4.108...   
8   [-5.613333333333333, -5.786666666666666, -5.98...   
9   [-5.577049341417479, -5.319152653371145, -5.61...   
10  [-5.724710227145333, -5.795883440819948, -5.16...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.578397389477615, -5.398929028023123, -5.3...   
1   [[-4.94, -6.25, -5.35, -5.453495214, -6.929917...   
2   [[-5.438158710462497, -5.756114955468336, -6.0...   
3   [[-5.035225263867772, -6.206340441327234, -5.7...   
4   [[-5.074999999999999, -6.144137553285714, -5.5...   
5   [[-5.187222, -6.2283454, -6.0013194, -6.294338...   
6   [[-5.105184952140003, -6.061422106417499, -6.3...   
7   [[-6.840275322159753, -5.898250267305669, -10....   
8   [[-5.613333333333333, -5.613333333333334, -6.4...   
9   [[-5.668521468550275, -5.922926449935176, -5.7...   
10  [[-8.142755300994278, -6.1217116992735505, -8....   

                                Test Predictions Mean  \
0   [-5.456002966533946, -5.589594080550133, -6.00...   
1   [-5.4334491173999995, -6.109483658749999, -6.1...   
2   [-5.474578210372668, -5.7609898221064, -5.9915...   
3   [-5.290232511373617, -5.949156646637054, -6.08...   
4   [-5.277395854313333, -5.8449290582106785, -5.8...   
5   [-5.1422596, -5.9502053, -6.1759214, -6.487588...   
6   [-5.220390062361003, -5.853894964167167, -6.51...   
7   [-6.245935243676091, -5.995156869402008, -9.18...   
8   [-5.6546666666666665, -5.666000000000001, -6.5...   
9   [-5.680455935240749, -5.884504614739118, -5.72...   
10  [-7.256875767635513, -5.893941967907572, -7.74...   

                                 Test Predictions Std  
0   [0.15829755552137664, 0.19194530482391176, 0.3...  
1   [0.7774683100598736, 0.2810326824999997, 0.680...  
2   [0.2297848378425105, 0.1734376116907267, 0.129...  
3   [0.28422953163014747, 0.34495294695443174, 0.3...  
4   [0.3020795118044788, 0.29665430089880984, 0.25...  
5   [0.40034124, 0.3403726, 0.2232477, 0.5249209, ...  
6   [0.2877532063996415, 0.27915582197438066, 0.28...  
7   [0.38906781926790107, 0.6047810638525762, 0.77...  
8   [0.14230796026770795, 0.14081350945290821, 0.2...  
9   [0.1555225405025675, 0.24280557670405, 0.11238...  
10  [0.9535730559000045, 0.959161727646277, 0.9152...

In [133]:
result_df.to_csv('results/Descriptors/Results_2D_padel_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_padel_MDCK.csv')

In [134]:
#2d padel descriptors const removal
df_train = pd.read_csv('features/Descriptors/Train_2d_padel_curated_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train, const_col = remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_padel_curated_MDCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = X_test.drop(const_col,axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 992)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 992)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000208 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3450
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 255
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.5961                0.6385   
DecisionTreeRegressor                    1.0721                0.7976   
RandomForestRegressor                    0.6095                0.6448   
GradientBoostingRegressor                0.6542                0.6464   
AdaBoostRegressor                        0.6284                0.6416   
XGBRegressor                             0.7197                0.6682   
ExtraTreesRegressor                      0.6603                0.6560   
LinearRegression                         1.3123                0.8872   
KNeighborsRegressor                      0.5899                0.6026   
SVR                                      0.6623                0.6444   
MLPRegressor                             1.3838                0.8951   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7721               0.0785   
DecisionTreeRegressor                     1.0354              -0.6572   
RandomForestRegressor                     0.7807               0.0579   
GradientBoostingRegressor                 0.8088              -0.0112   
AdaBoostRegressor                         0.7927               0.0286   
XGBRegressor                              0.8483              -0.1125   
ExtraTreesRegressor                       0.8126              -0.0208   
LinearRegression                          1.1456              -1.0286   
KNeighborsRegressor                       0.7681               0.0880   
SVR                                       0.8138              -0.0239   
MLPRegressor                              1.1764              -1.1392   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.3346                0.4345   
DecisionTreeRegressor                    0.0551                0.0802   
RandomForestRegressor                    0.3096                0.3422   
GradientBoostingRegressor                0.3167                0.3537   
AdaBoostRegressor                        0.3176                0.3416   
XGBRegressor                             0.2712                0.3061   
ExtraTreesRegressor                      0.3052                0.3340   
LinearRegression                         0.2001                0.1822   
KNeighborsRegressor                      0.3845                0.3882   
SVR                                      0.2250                0.2369   
MLPRegressor                             0.0622                0.1036   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.3518   0.4970    0.5932   0.4019   
DecisionTreeRegressor       0.4454   0.5858    0.6674   0.2428   
RandomForestRegressor       0.3090   0.4946    0.5559   0.4747   
GradientBoostingRegressor   0.3530   0.5242    0.5942   0.3999   
AdaBoostRegressor           0.2956   0.4683    0.5437   0.4975   
XGBRegressor                0.4233   0.5436    0.6506   0.2804   
ExtraTreesRegressor         0.3325   0.4885    0.5766   0.4348   
LinearRegression            0.9660   0.6423    0.9829  -0.6423   
KNeighborsRegressor         0.3567   0.4905    0.5972   0.3936   
SVR                         0.3024   0.4747    0.5499   0.4859   
MLPRegressor                0.8837   0.6702    0.9401  -0.5024   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6416                    0.4924  
DecisionTreeRegressor                       0.6718                    0.3769  
RandomForestRegressor                       0.7088                    0.3329  
GradientBoostingRegressor                   0.6934                    0.3164  
AdaBoostRegressor                           0.7310                    0.3494  
XGBRegressor                                0.6281                    0.3219  
ExtraTreesRegressor                         0.714

In [135]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.403401796264953, -5.801362849910222, -6.40...   
1   [-5.65, -5.06, -5.06, -5.793469425, -6.9299170...   
2   [-5.483237143234995, -5.443904415684999, -5.88...   
3   [-5.376889113842746, -5.434854725263953, -5.43...   
4   [-5.3182048668, -5.458891233125001, -5.6885478...   
5   [-5.268087, -5.429548, -5.2928333, -5.811682, ...   
6   [-5.539766940449997, -5.464338857130002, -6.22...   
7   [-5.933579957433534, -5.581520558444448, -4.10...   
8   [-5.613333333333333, -5.786666666666666, -5.98...   
9   [-5.577050067873874, -5.319139821801227, -5.61...   
10  [-5.632311161508756, -6.00421124383829, -5.094...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.578397389477615, -5.398929028023123, -5.3...   
1   [[-4.94, -6.25, -6.34, -5.309384159, -6.929917...   
2   [[-5.4674368109359985, -5.754115323200001, -5....   
3   [[-5.0901367715997825, -6.167809427820997, -5....   
4   [[-5.0825, -5.980655693846154, -5.616389587884...   
5   [[-5.187222, -6.2283454, -6.0013194, -6.294338...   
6   [[-5.153200000000003, -5.8744348275375025, -6....   
7   [[-6.840275322159753, -5.8982502673056665, -10...   
8   [[-5.613333333333333, -5.613333333333334, -6.4...   
9   [[-5.668565275900687, -5.922988097419806, -5.7...   
10  [[-7.52256313603541, -6.217643165445445, -10.0...   

                                Test Predictions Mean  \
0   [-5.456002966533946, -5.589594080550133, -6.00...   
1   [-5.7845234873999996, -6.388, -6.4179667323999...   
2   [-5.47905631107283, -5.758963871622236, -6.020...   
3   [-5.379353544744598, -5.970190494912644, -6.02...   
4   [-5.341388842486364, -5.878873885856188, -5.95...   
5   [-5.1422596, -5.9502053, -6.1759214, -6.487588...   
6   [-5.296561267994502, -5.845203012711002, -6.40...   
7   [-6.245935243676091, -5.995156869402008, -9.18...   
8   [-5.6546666666666665, -5.666000000000001, -6.5...   
9   [-5.680507704487146, -5.884555251776673, -5.72...   
10  [-6.606271698100963, -5.843735050692063, -8.93...   

                                 Test Predictions Std  
0   [0.15829755552137664, 0.19194530482391176, 0.3...  
1   [1.2245132566979549, 0.13629380029920649, 0.75...  
2   [0.19462603774082476, 0.1557406356407126, 0.18...  
3   [0.36237626956475594, 0.28568023244925306, 0.3...  
4   [0.2999271165116116, 0.2646538016568159, 0.322...  
5   [0.40034124, 0.3403726, 0.2232477, 0.5249209, ...  
6   [0.23135270253408194, 0.2506521521291158, 0.22...  
7   [0.3890678192678994, 0.604781063852574, 0.7704...  
8   [0.14230796026770795, 0.14081350945290821, 0.2...  
9   [0.15553094941624324, 0.24282524766983227, 0.1...  
10  [1.1034749920830662, 0.9236872679130275, 1.103...

In [136]:
result_df.to_csv('results/Descriptors/Results_2D_padel_const_rem_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_padel_const_rem_MDCK.csv')

In [137]:
#2d padel descriptors LVR
df_train = pd.read_csv('features/Descriptors/Train_2d_padel_curated_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train, const_col = remove_low_variance_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_padel_curated_MDCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = X_test.drop(const_col,axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 642)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 642)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000416 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2115
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 158
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6071                0.6320   
DecisionTreeRegressor                    1.0897                0.8485   
RandomForestRegressor                    0.6340                0.6681   
GradientBoostingRegressor                0.7305                0.7206   
AdaBoostRegressor                        0.6037                0.6306   
XGBRegressor                             0.7427                0.6901   
ExtraTreesRegressor                      0.6306                0.6453   
LinearRegression                         1.7155                0.9672   
KNeighborsRegressor                      0.6255                0.6300   
SVR                                      0.6519                0.6428   
MLPRegressor                             1.3689                0.9113   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7792               0.0615   
DecisionTreeRegressor                     1.0439              -0.6846   
RandomForestRegressor                     0.7963               0.0199   
GradientBoostingRegressor                 0.8547              -0.1292   
AdaBoostRegressor                         0.7770               0.0668   
XGBRegressor                              0.8618              -0.1481   
ExtraTreesRegressor                       0.7941               0.0251   
LinearRegression                          1.3098              -1.6519   
KNeighborsRegressor                       0.7909               0.0330   
SVR                                       0.8074              -0.0078   
MLPRegressor                              1.1700              -1.1161   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.3153                0.4181   
DecisionTreeRegressor                   -0.0984               -0.0872   
RandomForestRegressor                    0.2717                0.3219   
GradientBoostingRegressor                0.1850                0.2543   
AdaBoostRegressor                        0.3474                0.4180   
XGBRegressor                             0.2269                0.2701   
ExtraTreesRegressor                      0.3239                0.3270   
LinearRegression                         0.0494                0.0720   
KNeighborsRegressor                      0.3420                0.3497   
SVR                                      0.2441                0.2473   
MLPRegressor                             0.0136                0.0048   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.3582   0.5320    0.5985   0.3911   
DecisionTreeRegressor       0.3552   0.5178    0.5960   0.3962   
RandomForestRegressor       0.3049   0.4866    0.5521   0.4817   
GradientBoostingRegressor   0.3031   0.4884    0.5506   0.4847   
AdaBoostRegressor           0.2878   0.4587    0.5365   0.5107   
XGBRegressor                0.4035   0.5524    0.6353   0.3140   
ExtraTreesRegressor         0.3474   0.5066    0.5894   0.4095   
LinearRegression            1.1521   0.7444    1.0734  -0.9586   
KNeighborsRegressor         0.3479   0.4730    0.5898   0.4086   
SVR                         0.2998   0.4621    0.5476   0.4903   
MLPRegressor                0.3296   0.5141    0.5741   0.4397   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6440                    0.4429  
DecisionTreeRegressor                       0.7409                    0.4814  
RandomForestRegressor                       0.7223                    0.3769  
GradientBoostingRegressor                   0.7537                    0.3659  
AdaBoostRegressor                           0.7560                    0.3824  
XGBRegressor                                0.6761                    0.3604  
ExtraTreesRegressor                         0.718

In [138]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.67049629146648, -5.805221112870568, -5.974...   
1   [-5.65, -5.06, -5.93, -6.929917083, -5.4534952...   
2   [-5.482292255343995, -5.494367730160002, -6.07...   
3   [-5.451700027605727, -5.288713339684267, -5.83...   
4   [-5.6239874607600004, -5.481968892944445, -5.7...   
5   [-5.717794, -5.180936, -5.9201336, -6.508095, ...   
6   [-5.404169138677499, -5.483422383457501, -6.17...   
7   [-5.313971086140253, -5.182319228102754, -4.38...   
8   [-5.6433333333333335, -5.786666666666666, -6.0...   
9   [-5.5629726314868755, -5.274607552446739, -5.6...   
10  [-5.517479462346582, -5.597797527213495, -5.44...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.539770782456108, -5.8016739941095885, -6....   
1   [[-6.25, -6.25, -7.82, -6.927245587, -6.22, -6...   
2   [[-5.537773878516168, -5.722922395426667, -6.2...   
3   [[-5.429106075033576, -5.596073813594208, -6.7...   
4   [[-5.49, -6.070804529117647, -6.26, -6.8262354...   
5   [[-5.402845, -5.97451, -7.2954636, -6.9263606,...   
6   [[-5.335944082569998, -6.182733850860001, -6.4...   
7   [[-7.1480375976584245, -5.764346225545939, -10...   
8   [[-5.613333333333333, -5.613333333333333, -6.6...   
9   [[-5.6811635852896005, -5.933635474735576, -5....   
10  [[-7.695126408619904, -6.080312631795118, -6.6...   

                                Test Predictions Mean  \
0   [-5.480996963787577, -5.740174259279463, -6.33...   
1   [-5.9878313964, -6.164, -6.187915698199999, -6...   
2   [-5.536498807018068, -5.846024492133536, -6.28...   
3   [-5.623181096296291, -5.979260365304353, -6.47...   
4   [-5.516, -5.913437180820452, -6.35789329294761...   
5   [-5.416144, -6.0192065, -6.530117, -6.6797028,...   
6   [-5.3114532831215, -6.026817914924, -6.7569244...   
7   [-6.024871027257919, -5.935492072391254, -9.44...   
8   [-5.713333333333333, -5.713333333333333, -6.58...   
9   [-5.67638554944171, -5.8658612303191635, -5.74...   
10  [-6.873120553887793, -5.7946349686296035, -6.0...   

                                 Test Predictions Std  
0   [0.17991654081101616, 0.1389107118572342, 0.27...  
1   [0.5946257546140773, 0.17199999999999988, 0.94...  
2   [0.16374334310249322, 0.18203203370318802, 0.1...  
3   [0.16020219964190013, 0.36289724128792544, 0.2...  
4   [0.2979664410634193, 0.2768390658724569, 0.185...  
5   [0.19568738, 0.26684746, 0.4905301, 0.4867136,...  
6   [0.2456982340651495, 0.2751763576727589, 0.370...  
7   [0.5955075777816224, 1.04428875768273, 0.78134...  
8   [0.1707890186425604, 0.1707890186425604, 0.275...  
9   [0.14498050761268588, 0.2546827263646525, 0.11...  
10  [1.1355964301697568, 0.9032809429862589, 1.027...

In [139]:
result_df.to_csv('results/Descriptors/Results_2D_padel_LVR_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_padel_const_LVR_MDCK.csv')

In [140]:
#2d All descriptors
df_train_padel = pd.read_csv('features/Descriptors/Train_2d_padel_curated_MDCK.csv')
df_train_rdkit = pd.read_csv('features/Descriptors/Train_2d_RDKit_des_MDCK.csv')
df_train_mordred = pd.read_csv('features/Descriptors/Train_2d_Mordred_desc_MDCK.csv')

df_2d_train = df_train_rdkit.merge(df_train_mordred, on=['ID', 'SMILES', 'Permeability'], how='inner').merge(df_train_padel, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_2d_train

ID                                             SMILES  Permeability  \
0   1114  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -4.940000   
1   1113  CC(C)C[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@@H](Cc2...     -5.820000   
2   1117  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.650000   
3   1119  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.250000   
4   2428  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.350000   
5   2446  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -6.850000   
6   2445  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -5.270000   
7   2427  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -6.340000   
8   8145  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.569578   
9   1107  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -4.610000   
10  1116  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)N(C)C(=O)[C@H]2...     -5.220000   
11  1110  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...     -4.730000   
12  8121  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.927246   
13  5836  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -5.060000   
14  6187  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -5.010000   
15  6584  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.330000   
16  6571  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.100000   
17  5803  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -6.970000   
18  2422  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.630000   
19  2440  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -7.760000   
20  8140  CCC[C@H]1C(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=...     -5.453495   
21  8131  CCC[C@@H]1NC(=O)CN(CCC)C(=O)[C@H](CC(C)C)NC(=O...     -5.509834   
22  8346  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.672617   
23  8184  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.929917   
24  6505  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.930000   
25  8342  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -4.994304   
26  8160  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.167475   
27  8341  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.822199   
28  8344  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.241518   
29  8343  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.131653   
30  8156  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.178526   
31  8150  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.834862   
32  8152  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.105008   
33  8116  CCCN1CC(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=O)N...     -5.400722   
34  8128  CCCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=...     -5.793469   
35  8138  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.303671   
36  6666  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -7.820000   
37  1115  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.190000   
38  8126  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.983385   
39  8114  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.309384   
40  1111  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C...     -6.220000   
41  1109  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N(C)C(...     -6.120000   
42  1112  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](C)NC(=O)[...     -6.170000   
43  1018  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...     -4.500000   
44  1845  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.960000   
45  1847  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.740000   
46  1841  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.410000   
47  1017  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...     -6.550000   
48  1840  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.480000   
49  1844  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -5.100000   
50  1846  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.820000   

 

In [141]:
df_2d_train.to_csv('features/Descriptors/Train_2d_all_descriptors_MDCK.csv', index=False)

In [142]:
df_test_padel = pd.read_csv('features/Descriptors/Test_2d_padel_curated_MDCK.csv')
df_test_rdkit = pd.read_csv('features/Descriptors/Test_2d_RDKit_des_MDCK.csv')
df_test_mordred = pd.read_csv('features/Descriptors/Test_2d_Mordred_desc_MDCK.csv')

df_2d_test = df_test_rdkit.merge(df_test_mordred, on=['ID', 'SMILES', 'Permeability'], how='inner').merge(df_test_padel, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_2d_test

ID                                             SMILES  Permeability  \
0   1120  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.300000   
1   1118  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](Cc2...     -5.350000   
2   1121  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...     -6.200000   
3   8133  CCC[C@@H]1NC(=O)CN(CC)C(=O)[C@H](CC(C)C)NC(=O)...     -5.965681   
4   8143  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.676306   
5   8119  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.516110   
6   6496  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.060000   
7   8168  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(C)[C@...     -5.977700   
8   8345  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(CC(C)...     -6.342777   
9   6423  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)...     -7.210000   
10  1108  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -5.180000   
11  1843  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.400000   
12  1842  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.400000   

    MaxAbsEStateIndex  MaxEStateIndex  MinAbsEStateIndex  MinEStateIndex  \
0           15.211581       15.211581           0.031713       -1.206465   
1           14.834083       14.834083           0.037197       -1.184826   
2           14.571211       14.571211           0.032067       -1.213008   
3           14.507460       14.507460           0.015782       -1.174377   
4           14.432367       14.432367           0.010248       -1.181980   
5           14.337271       14.337271           0.011275       -1.179506   
6           14.798396       14.798396           0.082911       -1.653049   
7           14.228063       14.228063           0.008269       -1.181029   
8           14.235704       14.235704           0.008614       -1.181469   
9           14.765338       14.765338           0.082043       -1.652577   
10          14.121032       14.121032           0.089106       -1.124048   
11          14.424770       14.424770           0.002738       -1.061047   
12          14.311518       14.311518           0.013797       -1.013552   

         qed        SPS     MolWt  ...       AMW      WTPT-1    WTPT-2  \
0   0.159924  25.279070  1199.634  ...  6.243799  168.348068  1.957536   
1   0.240803  26.125000  1115.472  ...  6.406411  156.622606  1.957783   
2   0.153969  27.307692  1083.386  ...  6.601542  155.443185  1.992861   
3   0.218370  27.694444  1034.376  ...  6.500783  141.646739  1.967316   
4   0.206072  27.492958  1022.365  ...  6.465978  138.417801  1.949546   
5   0.205195  26.642857  1008.338  ...  6.500703  136.601049  1.951444   
6   0.157962  27.464789  1002.309  ...  6.339573  139.131996  1.959606   
7   0.216153  26.159420   996.327  ...  6.464993  133.378413  1.933020   
8   0.216153  26.159420   996.327  ...  6.464993  133.381424  1.933064   
9   0.137104  27.528571   988.282  ...  6.371851  137.310770  1.961582   
10  0.271385  28.764706   963.276  ...  6.250992  130.791399  1.923403   
11  0.252294  25.773585   730.951  ...  6.580557  106.143859  2.002714   
12  0.252518  26.820000   696.934  ...  6.331431   99.084602  1.981692   

       WTPT-3     WTPT-4     WTPT-5    WPATH   WPOL   XLogP  Zagreb  
0   56.909620  25.395733  31.513887  37307.0  146.0  10.656   424.0  
1   56.617512  25.292701  31.324812  31648.0  138.0   7.786   396.0  
2   56.706886  25.570597  31.136289  30176.0  124.0   9.100   392.0  
3   59.761039  28.238710  28.504056  24767.0  120.0   6.761   352.0  
4   59.630333  28.216709  28.395866  23619.0  120.0   6.424   344.0  
5   59.784728  28.235280  28.531690  22971.0  116.0   5.752   338.0  
6   56.808725  28.380436  28.428289  22927.0  118.0   7.404   354.0  
7   59.341751  28.115454  28.210938  22236.0  115.0   5.397   330.0  
8   59.345483  28.116662  28.212683  22278.0  115.0   5.397   330.0  
9   56.609941  28.393162  28.216778  22212.0  114.0   7.691   348.0  
10  56.234345  25.152766  31.081579  21154.0  120.0   5

In [143]:
df_2d_test.to_csv('features/Descriptors/Test_2d_all_descriptors_MDCK.csv', index=False)

In [144]:
#2d All descriptors
df_train = pd.read_csv('features/Descriptors/Train_2d_all_descriptors_MDCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_all_descriptors_MDCK.csv')
df_test = df_test.dropna()
X_test = df_test[X_train.columns]
# X_test = X_test.select_dtypes(include=['number'])
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 3097)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 3097)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001463 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 8625
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 645
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spli

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6042                0.6524   
DecisionTreeRegressor                    1.1485                0.8288   
RandomForestRegressor                    0.6194                0.6554   
GradientBoostingRegressor                0.6149                0.6308   
AdaBoostRegressor                        0.6617                0.6437   
XGBRegressor                             0.7467                0.6846   
ExtraTreesRegressor                      0.6596                0.6478   
LinearRegression                         1.2503                0.8521   
KNeighborsRegressor                      0.6515                0.6256   
SVR                                      0.6550                0.6382   
MLPRegressor                             1.5810                0.9249   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7773               0.0660   
DecisionTreeRegressor                     1.0717              -0.7755   
RandomForestRegressor                     0.7870               0.0426   
GradientBoostingRegressor                 0.7842               0.0494   
AdaBoostRegressor                         0.8134              -0.0228   
XGBRegressor                              0.8641              -0.1542   
ExtraTreesRegressor                       0.8122              -0.0197   
LinearRegression                          1.1182              -0.9328   
KNeighborsRegressor                       0.8071              -0.0071   
SVR                                       0.8093              -0.0126   
MLPRegressor                              1.2574              -1.4440   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.3254                0.4040   
DecisionTreeRegressor                    0.0245                0.0547   
RandomForestRegressor                    0.2862                0.3142   
GradientBoostingRegressor                0.3491                0.3830   
AdaBoostRegressor                        0.2891                0.2931   
XGBRegressor                             0.2347                0.2279   
ExtraTreesRegressor                      0.3064                0.3163   
LinearRegression                         0.2074                0.2160   
KNeighborsRegressor                      0.3031                0.3179   
SVR                                      0.2352                0.2358   
MLPRegressor                             0.0761                0.1354   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.3575   0.5034    0.5979   0.3922   
DecisionTreeRegressor       0.4134   0.5915    0.6430   0.2972   
RandomForestRegressor       0.3045   0.4863    0.5518   0.4823   
GradientBoostingRegressor   0.3347   0.5123    0.5785   0.4310   
AdaBoostRegressor           0.2876   0.4536    0.5363   0.5110   
XGBRegressor                0.3926   0.5407    0.6265   0.3326   
ExtraTreesRegressor         0.3348   0.4973    0.5786   0.4309   
LinearRegression            0.9142   0.6284    0.9561  -0.5542   
KNeighborsRegressor         0.3412   0.4607    0.5841   0.4200   
SVR                         0.3100   0.4795    0.5568   0.4729   
MLPRegressor                0.7356   0.6484    0.8577  -0.2506   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6329                    0.4759  
DecisionTreeRegressor                       0.7378                    0.4649  
RandomForestRegressor                       0.7170                    0.3329  
GradientBoostingRegressor                   0.7343                    0.3604  
AdaBoostRegressor                           0.7465                    0.3879  
XGBRegressor                                0.6928                    0.4429  
ExtraTreesRegressor                         0.717

In [145]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.398834542352998, -5.795523563234602, -6.36...   
1   [-5.65, -5.65, -5.06, -6.97, -6.927245587, -6....   
2   [-5.553200507706662, -5.4985353854399985, -5.8...   
3   [-5.590257603796829, -5.380282892026746, -5.29...   
4   [-5.485615466499999, -5.350972968, -5.85047193...   
5   [-5.426199, -5.6558065, -5.412433, -6.6082435,...   
6   [-5.711576382314997, -5.680839695740002, -6.04...   
7   [-6.236416024962559, -5.52986614368669, -4.327...   
8   [-5.6433333333333335, -5.786666666666666, -6.0...   
9   [-5.574691339590781, -5.323536379155233, -5.63...   
10  [-5.7074495910036624, -5.484736123912684, -5.7...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.585463287833846, -5.4145381101328525, -5....   
1   [[-4.94, -6.25, -5.93, -6.927245587, -6.927245...   
2   [[-5.445707530563093, -5.802792691306667, -5.9...   
3   [[-5.2901638753288855, -6.232781485105157, -6....   
4   [[-5.452081935684212, -5.850471938681818, -6.1...   
5   [[-5.3269997, -6.0302267, -7.1883125, -6.92458...   
6   [[-5.3472217196425005, -5.859398327020002, -6....   
7   [[-7.23594085809661, -6.508919449657144, -10.0...   
8   [[-5.613333333333333, -5.613333333333333, -6.4...   
9   [[-5.597179296276665, -5.919215563644628, -5.8...   
10  [[-9.179084395432971, -5.606553694527116, -5.2...   

                                Test Predictions Mean  \
0   [-5.476619920922344, -5.56661498267826, -5.999...   
1   [-6.0434491174, -6.13, -6.515983416599999, -6....   
2   [-5.560778472209314, -5.788078864083781, -6.03...   
3   [-5.602745047754733, -5.999065098833316, -6.23...   
4   [-5.382674045262297, -5.785748822383507, -6.19...   
5   [-5.50333, -5.7673287, -6.5794244, -6.609311, ...   
6   [-5.291143905661835, -5.831583293602, -6.51034...   
7   [-6.258621755568813, -6.077857718614071, -9.05...   
8   [-5.713333333333333, -5.713333333333333, -6.16...   
9   [-5.607106067035657, -5.867991475465223, -5.75...   
10  [-7.92497646592588, -5.539652637889511, -4.252...   

                                 Test Predictions Std  
0   [0.1665891663924703, 0.16808800470005247, 0.29...  
1   [1.1240680806425183, 0.23999999999999985, 0.84...  
2   [0.17738181744197687, 0.14882569425607337, 0.1...  
3   [0.31044032421438894, 0.30307227743267245, 0.2...  
4   [0.1646535072236347, 0.2403622750728152, 0.181...  
5   [0.2507678, 0.3387965, 0.6849785, 0.5494461, 0...  
6   [0.23056017867042272, 0.24108760597925202, 0.2...  
7   [0.8120853763196212, 0.9792849689826595, 1.419...  
8   [0.1707890186425604, 0.1707890186425604, 0.368...  
9   [0.12090419436010286, 0.23802966296425523, 0.1...  
10  [0.7974427630636419, 0.7952693935129603, 0.504...

In [146]:
result_df.to_csv('results/Descriptors/Results_2D_All_desc_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_All_desc_MDCK.csv')

In [147]:
#2d All descriptors const rem
df_train = pd.read_csv('features/Descriptors/Train_2d_all_descriptors_MDCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
X_train, const_col =  remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_all_descriptors_MDCK.csv')
df_test = df_test.dropna()
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 2274)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 2274)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000577 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 8625
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 645
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spli

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6042                0.6524   
DecisionTreeRegressor                    0.9040                0.7264   
RandomForestRegressor                    0.6202                0.6514   
GradientBoostingRegressor                0.6447                0.6467   
AdaBoostRegressor                        0.6007                0.6351   
XGBRegressor                             0.7467                0.6846   
ExtraTreesRegressor                      0.6608                0.6546   
LinearRegression                         1.2503                0.8521   
KNeighborsRegressor                      0.6515                0.6256   
SVR                                      0.6550                0.6383   
MLPRegressor                             1.4397                0.8839   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7773               0.0660   
DecisionTreeRegressor                     0.9508              -0.3974   
RandomForestRegressor                     0.7876               0.0412   
GradientBoostingRegressor                 0.8029               0.0034   
AdaBoostRegressor                         0.7751               0.0714   
XGBRegressor                              0.8641              -0.1542   
ExtraTreesRegressor                       0.8129              -0.0215   
LinearRegression                          1.1182              -0.9328   
KNeighborsRegressor                       0.8071              -0.0071   
SVR                                       0.8093              -0.0126   
MLPRegressor                              1.1999              -1.2256   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.3254                0.4040   
DecisionTreeRegressor                    0.1806                0.2039   
RandomForestRegressor                    0.2880                0.3323   
GradientBoostingRegressor                0.3349                0.3709   
AdaBoostRegressor                        0.3471                0.3793   
XGBRegressor                             0.2347                0.2279   
ExtraTreesRegressor                      0.3091                0.3083   
LinearRegression                         0.2074                0.2160   
KNeighborsRegressor                      0.3031                0.3179   
SVR                                      0.2352                0.2358   
MLPRegressor                             0.1207                0.1499   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.3575   0.5034    0.5979   0.3922   
DecisionTreeRegressor       0.5131   0.6335    0.7163   0.1277   
RandomForestRegressor       0.3019   0.4846    0.5495   0.4867   
GradientBoostingRegressor   0.3524   0.5220    0.5936   0.4009   
AdaBoostRegressor           0.3182   0.4813    0.5641   0.4591   
XGBRegressor                0.3926   0.5407    0.6265   0.3326   
ExtraTreesRegressor         0.3504   0.5136    0.5919   0.4043   
LinearRegression            0.9142   0.6284    0.9561  -0.5542   
KNeighborsRegressor         0.3412   0.4607    0.5841   0.4200   
SVR                         0.3100   0.4795    0.5568   0.4729   
MLPRegressor                0.6860   0.6382    0.8283  -0.1663   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6329                    0.4759  
DecisionTreeRegressor                       0.6648                    0.3494  
RandomForestRegressor                       0.7218                    0.3439  
GradientBoostingRegressor                   0.7207                    0.3164  
AdaBoostRegressor                           0.7173                    0.3439  
XGBRegressor                                0.6928                    0.4429  
ExtraTreesRegressor                         0.708

In [148]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.398834542352998, -5.795523563234602, -6.36...   
1   [-5.65, -5.33, -5.06, -6.929917083, -6.5695784...   
2   [-5.52422900831333, -5.497882969735, -5.831207...   
3   [-5.524701153267153, -5.368936213247834, -5.30...   
4   [-5.437988247636364, -5.517905422333333, -5.92...   
5   [-5.426199, -5.6558065, -5.412433, -6.6082435,...   
6   [-5.593799999999999, -5.59201741677, -6.036024...   
7   [-6.236416024962551, -5.529866143686691, -4.32...   
8   [-5.6433333333333335, -5.786666666666666, -6.0...   
9   [-5.574682147532249, -5.3235259430087085, -5.6...   
10  [-6.294034781655587, -6.04121396632022, -4.726...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.585463287833846, -5.4145381101328525, -5....   
1   [[-4.94, -6.25, -6.85, -6.927245587, -6.569578...   
2   [[-5.361069749624762, -5.751979597910001, -6.0...   
3   [[-5.279559945661648, -6.221010606906194, -6.2...   
4   [[-5.33, -5.936171729555557, -5.75609981414285...   
5   [[-5.3269997, -6.0302267, -7.1883125, -6.92458...   
6   [[-5.437719138677502, -6.0010197360075, -6.682...   
7   [[-7.235940858096592, -6.508919449657154, -10....   
8   [[-5.613333333333333, -5.613333333333333, -6.4...   
9   [[-5.597206175103655, -5.919260725273355, -5.8...   
10  [[-8.06383554538322, -6.0335869359957846, -4.0...   

                                Test Predictions Mean  \
0   [-5.476619920922344, -5.56661498267826, -5.999...   
1   [-5.720000000000001, -6.13, -6.8499667324, -6....   
2   [-5.5782871018265485, -5.767366189096625, -6.0...   
3   [-5.583699685034971, -5.972095366631095, -6.22...   
4   [-5.410123695047283, -5.853026274263493, -6.00...   
5   [-5.50333, -5.7673287, -6.5794244, -6.609311, ...   
6   [-5.295184672046334, -5.884049819499002, -6.54...   
7   [-6.258621755568816, -6.077857718614073, -9.05...   
8   [-5.713333333333333, -5.713333333333333, -6.16...   
9   [-5.607146731713048, -5.868059981146523, -5.75...   
10  [-6.841260359619612, -5.855262890260979, -4.00...   

                                 Test Predictions Std  
0   [0.1665891663924703, 0.16808800470005247, 0.29...  
1   [1.080499884312812, 0.23999999999999985, 0.898...  
2   [0.20441446472621344, 0.12260881001284571, 0.1...  
3   [0.3009049799065836, 0.3533322487085882, 0.231...  
4   [0.22498218253691746, 0.2576885874418354, 0.23...  
5   [0.2507678, 0.3387965, 0.6849785, 0.5494461, 0...  
6   [0.19220333505250942, 0.2600573195935361, 0.21...  
7   [0.8120853763196096, 0.9792849689826618, 1.419...  
8   [0.1707890186425604, 0.1707890186425604, 0.368...  
9   [0.12090097647892548, 0.2380574289997938, 0.11...  
10  [1.0477251961372707, 0.799544188185254, 0.0132...

In [149]:
result_df.to_csv('results/Descriptors/Results_2D_All_desc_const_rem_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_All_desc_const_rem_MDCK.csv')

In [150]:
#2d All descriptors LVR
df_train = pd.read_csv('features/Descriptors/Train_2d_all_descriptors_MDCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
X_train, const_col = remove_low_variance_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_all_descriptors_MDCK.csv')
df_test = df_test.dropna()
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 1534)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 1534)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000368 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 5567
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 419
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spli

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6202                0.6549   
DecisionTreeRegressor                    1.1278                0.8467   
RandomForestRegressor                    0.6388                0.6706   
GradientBoostingRegressor                0.7691                0.7112   
AdaBoostRegressor                        0.6392                0.6399   
XGBRegressor                             0.7669                0.6984   
ExtraTreesRegressor                      0.6573                0.6615   
LinearRegression                         1.5107                0.9304   
KNeighborsRegressor                      0.6246                0.6240   
SVR                                      0.6481                0.6385   
MLPRegressor                             1.2917                0.8726   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7875               0.0413   
DecisionTreeRegressor                     1.0620              -0.7435   
RandomForestRegressor                     0.7992               0.0126   
GradientBoostingRegressor                 0.8770              -0.1889   
AdaBoostRegressor                         0.7995               0.0119   
XGBRegressor                              0.8757              -0.1855   
ExtraTreesRegressor                       0.8108              -0.0161   
LinearRegression                          1.2291              -1.3353   
KNeighborsRegressor                       0.7903               0.0344   
SVR                                       0.8050              -0.0019   
MLPRegressor                              1.1365              -0.9968   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2980                0.4191   
DecisionTreeRegressor                    0.0881                0.0771   
RandomForestRegressor                    0.2598                0.2851   
GradientBoostingRegressor                0.1861                0.2655   
AdaBoostRegressor                        0.3055                0.3204   
XGBRegressor                             0.2632                0.3223   
ExtraTreesRegressor                      0.2911                0.2850   
LinearRegression                         0.1402                0.1425   
KNeighborsRegressor                      0.3493                0.3468   
SVR                                      0.2497                0.2574   
MLPRegressor                             0.1167                0.1530   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.3628   0.5291    0.6024   0.3832   
DecisionTreeRegressor       0.4273   0.6015    0.6537   0.2736   
RandomForestRegressor       0.3109   0.5044    0.5576   0.4715   
GradientBoostingRegressor   0.3247   0.5108    0.5699   0.4479   
AdaBoostRegressor           0.2864   0.4559    0.5351   0.5132   
XGBRegressor                0.5071   0.6044    0.7121   0.1380   
ExtraTreesRegressor         0.3514   0.5109    0.5928   0.4027   
LinearRegression            0.9913   0.6984    0.9956  -0.6853   
KNeighborsRegressor         0.3360   0.4529    0.5796   0.4288   
SVR                         0.3080   0.4708    0.5550   0.4764   
MLPRegressor                0.2433   0.4114    0.4933   0.5864   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6366                    0.4374  
DecisionTreeRegressor                       0.7205                    0.4099  
RandomForestRegressor                       0.7269                    0.3769  
GradientBoostingRegressor                   0.7452                    0.3824  
AdaBoostRegressor                           0.7482                    0.3549  
XGBRegressor                                0.6302                    0.4154  
ExtraTreesRegressor                         0.714

In [151]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.472616748078145, -5.709233727000539, -5.93...   
1   [-5.65, -5.33, -4.94, -6.929917083, -5.4007221...   
2   [-5.518439023949997, -5.592659368202501, -5.95...   
3   [-5.4230059651136235, -5.419638455641846, -5.1...   
4   [-5.536528333235293, -5.397920423312501, -5.93...   
5   [-5.545838, -5.4548984, -5.105486, -6.7403717,...   
6   [-5.547721626699999, -5.708027148260004, -6.29...   
7   [-5.555143134125656, -5.257041750450064, -4.51...   
8   [-5.6433333333333335, -5.786666666666666, -6.0...   
9   [-5.558808402299759, -5.284232892418047, -5.63...   
10  [-5.893071149807869, -5.769461024552119, -4.72...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.517975188264973, -5.695571364617792, -6.3...   
1   [[-4.94, -6.25, -5.93, -6.927245587, -6.927245...   
2   [[-5.545579830323331, -5.8574180560233335, -6....   
3   [[-5.281923325393852, -6.2331740472817385, -6....   
4   [[-5.22, -5.711712335857143, -6.21200000000000...   
5   [[-5.3349123, -6.447411, -7.447191, -6.9274735...   
6   [[-5.3742241829375015, -5.9507209872675, -6.50...   
7   [[-7.350648060853656, -6.6020549318248625, -10...   
8   [[-5.613333333333333, -5.613333333333333, -6.4...   
9   [[-5.631340628677342, -5.941054707923339, -5.8...   
10  [[-6.72819275052079, -5.922754874570927, -6.77...   

                                Test Predictions Mean  \
0   [-5.511361046759125, -5.7354806977985024, -6.3...   
1   [-5.927915698199999, -6.394, -6.43388243060000...   
2   [-5.591887287326967, -5.8672337871178675, -6.3...   
3   [-5.673037845530611, -6.14261411905416, -6.503...   
4   [-5.434631060228022, -5.801481927526995, -6.35...   
5   [-5.415261, -5.878441, -6.8081627, -6.549703, ...   
6   [-5.320330680593001, -5.953831516577667, -6.72...   
7   [-6.938244370143295, -6.038778975207282, -9.12...   
8   [-5.713333333333333, -5.6546666666666665, -6.2...   
9   [-5.622393674289135, -5.862704498277151, -5.78...   
10  [-5.944080806708486, -5.607879355993072, -7.01...   

                                 Test Predictions Std  
0   [0.17524771543909062, 0.18003445083722755, 0.1...  
1   [1.0828239861196156, 0.28799999999999987, 0.78...  
2   [0.16839517998077558, 0.16324390444848222, 0.1...  
3   [0.25168091248566377, 0.2516192704814364, 0.28...  
4   [0.24830455517216377, 0.16656163215923694, 0.1...  
5   [0.2844535, 0.3828769, 0.61360866, 0.52515084,...  
6   [0.22860814751030448, 0.24184585377215528, 0.3...  
7   [1.641474628054934, 1.3157624250802908, 1.6327...  
8   [0.1707890186425604, 0.14230796026770795, 0.30...  
9   [0.09667155426660792, 0.25314773372649585, 0.1...  
10  [1.2061820747479184, 0.8113301172112249, 0.875...

In [152]:
result_df.to_csv('results/Descriptors/Results_2D_All_desc_LVR_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_All_desc_LVR_MDCK.csv')

In [153]:
#2d All descriptors LVR
df_train = pd.read_csv('features/Descriptors/Train_2d_all_descriptors_MDCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
X_train, const_col = remove_low_variance_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_all_descriptors_MDCK.csv')
df_test = df_test.dropna()
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 1534)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 1534)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000355 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 5567
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 419
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spli

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6202                0.6549   
DecisionTreeRegressor                    1.1278                0.8467   
RandomForestRegressor                    0.6388                0.6706   
GradientBoostingRegressor                0.7691                0.7112   
AdaBoostRegressor                        0.6392                0.6399   
XGBRegressor                             0.7669                0.6984   
ExtraTreesRegressor                      0.6573                0.6615   
LinearRegression                         1.5107                0.9304   
KNeighborsRegressor                      0.6246                0.6240   
SVR                                      0.6481                0.6385   
MLPRegressor                             1.2917                0.8726   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7875               0.0413   
DecisionTreeRegressor                     1.0620              -0.7435   
RandomForestRegressor                     0.7992               0.0126   
GradientBoostingRegressor                 0.8770              -0.1889   
AdaBoostRegressor                         0.7995               0.0119   
XGBRegressor                              0.8757              -0.1855   
ExtraTreesRegressor                       0.8108              -0.0161   
LinearRegression                          1.2291              -1.3353   
KNeighborsRegressor                       0.7903               0.0344   
SVR                                       0.8050              -0.0019   
MLPRegressor                              1.1365              -0.9968   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2980                0.4191   
DecisionTreeRegressor                    0.0881                0.0771   
RandomForestRegressor                    0.2598                0.2851   
GradientBoostingRegressor                0.1861                0.2655   
AdaBoostRegressor                        0.3055                0.3204   
XGBRegressor                             0.2632                0.3223   
ExtraTreesRegressor                      0.2911                0.2850   
LinearRegression                         0.1402                0.1425   
KNeighborsRegressor                      0.3493                0.3468   
SVR                                      0.2497                0.2574   
MLPRegressor                             0.1167                0.1530   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.3628   0.5291    0.6024   0.3832   
DecisionTreeRegressor       0.4273   0.6015    0.6537   0.2736   
RandomForestRegressor       0.3109   0.5044    0.5576   0.4715   
GradientBoostingRegressor   0.3247   0.5108    0.5699   0.4479   
AdaBoostRegressor           0.2864   0.4559    0.5351   0.5132   
XGBRegressor                0.5071   0.6044    0.7121   0.1380   
ExtraTreesRegressor         0.3514   0.5109    0.5928   0.4027   
LinearRegression            0.9913   0.6984    0.9956  -0.6853   
KNeighborsRegressor         0.3360   0.4529    0.5796   0.4288   
SVR                         0.3080   0.4708    0.5550   0.4764   
MLPRegressor                0.2433   0.4114    0.4933   0.5864   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6366                    0.4374  
DecisionTreeRegressor                       0.7205                    0.4099  
RandomForestRegressor                       0.7269                    0.3769  
GradientBoostingRegressor                   0.7452                    0.3824  
AdaBoostRegressor                           0.7482                    0.3549  
XGBRegressor                                0.6302                    0.4154  
ExtraTreesRegressor                         0.714

In [154]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.472616748078145, -5.709233727000539, -5.93...   
1   [-5.65, -5.33, -4.94, -6.929917083, -5.4007221...   
2   [-5.518439023949997, -5.592659368202502, -5.95...   
3   [-5.4230059651136235, -5.419638455641846, -5.1...   
4   [-5.536528333235293, -5.397920423312501, -5.93...   
5   [-5.545838, -5.4548984, -5.105486, -6.7403717,...   
6   [-5.547721626699999, -5.708027148260003, -6.29...   
7   [-5.555143134125656, -5.257041750450064, -4.51...   
8   [-5.6433333333333335, -5.786666666666666, -6.0...   
9   [-5.558808402299759, -5.284232892418047, -5.63...   
10  [-5.893071149807869, -5.769461024552119, -4.72...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.517975188264973, -5.695571364617792, -6.3...   
1   [[-4.94, -6.25, -5.93, -6.927245587, -6.927245...   
2   [[-5.54557983032333, -5.8574180560233335, -6.3...   
3   [[-5.281923325393852, -6.2331740472817385, -6....   
4   [[-5.22, -5.711712335857143, -6.21200000000000...   
5   [[-5.3349123, -6.447411, -7.447191, -6.9274735...   
6   [[-5.374224182937501, -5.950720987267499, -6.5...   
7   [[-7.350648060853656, -6.6020549318248625, -10...   
8   [[-5.613333333333333, -5.613333333333333, -6.4...   
9   [[-5.631340628677342, -5.941054707923339, -5.8...   
10  [[-6.72819275052079, -5.922754874570927, -6.77...   

                                Test Predictions Mean  \
0   [-5.511361046759125, -5.7354806977985024, -6.3...   
1   [-5.927915698199999, -6.394, -6.43388243060000...   
2   [-5.591887287326967, -5.8672337871178675, -6.3...   
3   [-5.673037845530611, -6.14261411905416, -6.503...   
4   [-5.434631060228022, -5.801481927526995, -6.35...   
5   [-5.415261, -5.878441, -6.8081627, -6.549703, ...   
6   [-5.320330680593001, -5.953831516577667, -6.72...   
7   [-6.938244370143295, -6.038778975207282, -9.12...   
8   [-5.713333333333333, -5.6546666666666665, -6.2...   
9   [-5.622393674289135, -5.862704498277151, -5.78...   
10  [-5.944080806708486, -5.607879355993072, -7.01...   

                                 Test Predictions Std  
0   [0.17524771543909062, 0.18003445083722755, 0.1...  
1   [1.0828239861196156, 0.28799999999999987, 0.78...  
2   [0.16839517998077583, 0.16324390444848222, 0.1...  
3   [0.25168091248566377, 0.2516192704814364, 0.28...  
4   [0.24830455517216377, 0.16656163215923694, 0.1...  
5   [0.2844535, 0.3828769, 0.61360866, 0.52515084,...  
6   [0.22860814751030467, 0.24184585377215578, 0.3...  
7   [1.641474628054934, 1.3157624250802908, 1.6327...  
8   [0.1707890186425604, 0.14230796026770795, 0.30...  
9   [0.09667155426660792, 0.25314773372649585, 0.1...  
10  [1.2061820747479184, 0.8113301172112249, 0.875...

In [155]:
def features(df, target_column='Permeability', threshold=0.9):
    correlation_matrix = df.corr()
    
    features_to_drop = set()
    
    for feature in correlation_matrix.columns:
        if feature == target_column:
            continue 
        target_corr = correlation_matrix[target_column][feature]
        
        for other_feature in correlation_matrix.columns:
            if other_feature == feature or other_feature == target_column:
                continue
            
            if abs(correlation_matrix[feature][other_feature]) > threshold:
                other_target_corr = correlation_matrix[target_column][other_feature]

                if abs(other_target_corr) < abs(target_corr):
                    features_to_drop.add(other_feature)
                else:
                    features_to_drop.add(feature)
    selected_features = [col for col in df.columns if col not in features_to_drop and col != target_column]
    
    return selected_features

In [156]:
def remove_low_variance_columns(df, threshold=0.005):
    # df = df.drop(['ID','SMILES','Permeability'],axis=1)
    variances = df.var()
    
    low_variance_columns = variances[variances < threshold].index.tolist()
    
    df_cleaned = df.drop(columns=low_variance_columns)
    
    return df_cleaned, low_variance_columns

In [157]:
df_train = pd.read_csv('features/Descriptors/Train_2d_all_descriptors_MDCK.csv')
df_train =df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
X_train = df_train[selected_features] 
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_all_descriptors_MDCK.csv')
df_test =df_test.dropna()
X_test =  df_test[X_train.columns]
y_test =  df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 114)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 114)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000049 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 532
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 39
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits w

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.6330695006446432


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6226                0.6560   
DecisionTreeRegressor                    1.0671                0.7701   
RandomForestRegressor                    0.6419                0.6625   
GradientBoostingRegressor                0.7878                0.6944   
AdaBoostRegressor                        0.5798                0.6209   
XGBRegressor                             0.7579                0.6859   
ExtraTreesRegressor                      0.5740                0.6175   
LinearRegression                         1.6082                0.9624   
KNeighborsRegressor                      0.7606                0.6888   
SVR                                      0.6860                0.6628   
MLPRegressor                             1.7362                1.0173   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.7891               0.0375   
DecisionTreeRegressor                     1.0330              -0.6496   
RandomForestRegressor                     0.8012               0.0078   
GradientBoostingRegressor                 0.8876              -0.2179   
AdaBoostRegressor                         0.7614               0.1037   
XGBRegressor                              0.8706              -0.1716   
ExtraTreesRegressor                       0.7576               0.1127   
LinearRegression                          1.2681              -1.4860   
KNeighborsRegressor                       0.8721              -0.1758   
SVR                                       0.8282              -0.0604   
MLPRegressor                              1.3177              -1.6840   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2877                0.3383   
DecisionTreeRegressor                    0.2083                0.3295   
RandomForestRegressor                    0.2704                0.3006   
GradientBoostingRegressor                0.2043                0.2876   
AdaBoostRegressor                        0.3944                0.4145   
XGBRegressor                             0.2641                0.3381   
ExtraTreesRegressor                      0.3987                0.4086   
LinearRegression                         0.2070                0.1695   
KNeighborsRegressor                      0.1972                0.1884   
SVR                                      0.1776                0.1663   
MLPRegressor                            -0.0693               -0.0432   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.3476   0.4919    0.5896   0.4090   
DecisionTreeRegressor       0.3752   0.5203    0.6125   0.3622   
RandomForestRegressor       0.3152   0.4952    0.5614   0.4641   
GradientBoostingRegressor   0.3594   0.5258    0.5995   0.3890   
AdaBoostRegressor           0.2934   0.4753    0.5416   0.5013   
XGBRegressor                0.3923   0.5323    0.6264   0.3330   
ExtraTreesRegressor         0.3549   0.5168    0.5957   0.3966   
LinearRegression            1.2126   0.8841    1.1012  -1.0615   
KNeighborsRegressor         0.3584   0.4947    0.5987   0.3907   
SVR                         0.3053   0.4944    0.5525   0.4810   
MLPRegressor                0.9606   0.6022    0.9801  -0.6331   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6578                    0.5254  
DecisionTreeRegressor                       0.7445                    0.5640  
RandomForestRegressor                       0.7171                    0.3879  
GradientBoostingRegressor                   0.7213                    0.3549  
AdaBoostRegressor                           0.7583                    0.4429  
XGBRegressor                                0.7022                    0.4594  
ExtraTreesRegressor                         0.724

In [158]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.548005856854436, -6.210156543053598, -6.16...   
1   [-4.82, -5.06, -5.1, -6.929917083, -6.85, -6.0...   
2   [-5.474668559329998, -5.5425625373599985, -5.8...   
3   [-5.26325773426252, -5.198277552465221, -5.182...   
4   [-5.3116666666666665, -5.386910050214285, -5.8...   
5   [-5.3968806, -5.194106, -5.0974054, -6.10519, ...   
6   [-5.518493841589998, -5.577915665767501, -6.21...   
7   [-7.290057937284836, -6.011174879434157, -4.32...   
8   [-5.613333333333333, -5.786666666666666, -6.07...   
9   [-5.611257330776977, -5.304271046195673, -5.61...   
10  [-5.053385001682634, -6.2072611812155225, -4.6...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.548005856854436, -5.548005856854436, -6.3...   
1   [[-5.65, -6.25, -7.82, -6.927245587, -5.309384...   
2   [[-5.475277280235, -5.896353860989166, -6.5693...   
3   [[-5.18274530842576, -6.204779084159647, -7.02...   
4   [[-5.08, -5.813744955375, -6.5886227935, -6.63...   
5   [[-5.3973656, -6.2309556, -6.8224926, -6.92582...   
6   [[-5.456367045267502, -6.10451744097, -6.94380...   
7   [[-10.0, -7.379348057600826, -9.52464787639450...   
8   [[-5.613333333333333, -5.613333333333334, -6.3...   
9   [[-5.709943898132217, -6.117595258793534, -5.8...   
10  [[-9.093106189510044, -6.4861496564587044, -7....   

                                Test Predictions Mean  \
0   [-5.47724816891189, -5.598236636673891, -6.325...   
1   [-5.886, -6.133915698200001, -7.054, -6.734347...   
2   [-5.5991971558295335, -5.902812703299766, -6.4...   
3   [-5.57058261422696, -6.047013222165445, -6.564...   
4   [-5.488918470088571, -5.844599551275, -6.48321...   
5   [-5.695837, -6.0262384, -6.5893965, -6.633462,...   
6   [-5.4288558467231685, -6.014619735399, -6.9067...   
7   [-8.075043486507795, -6.18436158787148, -8.466...   
8   [-5.6259999999999994, -5.6546666666666665, -6....   
9   [-5.658092948811175, -5.938993710063983, -5.82...   
10  [-9.433610061004924, -6.102357346924283, -6.22...   

                                 Test Predictions Std  
0   [0.15491957815470736, 0.17661213959791738, 0.1...  
1   [0.2972944668169927, 0.41103590750392355, 0.70...  
2   [0.13982359958920706, 0.1548257564262451, 0.18...  
3   [0.23180838479343693, 0.24323163023899508, 0.2...  
4   [0.22019870008053288, 0.29192962898354, 0.1924...  
5   [0.28172338, 0.22305664, 0.19155224, 0.3943546...  
6   [0.17119738183910374, 0.20203919661707137, 0.3...  
7   [2.474338730537475, 1.2613237426136972, 1.3218...  
8   [0.16096100286853474, 0.14230796026770784, 0.3...  
9   [0.09822627486864736, 0.28780911384719526, 0.1...  
10  [0.4024053513696268, 1.0547045407064528, 0.821...

In [159]:
result_df.to_csv('results/Descriptors/Results_2D_All_desc_LVR_remove_corr_features_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_All_desc_LVRremove_corr_features_MDCK.csv')

In [160]:
#3d RDKit descriptors
df_train = pd.read_csv('features/Descriptors/Train_3d_RDKit_desc_MDCK.csv')
df_train = df_train.fillna(0)
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_3d_RDKit_desc_MDCK.csv')
df_test = df_test.fillna(0)
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 11)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 11)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000015 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 45
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 3
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with 

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-3.808580013206493


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.7768                0.7398   
DecisionTreeRegressor                    1.4229                0.9007   
RandomForestRegressor                    0.8687                0.7345   
GradientBoostingRegressor                1.2556                0.8804   
AdaBoostRegressor                        1.0699                0.7775   
XGBRegressor                             1.0532                0.7750   
ExtraTreesRegressor                      1.0092                0.7886   
LinearRegression                         0.9755                0.7751   
KNeighborsRegressor                      0.8682                0.7430   
SVR                                      0.7620                0.7033   
MLPRegressor                             3.1026                1.4394   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8814              -0.2008   
DecisionTreeRegressor                     1.1929              -1.1996   
RandomForestRegressor                     0.9321              -0.3429   
GradientBoostingRegressor                 1.1206              -0.9410   
AdaBoostRegressor                         1.0343              -0.6539   
XGBRegressor                              1.0263              -0.6282   
ExtraTreesRegressor                       1.0046              -0.5600   
LinearRegression                          0.9877              -0.5080   
KNeighborsRegressor                       0.9318              -0.3422   
SVR                                       0.8729              -0.1780   
MLPRegressor                              1.7614              -3.7961   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.2926               -0.2533   
DecisionTreeRegressor                    0.0124                0.0834   
RandomForestRegressor                    0.0423                0.1092   
GradientBoostingRegressor               -0.0511                0.0227   
AdaBoostRegressor                       -0.0427                0.1254   
XGBRegressor                             0.1043                0.1739   
ExtraTreesRegressor                      0.0395                0.0895   
LinearRegression                         0.0837                0.1180   
KNeighborsRegressor                      0.0884                0.0551   
SVR                                      0.0294               -0.0060   
MLPRegressor                            -0.0929               -0.1315   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.5624   0.6009    0.7500   0.0439   
DecisionTreeRegressor       0.4126   0.5665    0.6423   0.2986   
RandomForestRegressor       0.4107   0.5506    0.6408   0.3018   
GradientBoostingRegressor   0.5155   0.6224    0.7180   0.1237   
AdaBoostRegressor           0.4363   0.5618    0.6605   0.2583   
XGBRegressor                0.5620   0.6448    0.7497   0.0445   
ExtraTreesRegressor         0.4789   0.5916    0.6920   0.1858   
LinearRegression            0.6175   0.6102    0.7858  -0.0498   
KNeighborsRegressor         0.5154   0.6615    0.7179   0.1239   
SVR                         0.5201   0.5702    0.7212   0.1158   
MLPRegressor                2.8285   1.5391    1.6818  -3.8086   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.2111                    0.1376  
DecisionTreeRegressor                       0.5843                    0.2834  
RandomForestRegressor                       0.5707                    0.2091  
GradientBoostingRegressor                   0.4177                    0.1953  
AdaBoostRegressor                           0.5174                    0.3356  
XGBRegressor                                0.3773                    0.2036  
ExtraTreesRegressor                         0.442

In [161]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.863188972880598, -5.643007454782493, -5.65...   
1   [-5.63, -7.76, -6.17, -5.400722167, -6.34, -5....   
2   [-6.328722619590001, -6.803705458280001, -6.24...   
3   [-6.515545552123927, -7.650387024580412, -5.95...   
4   [-6.4110811367857155, -7.119859497, -6.1092160...   
5   [-6.0587716, -7.5935125, -5.782604, -5.475473,...   
6   [-6.246423757920001, -7.458844406520001, -6.19...   
7   [-6.556498279021809, -5.810144106796543, -7.15...   
8   [-6.506639027666666, -6.88, -5.946666666666666...   
9   [-6.068087540599281, -5.564761655767922, -5.94...   
10  [-7.455405381073196, -5.344056213870736, -4.77...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.847361139563147, -5.785170772975546, -5.8...   
1   [[-5.27, -4.94, -5.65, -6.927245587, -5.241517...   
2   [[-5.48231550354, -5.5531224875800005, -5.5927...   
3   [[-5.018757061986256, -5.468940987618433, -5.3...   
4   [[-5.327142857142858, -5.27, -5.385, -6.057878...   
5   [[-5.0637484, -5.1283937, -5.0460887, -6.00240...   
6   [[-5.273305700989998, -5.528882982480004, -5.5...   
7   [[-4.727734082963899, -5.68348841770661, -5.34...   
8   [[-4.94, -6.053333333333334, -5.61162072033333...   
9   [[-4.900907311403258, -5.264364958185834, -5.5...   
10  [[-7.4531492704649205, -6.52242187021951, -6.7...   

                                Test Predictions Mean  \
0   [-5.776704030015402, -5.749025230670178, -5.82...   
1   [-5.6379156982, -5.016, -5.564439713600001, -6...   
2   [-5.483814276568001, -5.5639481918980005, -5.6...   
3   [-5.335943392997036, -5.309824821708785, -5.23...   
4   [-5.421559090006349, -5.368887752662337, -5.42...   
5   [-5.2878046, -5.1547637, -5.2806525, -5.858015...   
6   [-5.39958773046, -5.424152884638003, -5.528689...   
7   [-4.8844879813655195, -5.610047807652637, -5.2...   
8   [-5.184741895666667, -5.885667206533334, -5.74...   
9   [-5.141869119868303, -5.2525698349584395, -5.5...   
10  [-7.806780922160916, -6.268248369303502, -7.11...   

                                 Test Predictions Std  
0   [0.1449470612082072, 0.1674137694644182, 0.146...  
1   [0.4835895882584466, 0.3417952603533291, 0.186...  
2   [0.17004579637783956, 0.08211744149626579, 0.1...  
3   [0.18983678445029248, 0.13462463825258017, 0.2...  
4   [0.200178571288708, 0.11629174163522532, 0.061...  
5   [0.15266897, 0.08986489, 0.19159171, 0.4680740...  
6   [0.27671276593242744, 0.11752844789243957, 0.1...  
7   [0.14381755797988482, 0.07437368912426277, 0.1...  
8   [0.48048421357202264, 0.27008056168897543, 0.2...  
9   [0.2180039633979658, 0.15869014465183331, 0.10...  
10  [0.514167178938247, 0.24702699629296107, 0.515...

In [162]:
result_df.to_csv('results/Descriptors/Results_3D_RDKit_desc_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_3D_RDKit_desc_MDCK.csv')

In [163]:
#3d Padel descriptors
df_train = pd.read_csv('features/Descriptors/Train_3d_padel_curated_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_3d_padel_curated_MDCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 431)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 431)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000238 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1513
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 101
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.7876                0.7662   
DecisionTreeRegressor                    0.6503                0.6583   
RandomForestRegressor                    0.4672                0.5377   
GradientBoostingRegressor                0.4946                0.5495   
AdaBoostRegressor                        0.5108                0.5401   
XGBRegressor                             0.5250                0.5823   
ExtraTreesRegressor                      0.4915                0.5646   
LinearRegression                         0.9531                0.7966   
KNeighborsRegressor                      0.5038                0.5542   
SVR                                      0.5677                0.5932   
MLPRegressor                             2.1748                1.2334   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8875              -0.2175   
DecisionTreeRegressor                     0.8064              -0.0052   
RandomForestRegressor                     0.6835               0.2777   
GradientBoostingRegressor                 0.7033               0.2355   
AdaBoostRegressor                         0.7147               0.2104   
XGBRegressor                              0.7246               0.1884   
ExtraTreesRegressor                       0.7011               0.2401   
LinearRegression                          0.9763              -0.4733   
KNeighborsRegressor                       0.7098               0.2212   
SVR                                       0.7535               0.1224   
MLPRegressor                              1.4747              -2.3619   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.0235                0.0038   
DecisionTreeRegressor                    0.3902                0.3713   
RandomForestRegressor                    0.5413                0.5753   
GradientBoostingRegressor                0.5029                0.5501   
AdaBoostRegressor                        0.4737                0.5261   
XGBRegressor                             0.4610                0.4454   
ExtraTreesRegressor                      0.4929                0.5137   
LinearRegression                         0.2097                0.1330   
KNeighborsRegressor                      0.4781                0.5236   
SVR                                      0.3938                0.4004   
MLPRegressor                             0.1230                0.0937   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4822   0.5304    0.6944   0.1802   
DecisionTreeRegressor       0.6434   0.6643    0.8021  -0.0937   
RandomForestRegressor       0.3142   0.4644    0.5606   0.4658   
GradientBoostingRegressor   0.3540   0.4940    0.5950   0.3982   
AdaBoostRegressor           0.3492   0.4692    0.5909   0.4063   
XGBRegressor                0.2593   0.4195    0.5092   0.5592   
ExtraTreesRegressor         0.3393   0.4629    0.5825   0.4232   
LinearRegression            1.0875   0.8369    1.0428  -0.8488   
KNeighborsRegressor         0.4736   0.5421    0.6882   0.1949   
SVR                         0.4185   0.4899    0.6469   0.2886   
MLPRegressor                1.8700   1.0882    1.3675  -2.1790   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4249                    0.4512  
DecisionTreeRegressor                       0.3992                    0.2448  
RandomForestRegressor                       0.7078                    0.5640  
GradientBoostingRegressor                   0.6402                    0.4649  
AdaBoostRegressor                           0.6402                    0.5695  
XGBRegressor                                0.7639                    0.5970  
ExtraTreesRegressor                         0.660

In [164]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.837871221180832, -5.690961856159556, -5.89...   
1   [-6.85, -5.06, -5.06, -5.303671307, -5.3093841...   
2   [-5.962157405740004, -5.27284915855, -5.472032...   
3   [-5.782370640549474, -5.167743135560243, -5.27...   
4   [-5.9277957545, -5.20466782675, -5.10285714285...   
5   [-5.8093762, -5.0663447, -5.059916, -6.033059,...   
6   [-5.891297472910002, -5.401496112600003, -5.62...   
7   [-6.432379302740648, -6.227333422319202, -6.06...   
8   [-5.583333333333333, -5.408287387000001, -5.53...   
9   [-5.859151862543014, -5.596564111703541, -5.63...   
10  [-5.056105579455914, -4.49191777988845, -4.0, ...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.733919084033116, -5.317926401298028, -6.0...   
1   [[-5.35, -5.309384159, -6.85, -6.927245587, -5...   
2   [[-5.918477825460001, -5.6472372448399994, -6....   
3   [[-6.114134432615404, -5.414834497717565, -6.7...   
4   [[-5.93, -5.396838867153846, -6.85526058257143...   
5   [[-5.6907873, -5.6185784, -6.4229207, -6.24030...   
6   [[-5.796532035220002, -5.3343842321400015, -6....   
7   [[-5.110355040985546, -4.221564784213455, -7.4...   
8   [[-5.613333333333333, -5.206666666666666, -6.2...   
9   [[-5.379117839060564, -5.244812879335735, -6.2...   
10  [[-8.377850999719874, -4.458126109411302, -4.0...   

                                Test Predictions Mean  \
0   [-5.556334911315856, -5.569052437553351, -6.03...   
1   [-6.212000000000001, -5.8658768318000005, -7.0...   
2   [-5.851593753556001, -5.495281857982, -6.45764...   
3   [-6.022150271641392, -5.406778866567728, -6.57...   
4   [-5.7786284442380955, -5.344544115136324, -6.6...   
5   [-5.885779, -5.4504633, -6.4145927, -6.2552977...   
6   [-5.738967335980001, -5.359579155846001, -6.47...   
7   [-4.520505732874167, -4.489529245230671, -7.62...   
8   [-5.560666666666666, -5.145999999999999, -6.40...   
9   [-5.43705106426585, -5.198781728036482, -6.148...   
10  [-7.9062113575918405, -5.425491565877726, -4.2...   

                                 Test Predictions Std  
0   [0.2865443556631922, 0.31667564973194223, 0.23...  
1   [0.852933760616849, 1.083107115533834, 0.68419...  
2   [0.11461876615617257, 0.08146468132159776, 0.2...  
3   [0.21426536852519834, 0.09893074276342258, 0.2...  
4   [0.2244159001007405, 0.19362101911671056, 0.30...  
5   [0.36640412, 0.24192826, 0.34065518, 0.3414788...  
6   [0.21955466895030068, 0.053082903054313076, 0....  
7   [0.394551122922211, 0.32921359222547875, 0.311...  
8   [0.14478182820291288, 0.059568821076503096, 0....  
9   [0.09464240579825538, 0.08868458675167412, 0.1...  
10  [0.8051381909689198, 0.6754187408884159, 0.282...

In [165]:
result_df.to_csv('results/Descriptors/Results_3D_padel_desc_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_3D_padel_desc_MDCK.csv')

In [166]:
df_train_rdkit = pd.read_csv('features/Descriptors/Train_3d_RDKit_desc_MDCK.csv')
df_train_rdkit = df_train_rdkit.fillna(0)
df_train_padel = pd.read_csv('features/Descriptors/Train_3d_padel_curated_MDCK.csv')

df_3d_descriptors = df_train_rdkit.merge(df_train_padel, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_3d_descriptors

ID                                             SMILES  Permeability  \
0   1114  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -4.940000   
1   1113  CC(C)C[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@@H](Cc2...     -5.820000   
2   1117  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.650000   
3   1119  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.250000   
4   2428  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.350000   
5   2446  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -6.850000   
6   2445  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -5.270000   
7   2427  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -6.340000   
8   8145  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.569578   
9   1107  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -4.610000   
10  1116  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)N(C)C(=O)[C@H]2...     -5.220000   
11  1110  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...     -4.730000   
12  8121  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.927246   
13  5836  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -5.060000   
14  6187  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -5.010000   
15  6584  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.330000   
16  6571  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.100000   
17  5803  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -6.970000   
18  2422  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.630000   
19  2440  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -7.760000   
20  8140  CCC[C@H]1C(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=...     -5.453495   
21  8131  CCC[C@@H]1NC(=O)CN(CCC)C(=O)[C@H](CC(C)C)NC(=O...     -5.509834   
22  8346  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.672617   
23  8184  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.929917   
24  6505  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.930000   
25  8342  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -4.994304   
26  8160  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.167475   
27  8341  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.822199   
28  8344  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.241518   
29  8343  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.131653   
30  8156  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.178526   
31  8150  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.834862   
32  8152  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.105008   
33  8116  CCCN1CC(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=O)N...     -5.400722   
34  8128  CCCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=...     -5.793469   
35  8138  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.303671   
36  6666  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -7.820000   
37  1115  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.190000   
38  8126  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.983385   
39  8114  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.309384   
40  1111  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C...     -6.220000   
41  1109  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N(C)C(...     -6.120000   
42  1112  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](C)NC(=O)[...     -6.170000   
43  1018  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...     -4.500000   
44  1845  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.960000   
45  1847  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.740000   
46  1841  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.410000   
47  1017  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...     -6.550000   
48  1840  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.480000   
49  1844  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -5.100000   
50  1846  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.820000   

 

In [167]:
nan_rows = df_3d_descriptors[df_3d_descriptors.isna().any(axis=1)]
nan_rows

Empty DataFrame
Columns: [ID, SMILES, Permeability, 3d_rdkit_1, 3d_rdkit_2, 3d_rdkit_3, 3d_rdkit_4, 3d_rdkit_5, 3d_rdkit_6, 3d_rdkit_7, 3d_rdkit_8, 3d_rdkit_9, 3d_rdkit_10, 3d_rdkit_11, TDB1u, TDB2u, TDB3u, TDB4u, TDB5u, TDB6u, TDB7u, TDB8u, TDB9u, TDB10u, TDB1m, TDB2m, TDB3m, TDB4m, TDB5m, TDB6m, TDB7m, TDB8m, TDB9m, TDB10m, TDB1v, TDB2v, TDB3v, TDB4v, TDB5v, TDB6v, TDB7v, TDB8v, TDB9v, TDB10v, TDB1e, TDB2e, TDB3e, TDB4e, TDB5e, TDB6e, TDB7e, TDB8e, TDB9e, TDB10e, TDB1p, TDB2p, TDB3p, TDB4p, TDB5p, TDB6p, TDB7p, TDB8p, TDB9p, TDB10p, TDB1i, TDB2i, TDB3i, TDB4i, TDB5i, TDB6i, TDB7i, TDB8i, TDB9i, TDB10i, TDB1s, TDB2s, TDB3s, TDB4s, TDB5s, TDB6s, TDB7s, TDB8s, TDB9s, TDB10s, TDB1r, TDB2r, TDB3r, TDB4r, TDB5r, TDB6r, TDB7r, TDB8r, TDB9r, TDB10r, PPSA-1, PPSA-2, PPSA-3, PNSA-1, PNSA-2, PNSA-3, ...]
Index: []

[0 rows x 445 columns]

In [168]:
df_3d_descriptors.to_csv('features/Descriptors/Train_3d_all_descriptors_MDCK.csv', index=False)

In [169]:
df_test_rdkit = pd.read_csv('features/Descriptors/Test_3d_RDKit_desc_MDCK.csv')
df_test_rdkit = df_test_rdkit.fillna(0)
df_test_padel = pd.read_csv('features/Descriptors/Test_3d_padel_curated_MDCK.csv')

df_3d_descriptors = df_test_rdkit.merge(df_test_padel, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_3d_descriptors

ID                                             SMILES  Permeability  \
0   1120  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.300000   
1   1118  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](Cc2...     -5.350000   
2   1121  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...     -6.200000   
3   8133  CCC[C@@H]1NC(=O)CN(CC)C(=O)[C@H](CC(C)C)NC(=O)...     -5.965681   
4   8143  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.676306   
5   8119  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.516110   
6   6496  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.060000   
7   8168  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(C)[C@...     -5.977700   
8   8345  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(CC(C)...     -6.342777   
9   6423  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)...     -7.210000   
10  1108  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -5.180000   
11  1843  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.400000   
12  1842  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.400000   

      3d_rdkit_1    3d_rdkit_2    3d_rdkit_3  3d_rdkit_4  3d_rdkit_5  \
0   22357.644558  37861.181847  52559.409996    0.425379    0.720350   
1   19794.004419  32295.388220  43015.692005    0.460158    0.750782   
2   18147.501441  36587.928085  50658.631132    0.358231    0.722245   
3   18985.055772  27600.224516  41557.897367    0.456834    0.664139   
4   18918.681724  24420.003395  37944.148485    0.498593    0.643578   
5   14567.155879  28123.521304  38667.611811    0.376728    0.727315   
6   11539.242278  31493.356816  36143.419934    0.319263    0.871344   
7   16026.114888  23552.590294  33895.660179    0.472807    0.694856   
8   15370.736859  22402.923302  28261.502638    0.543875    0.792701   
9   14373.054695  28219.289724  34294.814421    0.419103    0.822844   
10  13825.721860  25043.655054  34838.767120    0.396849    0.718844   
11  10346.450476  10558.396951  19030.157172    0.543687    0.554824   
12   7683.078045  10460.842058  14799.158044    0.519156    0.706854   

    3d_rdkit_6  3d_rdkit_7  ...       P1s       P2s       E1s       E2s  \
0     6.856039    0.000032  ...  0.538922  0.327869  0.524865  0.537605   
1     6.529163    0.000038  ...  0.566363  0.291189  0.444583  0.539683   
2     6.974313    0.000040  ...  0.585065  0.343748  0.509549  0.449964   
3     6.527399    0.000035  ...  0.510944  0.431114  0.440987  0.473812   
4     6.304947    0.000034  ...  0.507722  0.406031  0.519823  0.544516   
5     6.351596    0.000050  ...  0.520358  0.404704  0.497301  0.484967   
6     6.284649    0.000076  ...  0.687047  0.252612  0.485191  0.393955   
7     6.072283    0.000043  ...  0.486963  0.412405  0.532151  0.496837   
8     5.756675    0.000052  ...  0.566916  0.363249  0.588852  0.553764   
9     6.236939    0.000057  ...  0.566683  0.346100  0.511976  0.468069   
10    6.185394    0.000052  ...  0.531236  0.388502  0.523799  0.502842   
11    5.226582    0.000054  ...  0.522503  0.392542  0.472921  0.421803   
12    4.861511    0.000092  ...  0.497178  0.400169  0.413844  0.487313   

         E3s         Ts          As           Vs        Ks        Ds  
0   0.374733  48.372354  683.620826  3396.096064  0.308384  1.437203  
1   0.357508  41.316066  490.042107  2188.204700  0.349545  1.341774  
2   0.374446  51.553116  710.235475  2723.391067  0.393219  1.333960  
3   0.406420  50.076001  689.240384  2342.004744  0.413087  1.321219  
4   0.426875  45.471900  589.208424  2306.378610  0.370630  1.491215  
5   0.300594  49.677484  690.784960  2675.200579  0.387593  1.282862  
6   0.404621  49.499572  564.175291  1883.827401  0.530571  1.283767  
7   0.370279  43.965756  563.139411  2324.612455  0.349052  1.399267  
8   0.271499  51.266910  711.978056  2701.028559  0.395248  1.414115  
9   0.382243  44.726179  551.597017  2126.801755  0.369175  1.362288  
10  0.421705  44.313812  550.245259  2036.042466  0.379606  1.448347  
11  0.368107  3

In [170]:
nan_rows = df_3d_descriptors[df_3d_descriptors.isna().any(axis=1)]
nan_rows

Empty DataFrame
Columns: [ID, SMILES, Permeability, 3d_rdkit_1, 3d_rdkit_2, 3d_rdkit_3, 3d_rdkit_4, 3d_rdkit_5, 3d_rdkit_6, 3d_rdkit_7, 3d_rdkit_8, 3d_rdkit_9, 3d_rdkit_10, 3d_rdkit_11, TDB1u, TDB2u, TDB3u, TDB4u, TDB5u, TDB6u, TDB7u, TDB8u, TDB9u, TDB10u, TDB1m, TDB2m, TDB3m, TDB4m, TDB5m, TDB6m, TDB7m, TDB8m, TDB9m, TDB10m, TDB1v, TDB2v, TDB3v, TDB4v, TDB5v, TDB6v, TDB7v, TDB8v, TDB9v, TDB10v, TDB1e, TDB2e, TDB3e, TDB4e, TDB5e, TDB6e, TDB7e, TDB8e, TDB9e, TDB10e, TDB1p, TDB2p, TDB3p, TDB4p, TDB5p, TDB6p, TDB7p, TDB8p, TDB9p, TDB10p, TDB1i, TDB2i, TDB3i, TDB4i, TDB5i, TDB6i, TDB7i, TDB8i, TDB9i, TDB10i, TDB1s, TDB2s, TDB3s, TDB4s, TDB5s, TDB6s, TDB7s, TDB8s, TDB9s, TDB10s, TDB1r, TDB2r, TDB3r, TDB4r, TDB5r, TDB6r, TDB7r, TDB8r, TDB9r, TDB10r, PPSA-1, PPSA-2, PPSA-3, PNSA-1, PNSA-2, PNSA-3, ...]
Index: []

[0 rows x 445 columns]

In [171]:
df_3d_descriptors.to_csv('features/Descriptors/Test_3d_all_descriptors_MDCK.csv', index=False)

In [172]:
#3d All descriptors
df_train = pd.read_csv('features/Descriptors/Train_3d_all_descriptors_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_3d_all_descriptors_MDCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

models_3dall = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models_3dall, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 442)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 442)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000265 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1558
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 104
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.7938                0.7692   
DecisionTreeRegressor                    1.0377                0.7786   
RandomForestRegressor                    0.4650                0.5308   
GradientBoostingRegressor                0.5197                0.5649   
AdaBoostRegressor                        0.4328                0.5098   
XGBRegressor                             0.5388                0.5882   
ExtraTreesRegressor                      0.5175                0.5774   
LinearRegression                         0.8622                0.7315   
KNeighborsRegressor                      0.5288                0.5841   
SVR                                      0.5664                0.5945   
MLPRegressor                             2.5867                1.3417   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8909              -0.2271   
DecisionTreeRegressor                     1.0187              -0.6041   
RandomForestRegressor                     0.6819               0.2812   
GradientBoostingRegressor                 0.7209               0.1967   
AdaBoostRegressor                         0.6579               0.3310   
XGBRegressor                              0.7340               0.1671   
ExtraTreesRegressor                       0.7194               0.2000   
LinearRegression                          0.9285              -0.3328   
KNeighborsRegressor                       0.7272               0.1825   
SVR                                       0.7526               0.1245   
MLPRegressor                              1.6083              -2.9987   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.0321               -0.0042   
DecisionTreeRegressor                    0.1998                0.2571   
RandomForestRegressor                    0.5458                0.5743   
GradientBoostingRegressor                0.4713                0.5056   
AdaBoostRegressor                        0.5871                0.6294   
XGBRegressor                             0.4441                0.4449   
ExtraTreesRegressor                      0.4477                0.4319   
LinearRegression                         0.2747                0.2037   
KNeighborsRegressor                      0.4437                0.4703   
SVR                                      0.3932                0.4216   
MLPRegressor                             0.0926                0.1510   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4823   0.5315    0.6944   0.1802   
DecisionTreeRegressor       0.5499   0.5483    0.7415   0.0652   
RandomForestRegressor       0.3092   0.4541    0.5561   0.4743   
GradientBoostingRegressor   0.3566   0.4990    0.5972   0.3937   
AdaBoostRegressor           0.3322   0.4646    0.5764   0.4352   
XGBRegressor                0.2691   0.4322    0.5187   0.5425   
ExtraTreesRegressor         0.3501   0.4705    0.5917   0.4048   
LinearRegression            0.9529   0.8123    0.9762  -0.6199   
KNeighborsRegressor         0.5038   0.5720    0.7098   0.1435   
SVR                         0.4158   0.4825    0.6448   0.2932   
MLPRegressor                2.3390   1.2038    1.5294  -2.9764   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4247                    0.4512  
DecisionTreeRegressor                       0.4932                    0.3824  
RandomForestRegressor                       0.7124                    0.5695  
GradientBoostingRegressor                   0.6379                    0.4374  
AdaBoostRegressor                           0.6635                    0.5640  
XGBRegressor                                0.7561                    0.5970  
ExtraTreesRegressor                         0.644

In [173]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.837871221180832, -5.690961856159556, -5.89...   
1   [-6.569578491, -5.22, -5.22, -5.303671307, -5....   
2   [-5.886644928520001, -5.263258779780001, -5.36...   
3   [-5.930963039127117, -5.062173628323773, -5.16...   
4   [-6.25, -5.137142857142856, -5.113333333333333...   
5   [-6.08846, -5.0673137, -5.0674872, -6.0345607,...   
6   [-6.028106844370004, -5.316536553679999, -5.59...   
7   [-7.115310133291685, -6.028495464786285, -5.96...   
8   [-5.583333333333333, -5.408287387000001, -5.44...   
9   [-6.007534341177215, -5.546078596820685, -5.70...   
10  [-4.0, -5.005195024447222, -4.0, -5.0986558793...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.733919084033116, -5.317926401298028, -6.0...   
1   [[-5.35, -5.35, -5.93, -6.927245587, -5.303671...   
2   [[-5.958469749130002, -5.589211166320005, -6.5...   
3   [[-6.1441924130801375, -5.537911862146065, -6....   
4   [[-5.801368406076923, -5.253333333333333, -6.8...   
5   [[-5.696285, -5.609829, -6.9147677, -6.2541738...   
6   [[-5.79835102306, -5.365162132960003, -6.67743...   
7   [[-5.203364902647311, -4.3865801477960185, -6....   
8   [[-5.613333333333333, -5.206666666666666, -6.4...   
9   [[-5.412896481687582, -5.29375446671756, -6.16...   
10  [[-8.841650623200891, -4.259717205101841, -4.5...   

                                Test Predictions Mean  \
0   [-5.559022073543207, -5.574374334041286, -6.03...   
1   [-6.298, -5.397999999999999, -6.61399999999999...   
2   [-5.888140665762, -5.472325882242001, -6.44145...   
3   [-5.976305596051986, -5.3634547539018, -6.5607...   
4   [-5.78391633925348, -5.355111063227451, -6.461...   
5   [-5.89615, -5.460052, -6.6644516, -6.19325, -5...   
6   [-5.758603403784, -5.33152004009, -6.432154002...   
7   [-4.617870011492105, -4.435944686826875, -7.30...   
8   [-5.560666666666666, -5.145999999999999, -6.44...   
9   [-5.449708881288661, -5.22091670614579, -6.107...   
10  [-9.295456145379761, -5.168337365081749, -4.60...   

                                 Test Predictions Std  
0   [0.2891167107383283, 0.3159169028802354, 0.239...  
1   [0.8304552968101295, 0.5004557922534216, 0.966...  
2   [0.15035613854267982, 0.06166922607076245, 0.2...  
3   [0.2964584079899877, 0.16082487882990454, 0.36...  
4   [0.12270308584541771, 0.1335543759903669, 0.34...  
5   [0.26275367, 0.24402368, 0.5592756, 0.29224274...  
6   [0.17869162197623314, 0.0583221513850547, 0.26...  
7   [0.39443937274574814, 0.2726170324801912, 0.28...  
8   [0.14478182820291288, 0.059568821076503096, 0....  
9   [0.09466492239606225, 0.08712203376711537, 0.1...  
10  [0.5818162251136829, 0.8535063685430471, 0.592...

In [174]:
result_df.to_csv('results/Descriptors/Results_3D_All_desc_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_3D_All_desc_MDCK.csv')

In [175]:
#3d All descriptors const rem
df_train = pd.read_csv('features/Descriptors/Train_3d_all_descriptors_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train,  const_col =  remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_3d_all_descriptors_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 442)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 442)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000104 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1558
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 104
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.7938                0.7692   
DecisionTreeRegressor                    1.0377                0.7786   
RandomForestRegressor                    0.4650                0.5308   
GradientBoostingRegressor                0.5197                0.5649   
AdaBoostRegressor                        0.4328                0.5098   
XGBRegressor                             0.5388                0.5882   
ExtraTreesRegressor                      0.5175                0.5774   
LinearRegression                         0.8622                0.7315   
KNeighborsRegressor                      0.5288                0.5841   
SVR                                      0.5664                0.5945   
MLPRegressor                             2.5867                1.3417   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8909              -0.2271   
DecisionTreeRegressor                     1.0187              -0.6041   
RandomForestRegressor                     0.6819               0.2812   
GradientBoostingRegressor                 0.7209               0.1967   
AdaBoostRegressor                         0.6579               0.3310   
XGBRegressor                              0.7340               0.1671   
ExtraTreesRegressor                       0.7194               0.2000   
LinearRegression                          0.9285              -0.3328   
KNeighborsRegressor                       0.7272               0.1825   
SVR                                       0.7526               0.1245   
MLPRegressor                              1.6083              -2.9987   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                           -0.0321               -0.0042   
DecisionTreeRegressor                    0.1998                0.2571   
RandomForestRegressor                    0.5458                0.5743   
GradientBoostingRegressor                0.4713                0.5056   
AdaBoostRegressor                        0.5871                0.6294   
XGBRegressor                             0.4441                0.4449   
ExtraTreesRegressor                      0.4477                0.4319   
LinearRegression                         0.2747                0.2037   
KNeighborsRegressor                      0.4437                0.4703   
SVR                                      0.3932                0.4216   
MLPRegressor                             0.0926                0.1510   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4823   0.5315    0.6944   0.1802   
DecisionTreeRegressor       0.5499   0.5483    0.7415   0.0652   
RandomForestRegressor       0.3092   0.4541    0.5561   0.4743   
GradientBoostingRegressor   0.3566   0.4990    0.5972   0.3937   
AdaBoostRegressor           0.3322   0.4646    0.5764   0.4352   
XGBRegressor                0.2691   0.4322    0.5187   0.5425   
ExtraTreesRegressor         0.3501   0.4705    0.5917   0.4048   
LinearRegression            0.9529   0.8123    0.9762  -0.6199   
KNeighborsRegressor         0.5038   0.5720    0.7098   0.1435   
SVR                         0.4158   0.4825    0.6448   0.2932   
MLPRegressor                2.3390   1.2038    1.5294  -2.9764   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4247                    0.4512  
DecisionTreeRegressor                       0.4932                    0.3824  
RandomForestRegressor                       0.7124                    0.5695  
GradientBoostingRegressor                   0.6379                    0.4374  
AdaBoostRegressor                           0.6635                    0.5640  
XGBRegressor                                0.7561                    0.5970  
ExtraTreesRegressor                         0.644

In [176]:
result_df.to_csv('results/Descriptors/Results_3D_All_desc_const_rem_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_3D_All_desc_const_rem_MDCK.csv')

In [177]:
#3d All descriptors LVR
df_train = pd.read_csv('features/Descriptors/Train_3d_all_descriptors_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train,  const_col =  remove_low_variance_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_3d_all_descriptors_MDCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 370)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 370)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000091 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1305
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 87
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits 

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.7618                0.7331   
DecisionTreeRegressor                    0.9107                0.7261   
RandomForestRegressor                    0.5201                0.5535   
GradientBoostingRegressor                0.5481                0.5700   
AdaBoostRegressor                        0.5602                0.5630   
XGBRegressor                             0.5146                0.5379   
ExtraTreesRegressor                      0.5386                0.5921   
LinearRegression                         1.0833                0.8424   
KNeighborsRegressor                      0.5425                0.6008   
SVR                                      0.6104                0.6035   
MLPRegressor                             1.9445                1.1162   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8728              -0.1777   
DecisionTreeRegressor                     0.9543              -0.4078   
RandomForestRegressor                     0.7212               0.1959   
GradientBoostingRegressor                 0.7403               0.1527   
AdaBoostRegressor                         0.7485               0.1340   
XGBRegressor                              0.7174               0.2045   
ExtraTreesRegressor                       0.7339               0.1674   
LinearRegression                          1.0408              -0.6746   
KNeighborsRegressor                       0.7365               0.1614   
SVR                                       0.7813               0.0565   
MLPRegressor                              1.3945              -2.0059   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.0274                0.0781   
DecisionTreeRegressor                    0.2503                0.2879   
RandomForestRegressor                    0.4427                0.5087   
GradientBoostingRegressor                0.4254                0.4812   
AdaBoostRegressor                        0.3917                0.4330   
XGBRegressor                             0.4868                0.5434   
ExtraTreesRegressor                      0.4143                0.4467   
LinearRegression                         0.1075                0.0830   
KNeighborsRegressor                      0.4197                0.4798   
SVR                                      0.3219                0.3051   
MLPRegressor                             0.2074                0.2517   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4567   0.5233    0.6758   0.2236   
DecisionTreeRegressor       0.5351   0.5815    0.7315   0.0902   
RandomForestRegressor       0.3236   0.4519    0.5688   0.4499   
GradientBoostingRegressor   0.4486   0.5183    0.6698   0.2374   
AdaBoostRegressor           0.3499   0.4555    0.5915   0.4051   
XGBRegressor                0.3611   0.5120    0.6010   0.3860   
ExtraTreesRegressor         0.3624   0.4777    0.6020   0.3838   
LinearRegression            0.6974   0.6662    0.8351  -0.1856   
KNeighborsRegressor         0.3886   0.4948    0.6234   0.3393   
SVR                         0.3735   0.4668    0.6111   0.3651   
MLPRegressor                1.8641   1.0566    1.3653  -2.1690   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4783                    0.5089  
DecisionTreeRegressor                       0.4241                    0.3549  
RandomForestRegressor                       0.6973                    0.6135  
GradientBoostingRegressor                   0.5142                    0.4209  
AdaBoostRegressor                           0.6380                    0.5695  
XGBRegressor                                0.6555                    0.4429  
ExtraTreesRegressor                         0.626

In [178]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.812772876329546, -5.677708137107258, -5.88...   
1   [-6.34, -4.94, -5.06, -6.929917083, -6.9299170...   
2   [-5.953685100350001, -5.279664158810002, -5.37...   
3   [-6.122727656868503, -5.0307587002566825, -5.2...   
4   [-6.153565379, -5.2410529627692295, -5.1408960...   
5   [-6.1222277, -5.1070056, -5.0919137, -5.780672...   
6   [-5.958760617840004, -5.4144259057200035, -5.7...   
7   [-6.6994995022378285, -5.783981668881271, -6.0...   
8   [-5.583333333333333, -5.786666666666666, -5.44...   
9   [-5.8054395186444925, -5.462345637843317, -5.6...   
10  [-4.0, -6.22580775912539, -4.0, -4.68698261363...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.7087442118983045, -5.305590849064757, -6....   
1   [[-6.569578491, -5.65, -5.793469425, -6.569578...   
2   [[-6.053498501330004, -5.532893981240001, -6.5...   
3   [[-6.307836033867727, -5.5420826846471325, -6....   
4   [[-6.196596415166667, -5.329700690416665, -6.5...   
5   [[-6.3238688, -5.67615, -7.0364385, -6.506613,...   
6   [[-5.760247443460002, -5.423271837560004, -6.6...   
7   [[-5.537847773985432, -4.244706561532601, -7.0...   
8   [[-5.613333333333333, -5.206666666666666, -6.2...   
9   [[-5.438656631546392, -5.246895496558645, -6.1...   
10  [[-8.476212885940466, -5.018246129783234, -5.3...   

                                Test Predictions Mean  \
0   [-5.629838628331656, -5.544465162649217, -5.99...   
1   [-6.2804391856, -5.3688608714, -6.4140587006, ...   
2   [-6.029058468714004, -5.4916381674179995, -6.3...   
3   [-6.202674990987974, -5.449856050004416, -6.38...   
4   [-5.896085469982539, -5.27768955111111, -6.378...   
5   [-6.0467625, -5.524417, -6.7239823, -6.4559145...   
6   [-5.786895090468001, -5.398370242066, -6.44544...   
7   [-4.889454706279375, -4.662136181411768, -7.43...   
8   [-5.6546666666666665, -5.167333333333334, -6.4...   
9   [-5.474902919457266, -5.197397646291375, -6.12...   
10  [-8.796719538362522, -5.696826774515121, -5.42...   

                                 Test Predictions Std  
0   [0.2432872968053441, 0.291300675157427, 0.1874...  
1   [0.6406564117943924, 0.5115546360066238, 0.468...  
2   [0.09949515846933397, 0.03758754417144964, 0.2...  
3   [0.3270602821766599, 0.19596624172390653, 0.27...  
4   [0.29200737735487514, 0.04365256185844207, 0.2...  
5   [0.27607512, 0.10554468, 0.46849626, 0.3791127...  
6   [0.17974459520193564, 0.07807718874141853, 0.2...  
7   [0.55012986156203, 0.43246481831709493, 0.3196...  
8   [0.14230796026770795, 0.05836284967530473, 0.1...  
9   [0.08590391269054908, 0.08966866510890902, 0.1...  
10  [0.4130241863424445, 0.6269728771893931, 0.780...

In [179]:
result_df.to_csv('results/Descriptors/Results_3D_All_desc_LVR_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_3D_All_desc_LVR_MDCK.csv')

In [180]:
#2d and 3d descriptors all
df_train_2d = pd.read_csv('features/Descriptors/Train_2d_all_descriptors_MDCK.csv')
df_train_2d
df_train_3d = pd.read_csv('features/Descriptors/Train_3d_all_descriptors_MDCK.csv')
df_train_3d

df_2d_3d_train = df_train_2d.merge(df_train_3d, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_2d_3d_train.to_csv('features/Descriptors/Train_2d_3d_all_descriptors_MDCK.csv', index=False)
df_2d_3d_train

ID                                             SMILES  Permeability  \
0   1114  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -4.940000   
1   1113  CC(C)C[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@@H](Cc2...     -5.820000   
2   1117  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.650000   
3   1119  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.250000   
4   2428  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.350000   
5   2446  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -6.850000   
6   2445  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -5.270000   
7   2427  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -6.340000   
8   8145  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.569578   
9   1107  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -4.610000   
10  1116  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)N(C)C(=O)[C@H]2...     -5.220000   
11  1110  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...     -4.730000   
12  8121  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -6.927246   
13  5836  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -5.060000   
14  6187  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -5.010000   
15  6584  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.330000   
16  6571  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.100000   
17  5803  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N...     -6.970000   
18  2422  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N(C)[C@@H](C)C(=...     -5.630000   
19  2440  CCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=O...     -7.760000   
20  8140  CCC[C@H]1C(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=...     -5.453495   
21  8131  CCC[C@@H]1NC(=O)CN(CCC)C(=O)[C@H](CC(C)C)NC(=O...     -5.509834   
22  8346  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.672617   
23  8184  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.929917   
24  6505  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.930000   
25  8342  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -4.994304   
26  8160  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.167475   
27  8341  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.822199   
28  8344  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -5.241518   
29  8343  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(CC(C)C...     -6.131653   
30  8156  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -6.178526   
31  8150  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.834862   
32  8152  CCOC(=O)[C@@H]1CSCC(=O)N[C@H](CC)C(=O)N(C)[C@@...     -5.105008   
33  8116  CCCN1CC(=O)N[C@@H](CC)C(=O)N(C)[C@@H](C)C(=O)N...     -5.400722   
34  8128  CCCN1CC(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C(=...     -5.793469   
35  8138  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.303671   
36  6666  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N...     -7.820000   
37  1115  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...     -5.190000   
38  8126  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.983385   
39  8114  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC(C)C)C(=O)N(C...     -5.309384   
40  1111  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C...     -6.220000   
41  1109  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N(C)C(...     -6.120000   
42  1112  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](C)NC(=O)[...     -6.170000   
43  1018  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...     -4.500000   
44  1845  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.960000   
45  1847  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.740000   
46  1841  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.410000   
47  1017  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...     -6.550000   
48  1840  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -4.480000   
49  1844  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...     -5.100000   
50  1846  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.820000   

 

In [181]:
df_test_2d = pd.read_csv('features/Descriptors/Test_2d_all_descriptors_MDCK.csv')
df_test_2d
df_test_3d = pd.read_csv('features/Descriptors/Test_3d_all_descriptors_MDCK.csv')
df_test_3d

df_2d_3d_test = df_test_2d.merge(df_test_3d, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_2d_3d_test.to_csv('features/Descriptors/Test_2d_3d_all_descriptors_MDCK.csv', index=False)
df_2d_3d_test

ID                                             SMILES  Permeability  \
0   1120  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...     -6.300000   
1   1118  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](Cc2...     -5.350000   
2   1121  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...     -6.200000   
3   8133  CCC[C@@H]1NC(=O)CN(CC)C(=O)[C@H](CC(C)C)NC(=O)...     -5.965681   
4   8143  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.676306   
5   8119  CCC[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H](CC(C)C)...     -5.516110   
6   6496  CC(=O)N1CCC[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N[...     -5.060000   
7   8168  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(C)[C@...     -5.977700   
8   8345  CCOC(=O)[C@@H]1CSCC(=O)N[C@@H](CC)C(=O)N(CC(C)...     -6.342777   
9   6423  CC(=O)N1CCC[C@@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)...     -7.210000   
10  1108  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -5.180000   
11  1843  CC[C@H](C)[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@...     -4.400000   
12  1842  CC[C@H](C)[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H...     -4.400000   

    MaxAbsEStateIndex  MaxEStateIndex  MinAbsEStateIndex  MinEStateIndex  \
0           15.211581       15.211581           0.031713       -1.206465   
1           14.834083       14.834083           0.037197       -1.184826   
2           14.571211       14.571211           0.032067       -1.213008   
3           14.507460       14.507460           0.015782       -1.174377   
4           14.432367       14.432367           0.010248       -1.181980   
5           14.337271       14.337271           0.011275       -1.179506   
6           14.798396       14.798396           0.082911       -1.653049   
7           14.228063       14.228063           0.008269       -1.181029   
8           14.235704       14.235704           0.008614       -1.181469   
9           14.765338       14.765338           0.082043       -1.652577   
10          14.121032       14.121032           0.089106       -1.124048   
11          14.424770       14.424770           0.002738       -1.061047   
12          14.311518       14.311518           0.013797       -1.013552   

         qed        SPS     MolWt  ...       P1s       P2s       E1s  \
0   0.159924  25.279070  1199.634  ...  0.538922  0.327869  0.524865   
1   0.240803  26.125000  1115.472  ...  0.566363  0.291189  0.444583   
2   0.153969  27.307692  1083.386  ...  0.585065  0.343748  0.509549   
3   0.218370  27.694444  1034.376  ...  0.510944  0.431114  0.440987   
4   0.206072  27.492958  1022.365  ...  0.507722  0.406031  0.519823   
5   0.205195  26.642857  1008.338  ...  0.520358  0.404704  0.497301   
6   0.157962  27.464789  1002.309  ...  0.687047  0.252612  0.485191   
7   0.216153  26.159420   996.327  ...  0.486963  0.412405  0.532151   
8   0.216153  26.159420   996.327  ...  0.566916  0.363249  0.588852   
9   0.137104  27.528571   988.282  ...  0.566683  0.346100  0.511976   
10  0.271385  28.764706   963.276  ...  0.531236  0.388502  0.523799   
11  0.252294  25.773585   730.951  ...  0.522503  0.392542  0.472921   
12  0.252518  26.820000   696.934  ...  0.497178  0.400169  0.413844   

         E2s       E3s         Ts          As           Vs        Ks        Ds  
0   0.537605  0.374733  48.372354  683.620826  3396.096064  0.308384  1.437203  
1   0.539683  0.357508  41.316066  490.042107  2188.204700  0.349545  1.341774  
2   0.449964  0.374446  51.553116  710.235475  2723.391067  0.393219  1.333960  
3   0.473812  0.406420  50.076001  689.240384  2342.004744  0.413087  1.321219  
4   0.544516  0.426875  45.471900  589.208424  2306.378610  0.370630  1.491215  
5   0.484967  0.300594  49.677484  690.784960  2675.200579  0.387593  1.282862  
6   0.393955  0.404621  49.499572  564.175291  1883.827401  0.530571  1.283767  
7   0.496837  0.370279  43.965756  563.139411  2324.612455  0.349052  1.399267  
8   0.553764  0.271499  51.266910  711.978056  2701.028559  0.395248  1.414115  
9   0.468069  0.382243  44.726179  551.5970

In [182]:
#All 2d and 3d descriptors
df_train = pd.read_csv('features/Descriptors/Train_2d_3d_all_descriptors_MDCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_3d_all_descriptors_MDCK.csv')
df_test = df_test.dropna()
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 3539)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 3539)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000684 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 10183
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 749
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spl

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6551                0.6804   
DecisionTreeRegressor                    0.7790                0.6813   
RandomForestRegressor                    0.5214                0.5785   
GradientBoostingRegressor                0.4969                0.5730   
AdaBoostRegressor                        0.5126                0.5581   
XGBRegressor                             0.5723                0.6026   
ExtraTreesRegressor                      0.5834                0.6217   
LinearRegression                         0.7728                0.6965   
KNeighborsRegressor                      0.6093                0.6176   
SVR                                      0.6213                0.6225   
MLPRegressor                             1.4264                0.8638   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8094              -0.0127   
DecisionTreeRegressor                     0.8826              -0.2042   
RandomForestRegressor                     0.7221               0.1940   
GradientBoostingRegressor                 0.7049               0.2319   
AdaBoostRegressor                         0.7160               0.2076   
XGBRegressor                              0.7565               0.1153   
ExtraTreesRegressor                       0.7638               0.0982   
LinearRegression                          0.8791              -0.1947   
KNeighborsRegressor                       0.7806               0.0581   
SVR                                       0.7882               0.0396   
MLPRegressor                              1.1943              -1.2051   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2479                0.3164   
DecisionTreeRegressor                    0.2808                0.2513   
RandomForestRegressor                    0.4419                0.5111   
GradientBoostingRegressor                0.4890                0.5061   
AdaBoostRegressor                        0.4771                0.5435   
XGBRegressor                             0.4061                0.4362   
ExtraTreesRegressor                      0.3790                0.4269   
LinearRegression                         0.3376                0.2498   
KNeighborsRegressor                      0.3663                0.3544   
SVR                                      0.2998                0.2720   
MLPRegressor                             0.1556                0.2191   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.3932   0.5127    0.6270   0.3316   
DecisionTreeRegressor       0.3609   0.4869    0.6008   0.3864   
RandomForestRegressor       0.2722   0.4447    0.5217   0.5373   
GradientBoostingRegressor   0.3413   0.5061    0.5842   0.4198   
AdaBoostRegressor           0.2690   0.4377    0.5186   0.5427   
XGBRegressor                0.3584   0.5070    0.5987   0.3906   
ExtraTreesRegressor         0.3152   0.4685    0.5614   0.4642   
LinearRegression            1.1598   0.7835    1.0770  -0.9718   
KNeighborsRegressor         0.3369   0.4582    0.5804   0.4272   
SVR                         0.3420   0.4833    0.5848   0.4186   
MLPRegressor                0.8467   0.7702    0.9202  -0.4395   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5787                    0.3769  
DecisionTreeRegressor                       0.7259                    0.5199  
RandomForestRegressor                       0.7570                    0.5750  
GradientBoostingRegressor                   0.6814                    0.4594  
AdaBoostRegressor                           0.7431                    0.6135  
XGBRegressor                                0.6977                    0.4924  
ExtraTreesRegressor                         0.708

In [183]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.385188685014141, -5.6070423083280865, -6.4...   
1   [-5.65, -5.33, -5.06, -5.793469425, -6.9299170...   
2   [-5.749899094070002, -5.431484174089998, -5.60...   
3   [-5.721914710011272, -5.144315314957571, -5.27...   
4   [-5.650000000000001, -5.173333333333333, -5.30...   
5   [-5.805778, -5.108463, -5.2194166, -6.3724723,...   
6   [-5.6754582644000005, -5.51351238957, -5.74303...   
7   [-6.306705139828235, -5.789430564074796, -5.61...   
8   [-5.6433333333333335, -5.786666666666666, -5.9...   
9   [-5.4976492771903125, -5.328093634502577, -5.6...   
10  [-5.525999893590621, -4.937662345204934, -5.76...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.572068832530054, -5.398194853183809, -5.5...   
1   [[-5.93, -6.25, -6.97, -6.927245587, -5.453495...   
2   [[-5.853891657530003, -5.5391950139400015, -6....   
3   [[-6.250669991193625, -5.448801217398834, -6.4...   
4   [[-5.65, -5.4648029049230775, -6.2526377125833...   
5   [[-6.1840267, -5.850236, -6.5278716, -6.856331...   
6   [[-5.52496130623, -5.566031033970001, -6.79660...   
7   [[-5.308278163647166, -5.138626863179043, -8.7...   
8   [[-5.613333333333333, -5.613333333333334, -6.6...   
9   [[-5.466860485958558, -5.533279948765775, -5.8...   
10  [[-6.4093107836981265, -4.0, -10.0, -6.9303033...   

                                Test Predictions Mean  \
0   [-5.542283309028968, -5.565932012645861, -5.90...   
1   [-5.983915698200001, -6.0763305102, -6.6814491...   
2   [-5.750280323782001, -5.485610486260001, -6.25...   
3   [-5.855233851259328, -5.527939220772208, -6.62...   
4   [-5.516862187262499, -5.419313030922145, -6.44...   
5   [-5.809245, -5.5791035, -6.7244287, -6.4792223...   
6   [-5.474677365296001, -5.531012374278001, -6.57...   
7   [-5.214300693191923, -5.416699115715996, -8.85...   
8   [-5.6546666666666665, -5.666000000000001, -6.4...   
9   [-5.510218916926129, -5.566038306879546, -5.80...   
10  [-7.2721494763535945, -4.291317225032536, -6.3...   

                                 Test Predictions Std  
0   [0.18035447965365928, 0.2221526803914395, 0.19...  
1   [0.41119974065844683, 0.2300002870641018, 0.81...  
2   [0.07942643670325907, 0.11938998875513067, 0.1...  
3   [0.349039318273725, 0.22007150330142053, 0.348...  
4   [0.19065124654119572, 0.15119961509681928, 0.2...  
5   [0.31351328, 0.2342805, 0.42852277, 0.51039153...  
6   [0.1928856578959878, 0.1944379799505357, 0.123...  
7   [0.296587525538262, 0.7078409193883037, 0.4117...  
8   [0.14230796026770795, 0.14081350945290821, 0.1...  
9   [0.11877498263283152, 0.21783368413245263, 0.1...  
10  [0.799542530566235, 0.5826344500650724, 1.9802...

In [184]:
result_df.to_csv('results/Descriptors/Results_2D_3D_All_desc_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_3D_All_desc_MDCK.csv')

In [185]:
#All 2d and 3d descriptors const rem
df_train = pd.read_csv('features/Descriptors/Train_2d_3d_all_descriptors_MDCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
X_train,  const_col =  remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_3d_all_descriptors_MDCK.csv')
df_test = df_test.dropna()
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 2716)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 2716)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000662 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 10183
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 749
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spl

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.6551                0.6804   
DecisionTreeRegressor                    0.9528                0.7685   
RandomForestRegressor                    0.5210                0.5814   
GradientBoostingRegressor                0.4639                0.5520   
AdaBoostRegressor                        0.5573                0.5859   
XGBRegressor                             0.5723                0.6026   
ExtraTreesRegressor                      0.6190                0.6435   
LinearRegression                         0.7728                0.6965   
KNeighborsRegressor                      0.6093                0.6176   
SVR                                      0.6213                0.6225   
MLPRegressor                             1.3918                0.9018   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8094              -0.0127   
DecisionTreeRegressor                     0.9761              -0.4730   
RandomForestRegressor                     0.7218               0.1946   
GradientBoostingRegressor                 0.6811               0.2828   
AdaBoostRegressor                         0.7465               0.1385   
XGBRegressor                              0.7565               0.1153   
ExtraTreesRegressor                       0.7868               0.0431   
LinearRegression                          0.8791              -0.1947   
KNeighborsRegressor                       0.7806               0.0581   
SVR                                       0.7882               0.0395   
MLPRegressor                              1.1798              -1.1516   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2479                0.3164   
DecisionTreeRegressor                    0.2094                0.1735   
RandomForestRegressor                    0.4438                0.5242   
GradientBoostingRegressor                0.5351                0.5562   
AdaBoostRegressor                        0.4184                0.4662   
XGBRegressor                             0.4061                0.4362   
ExtraTreesRegressor                      0.3234                0.3281   
LinearRegression                         0.3376                0.2498   
KNeighborsRegressor                      0.3663                0.3544   
SVR                                      0.2998                0.2720   
MLPRegressor                             0.2228                0.2096   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.3932   0.5127    0.6270   0.3316   
DecisionTreeRegressor       0.5209   0.6305    0.7217   0.1145   
RandomForestRegressor       0.2656   0.4382    0.5154   0.5484   
GradientBoostingRegressor   0.3523   0.5124    0.5936   0.4010   
AdaBoostRegressor           0.2840   0.4264    0.5329   0.5172   
XGBRegressor                0.3584   0.5070    0.5987   0.3906   
ExtraTreesRegressor         0.3053   0.4682    0.5526   0.4809   
LinearRegression            1.1598   0.7835    1.0770  -0.9718   
KNeighborsRegressor         0.3369   0.4582    0.5804   0.4272   
SVR                         0.3420   0.4833    0.5848   0.4186   
MLPRegressor                0.8616   0.7858    0.9282  -0.4648   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5787                    0.3769  
DecisionTreeRegressor                       0.5418                    0.3989  
RandomForestRegressor                       0.7650                    0.5750  
GradientBoostingRegressor                   0.6729                    0.4759  
AdaBoostRegressor                           0.7310                    0.5640  
XGBRegressor                                0.6977                    0.4924  
ExtraTreesRegressor                         0.712

In [186]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.385188685014141, -5.6070423083280865, -6.4...   
1   [-5.65, -5.06, -5.33, -6.929917083, -5.4007221...   
2   [-5.7671244946, -5.47353290083, -5.56611199528...   
3   [-5.706851004899697, -5.11217875624988, -5.265...   
4   [-5.5106911800625, -5.202832213687499, -5.3644...   
5   [-5.805778, -5.108463, -5.2194166, -6.3724723,...   
6   [-5.624187237, -5.489488923189999, -5.81584303...   
7   [-6.306705139828233, -5.789430564074801, -5.61...   
8   [-5.6433333333333335, -5.786666666666666, -5.9...   
9   [-5.49764705779118, -5.328094158535443, -5.641...   
10  [-5.953034430039709, -4.937995622920759, -4.85...   

                                        Y Test actual  \
0   0    -6.300000
1    -5.350000
2    -6.200000
3...   
1   0    -6.300000
1    -5.350000
2    -6.200000
3...   
2   0    -6.300000
1    -5.350000
2    -6.200000
3...   
3   0    -6.300000
1    -5.350000
2    -6.200000
3...   
4   0    -6.300000
1    -5.350000
2    -6.200000
3...   
5   0    -6.300000
1    -5.350000
2    -6.200000
3...   
6   0    -6.300000
1    -5.350000
2    -6.200000
3...   
7   0    -6.300000
1    -5.350000
2    -6.200000
3...   
8   0    -6.300000
1    -5.350000
2    -6.200000
3...   
9   0    -6.300000
1    -5.350000
2    -6.200000
3...   
10  0    -6.300000
1    -5.350000
2    -6.200000
3...   

                                Test prediction folds  \
0   [[-5.572068832530054, -5.398194853183809, -5.5...   
1   [[-6.85, -6.25, -5.93, -6.927245587, -5.303671...   
2   [[-5.840858227130002, -5.47524905246, -6.25252...   
3   [[-6.216939686838095, -5.435487836881435, -6.6...   
4   [[-5.5106911800625, -5.507348526642856, -6.173...   
5   [[-6.1840267, -5.850236, -6.5278716, -6.856331...   
6   [[-5.425353157690001, -5.370200240910002, -6.7...   
7   [[-5.30827816364717, -5.138626863179046, -8.72...   
8   [[-5.613333333333333, -5.613333333333334, -6.6...   
9   [[-5.466910041704217, -5.533331044797736, -5.8...   
10  [[-4.0, -4.0, -5.129254621085442, -6.936722570...   

                                Test Predictions Mean  \
0   [-5.542283309028968, -5.565932012645861, -5.90...   
1   [-5.7659156982, -6.188, -6.651999999999999, -6...   
2   [-5.757386442873999, -5.497085648210001, -6.25...   
3   [-5.896049542365603, -5.527895374787274, -6.69...   
4   [-5.556474800675, -5.449582230788852, -6.34286...   
5   [-5.809245, -5.5791035, -6.7244287, -6.4792223...   
6   [-5.438967877492, -5.5296410195500005, -6.5316...   
7   [-5.2143006931919205, -5.4166991157159945, -8....   
8   [-5.6546666666666665, -5.666000000000001, -6.4...   
9   [-5.510241160085745, -5.566067659577447, -5.80...   
10  [-4.9676989784211445, -4.183933208918508, -4.2...   

                                 Test Predictions Std  
0   [0.18035447965365928, 0.2221526803914395, 0.19...  
1   [0.8071235786004356, 0.4569638935408353, 1.004...  
2   [0.10291923567494045, 0.09381271627035664, 0.0...  
3   [0.3035200699225455, 0.2191428489343412, 0.330...  
4   [0.19484934534479553, 0.12248377593261675, 0.2...  
5   [0.31351328, 0.2342805, 0.42852277, 0.51039153...  
6   [0.21678243841412795, 0.2204941854076667, 0.10...  
7   [0.2965875255382647, 0.7078409193883047, 0.411...  
8   [0.14230796026770795, 0.14081350945290821, 0.1...  
9   [0.11877784788486262, 0.2178481789110824, 0.10...  
10  [1.1277304005924982, 0.3678664178370159, 0.438...

In [187]:
result_df.to_csv('results/Descriptors/Results_2D_3D_All_desc_const_rem_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_3D_All_desc_const_rem_MDCK.csv')

In [188]:
#All 2d and 3d descriptors LVR
df_train = pd.read_csv('features/Descriptors/Train_2d_3d_all_descriptors_MDCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
X_train,  const_col =  remove_low_variance_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_3d_all_descriptors_MDCK.csv')
df_test = df_test.dropna()
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (51, 1904)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 1904)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000412 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 6872
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 506
[LightGBM] [Info] Start training from score -5.753098
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spli

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.7086                0.7043   
DecisionTreeRegressor                    1.0126                0.8244   
RandomForestRegressor                    0.5504                0.6012   
GradientBoostingRegressor                0.5385                0.5888   
AdaBoostRegressor                        0.5484                0.5515   
XGBRegressor                             0.5697                0.5914   
ExtraTreesRegressor                      0.5428                0.6034   
LinearRegression                         0.9834                0.7889   
KNeighborsRegressor                      0.6187                0.6299   
SVR                                      0.6326                0.6335   
MLPRegressor                             1.5743                0.9401   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.8418              -0.0955   
DecisionTreeRegressor                     1.0063              -0.5654   
RandomForestRegressor                     0.7419               0.1492   
GradientBoostingRegressor                 0.7339               0.1675   
AdaBoostRegressor                         0.7405               0.1523   
XGBRegressor                              0.7548               0.1194   
ExtraTreesRegressor                       0.7367               0.1610   
LinearRegression                          0.9916              -0.5201   
KNeighborsRegressor                       0.7866               0.0435   
SVR                                       0.7953               0.0221   
MLPRegressor                              1.2547              -1.4337   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.1610                0.2433   
DecisionTreeRegressor                    0.1473                0.1949   
RandomForestRegressor                    0.3907                0.4802   
GradientBoostingRegressor                0.4348                0.5488   
AdaBoostRegressor                        0.4332                0.5336   
XGBRegressor                             0.3995                0.4236   
ExtraTreesRegressor                      0.4200                0.4529   
LinearRegression                         0.1880                0.1624   
KNeighborsRegressor                      0.3527                0.3727   
SVR                                      0.2873                0.2640   
MLPRegressor                            -0.0396                0.0469   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4106   0.5170    0.6408   0.3020   
DecisionTreeRegressor       0.3960   0.5095    0.6293   0.3269   
RandomForestRegressor       0.2802   0.4624    0.5293   0.5237   
GradientBoostingRegressor   0.3870   0.5208    0.6221   0.3421   
AdaBoostRegressor           0.2681   0.4427    0.5178   0.5442   
XGBRegressor                0.4767   0.5736    0.6904   0.1896   
ExtraTreesRegressor         0.3044   0.4737    0.5517   0.4825   
LinearRegression            1.1075   0.7275    1.0524  -0.8828   
KNeighborsRegressor         0.3545   0.4874    0.5954   0.3973   
SVR                         0.3259   0.4675    0.5709   0.4460   
MLPRegressor                0.5655   0.5911    0.7520   0.0387   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5552                    0.4429  
DecisionTreeRegressor                       0.6550                    0.4594  
RandomForestRegressor                       0.7537                    0.6245  
GradientBoostingRegressor                   0.6178                    0.4704  
AdaBoostRegressor                           0.7463                    0.6575  
XGBRegressor                                0.5752                    0.3934  
ExtraTreesRegressor                         0.709

In [189]:
result_df.to_csv('results/Descriptors/Results_2D_3D_All_desc_LVR_MDCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_3D_All_desc_LVR_MDCK.csv')

In [54]:
#Stacked architecture model
import os
import numpy as np
import pandas as pd
from sklearn.model_selection import KFold
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor, AdaBoostRegressor, ExtraTreesRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.svm import SVR
from sklearn.neural_network import MLPRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
from scipy.stats import pearsonr, spearmanr
import lightgbm as lgb
import xgboost as xgb
from tqdm import tqdm
def features(df, target_column='Permeability', threshold=0.9):
    correlation_matrix = df.corr()
    
    features_to_drop = set()
    
    for feature in correlation_matrix.columns:
        if feature == target_column:
            continue 
        target_corr = correlation_matrix[target_column][feature]
        
        for other_feature in correlation_matrix.columns:
            if other_feature == feature or other_feature == target_column:
                continue
            
            if abs(correlation_matrix[feature][other_feature]) > threshold:
                other_target_corr = correlation_matrix[target_column][other_feature]

                if abs(other_target_corr) < abs(target_corr):
                    features_to_drop.add(other_feature)
                else:
                    features_to_drop.add(feature)
    selected_features = [col for col in df.columns if col not in features_to_drop and col != target_column]
    
    return selected_features

In [55]:
def remove_low_variance_columns(df, threshold=0.005):
    # df = df.drop(['ID','SMILES','Permeability'],axis=1)
    variances = df.var()
    
    low_variance_columns = variances[variances < threshold].index.tolist()
    
    df_cleaned = df.drop(columns=low_variance_columns)
    
    return df_cleaned, low_variance_columns

In [56]:
from tqdm import tqdm
# 2D and 3D descriptors dataframes
df_desc_train = pd.read_csv('/home/users/akshay/PCPpred/MDCK/features/Descriptors/Train_2d_3d_all_descriptors_MDCK.csv')
df_train = df_desc_train.sort_values(by='ID')
df_train =df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_desc_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
df_desc_test = pd.read_csv('/home/users/akshay/PCPpred/MDCK/features/Descriptors/Test_2d_3d_all_descriptors_MDCK.csv')
df_desc_test = df_desc_test.sort_values(by='ID')
df_desc_test =df_desc_test.dropna()
df_desc_test =  df_desc_test[df_desc_train.columns]


# Fingerprints
df_fp_train = pd.read_csv('/home/users/akshay/PCPpred/MDCK/features/Fingerprints/Train/All_fingerprints_train_MDCK.csv')
df_train = df_fp_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_fp_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
df_fp_test = pd.read_csv('/home/users/akshay/PCPpred/MDCK/features/Fingerprints/Test/All_fingerprints_test_MDCK.csv')
df_fp_test = df_fp_test.sort_values(by='ID')
df_fp_test = df_fp_test.dropna()
df_fp_test =  df_fp_test[df_fp_train.columns]


#Smiles Embeddings
df_emb_train = pd.read_csv('/home/users/akshay/PCPpred/MDCK/features/Embeddings/Train_MoLFormer-XL-both-10pct_model_1_fine_tuned_embeddings_mdck.csv')
df_train = df_emb_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_emb_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
df_emb_test = pd.read_csv('/home/users/akshay/PCPpred/MDCK/features/Embeddings/Test_MoLFormer-XL-both-10pct_model_1_fine_tuned_embeddings_mdck.csv')
df_emb_test = df_emb_test.sort_values(by='ID')
df_emb_test = df_emb_test.dropna()
df_emb_test =  df_emb_test[df_emb_train.columns]

#ATomic features
df_atomic_train = pd.read_csv('/home/users/akshay/PCPpred/MDCK/features/Atomic/Train_all_atomic_desc_MDCK.csv')
df_train = df_atomic_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_atomic_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
# df_atomic_train =pd.concat( [df_train['SMILES'], df_train.select_dtypes(include=['number'])], axis=1)
df_atomic_test = pd.read_csv('/home/users/akshay/PCPpred/MDCK/features/Atomic/Test_all_atomic_desc_MDCK.csv')
df_atomic_test = df_atomic_test.sort_values(by='ID')
df_atomic_test = df_atomic_test.dropna()
df_atomic_test =  df_atomic_test[df_atomic_train.columns]


print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Data Loading completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
df_fp_test = df_fp_test[df_fp_test['ID'].isin(df_desc_test['ID'])]
df_fp_train = df_fp_train[df_fp_train['ID'].isin(df_desc_train['ID'])]

df_emb_test = df_emb_test[df_emb_test['ID'].isin(df_desc_test['ID'])]
df_emb_train = df_emb_train[df_emb_train['ID'].isin(df_desc_train['ID'])]

df_atomic_test = df_atomic_test[df_atomic_test['ID'].isin(df_desc_test['ID'])]
df_atomic_train = df_atomic_train[df_atomic_train['ID'].isin(df_desc_train['ID'])]
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Data Processing completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_desc_train.shape)
print(df_desc_test.shape)
print(df_fp_train.shape)
print(df_fp_test.shape)
print(df_emb_train.shape)
print(df_emb_test.shape)
print(df_atomic_train.shape)
print(df_atomic_test.shape)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_desc_train)
print(df_desc_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_fp_train)
print(df_fp_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_emb_train)
print(df_emb_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_atomic_train)
print(df_atomic_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
target_column = 'Permeability'
def scale_features(df_train, df_test):
    scaler = StandardScaler()
    train_features = df_train.drop(columns=['ID', 'SMILES', target_column])
    test_features = df_test.drop(columns=['ID', 'SMILES', target_column])
    scaler.fit(train_features)
    train_scaled = pd.DataFrame(scaler.transform(train_features), columns=train_features.columns, index=df_train.index)
    test_scaled = pd.DataFrame(scaler.transform(test_features), columns=test_features.columns, index=df_test.index)
    df_train_scaled = pd.concat([df_train[['ID', 'SMILES', target_column]], train_scaled], axis=1)
    df_test_scaled = pd.concat([df_test[['ID', 'SMILES', target_column]], test_scaled], axis=1)
    return df_train_scaled, df_test_scaled

df_desc_train, df_desc_test = scale_features(df_desc_train, df_desc_test)
df_fp_train, df_fp_test = scale_features(df_fp_train, df_fp_test)
df_emb_train, df_emb_test = scale_features(df_emb_train, df_emb_test)
df_atomic_train, df_atomic_test = scale_features(df_atomic_train, df_atomic_test)
models_weak = [
    lgb.LGBMRegressor(objective='regression', metric='rmse', boosting_type='gbdt', num_leaves=31, learning_rate=0.05, random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    KNeighborsRegressor(),
    SVR(),   
    MLPRegressor(random_state=101, max_iter=500),
    DecisionTreeRegressor(random_state=101),
]

models_meta = [
    lgb.LGBMRegressor(objective='regression', metric='rmse', boosting_type='gbdt', num_leaves=31, learning_rate=0.05, random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(),
    KNeighborsRegressor(),
    SVR(),
    MLPRegressor(random_state=101)
]


XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
Data Loading completed
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
Data Processing completed
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
(51, 170)
(13, 170)
(51, 90)
(13, 90)
(51, 625)
(13, 625)
(51, 8)
(13, 8)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
      ID                                             SMILES  Permeability  \
47  1017  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...     -6.550000   
43  1018  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...     -4.500000   
9   1107  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N...     -4.610000   
41  1109  C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@@H](C)N(C)C(...     -6.120000   
11  1110  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[

In [57]:
dataframes = [(df_desc_train, df_desc_test), (df_fp_train, df_fp_test), (df_emb_train, df_emb_test), (df_atomic_train, df_atomic_test)]
target_column = 'Permeability'


meta_features_train = []
meta_features_test = []

# Stage 1: Train weak learners with 5-fold cross-validation
for df_train, df_test in tqdm(dataframes, desc="Processing dataframe pairs"):
    X_weak = df_train.drop(columns=['ID', 'SMILES', target_column])
    X_eval = df_test.drop(columns=['ID', 'SMILES', target_column])
    y_weak = df_train[target_column]
    y_eval = df_test[target_column]

    kf = KFold(n_splits=5, shuffle=True, random_state=101)

    # Storing predictions for the current dataframe
    fold_meta_features_train = np.zeros((X_weak.shape[0], len(models_weak)))
    fold_meta_features_test = np.zeros((X_eval.shape[0], len(models_weak)))

    for i, model in tqdm(enumerate(models_weak), desc="Training models"):
        fold_predictions = np.zeros(X_weak.shape[0])
        test_predictions_folds = []

        for train_index, val_index in kf.split(X_weak):
            X_train, X_val = X_weak.iloc[train_index], X_weak.iloc[val_index]
            y_train, y_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
            
            model.fit(X_train, y_train)

            # Predictions for validation set
            fold_predictions[val_index] =  np.clip( model.predict(X_val), -10, -4.0)

            # Predictions for test set
            test_predictions_fold =  np.clip( model.predict(X_eval), -10, -4.0)
            test_predictions_folds.append(test_predictions_fold)

        # Store predictions for the meta-learner
        fold_meta_features_train[:, i] = fold_predictions
        fold_meta_features_test[:, i] = np.mean(test_predictions_folds, axis=0)

    meta_features_train.append(fold_meta_features_train)
    meta_features_test.append(fold_meta_features_test)

# Convert lists to arrays for the meta-learner
meta_features_train = np.hstack(meta_features_train)
meta_features_test = np.hstack(meta_features_test)

print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print("Dimensions of meta_features_train:", meta_features_train.shape)
print("Dimensions of meta_features_test:", meta_features_test.shape)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Stage 1 completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')

# Stage 2: Train the meta-learner using predictions from weak learners
kf = KFold(n_splits=5, shuffle=True, random_state=101)
results = {}
predictions = []
for model in models_meta:
    model_name = model.__class__.__name__
    predictions_train = []
    actual_y_train = []
    
    test_predictions_folds = []

    for train_index, val_index in kf.split(meta_features_train):
        X_fold_train, X_fold_val = meta_features_train[train_index], meta_features_train[val_index]
        y_fold_train, y_fold_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
        
        model.fit(X_fold_train, y_fold_train)

        y_pred_fold = model.predict(X_fold_val)
        y_pred_fold = np.clip(y_pred_fold, -10, -4.0)
        predictions_train.extend(y_pred_fold)
        actual_y_train.extend(y_fold_val)

        # Predictions for test set
        test_predictions_fold = model.predict(meta_features_test)
        test_predictions_fold = np.clip(test_predictions_fold, -10, -4.0)
        test_predictions_folds.append(test_predictions_fold)

    # Metrics
    predictions_test_mean = np.mean(test_predictions_folds, axis=0)
    predictions_test_std = np.std(test_predictions_folds, axis=0)

    mse_train = mean_squared_error(actual_y_train, predictions_train)
    mae_train = mean_absolute_error(actual_y_train, predictions_train)
    rmse_train = np.sqrt(mse_train)
    r2_train = r2_score(actual_y_train, predictions_train)
    pearson_train, _ = pearsonr(actual_y_train, predictions_train)
    spearman_train, _ = spearmanr(actual_y_train, predictions_train)

    mse_test = mean_squared_error(y_eval, predictions_test_mean)
    mae_test = mean_absolute_error(y_eval, predictions_test_mean)
    rmse_test = np.sqrt(mse_test)
    r2_test = r2_score(y_eval, predictions_test_mean)
    pearson_test, _ = pearsonr(y_eval, predictions_test_mean)
    spearman_test, _ = spearmanr(y_eval, predictions_test_mean)
    print(f'{model_name} Evaluation completed: Test R2 score: {r2_test}')

    predictions.append({
            'Model': model_name,
            'Y Train pred': predictions_train,
            'Y Test actual': y_eval,
            'Test prediction folds': test_predictions_folds,
            'Test Predictions Mean': predictions_test_mean,
            'Test Predictions Std': predictions_test_std,

        })

    results[model_name] = {
        'Train MSE (5 fold CV)': mse_train,
        'Train MAE (5 fold CV)': mae_train,
        'Train RMSE (5 fold CV)': rmse_train,
        'Train R2 (5 fold CV)': r2_train,
        'Train PCC (5 fold CV)': pearson_train,
        'Train SCC (5 fold CV)': spearman_train,
        'Test MSE': mse_test,
        'Test MAE': mae_test,
        'Test RMSE': rmse_test,
        'Test R2': r2_test,
        'Test PCC': pearson_test,
        'Test SCC': spearman_test,
    }

results_df = pd.DataFrame(results).T
prediction_df = pd.DataFrame(predictions)
results_df

Processing dataframe pairs:   0%|          | 0/4 [00:00<?, ?it/s]
Training models: 0it [00:00, ?it/s]
Training models: 1it [00:00,  7.05it/s]

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000472 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 576
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 41
[LightGBM] [Info] Start training from score -5.726629
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, be


Training models: 2it [00:01,  1.01it/s]
Training models: 3it [00:02,  1.07it/s]
Training models: 4it [00:03,  1.31it/s]
Training models: 5it [00:04,  1.08it/s]
Training models: 6it [00:05,  1.00s/it]
Training models: 10it [00:05,  1.70it/s][A
Processing dataframe pairs:  25%|██▌       | 1/4 [00:05<00:17,  5.89s/it]
Training models: 0it [00:00, ?it/s]

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.084261 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 15
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 2
[LightGBM] [Info] Start training from score -5.726629
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best


Training models: 1it [00:00,  2.90it/s]

...


Training models: 2it [00:01,  1.04it/s]
Training models: 3it [00:04,  1.85s/it]
Training models: 4it [00:05,  1.58s/it]
Training models: 5it [00:07,  1.74s/it]
Training models: 6it [00:09,  1.57s/it]
Training models: 8it [00:09,  1.21it/s]
Training models: 10it [00:10,  1.02s/it][A
Processing dataframe pairs:  75%|███████▌  | 3/4 [00:20<00:07,  7.46s/it]
Training models: 0it [00:00, ?it/s]

[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 0
[LightGBM] [Info] Start training from score -5.726629
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the spl


Training models: 2it [00:01,  1.13it/s]
Training models: 3it [00:01,  1.69it/s]
Training models: 5it [00:02,  2.46it/s]
Training models: 6it [00:03,  1.62it/s]/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (500) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (500) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (500) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packag

XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
Dimensions of meta_features_train: (51, 40)
Dimensions of meta_features_test: (13, 40)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
Stage 1 completed
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000203 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 40
[LightGBM] [Info] Number of data points in the train set: 40, number of used features: 3
[LightGBM] [Info] Start training from score -5.726629
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain:

Train MSE (5 fold CV)  Train MAE (5 fold CV)  \
LGBMRegressor                           0.672759               0.677840   
DecisionTreeRegressor                   1.007549               0.782618   
RandomForestRegressor                   0.643900               0.650612   
GradientBoostingRegressor               0.790305               0.730456   
AdaBoostRegressor                       0.760666               0.690092   
XGBRegressor                            0.755171               0.682201   
ExtraTreesRegressor                     0.609198               0.627755   
LinearRegression                        8.711717               2.495084   
KNeighborsRegressor                     0.672736               0.671215   
SVR                                     0.703345               0.695584   
MLPRegressor                            1.050894               0.849980   

                           Train RMSE (5 fold CV)  Train R2 (5 fold CV)  \
LGBMRegressor                            0.820219             -0.039984   
DecisionTreeRegressor                    1.003767             -0.557519   
RandomForestRegressor                    0.802434              0.004628   
GradientBoostingRegressor                0.888991             -0.221692   
AdaBoostRegressor                        0.872162             -0.175875   
XGBRegressor                             0.869006             -0.167380   
ExtraTreesRegressor                      0.780511              0.058272   
LinearRegression                         2.951562            -12.466998   
KNeighborsRegressor                      0.820205             -0.039949   
SVR                                      0.838657             -0.087265   
MLPRegressor                             1.025131             -0.624523   

                           Train PCC (5 fold CV)  Train SCC (5 fold CV)  \
LGBMRegressor                           0.173311               0.190018   
DecisionTreeRegressor                   0.123583               0.246589   
RandomForestRegressor                   0.269170               0.358289   
GradientBoostingRegressor               0.171261               0.225797   
AdaBoostRegressor                       0.209868               0.291342   
XGBRegressor                            0.208131               0.290369   
ExtraTreesRegressor                     0.315770               0.398833   
LinearRegression                        0.089163               0.043912   
KNeighborsRegressor                     0.185641               0.173522   
SVR                                     0.099546               0.066925   
MLPRegressor                            0.210149               0.218602   

                           Test MSE  Test MAE  Test RMSE   Test R2  Test PCC  \
LGBMRegressor              0.412700  0.532822   0.642417  0.298399  0.588641   
DecisionTreeRegressor      0.485365  0.620955   0.696681  0.174866  0.457657   
RandomForestRegressor      0.341112  0.528744   0.584048  0.420100  0.666757   
GradientBoostingRegressor  0.406180  0.563063   0.637323  0.309481  0.558272   
AdaBoostRegressor          0.359522  0.526723   0.599602  0.388802  0.634750   
XGBRegressor               0.374868  0.511002   0.612265  0.362714  0.603567   
ExtraTreesRegressor        0.445883  0.577411   0.667745  0.241986  0.500408   
LinearRegression           1.840420  1.114424   1.356621 -2.128767 -0.131687   
KNeighborsRegressor        0.468766  0.603475   0.684665  0.203084  0.456649   
SVR                        0.440483  0.525037   0.663689  0.251165  0.565083   
MLPRegressor               0.805157  0.765349   0.897306 -0.368791  0.753597   

                           Test SCC  
LGBMRegressor              0.493113  
DecisionTreeRegressor      0.277854  
RandomForestRegressor      0.398900  
GradientBoostingRegressor  0.316369  
AdaBoostRegressor          0.310867  
XGBRegressor               0.398900  
ExtraTreesRegressor        0.261348  
LinearRegression          -0.294361  
KNeighborsRegressor  

In [58]:
results_df.to_csv('/home/users/akshay/PCPpred/MDCK/results/Stacked/Results_5_folds_stacked_archi_MDCK.csv')
prediction_df.to_csv('/home/users/akshay/PCPpred/MDCK/results/Stacked/Prediction_data_5_folds_stacked_archi_MDCK.csv')

In [59]:
dataframes = [(df_desc_train, df_desc_test), (df_fp_train, df_fp_test), (df_emb_train, df_emb_test), (df_atomic_train, df_atomic_test)]
target_column = 'Permeability'


meta_features_train = []
meta_features_test = []

# Stage 1: Train weak learners with 10-fold cross-validation
for df_train, df_test in tqdm(dataframes, desc="Processing dataframe pairs"):
    X_weak = df_train.drop(columns=['ID', 'SMILES', target_column])
    X_eval = df_test.drop(columns=['ID', 'SMILES', target_column])
    y_weak = df_train[target_column]
    y_eval = df_test[target_column]

    kf = KFold(n_splits=10, shuffle=True, random_state=101)

    # Storing predictions for the current dataframe
    fold_meta_features_train = np.zeros((X_weak.shape[0], len(models_weak)))
    fold_meta_features_test = np.zeros((X_eval.shape[0], len(models_weak)))

    for i, model in tqdm(enumerate(models_weak), desc="Training models"):
        fold_predictions = np.zeros(X_weak.shape[0])
        test_predictions_folds = []

        for train_index, val_index in kf.split(X_weak):
            X_train, X_val = X_weak.iloc[train_index], X_weak.iloc[val_index]
            y_train, y_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
            
            model.fit(X_train, y_train)

            # Predictions for validation set
            fold_predictions[val_index] =  np.clip( model.predict(X_val), -10, -4.0)

            # Predictions for test set
            test_predictions_fold =  np.clip( model.predict(X_eval), -10, -4.0)
            test_predictions_folds.append(test_predictions_fold)

        # Store predictions for the meta-learner
        fold_meta_features_train[:, i] = fold_predictions
        fold_meta_features_test[:, i] = np.mean(test_predictions_folds, axis=0)

    meta_features_train.append(fold_meta_features_train)
    meta_features_test.append(fold_meta_features_test)

# Convert lists to arrays for the meta-learner
meta_features_train = np.hstack(meta_features_train)
meta_features_test = np.hstack(meta_features_test)

print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print("Dimensions of meta_features_train:", meta_features_train.shape)
print("Dimensions of meta_features_test:", meta_features_test.shape)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Stage 1 completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')

# Stage 2: Train the meta-learner using predictions from weak learners
kf = KFold(n_splits=10, shuffle=True, random_state=101)
results = {}
predictions = []
for model in models_meta:
    model_name = model.__class__.__name__
    predictions_train = []
    actual_y_train = []
    
    test_predictions_folds = []

    for train_index, val_index in kf.split(meta_features_train):
        X_fold_train, X_fold_val = meta_features_train[train_index], meta_features_train[val_index]
        y_fold_train, y_fold_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
        
        model.fit(X_fold_train, y_fold_train)

        y_pred_fold = model.predict(X_fold_val)
        y_pred_fold = np.clip(y_pred_fold, -10, -4.0)
        predictions_train.extend(y_pred_fold)
        actual_y_train.extend(y_fold_val)

        # Predictions for test set
        test_predictions_fold = model.predict(meta_features_test)
        test_predictions_fold = np.clip(test_predictions_fold, -10, -4.0)
        test_predictions_folds.append(test_predictions_fold)

    # Metrics
    predictions_test_mean = np.mean(test_predictions_folds, axis=0)
    predictions_test_std = np.std(test_predictions_folds, axis=0)

    mse_train = mean_squared_error(actual_y_train, predictions_train)
    mae_train = mean_absolute_error(actual_y_train, predictions_train)
    rmse_train = np.sqrt(mse_train)
    r2_train = r2_score(actual_y_train, predictions_train)
    pearson_train, _ = pearsonr(actual_y_train, predictions_train)
    spearman_train, _ = spearmanr(actual_y_train, predictions_train)

    mse_test = mean_squared_error(y_eval, predictions_test_mean)
    mae_test = mean_absolute_error(y_eval, predictions_test_mean)
    rmse_test = np.sqrt(mse_test)
    r2_test = r2_score(y_eval, predictions_test_mean)
    pearson_test, _ = pearsonr(y_eval, predictions_test_mean)
    spearman_test, _ = spearmanr(y_eval, predictions_test_mean)
    print(f'{model_name} Evaluation completed: Test R2 score: {r2_test}')

    predictions.append({
            'Model': model_name,
            'Y Train pred': predictions_train,
            'Y Test actual': y_eval,
            'Test prediction folds': test_predictions_folds,
            'Test Predictions Mean': predictions_test_mean,
            'Test Predictions Std': predictions_test_std,

        })

    results[model_name] = {
        'Train MSE (10 fold CV)': mse_train,
        'Train MAE (10 fold CV)': mae_train,
        'Train RMSE (10 fold CV)': rmse_train,
        'Train R2 (10 fold CV)': r2_train,
        'Train PCC (10 fold CV)': pearson_train,
        'Train SCC (10 fold CV)': spearman_train,
        'Test MSE': mse_test,
        'Test MAE': mae_test,
        'Test RMSE': rmse_test,
        'Test R2': r2_test,
        'Test PCC': pearson_test,
        'Test SCC': spearman_test,
    }

results_df = pd.DataFrame(results).T
prediction_df = pd.DataFrame(predictions)
results_df

Processing dataframe pairs:   0%|          | 0/4 [00:00<?, ?it/s]
Training models: 0it [00:00, ?it/s]

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.022931 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2471
[LightGBM] [Info] Number of data points in the train set: 45, number of used features: 159
[LightGBM] [Info] Start training from score -5.697548
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 


Training models: 1it [00:00,  2.92it/s]

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001252 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2541
[LightGBM] [Info] Number of data points in the train set: 46, number of used features: 159
[LightGBM] [Info] Start training from score -5.634214
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 


Training models: 2it [00:03,  1.99s/it]
Training models: 3it [00:05,  1.96s/it]
Training models: 4it [00:06,  1.60s/it]
Training models: 5it [00:08,  1.72s/it]
Training models: 6it [00:10,  1.99s/it]
Training models: 7it [00:11,  1.40s/it]
Training models: 10it [00:11,  1.20s/it][A
Processing dataframe pairs:  25%|██▌       | 1/4 [00:11<00:35, 11.97s/it]
Training models: 0it [00:00, ?it/s]

...

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: F

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


RandomForestRegressor Evaluation completed: Test R2 score: 0.4968325536353675
GradientBoostingRegressor Evaluation completed: Test R2 score: 0.30981015223818675
AdaBoostRegressor Evaluation completed: Test R2 score: 0.40945978620869417
XGBRegressor Evaluation completed: Test R2 score: 0.3211462673156895
ExtraTreesRegressor Evaluation completed: Test R2 score: 0.37224168827583015
LinearRegression Evaluation completed: Test R2 score: -0.3331303192510191
KNeighborsRegressor Evaluation completed: Test R2 score: 0.26824945515748644
SVR Evaluation completed: Test R2 score: 0.24929234952007218
MLPRegressor Evaluation completed: Test R2 score: -0.48373968843332626


Train MSE (10 fold CV)  Train MAE (10 fold CV)  \
LGBMRegressor                            0.551521                0.617126   
DecisionTreeRegressor                    1.019389                0.771138   
RandomForestRegressor                    0.538691                0.581182   
GradientBoostingRegressor                0.667545                0.631001   
AdaBoostRegressor                        0.654182                0.630173   
XGBRegressor                             0.648811                0.613275   
ExtraTreesRegressor                      0.567393                0.603428   
LinearRegression                         2.921970                1.295671   
KNeighborsRegressor                      0.666412                0.637890   
SVR                                      0.642510                0.651104   
MLPRegressor                             1.180590                0.901195   

                           Train RMSE (10 fold CV)  Train R2 (10 fold CV)  \
LGBMRegressor                             0.742645               0.147432   
DecisionTreeRegressor                     1.009648              -0.575822   
RandomForestRegressor                     0.733956               0.167266   
GradientBoostingRegressor                 0.817034              -0.031924   
AdaBoostRegressor                         0.808815              -0.011267   
XGBRegressor                              0.805488              -0.002964   
ExtraTreesRegressor                       0.753255               0.122896   
LinearRegression                          1.709377              -3.516924   
KNeighborsRegressor                       0.816341              -0.030173   
SVR                                       0.801567               0.006777   
MLPRegressor                              1.086549              -0.825013   

                           Train PCC (10 fold CV)  Train SCC (10 fold CV)  \
LGBMRegressor                            0.393938                0.395538   
DecisionTreeRegressor                    0.217659                0.401340   
RandomForestRegressor                    0.438130                0.481504   
GradientBoostingRegressor                0.344811                0.426661   
AdaBoostRegressor                        0.325032                0.427893   
XGBRegressor                             0.378363                0.425485   
ExtraTreesRegressor                      0.396200                0.470780   
LinearRegression                         0.279559                0.279425   
KNeighborsRegressor                      0.202036                0.228738   
SVR                                      0.251528                0.227924   
MLPRegressor                             0.130361                0.108238   

                           Test MSE  Test MAE  Test RMSE   Test R2  Test PCC  \
LGBMRegressor              0.402364  0.539872   0.634322  0.315969  0.580779   
DecisionTreeRegressor      0.406236  0.547043   0.637367  0.309386  0.572756   
RandomForestRegressor      0.295976  0.481985   0.544037  0.496833  0.720522   
GradientBoostingRegressor  0.405987  0.527839   0.637171  0.309810  0.627320   
AdaBoostRegressor          0.347371  0.487988   0.589382  0.409460  0.723742   
XGBRegressor               0.399319  0.521251   0.631917  0.321146  0.646088   
ExtraTreesRegressor        0.369263  0.491644   0.607670  0.372242  0.652011   
LinearRegression           0.784181  0.684510   0.885540 -0.333130  0.586585   
KNeighborsRegressor        0.430434  0.571900   0.656075  0.268249  0.553076   
SVR                        0.441585  0.521238   0.664519  0.249292  0.617169   
MLPRegressor               0.872773  0.810202   0.934223 -0.483740  0.756195   

                           Test SCC  
LGBMRegressor              0.464925  
DecisionTreeRegressor      0.453921  
RandomForestRegressor      0.431912  
GradientBoostingRegressor  0.431912  
AdaBoostRegressor          0.547456  
XGBRegressor               0.492435  
ExtraTreesRegressor      

In [60]:
results_df.to_csv('/home/users/akshay/PCPpred/MDCK/results/Stacked/Results_10_folds_stacked_archi_MDCK.csv')
prediction_df.to_csv('/home/users/akshay/PCPpred/MDCK/results/Stacked/Prediction_data_10_folds_stacked_archi_MDCK.csv')

In [61]:
dataframes = [(df_desc_train, df_desc_test), (df_fp_train, df_fp_test), (df_emb_train, df_emb_test), (df_atomic_train, df_atomic_test)]
target_column = 'Permeability'


meta_features_train = []
meta_features_test = []

# Stage 1: Train weak learners with 15-fold cross-validation
for df_train, df_test in tqdm(dataframes, desc="Processing dataframe pairs"):
    X_weak = df_train.drop(columns=['ID', 'SMILES', target_column])
    X_eval = df_test.drop(columns=['ID', 'SMILES', target_column])
    y_weak = df_train[target_column]
    y_eval = df_test[target_column]

    kf = KFold(n_splits=15, shuffle=True, random_state=101)

    # Storing predictions for the current dataframe
    fold_meta_features_train = np.zeros((X_weak.shape[0], len(models_weak)))
    fold_meta_features_test = np.zeros((X_eval.shape[0], len(models_weak)))

    for i, model in tqdm(enumerate(models_weak), desc="Training models"):
        fold_predictions = np.zeros(X_weak.shape[0])
        test_predictions_folds = []

        for train_index, val_index in kf.split(X_weak):
            X_train, X_val = X_weak.iloc[train_index], X_weak.iloc[val_index]
            y_train, y_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
            
            model.fit(X_train, y_train)

            # Predictions for validation set
            fold_predictions[val_index] =  np.clip( model.predict(X_val), -10, -4.0)

            # Predictions for test set
            test_predictions_fold =  np.clip( model.predict(X_eval), -10, -4.0)
            test_predictions_folds.append(test_predictions_fold)

        # Store predictions for the meta-learner
        fold_meta_features_train[:, i] = fold_predictions
        fold_meta_features_test[:, i] = np.mean(test_predictions_folds, axis=0)

    meta_features_train.append(fold_meta_features_train)
    meta_features_test.append(fold_meta_features_test)

# Convert lists to arrays for the meta-learner
meta_features_train = np.hstack(meta_features_train)
meta_features_test = np.hstack(meta_features_test)

print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print("Dimensions of meta_features_train:", meta_features_train.shape)
print("Dimensions of meta_features_test:", meta_features_test.shape)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Stage 1 completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')

# Stage 2: Train the meta-learner using predictions from weak learners
kf = KFold(n_splits=15, shuffle=True, random_state=101)
results = {}
predictions = []
for model in models_meta:
    model_name = model.__class__.__name__
    predictions_train = []
    actual_y_train = []
    
    test_predictions_folds = []

    for train_index, val_index in kf.split(meta_features_train):
        X_fold_train, X_fold_val = meta_features_train[train_index], meta_features_train[val_index]
        y_fold_train, y_fold_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
        
        model.fit(X_fold_train, y_fold_train)

        y_pred_fold = model.predict(X_fold_val)
        y_pred_fold = np.clip(y_pred_fold, -10, -4.0)
        predictions_train.extend(y_pred_fold)
        actual_y_train.extend(y_fold_val)

        # Predictions for test set
        test_predictions_fold = model.predict(meta_features_test)
        test_predictions_fold = np.clip(test_predictions_fold, -10, -4.0)
        test_predictions_folds.append(test_predictions_fold)

    # Metrics
    predictions_test_mean = np.mean(test_predictions_folds, axis=0)
    predictions_test_std = np.std(test_predictions_folds, axis=0)

    mse_train = mean_squared_error(actual_y_train, predictions_train)
    mae_train = mean_absolute_error(actual_y_train, predictions_train)
    rmse_train = np.sqrt(mse_train)
    r2_train = r2_score(actual_y_train, predictions_train)
    pearson_train, _ = pearsonr(actual_y_train, predictions_train)
    spearman_train, _ = spearmanr(actual_y_train, predictions_train)

    mse_test = mean_squared_error(y_eval, predictions_test_mean)
    mae_test = mean_absolute_error(y_eval, predictions_test_mean)
    rmse_test = np.sqrt(mse_test)
    r2_test = r2_score(y_eval, predictions_test_mean)
    pearson_test, _ = pearsonr(y_eval, predictions_test_mean)
    spearman_test, _ = spearmanr(y_eval, predictions_test_mean)
    print(f'{model_name} Evaluation completed: Test R2 score: {r2_test}')

    predictions.append({
            'Model': model_name,
            'Y Train pred': predictions_train,
            'Y Test actual': y_eval,
            'Test prediction folds': test_predictions_folds,
            'Test Predictions Mean': predictions_test_mean,
            'Test Predictions Std': predictions_test_std,

        })

    results[model_name] = {
        'Train MSE (15 fold CV)': mse_train,
        'Train MAE (15 fold CV)': mae_train,
        'Train RMSE (15 fold CV)': rmse_train,
        'Train R2 (15 fold CV)': r2_train,
        'Train PCC (15 fold CV)': pearson_train,
        'Train SCC (15 fold CV)': spearman_train,
        'Test MSE': mse_test,
        'Test MAE': mae_test,
        'Test RMSE': rmse_test,
        'Test R2': r2_test,
        'Test PCC': pearson_test,
        'Test SCC': spearman_test,
    }

results_df = pd.DataFrame(results).T
prediction_df = pd.DataFrame(predictions)
results_df

Processing dataframe pairs:   0%|          | 0/4 [00:00<?, ?it/s]
Training models: 0it [00:00, ?it/s]

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.005858 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2589
[LightGBM] [Info] Number of data points in the train set: 47, number of used features: 159
[LightGBM] [Info] Start training from score -5.715950
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: 


Training models: 1it [00:00,  1.87it/s]

[LightGBM] [Info] Total Bins 2641
[LightGBM] [Info] Number of data points in the train set: 48, number of used features: 160
[LightGBM] [Info] Start training from score -5.687277
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -


Training models: 2it [00:13,  7.91s/it]
Training models: 3it [00:16,  5.66s/it]
Training models: 4it [00:18,  4.08s/it]
Training models: 5it [06:39, 139.96s/it]
Training models: 6it [06:54, 97.63s/it] 
Training models: 7it [06:58, 66.99s/it]
Training models: 9it [07:09, 37.39s/it]
Training models: 10it [07:09, 43.00s/it]
Processing dataframe pairs:  25%|██▌       | 1/4 [07:09<21:29, 430.00s/it]
Training models: 0it [00:00, ?it/s]

...


Training models: 2it [00:05,  2.94s/it]
Training models: 3it [00:05,  1.83s/it]
Training models: 4it [00:05,  1.19s/it]
Training models: 5it [00:07,  1.43s/it]
Training models: 6it [00:11,  2.26s/it]/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (500) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (500) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (500) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anacond

XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
Dimensions of meta_features_train: (51, 40)
Dimensions of meta_features_test: (13, 40)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
Stage 1 completed
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000894 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 654
[LightGBM] [Info] Number of data points in the train set: 47, number of used features: 40
[LightGBM] [Info] Start training from score -5.715950
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gai

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: F

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000429 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 662
[LightGBM] [Info] Number of data points in the train set: 48, number of used features: 40
[LightGBM] [Info] Start training from score -5.652255
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, be

Train MSE (15 fold CV)  Train MAE (15 fold CV)  \
LGBMRegressor                            0.514498                0.586608   
DecisionTreeRegressor                    0.812082                0.687269   
RandomForestRegressor                    0.575855                0.591858   
GradientBoostingRegressor                0.594772                0.606723   
AdaBoostRegressor                        0.617556                0.613691   
XGBRegressor                             0.781390                0.663404   
ExtraTreesRegressor                      0.487118                0.537305   
LinearRegression                         2.437114                1.238250   
KNeighborsRegressor                      0.464257                0.504093   
SVR                                      0.596423                0.639540   
MLPRegressor                             1.022372                0.828193   

                           Train RMSE (15 fold CV)  Train R2 (15 fold CV)  \
LGBMRegressor                             0.717285               0.204663   
DecisionTreeRegressor                     0.901156              -0.255356   
RandomForestRegressor                     0.758851               0.109815   
GradientBoostingRegressor                 0.771214               0.080573   
AdaBoostRegressor                         0.785847               0.045352   
XGBRegressor                              0.883963              -0.207911   
ExtraTreesRegressor                       0.697938               0.246989   
LinearRegression                          1.561126              -2.767409   
KNeighborsRegressor                       0.681364               0.282329   
SVR                                       0.772284               0.078020   
MLPRegressor                              1.011124              -0.580433   

                           Train PCC (15 fold CV)  Train SCC (15 fold CV)  \
LGBMRegressor                            0.452797                0.445583   
DecisionTreeRegressor                    0.299210                0.237343   
RandomForestRegressor                    0.381461                0.451277   
GradientBoostingRegressor                0.398492                0.371502   
AdaBoostRegressor                        0.358927                0.344495   
XGBRegressor                             0.287151                0.287292   
ExtraTreesRegressor                      0.503174                0.549062   
LinearRegression                         0.302817                0.246561   
KNeighborsRegressor                      0.537362                0.455033   
SVR                                      0.325459                0.303763   
MLPRegressor                             0.210811                0.195661   

                           Test MSE  Test MAE  Test RMSE   Test R2  Test PCC  \
LGBMRegressor              0.482803  0.589332   0.694840  0.179221  0.460191   
DecisionTreeRegressor      0.351141  0.490043   0.592571  0.403051  0.753973   
RandomForestRegressor      0.271042  0.478720   0.520617  0.539221  0.757333   
GradientBoostingRegressor  0.339599  0.476943   0.582751  0.422673  0.743347   
AdaBoostRegressor          0.299102  0.499617   0.546902  0.491518  0.733347   
XGBRegressor               0.304233  0.498019   0.551574  0.482795  0.713454   
ExtraTreesRegressor        0.358384  0.510474   0.598652  0.390736  0.682964   
LinearRegression           0.591434  0.646079   0.769048 -0.005456  0.656641   
KNeighborsRegressor        0.402119  0.550019   0.634128  0.316386  0.637926   
SVR                        0.439060  0.537055   0.662616  0.253585  0.633955   
MLPRegressor               0.797735  0.773790   0.893160 -0.356172  0.743953   

                           Test SCC  
LGBMRegressor              0.253444  
DecisionTreeRegressor      0.668501  
RandomForestRegressor      0.442917  
GradientBoostingRegressor  0.569464  
AdaBoostRegressor          0.376892  
XGBRegressor               0.541954  
ExtraTreesRegressor      

In [62]:
results_df.to_csv('/home/users/akshay/PCPpred/MDCK/results/Stacked/Results_15_folds_stacked_archi_MDCK.csv')
prediction_df.to_csv('/home/users/akshay/PCPpred/MDCK/results/Stacked/Prediction_data_15_folds_stacked_archi_MDCK.csv')

In [63]:
dataframes = [(df_desc_train, df_desc_test), (df_fp_train, df_fp_test), (df_emb_train, df_emb_test), (df_atomic_train, df_atomic_test)]
target_column = 'Permeability'


meta_features_train = []
meta_features_test = []

# Stage 1: Train weak learners with 20-fold cross-validation
for df_train, df_test in tqdm(dataframes, desc="Processing dataframe pairs"):
    X_weak = df_train.drop(columns=['ID', 'SMILES', target_column])
    X_eval = df_test.drop(columns=['ID', 'SMILES', target_column])
    y_weak = df_train[target_column]
    y_eval = df_test[target_column]

    kf = KFold(n_splits=20, shuffle=True, random_state=101)

    # Storing predictions for the current dataframe
    fold_meta_features_train = np.zeros((X_weak.shape[0], len(models_weak)))
    fold_meta_features_test = np.zeros((X_eval.shape[0], len(models_weak)))

    for i, model in tqdm(enumerate(models_weak), desc="Training models"):
        fold_predictions = np.zeros(X_weak.shape[0])
        test_predictions_folds = []

        for train_index, val_index in kf.split(X_weak):
            X_train, X_val = X_weak.iloc[train_index], X_weak.iloc[val_index]
            y_train, y_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
            
            model.fit(X_train, y_train)

            # Predictions for validation set
            fold_predictions[val_index] =  np.clip( model.predict(X_val), -10, -4.0)

            # Predictions for test set
            test_predictions_fold =  np.clip( model.predict(X_eval), -10, -4.0)
            test_predictions_folds.append(test_predictions_fold)

        # Store predictions for the meta-learner
        fold_meta_features_train[:, i] = fold_predictions
        fold_meta_features_test[:, i] = np.mean(test_predictions_folds, axis=0)

    meta_features_train.append(fold_meta_features_train)
    meta_features_test.append(fold_meta_features_test)

# Convert lists to arrays for the meta-learner
meta_features_train = np.hstack(meta_features_train)
meta_features_test = np.hstack(meta_features_test)

print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print("Dimensions of meta_features_train:", meta_features_train.shape)
print("Dimensions of meta_features_test:", meta_features_test.shape)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Stage 1 completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')

# Stage 2: Train the meta-learner using predictions from weak learners
kf = KFold(n_splits=20, shuffle=True, random_state=101)
results = {}
predictions = []
for model in models_meta:
    model_name = model.__class__.__name__
    predictions_train = []
    actual_y_train = []
    
    test_predictions_folds = []

    for train_index, val_index in kf.split(meta_features_train):
        X_fold_train, X_fold_val = meta_features_train[train_index], meta_features_train[val_index]
        y_fold_train, y_fold_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
        
        model.fit(X_fold_train, y_fold_train)

        y_pred_fold = model.predict(X_fold_val)
        y_pred_fold = np.clip(y_pred_fold, -10, -4.0)
        predictions_train.extend(y_pred_fold)
        actual_y_train.extend(y_fold_val)

        # Predictions for test set
        test_predictions_fold = model.predict(meta_features_test)
        test_predictions_fold = np.clip(test_predictions_fold, -10, -4.0)
        test_predictions_folds.append(test_predictions_fold)

    # Metrics
    predictions_test_mean = np.mean(test_predictions_folds, axis=0)
    predictions_test_std = np.std(test_predictions_folds, axis=0)

    mse_train = mean_squared_error(actual_y_train, predictions_train)
    mae_train = mean_absolute_error(actual_y_train, predictions_train)
    rmse_train = np.sqrt(mse_train)
    r2_train = r2_score(actual_y_train, predictions_train)
    pearson_train, _ = pearsonr(actual_y_train, predictions_train)
    spearman_train, _ = spearmanr(actual_y_train, predictions_train)

    mse_test = mean_squared_error(y_eval, predictions_test_mean)
    mae_test = mean_absolute_error(y_eval, predictions_test_mean)
    rmse_test = np.sqrt(mse_test)
    r2_test = r2_score(y_eval, predictions_test_mean)
    pearson_test, _ = pearsonr(y_eval, predictions_test_mean)
    spearman_test, _ = spearmanr(y_eval, predictions_test_mean)
    print(f'{model_name} Evaluation completed: Test R2 score: {r2_test}')

    predictions.append({
            'Model': model_name,
            'Y Train pred': predictions_train,
            'Y Test actual': y_eval,
            'Test prediction folds': test_predictions_folds,
            'Test Predictions Mean': predictions_test_mean,
            'Test Predictions Std': predictions_test_std,

        })

    results[model_name] = {
        'Train MSE (20 fold CV)': mse_train,
        'Train MAE (20 fold CV)': mae_train,
        'Train RMSE (20 fold CV)': rmse_train,
        'Train R2 (20 fold CV)': r2_train,
        'Train PCC (20 fold CV)': pearson_train,
        'Train SCC (20 fold CV)': spearman_train,
        'Test MSE': mse_test,
        'Test MAE': mae_test,
        'Test RMSE': rmse_test,
        'Test R2': r2_test,
        'Test PCC': pearson_test,
        'Test SCC': spearman_test,
    }

results_df = pd.DataFrame(results).T
prediction_df = pd.DataFrame(predictions)
results_df

Processing dataframe pairs:   0%|          | 0/4 [00:00<?, ?it/s]
Training models: 0it [00:00, ?it/s]

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001404 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2656
[LightGBM] [Info] Number of data points in the train set: 48, number of used features: 160
[LightGBM] [Info] Start training from score -5.707480
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 


Training models: 1it [00:00,  1.71it/s]

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002977 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2718
[LightGBM] [Info] Number of data points in the train set: 49, number of used features: 160
[LightGBM] [Info] Start training from score -5.677426
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 


Training models: 2it [00:07,  4.02s/it]
Training models: 3it [00:11,  4.03s/it]
Training models: 4it [00:13,  3.31s/it]
Training models: 5it [00:17,  3.50s/it]
Training models: 6it [00:22,  4.03s/it]
Training models: 7it [00:22,  2.78s/it]
Training models: 9it [00:23,  1.83s/it]
Training models: 10it [00:24,  2.41s/it]
Processing dataframe pairs:  25%|██▌       | 1/4 [00:24<01:12, 24.11s/it]
Training models: 0it [00:00, ?it/s]

...

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: F

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: F

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000416 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 687
[LightGBM] [Info] Number of data points in the train set: 49, number of used features: 40
[LightGBM] [Info] Start training from score -5.627732
[LightGBM] [Warning] No further splits with positive gain, be

Train MSE (20 fold CV)  Train MAE (20 fold CV)  \
LGBMRegressor                            0.635044                0.688536   
DecisionTreeRegressor                    0.913954                0.670114   
RandomForestRegressor                    0.536702                0.579232   
GradientBoostingRegressor                0.630371                0.566901   
AdaBoostRegressor                        0.615080                0.608444   
XGBRegressor                             0.850271                0.720651   
ExtraTreesRegressor                      0.520016                0.565823   
LinearRegression                         2.311653                1.196307   
KNeighborsRegressor                      0.484336                0.510480   
SVR                                      0.630563                0.649474   
MLPRegressor                             1.005966                0.810364   

                           Train RMSE (20 fold CV)  Train R2 (20 fold CV)  \
LGBMRegressor                             0.796896               0.018318   
DecisionTreeRegressor                     0.956009              -0.412835   
RandomForestRegressor                     0.732599               0.170340   
GradientBoostingRegressor                 0.793959               0.025542   
AdaBoostRegressor                         0.784270               0.049179   
XGBRegressor                              0.922101              -0.314390   
ExtraTreesRegressor                       0.721122               0.196133   
LinearRegression                          1.520412              -2.573467   
KNeighborsRegressor                       0.695942               0.251290   
SVR                                       0.794080               0.025245   
MLPRegressor                              1.002978              -0.555071   

                           Train PCC (20 fold CV)  Train SCC (20 fold CV)  \
LGBMRegressor                            0.237011                0.245481   
DecisionTreeRegressor                    0.288062                0.447734   
RandomForestRegressor                    0.444478                0.497025   
GradientBoostingRegressor                0.399837                0.504627   
AdaBoostRegressor                        0.351791                0.363998   
XGBRegressor                             0.256318                0.244168   
ExtraTreesRegressor                      0.463733                0.502048   
LinearRegression                         0.412747                0.371756   
KNeighborsRegressor                      0.509640                0.512953   
SVR                                      0.250612                0.232222   
MLPRegressor                             0.210377                0.195932   

                           Test MSE  Test MAE  Test RMSE   Test R2  Test PCC  \
LGBMRegressor              0.425316  0.552818   0.652162  0.276951  0.533966   
DecisionTreeRegressor      0.622966  0.658357   0.789282 -0.059059  0.280419   
RandomForestRegressor      0.325268  0.488703   0.570323  0.447035  0.672367   
GradientBoostingRegressor  0.446344  0.544581   0.668090  0.241202  0.517032   
AdaBoostRegressor          0.312541  0.485675   0.559053  0.468672  0.709441   
XGBRegressor               0.398828  0.551599   0.631528  0.321981  0.575448   
ExtraTreesRegressor        0.393556  0.520277   0.627340  0.330944  0.600502   
LinearRegression           0.545206  0.572366   0.738380  0.073135  0.672760   
KNeighborsRegressor        0.396439  0.530327   0.629634  0.326042  0.689736   
SVR                        0.422743  0.517094   0.650187  0.281325  0.652071   
MLPRegressor               0.763989  0.750764   0.874064 -0.298803  0.742750   

                           Test SCC  
LGBMRegressor              0.454545  
DecisionTreeRegressor      0.178817  
RandomForestRegressor      0.514443  
GradientBoostingRegressor  0.162311  
AdaBoostRegressor          0.453921  
XGBRegressor               0.343879  
ExtraTreesRegressor      

In [64]:
results_df.to_csv('/home/users/akshay/PCPpred/MDCK/results/Stacked/Results_20_folds_stacked_archi_MDCK.csv')
prediction_df.to_csv('/home/users/akshay/PCPpred/MDCK/results/Stacked/Prediction_data_20_folds_stacked_archi_MDCK.csv')

In [65]:
#Saving the best model
#KR fingerprints (4680 fp)

import os
import joblib 


def train_and_test_predict(models, X_train, y_train, X_test, y_test, save_dir='models_MDCK'):
   
    os.makedirs(save_dir, exist_ok=True)

    kf = KFold(n_splits=5, shuffle=True, random_state=101)
    results = {}
    predictions = []  

    for model in models:
        model_name = model.__class__.__name__
        predictions_train = []
        actual_y_train = []
        test_predictions_folds = []

        fold_no = 1
        for train_index, val_index in kf.split(X_train):
            X_train_fold, X_val_fold = X_train.iloc[train_index], X_train.iloc[val_index]
            y_train_fold, y_val_fold = y_train.iloc[train_index], y_train.iloc[val_index]

            model.fit(X_train_fold, y_train_fold)

            fold_model_path = os.path.join(save_dir, f"{model_name}_fold{fold_no}_mdck.joblib")
            joblib.dump(model, fold_model_path)

            y_pred_fold = model.predict(X_val_fold)
            y_pred_fold = np.clip(y_pred_fold, -10, -4.0)
            predictions_train.extend(y_pred_fold)
            actual_y_train.extend(y_val_fold)

            predictions_test_fold = model.predict(X_test)
            predictions_test_fold = np.clip(predictions_test_fold, -10, -4.0)
            test_predictions_folds.append(predictions_test_fold)

            fold_no += 1

        mse_train = mean_squared_error(actual_y_train, predictions_train)
        mae_train = mean_absolute_error(actual_y_train, predictions_train)
        rmse_train = np.sqrt(mse_train)
        r2_train = r2_score(actual_y_train, predictions_train)
        pearson_train, _ = pearsonr(actual_y_train, predictions_train)
        spearman_train, _ = spearmanr(actual_y_train, predictions_train)

        predictions_test_mean = np.mean(test_predictions_folds, axis=0)
        predictions_test_std = np.std(test_predictions_folds, axis=0)

        mse_test = mean_squared_error(y_test, predictions_test_mean)
        mae_test = mean_absolute_error(y_test, predictions_test_mean)
        rmse_test = np.sqrt(mse_test)
        r2_test = r2_score(y_test, predictions_test_mean)
        pearson_test, _ = pearsonr(y_test, predictions_test_mean)
        spearman_test, _ = spearmanr(y_test, predictions_test_mean)

        predictions.append({
            'Model': model_name,
            'Y Train pred': predictions_train,
            'Y Test actual': y_test,
            'Test prediction folds': test_predictions_folds,
            'Test Predictions Mean': predictions_test_mean,
            'Test Predictions Std': predictions_test_std,
        })

        results[model_name] = {
            'Train MSE (5 fold cv)': f"{mse_train:.4f}",
            'Train MAE (5 fold cv)': f"{mae_train:.4f}",
            'Train RMSE (5 fold cv)': f"{rmse_train:.4f}",
            'Train R2 (5 fold cv)': f"{r2_train:.4f}",
            'Train PCC (5 fold cv)': f"{pearson_train:.4f}",
            'Train SCC (5 fold cv)': f"{spearman_train:.4f}",
            'Test MSE': f"{mse_test:.4f}",
            'Test MAE': f"{mae_test:.4f}",
            'Test RMSE': f"{rmse_test:.4f}",
            'Test R2': f"{r2_test:.4f}",
            'Test Pearson Correlation': f"{pearson_test:.4f}",
            'Test Spearman Correlation': f"{spearman_test:.4f}",
        }

    results_df = pd.DataFrame(results).T
    predictions_df = pd.DataFrame(predictions)

    return results_df, predictions_df

df_train = pd.read_csv('/home/users/akshay/PCPpred/MDCK/features/Fingerprints/Train/KlekotaRoth_train_MDCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('/home/users/akshay/PCPpred/MDCK/features/Fingerprints/Test/KlekotaRoth_test_MDCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

# Saving the scaler
joblib.dump(scaler, '/home/users/akshay/PCPpred/MDCK/models_MDCK/scaler_KR_fp_mdck.joblib')

models = [
    AdaBoostRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df


X_train shape:  (51, 4860)
y_train shape:  (51,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (13, 4860)
y_test shape:  (13,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
AdaBoostRegressor                0.7880                0.7035   

                  Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
AdaBoostRegressor                 0.8877              -0.2181   

                  Train PCC (5 fold cv) Train SCC (5 fold cv) Test MSE  \
AdaBoostRegressor                0.1957                0.2251   0.1869   

                  Test MAE Test RMSE Test R2 Test Pearson Correlation  \
AdaBoostRegressor   0.3746    0.4323  0.6823                   0.8344   

                  Test Spearman Correlation  
AdaBoostRegressor                    0.6179

In [66]:
models_dir = '/home/users/akshay/PCPpred/MDCK/models_MDCK' 
scaler_path = '/home/users/akshay/PCPpred/MDCK/models_MDCK/scaler_KR_fp_mdck.joblib' 
model_base_name = 'AdaBoostRegressor'                   
n_folds = 5                                    


df_new_test = pd.read_csv('/home/users/akshay/PCPpred/MDCK/features/Fingerprints/Test/KlekotaRoth_test_MDCK.csv')

X_new_test_features = df_new_test.drop(columns=['ID', 'SMILES','Permeability'], errors='ignore')
y_test = df_new_test['Permeability']

scaler = joblib.load(scaler_path)
X_new_scaled = scaler.transform(X_new_test_features)
X_new_scaled = pd.DataFrame(X_new_scaled, columns=X_new_test_features.columns,index=X_new_test_features.index)

all_fold_preds = []

for fold in range(1, n_folds + 1):
    fold_model_path = os.path.join(models_dir, f"{model_base_name}_fold{fold}_mdck.joblib")
    fold_model = joblib.load(fold_model_path)
    preds = fold_model.predict(X_new_scaled)
    preds = np.clip(preds, -10, -4.0)  
    all_fold_preds.append(preds)


all_fold_preds = np.array(all_fold_preds)
mean_prediction = np.mean(all_fold_preds, axis=0)

mse_test = mean_squared_error(y_test, mean_prediction)
print(f"{mse_test:.4f}")
mae_test = mean_absolute_error(y_test, mean_prediction)
print(f"{mae_test:.4f}")
rmse_test = np.sqrt(mse_test)
print(f"{rmse_test:.4f}")
r2_test = r2_score(y_test, mean_prediction)
print(f"{r2_test:.4f}")
pearson_test, _ = pearsonr(y_test, mean_prediction)
print(f"{pearson_test:.4f}")
spearman_test, _ = spearmanr(y_test, mean_prediction)
print(f"{spearman_test:.4f}")

# df_new_test['Predicted_Permeability'] = mean_prediction
# df_new_test.to_csv('path_to_save_predictions.csv', index=False)

print("Prediction on new data complete.")


0.1869
0.3746
0.4323
0.6823
0.8344
0.6179
Prediction on new data complete.
